In [ ]:
import re

In [ ]:
from sqlab.nb_tools import show_tables

class ColumnGetter:
    def __getitem__(self, label):
        return list(_.dict()[label])
col = ColumnGetter()

def print_assert(label):
    print(f'assert col["{label}"] == {col[label]}')

In [ ]:
%config SqlMagic.dsn_filename = "cnx.ini"
%config SqlMagic.displaycon = False
%config SqlMagic.displaylimit = 0
%reload_ext sql
%sql --section cnx
show_tables()

Connecting to 'cnx'

Table            Columns      
------------------------------
ints             n, hash      
sqlab_metadata   name, value  
sqlab_msg        msg          


# Comptes des mille et un n
Une table, une colonne : les entiers de 0 à 1000.

# Curiosités numériques
Croyez-le ou non : une simple liste d'entiers, c'est tout ce qu'il faut pour pousser SQL dans ses derniers retranchements.

Au programme : tripatouillage de nombres (bien sûr) et de chaînes de caractères, conditions en pagaille, jointures dans tous les sens, sous-requêtes plus ou moins tordues, regroupements des familles, CTE sans tabous, agrégats pas toujours ragoutants… Bref, une plongée vertigineuse dans les profondeurs du langage, dont vous ne ressortirez pas… entier !

Vous l'avez compris : cette série demande quand même une certaine maîtrise de SQL. Par contre, côté maths, pas de panique : on reste niveau collège — opérateurs arithmétiques, diviseurs, facteurs premiers, rien de foufou.

Alors, qu'attendez-vous ? 1, 2, 3, comptez !

## Suites numériques
Filtrez une liste d'entiers pour la réduire aux premiers termes de suites bien connues.

### Carrés parfaits

**Atelier [002].** Un entier est un **carré parfait** si et seulement si sa racine carrée est entière.

| Exemple | Racine carrée | Propriété | Carré parfait |
|---:|:--:|:--:|:--:|
| $16$ | $4$ | entière | ✅ |
| $20$ | $$4,4721\dots$$ | non entière | ❌ |

_Défi._ Listez par ordre croissant les carrés parfaits inférieurs ou égaux à 1000.

<figure>
  <img src="https://raw.githubusercontent.com/laowantong/sqlab_ints/refs/heads/main/assets/square-numbers.svg"/>
  <figcaption>Construction des 6 premiers carrés parfaits non nuls (NB. Notre définition inclut aussi 0).</figcaption>
</figure>

In [ ]:
%%sql
-- Solution recommandée. En ne gardant que les entiers dont la racine carrée a une partie fractionnaire nulle.
-- Notez l'emploi inhabituel de l'opérateur modulo.
SELECT n
     , salt_002(sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE sqrt(n) MOD 1 = 0

32 rows affected.

n 
 token 
 
 
 
 
 0 
 125856070581408 
 
 
 1 
 125856070581408 
 
 
 4 
 125856070581408 
 
 
 9 
 125856070581408 
 
 
 16 
 125856070581408 
 
 
 25 
 125856070581408 
 
 
 36 
 125856070581408 
 
 
 49 
 125856070581408 
 
 
 64 
 125856070581408 
 
 
 81 
 125856070581408 
 
 
 100 
 125856070581408 
 
 
 121 
 125856070581408 
 
 
 144 
 125856070581408 
 
 
 169 
 125856070581408 
 
 
 196 
 125856070581408 
 
 
 225 
 125856070581408 
 
 
 256 
 125856070581408 
 
 
 289 
 125856070581408 
 
 
 324 
 125856070581408 
 
 
 361 
 125856070581408 
 
 
 400 
 125856070581408 
 
 
 441 
 125856070581408 
 
 
 484 
 125856070581408 
 
 
 529 
 125856070581408 
 
 
 576 
 125856070581408 
 
 
 625 
 125856070581408 
 
 
 676 
 125856070581408 
 
 
 729 
 125856070581408 
 
 
 784 
 125856070581408 
 
 
 841 
 125856070581408 
 
 
 900 
 125856070581408 
 
 
 961 
 125856070581408

In [ ]:
%%sql
-- Variante. En ne gardant que les entiers dont la racine carrée est différente de sa propre partie entière.
-- Cela demande à calculer deux fois la racine carrée.
SELECT n
     , salt_002(sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE sqrt(n) = floor(sqrt(n))

32 rows affected.

n 
 token 
 
 
 
 
 0 
 125856070581408 
 
 
 1 
 125856070581408 
 
 
 4 
 125856070581408 
 
 
 9 
 125856070581408 
 
 
 16 
 125856070581408 
 
 
 25 
 125856070581408 
 
 
 36 
 125856070581408 
 
 
 49 
 125856070581408 
 
 
 64 
 125856070581408 
 
 
 81 
 125856070581408 
 
 
 100 
 125856070581408 
 
 
 121 
 125856070581408 
 
 
 144 
 125856070581408 
 
 
 169 
 125856070581408 
 
 
 196 
 125856070581408 
 
 
 225 
 125856070581408 
 
 
 256 
 125856070581408 
 
 
 289 
 125856070581408 
 
 
 324 
 125856070581408 
 
 
 361 
 125856070581408 
 
 
 400 
 125856070581408 
 
 
 441 
 125856070581408 
 
 
 484 
 125856070581408 
 
 
 529 
 125856070581408 
 
 
 576 
 125856070581408 
 
 
 625 
 125856070581408 
 
 
 676 
 125856070581408 
 
 
 729 
 125856070581408 
 
 
 784 
 125856070581408 
 
 
 841 
 125856070581408 
 
 
 900 
 125856070581408 
 
 
 961 
 125856070581408

In [ ]:
%%sql
-- Variante. En ne gardant que les entiers $a$ égaux au carré d'un entier $b$ (différent de $a$, sauf pour 0 et 1).
-- Peu performant, du fait de l'auto-jointure.
SELECT A.n
     , salt_002(sum(nn(A.hash)) OVER ()) AS token
FROM ints A
JOIN ints B ON A.n = B.n * B.n

32 rows affected.

n 
 token 
 
 
 
 
 0 
 125856070581408 
 
 
 1 
 125856070581408 
 
 
 4 
 125856070581408 
 
 
 9 
 125856070581408 
 
 
 16 
 125856070581408 
 
 
 25 
 125856070581408 
 
 
 36 
 125856070581408 
 
 
 49 
 125856070581408 
 
 
 64 
 125856070581408 
 
 
 81 
 125856070581408 
 
 
 100 
 125856070581408 
 
 
 121 
 125856070581408 
 
 
 144 
 125856070581408 
 
 
 169 
 125856070581408 
 
 
 196 
 125856070581408 
 
 
 225 
 125856070581408 
 
 
 256 
 125856070581408 
 
 
 289 
 125856070581408 
 
 
 324 
 125856070581408 
 
 
 361 
 125856070581408 
 
 
 400 
 125856070581408 
 
 
 441 
 125856070581408 
 
 
 484 
 125856070581408 
 
 
 529 
 125856070581408 
 
 
 576 
 125856070581408 
 
 
 625 
 125856070581408 
 
 
 676 
 125856070581408 
 
 
 729 
 125856070581408 
 
 
 784 
 125856070581408 
 
 
 841 
 125856070581408 
 
 
 900 
 125856070581408 
 
 
 961 
 125856070581408

In [ ]:
%%sql
-- Variante. Même idée, mais exprimée de façon plus procédurale, avec une requête imbriquée dans la clause `WHERE`.
-- On a également borné $b$ à $\sqrt{1000} < 32$. Attention : si vous travaillez sur une table plus grande,
-- vous devrez ajuster cette valeur.
SELECT n
     , salt_002(sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE n IN
        (SELECT n * n
         FROM ints
         WHERE n < 32 )

32 rows affected.

n 
 token 
 
 
 
 
 0 
 125856070581408 
 
 
 1 
 125856070581408 
 
 
 4 
 125856070581408 
 
 
 9 
 125856070581408 
 
 
 16 
 125856070581408 
 
 
 25 
 125856070581408 
 
 
 36 
 125856070581408 
 
 
 49 
 125856070581408 
 
 
 64 
 125856070581408 
 
 
 81 
 125856070581408 
 
 
 100 
 125856070581408 
 
 
 121 
 125856070581408 
 
 
 144 
 125856070581408 
 
 
 169 
 125856070581408 
 
 
 196 
 125856070581408 
 
 
 225 
 125856070581408 
 
 
 256 
 125856070581408 
 
 
 289 
 125856070581408 
 
 
 324 
 125856070581408 
 
 
 361 
 125856070581408 
 
 
 400 
 125856070581408 
 
 
 441 
 125856070581408 
 
 
 484 
 125856070581408 
 
 
 529 
 125856070581408 
 
 
 576 
 125856070581408 
 
 
 625 
 125856070581408 
 
 
 676 
 125856070581408 
 
 
 729 
 125856070581408 
 
 
 784 
 125856070581408 
 
 
 841 
 125856070581408 
 
 
 900 
 125856070581408 
 
 
 961 
 125856070581408

In [ ]:
%%sql
-- Variante. Autre idée avec une auto-jointure, mais plus élégante : vérifier simplement que la racine carrée
-- se trouve dans le tableau des entiers. Même problème potentiel de performance cependant.
SELECT n
     , salt_002(sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE sqrt(n) IN (
    SELECT n
    FROM ints
  )

32 rows affected.

n 
 token 
 
 
 
 
 0 
 125856070581408 
 
 
 1 
 125856070581408 
 
 
 4 
 125856070581408 
 
 
 9 
 125856070581408 
 
 
 16 
 125856070581408 
 
 
 25 
 125856070581408 
 
 
 36 
 125856070581408 
 
 
 49 
 125856070581408 
 
 
 64 
 125856070581408 
 
 
 81 
 125856070581408 
 
 
 100 
 125856070581408 
 
 
 121 
 125856070581408 
 
 
 144 
 125856070581408 
 
 
 169 
 125856070581408 
 
 
 196 
 125856070581408 
 
 
 225 
 125856070581408 
 
 
 256 
 125856070581408 
 
 
 289 
 125856070581408 
 
 
 324 
 125856070581408 
 
 
 361 
 125856070581408 
 
 
 400 
 125856070581408 
 
 
 441 
 125856070581408 
 
 
 484 
 125856070581408 
 
 
 529 
 125856070581408 
 
 
 576 
 125856070581408 
 
 
 625 
 125856070581408 
 
 
 676 
 125856070581408 
 
 
 729 
 125856070581408 
 
 
 784 
 125856070581408 
 
 
 841 
 125856070581408 
 
 
 900 
 125856070581408 
 
 
 961 
 125856070581408

In [ ]:
%%sql
-- Indication. Vous éliminez les carrés parfaits au lieu de les garder. Inversez votre condition.
SELECT n
     , salt_002(sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE sqrt(n) MOD 1 != 0

969 rows affected.

n 
 token 
 
 
 
 
 2 
 455354753305299 
 
 
 3 
 455354753305299 
 
 
 5 
 455354753305299 
 
 
 6 
 455354753305299 
 
 
 7 
 455354753305299 
 
 
 8 
 455354753305299 
 
 
 10 
 455354753305299 
 
 
 11 
 455354753305299 
 
 
 12 
 455354753305299 
 
 
 13 
 455354753305299 
 
 
 14 
 455354753305299 
 
 
 15 
 455354753305299 
 
 
 17 
 455354753305299 
 
 
 18 
 455354753305299 
 
 
 19 
 455354753305299 
 
 
 20 
 455354753305299 
 
 
 21 
 455354753305299 
 
 
 22 
 455354753305299 
 
 
 23 
 455354753305299 
 
 
 24 
 455354753305299 
 
 
 26 
 455354753305299 
 
 
 27 
 455354753305299 
 
 
 28 
 455354753305299 
 
 
 29 
 455354753305299 
 
 
 30 
 455354753305299 
 
 
 31 
 455354753305299 
 
 
 32 
 455354753305299 
 
 
 33 
 455354753305299 
 
 
 34 
 455354753305299 
 
 
 35 
 455354753305299 
 
 
 37 
 455354753305299 
 
 
 38 
 455354753305299 
 
 
 39 
 455354753305299 
 
 
 40 
 455354753305299 
 
 
 41 
 455354753305299 
 
 
 42 
 455354753305299 
 
 
 43 
 455354753305299 
 
 
 44 
 455354753305299 
 
 
 45 
 455354753305299 
 
 
 46 
 455354753305299 
 
 
 47 
 455354753305299 
 
 
 48 
 455354753305299 
 
 
 50 
 455354753305299 
 
 
 51 
 455354753305299 
 
 
 52 
 455354753305299 
 
 
 53 
 455354753305299 
 
 
 54 
 455354753305299 
 
 
 55 
 455354753305299 
 
 
 56 
 455354753305299 
 
 
 57 
 455354753305299 
 
 
 58 
 455354753305299 
 
 
 59 
 455354753305299 
 
 
 60 
 455354753305299 
 
 
 61 
 455354753305299 
 
 
 62 
 455354753305299 
 
 
 63 
 455354753305299 
 
 
 65 
 455354753305299 
 
 
 66 
 455354753305299 
 
 
 67 
 455354753305299 
 
 
 68 
 455354753305299 
 
 
 69 
 455354753305299 
 
 
 70 
 455354753305299 
 
 
 71 
 455354753305299 
 
 
 72 
 455354753305299 
 
 
 73 
 455354753305299 
 
 
 74 
 455354753305299 
 
 
 75 
 455354753305299 
 
 
 76 
 455354753305299 
 
 
 77 
 455354753305299 
 
 
 78 
 455354753305299 
 
 
 79 
 455354753305299 
 
 
 80 
 455354753305299 
 
 
 82 
 455354753305299 
 
 
 83 
 455354753305299 
 
 
 84 
 455354753305299 
 
 
 85 
 455354753305299 
 
 
 86 
 455354753305299 
 
 
 87 
 455354753305299 
 
 
 88 
 455354753305299 
 
 
 89 
 455354753305299 
 
 
 90 
 455354753305299 
 
 
 91 
 455354753305299 
 
 
 92 
 455354753305299 
 
 
 93 
 455354753305299 
 
 
 94 
 455354753305299 
 
 
 95 
 455354753305299 
 
 
 96 
 455354753305299 
 
 
 97 
 455354753305299 
 
 
 98 
 455354753305299 
 
 
 99 
 455354753305299 
 
 
 101 
 455354753305299 
 
 
 102 
 455354753305299 
 
 
 103 
 455354753305299 
 
 
 104 
 455354753305299 
 
 
 105 
 455354753305299 
 
 
 106 
 455354753305299 
 
 
 107 
 455354753305299 
 
 
 108 
 455354753305299 
 
 
 109 
 455354753305299 
 
 
 110 
 455354753305299 
 
 
 111 
 455354753305299 
 
 
 112 
 455354753305299 
 
 
 113 
 455354753305299 
 
 
 114 
 455354753305299 
 
 
 115 
 455354753305299 
 
 
 116 
 455354753305299 
 
 
 117 
 455354753305299 
 
 
 118 
 455354753305299 
 
 
 119 
 455354753305299 
 
 
 120 
 455354753305299 
 
 
 122 
 455354753305299 
 
 
 123 
 455354753305299 
 
 
 124 
 455354753305299 
 
 
 125 
 455354753305299 
 
 
 126 
 455354753305299 
 
 
 127 
 455354753305299 
 
 
 128 
 455354753305299 
 
 
 129 
 455354753305299 
 
 
 130 
 455354753305299 
 
 
 131 
 455354753305299 
 
 
 132 
 455354753305299 
 
 
 133 
 455354753305299 
 
 
 134 
 455354753305299 
 
 
 135 
 455354753305299 
 
 
 136 
 455354753305299 
 
 
 137 
 455354753305299 
 
 
 138 
 455354753305299 
 
 
 139 
 455354753305299 
 
 
 140 
 455354753305299 
 
 
 141 
 455354753305299 
 
 
 142 
 455354753305299 
 
 
 143 
 455354753305299 
 
 
 145 
 455354753305299 
 
 
 146 
 455354753305299 
 
 
 147 
 455354753305299 
 
 
 148 
 455354753305299 
 
 
 149 
 455354753305299 
 
 
 150 
 455354753305299 
 
 
 151 
 455354753305299 
 
 
 152 
 455354753305299 
 
 
 153 
 455354753305299 
 
 
 154 
 455354753305299 
 
 
 155 
 455354753305299 
 
 
 156 
 455354753305299 
 
 
 157 
 455354753305299 
 
 
 158 
 4553547533

### Entiers palindromiques

**Atelier [052].** Un entier est **palindromique** si sa représentation décimale se lit de la même façon de gauche à droite et de droite à gauche.

| Exemple | De droite à gauche | Palindromique |
|---:|:--:|:--:|
| $7$ | $7$ | ✅ |
| $121$ | $121$ | ✅ |
| $123$ | $$321$$ | ❌ |

_Défi._ Listez par ordre croissant les entiers palindromiques inférieurs ou égaux à 1000.

In [ ]:
%%sql
-- Il suffit de comparer la chaîne correspondante à son inverse.
SELECT n
     , salt_052(sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE cast(n AS CHAR) = reverse(cast(n AS CHAR))

109 rows affected.

n 
 token 
 
 
 
 
 0 
 240070160009025 
 
 
 1 
 240070160009025 
 
 
 2 
 240070160009025 
 
 
 3 
 240070160009025 
 
 
 4 
 240070160009025 
 
 
 5 
 240070160009025 
 
 
 6 
 240070160009025 
 
 
 7 
 240070160009025 
 
 
 8 
 240070160009025 
 
 
 9 
 240070160009025 
 
 
 11 
 240070160009025 
 
 
 22 
 240070160009025 
 
 
 33 
 240070160009025 
 
 
 44 
 240070160009025 
 
 
 55 
 240070160009025 
 
 
 66 
 240070160009025 
 
 
 77 
 240070160009025 
 
 
 88 
 240070160009025 
 
 
 99 
 240070160009025 
 
 
 101 
 240070160009025 
 
 
 111 
 240070160009025 
 
 
 121 
 240070160009025 
 
 
 131 
 240070160009025 
 
 
 141 
 240070160009025 
 
 
 151 
 240070160009025 
 
 
 161 
 240070160009025 
 
 
 171 
 240070160009025 
 
 
 181 
 240070160009025 
 
 
 191 
 240070160009025 
 
 
 202 
 240070160009025 
 
 
 212 
 240070160009025 
 
 
 222 
 240070160009025 
 
 
 232 
 240070160009025 
 
 
 242 
 240070160009025 
 
 
 252 
 240070160009025 
 
 
 262 
 240070160009025 
 
 
 272 
 240070160009025 
 
 
 282 
 240070160009025 
 
 
 292 
 240070160009025 
 
 
 303 
 240070160009025 
 
 
 313 
 240070160009025 
 
 
 323 
 240070160009025 
 
 
 333 
 240070160009025 
 
 
 343 
 240070160009025 
 
 
 353 
 240070160009025 
 
 
 363 
 240070160009025 
 
 
 373 
 240070160009025 
 
 
 383 
 240070160009025 
 
 
 393 
 240070160009025 
 
 
 404 
 240070160009025 
 
 
 414 
 240070160009025 
 
 
 424 
 240070160009025 
 
 
 434 
 240070160009025 
 
 
 444 
 240070160009025 
 
 
 454 
 240070160009025 
 
 
 464 
 240070160009025 
 
 
 474 
 240070160009025 
 
 
 484 
 240070160009025 
 
 
 494 
 240070160009025 
 
 
 505 
 240070160009025 
 
 
 515 
 240070160009025 
 
 
 525 
 240070160009025 
 
 
 535 
 240070160009025 
 
 
 545 
 240070160009025 
 
 
 555 
 240070160009025 
 
 
 565 
 240070160009025 
 
 
 575 
 240070160009025 
 
 
 585 
 240070160009025 
 
 
 595 
 240070160009025 
 
 
 606 
 240070160009025 
 
 
 616 
 240070160009025 
 
 
 626 
 240070160009025 
 
 
 636 
 240070160009025 
 
 
 646 
 240070160009025 
 
 
 656 
 240070160009025 
 
 
 666 
 240070160009025 
 
 
 676 
 240070160009025 
 
 
 686 
 240070160009025 
 
 
 696 
 240070160009025 
 
 
 707 
 240070160009025 
 
 
 717 
 240070160009025 
 
 
 727 
 240070160009025 
 
 
 737 
 240070160009025 
 
 
 747 
 240070160009025 
 
 
 757 
 240070160009025 
 
 
 767 
 240070160009025 
 
 
 777 
 240070160009025 
 
 
 787 
 240070160009025 
 
 
 797 
 240070160009025 
 
 
 808 
 240070160009025 
 
 
 818 
 240070160009025 
 
 
 828 
 240070160009025 
 
 
 838 
 240070160009025 
 
 
 848 
 240070160009025 
 
 
 858 
 240070160009025 
 
 
 868 
 240070160009025 
 
 
 878 
 240070160009025 
 
 
 888 
 240070160009025 
 
 
 898 
 240070160009025 
 
 
 909 
 240070160009025 
 
 
 919 
 240070160009025 
 
 
 929 
 240070160009025 
 
 
 939 
 240070160009025 
 
 
 949 
 240070160009025 
 
 
 959 
 240070160009025 
 
 
 969 
 240070160009025 
 
 
 979 
 240070160009025 
 
 
 989 
 240070160009025 
 
 
 999 
 240070160009025

In [ ]:
%%sql
-- Variante. MySQL est notoirement peu regardant sur les types. Dans la version ci-dessous, il convertit
-- implicitement l’entier `n` en chaîne de caractères pour appliquer la fonction `REVERSE`, puis reconvertit
-- le résultat en entier pour la comparaison. Cela dit, pour éviter toute ambiguïté ou comportement implicite,
-- on préférera `CAST(n AS CHAR)`, plus rigoureux et plus portable.
SELECT n
     , salt_052(sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE n = reverse(n)

109 rows affected.

n 
 token 
 
 
 
 
 0 
 240070160009025 
 
 
 1 
 240070160009025 
 
 
 2 
 240070160009025 
 
 
 3 
 240070160009025 
 
 
 4 
 240070160009025 
 
 
 5 
 240070160009025 
 
 
 6 
 240070160009025 
 
 
 7 
 240070160009025 
 
 
 8 
 240070160009025 
 
 
 9 
 240070160009025 
 
 
 11 
 240070160009025 
 
 
 22 
 240070160009025 
 
 
 33 
 240070160009025 
 
 
 44 
 240070160009025 
 
 
 55 
 240070160009025 
 
 
 66 
 240070160009025 
 
 
 77 
 240070160009025 
 
 
 88 
 240070160009025 
 
 
 99 
 240070160009025 
 
 
 101 
 240070160009025 
 
 
 111 
 240070160009025 
 
 
 121 
 240070160009025 
 
 
 131 
 240070160009025 
 
 
 141 
 240070160009025 
 
 
 151 
 240070160009025 
 
 
 161 
 240070160009025 
 
 
 171 
 240070160009025 
 
 
 181 
 240070160009025 
 
 
 191 
 240070160009025 
 
 
 202 
 240070160009025 
 
 
 212 
 240070160009025 
 
 
 222 
 240070160009025 
 
 
 232 
 240070160009025 
 
 
 242 
 240070160009025 
 
 
 252 
 240070160009025 
 
 
 262 
 240070160009025 
 
 
 272 
 240070160009025 
 
 
 282 
 240070160009025 
 
 
 292 
 240070160009025 
 
 
 303 
 240070160009025 
 
 
 313 
 240070160009025 
 
 
 323 
 240070160009025 
 
 
 333 
 240070160009025 
 
 
 343 
 240070160009025 
 
 
 353 
 240070160009025 
 
 
 363 
 240070160009025 
 
 
 373 
 240070160009025 
 
 
 383 
 240070160009025 
 
 
 393 
 240070160009025 
 
 
 404 
 240070160009025 
 
 
 414 
 240070160009025 
 
 
 424 
 240070160009025 
 
 
 434 
 240070160009025 
 
 
 444 
 240070160009025 
 
 
 454 
 240070160009025 
 
 
 464 
 240070160009025 
 
 
 474 
 240070160009025 
 
 
 484 
 240070160009025 
 
 
 494 
 240070160009025 
 
 
 505 
 240070160009025 
 
 
 515 
 240070160009025 
 
 
 525 
 240070160009025 
 
 
 535 
 240070160009025 
 
 
 545 
 240070160009025 
 
 
 555 
 240070160009025 
 
 
 565 
 240070160009025 
 
 
 575 
 240070160009025 
 
 
 585 
 240070160009025 
 
 
 595 
 240070160009025 
 
 
 606 
 240070160009025 
 
 
 616 
 240070160009025 
 
 
 626 
 240070160009025 
 
 
 636 
 240070160009025 
 
 
 646 
 240070160009025 
 
 
 656 
 240070160009025 
 
 
 666 
 240070160009025 
 
 
 676 
 240070160009025 
 
 
 686 
 240070160009025 
 
 
 696 
 240070160009025 
 
 
 707 
 240070160009025 
 
 
 717 
 240070160009025 
 
 
 727 
 240070160009025 
 
 
 737 
 240070160009025 
 
 
 747 
 240070160009025 
 
 
 757 
 240070160009025 
 
 
 767 
 240070160009025 
 
 
 777 
 240070160009025 
 
 
 787 
 240070160009025 
 
 
 797 
 240070160009025 
 
 
 808 
 240070160009025 
 
 
 818 
 240070160009025 
 
 
 828 
 240070160009025 
 
 
 838 
 240070160009025 
 
 
 848 
 240070160009025 
 
 
 858 
 240070160009025 
 
 
 868 
 240070160009025 
 
 
 878 
 240070160009025 
 
 
 888 
 240070160009025 
 
 
 898 
 240070160009025 
 
 
 909 
 240070160009025 
 
 
 919 
 240070160009025 
 
 
 929 
 240070160009025 
 
 
 939 
 240070160009025 
 
 
 949 
 240070160009025 
 
 
 959 
 240070160009025 
 
 
 969 
 240070160009025 
 
 
 979 
 240070160009025 
 
 
 989 
 240070160009025 
 
 
 999 
 240070160009025

In [ ]:
%%sql
-- Indication. En effet, tous les entiers réduits à un seul chiffre sont palindromiques,
-- mais on les veut jusqu'à 1000 !
SELECT n
     , salt_052(sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE n < 10

10 rows affected.

n 
 token 
 
 
 
 
 0 
 259210820430640 
 
 
 1 
 259210820430640 
 
 
 2 
 259210820430640 
 
 
 3 
 259210820430640 
 
 
 4 
 259210820430640 
 
 
 5 
 259210820430640 
 
 
 6 
 259210820430640 
 
 
 7 
 259210820430640 
 
 
 8 
 259210820430640 
 
 
 9 
 259210820430640

### Nombres triangulaires

**Atelier [043].** Un entier est **triangulaire** si et seulement s'il peut s'écrire sous la forme $\frac{n (n+1)}{2}$ avec $n$ entier positif ou nul.

| Exemple | Forme cherchée | Triangulaire |
|---:|:--:|:--:|
| $15$ | $$5\times6\div2$$ | ✅ |
| $16$ | ❌ | ❌ |

_Défi._ Listez par ordre croissant les nombres triangulaires inférieurs ou égaux à 1000.

<figure>
  <img src="https://raw.githubusercontent.com/laowantong/sqlab_ints/refs/heads/main/assets/triangular-numbers.svg"/>
  <figcaption>Construction des six premiers nombres triangulaires non nuls (NB. : notre définition inclut aussi 0).</figcaption>
</figure>

In [ ]:
x = 45 # le dixième nombre de la colonne
# Javascript: result[9]?.n ?? 7_531_148

In [ ]:
%%sql
-- On parcourt tous les entiers $A_i$ de la liste, et on ne garde que ceux pour lesquels il existe un entier $B_i$
-- vérifiant l'équation. Comme on connaît la borne supérieure ($1000$, qui est plus petit $45\times 46\div 2=1035$), on
-- peut (facultativement) insérer la « garde » `B.n < 45`.
SELECT n
     , salt_043({{x}} + sum(nn(A.hash)) OVER ()) AS token
FROM ints A
WHERE EXISTS
        (SELECT 1
         FROM ints B
         WHERE B.n < 45
             AND A.n = B.n * (B.n + 1) / 2 )

45 rows affected.

n 
 token 
 
 
 
 
 0 
 103209978926087 
 
 
 1 
 103209978926087 
 
 
 3 
 103209978926087 
 
 
 6 
 103209978926087 
 
 
 10 
 103209978926087 
 
 
 15 
 103209978926087 
 
 
 21 
 103209978926087 
 
 
 28 
 103209978926087 
 
 
 36 
 103209978926087 
 
 
 45 
 103209978926087 
 
 
 55 
 103209978926087 
 
 
 66 
 103209978926087 
 
 
 78 
 103209978926087 
 
 
 91 
 103209978926087 
 
 
 105 
 103209978926087 
 
 
 120 
 103209978926087 
 
 
 136 
 103209978926087 
 
 
 153 
 103209978926087 
 
 
 171 
 103209978926087 
 
 
 190 
 103209978926087 
 
 
 210 
 103209978926087 
 
 
 231 
 103209978926087 
 
 
 253 
 103209978926087 
 
 
 276 
 103209978926087 
 
 
 300 
 103209978926087 
 
 
 325 
 103209978926087 
 
 
 351 
 103209978926087 
 
 
 378 
 103209978926087 
 
 
 406 
 103209978926087 
 
 
 435 
 103209978926087 
 
 
 465 
 103209978926087 
 
 
 496 
 103209978926087 
 
 
 528 
 103209978926087 
 
 
 561 
 103209978926087 
 
 
 595 
 103209978926087 
 
 
 630 
 103209978926087 
 
 
 666 
 103209978926087 
 
 
 703 
 103209978926087 
 
 
 741 
 103209978926087 
 
 
 780 
 103209978926087 
 
 
 820 
 103209978926087 
 
 
 861 
 103209978926087 
 
 
 903 
 103209978926087 
 
 
 946 
 103209978926087 
 
 
 990 
 103209978926087

In [ ]:
assert col['n'][9] == x

In [ ]:
%%sql
-- Variante. Avec une auto-jointure.
SELECT A.n
     , salt_043({{x}} + sum(nn(A.hash)) OVER ()) AS token
FROM ints A
JOIN ints B ON A.n = B.n * (B.n + 1) / 2
WHERE B.n < 45
ORDER BY A.n

45 rows affected.

n 
 token 
 
 
 
 
 0 
 103209978926087 
 
 
 1 
 103209978926087 
 
 
 3 
 103209978926087 
 
 
 6 
 103209978926087 
 
 
 10 
 103209978926087 
 
 
 15 
 103209978926087 
 
 
 21 
 103209978926087 
 
 
 28 
 103209978926087 
 
 
 36 
 103209978926087 
 
 
 45 
 103209978926087 
 
 
 55 
 103209978926087 
 
 
 66 
 103209978926087 
 
 
 78 
 103209978926087 
 
 
 91 
 103209978926087 
 
 
 105 
 103209978926087 
 
 
 120 
 103209978926087 
 
 
 136 
 103209978926087 
 
 
 153 
 103209978926087 
 
 
 171 
 103209978926087 
 
 
 190 
 103209978926087 
 
 
 210 
 103209978926087 
 
 
 231 
 103209978926087 
 
 
 253 
 103209978926087 
 
 
 276 
 103209978926087 
 
 
 300 
 103209978926087 
 
 
 325 
 103209978926087 
 
 
 351 
 103209978926087 
 
 
 378 
 103209978926087 
 
 
 406 
 103209978926087 
 
 
 435 
 103209978926087 
 
 
 465 
 103209978926087 
 
 
 496 
 103209978926087 
 
 
 528 
 103209978926087 
 
 
 561 
 103209978926087 
 
 
 595 
 103209978926087 
 
 
 630 
 103209978926087 
 
 
 666 
 103209978926087 
 
 
 703 
 103209978926087 
 
 
 741 
 103209978926087 
 
 
 780 
 103209978926087 
 
 
 820 
 103209978926087 
 
 
 861 
 103209978926087 
 
 
 903 
 103209978926087 
 
 
 946 
 103209978926087 
 
 
 990 
 103209978926087

In [ ]:
assert col['n'][9] == x

In [ ]:
%%sql
-- Variante. Avec une sous-requête dans le `WHERE`.
SELECT n
     , salt_043({{x}} + sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE n IN
        (SELECT n * (n + 1) / 2
         FROM ints
         WHERE n < 45 )

45 rows affected.

n 
 token 
 
 
 
 
 0 
 103209978926087 
 
 
 1 
 103209978926087 
 
 
 3 
 103209978926087 
 
 
 6 
 103209978926087 
 
 
 10 
 103209978926087 
 
 
 15 
 103209978926087 
 
 
 21 
 103209978926087 
 
 
 28 
 103209978926087 
 
 
 36 
 103209978926087 
 
 
 45 
 103209978926087 
 
 
 55 
 103209978926087 
 
 
 66 
 103209978926087 
 
 
 78 
 103209978926087 
 
 
 91 
 103209978926087 
 
 
 105 
 103209978926087 
 
 
 120 
 103209978926087 
 
 
 136 
 103209978926087 
 
 
 153 
 103209978926087 
 
 
 171 
 103209978926087 
 
 
 190 
 103209978926087 
 
 
 210 
 103209978926087 
 
 
 231 
 103209978926087 
 
 
 253 
 103209978926087 
 
 
 276 
 103209978926087 
 
 
 300 
 103209978926087 
 
 
 325 
 103209978926087 
 
 
 351 
 103209978926087 
 
 
 378 
 103209978926087 
 
 
 406 
 103209978926087 
 
 
 435 
 103209978926087 
 
 
 465 
 103209978926087 
 
 
 496 
 103209978926087 
 
 
 528 
 103209978926087 
 
 
 561 
 103209978926087 
 
 
 595 
 103209978926087 
 
 
 630 
 103209978926087 
 
 
 666 
 103209978926087 
 
 
 703 
 103209978926087 
 
 
 741 
 103209978926087 
 
 
 780 
 103209978926087 
 
 
 820 
 103209978926087 
 
 
 861 
 103209978926087 
 
 
 903 
 103209978926087 
 
 
 946 
 103209978926087 
 
 
 990 
 103209978926087

In [ ]:
assert col['n'][9] == x

In [ ]:
%%sql
-- Indication. On ne cherche pas les nombres qui vérifient l'égalité $n = \frac{n(n+1)}{2}$ mais ceux qui peuvent
-- s'écrire sous la forme de sa partie droite.
SELECT n
     , salt_043(7531148 + sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE n = n * (n + 1) / 2

2 rows affected.

n 
 token 
 
 
 
 
 0 
 81063761713588 
 
 
 1 
 81063761713588

In [ ]:
x = 90

In [ ]:
%%sql
-- Indication. Vous avez oublié le numérateur de la formule.
SELECT A.n
     , salt_043({{x}} + sum(nn(A.hash)) OVER ()) AS token
FROM ints A
JOIN ints B ON A.n = B.n * (B.n + 1)
WHERE B.n < 45
ORDER BY A.n;

32 rows affected.

n 
 token 
 
 
 
 
 0 
 96800835160244 
 
 
 2 
 96800835160244 
 
 
 6 
 96800835160244 
 
 
 12 
 96800835160244 
 
 
 20 
 96800835160244 
 
 
 30 
 96800835160244 
 
 
 42 
 96800835160244 
 
 
 56 
 96800835160244 
 
 
 72 
 96800835160244 
 
 
 90 
 96800835160244 
 
 
 110 
 96800835160244 
 
 
 132 
 96800835160244 
 
 
 156 
 96800835160244 
 
 
 182 
 96800835160244 
 
 
 210 
 96800835160244 
 
 
 240 
 96800835160244 
 
 
 272 
 96800835160244 
 
 
 306 
 96800835160244 
 
 
 342 
 96800835160244 
 
 
 380 
 96800835160244 
 
 
 420 
 96800835160244 
 
 
 462 
 96800835160244 
 
 
 506 
 96800835160244 
 
 
 552 
 96800835160244 
 
 
 600 
 96800835160244 
 
 
 650 
 96800835160244 
 
 
 702 
 96800835160244 
 
 
 756 
 96800835160244 
 
 
 812 
 96800835160244 
 
 
 870 
 96800835160244 
 
 
 930 
 96800835160244 
 
 
 992 
 96800835160244

In [ ]:
assert col['n'][9] == x

In [ ]:
x = 162

In [ ]:
%%sql
-- Indication. Vous avez oublié le $+ 1$ dans la formule.
SELECT A.n
     , salt_043({{x}} + sum(nn(A.hash)) OVER ()) AS token
FROM ints A
JOIN ints B ON A.n = B.n * B.n / 2
WHERE B.n < 45
ORDER BY A.n

23 rows affected.

n 
 token 
 
 
 
 
 0 
 76118056186574 
 
 
 2 
 76118056186574 
 
 
 8 
 76118056186574 
 
 
 18 
 76118056186574 
 
 
 32 
 76118056186574 
 
 
 50 
 76118056186574 
 
 
 72 
 76118056186574 
 
 
 98 
 76118056186574 
 
 
 128 
 76118056186574 
 
 
 162 
 76118056186574 
 
 
 200 
 76118056186574 
 
 
 242 
 76118056186574 
 
 
 288 
 76118056186574 
 
 
 338 
 76118056186574 
 
 
 392 
 76118056186574 
 
 
 450 
 76118056186574 
 
 
 512 
 76118056186574 
 
 
 578 
 76118056186574 
 
 
 648 
 76118056186574 
 
 
 722 
 76118056186574 
 
 
 800 
 76118056186574 
 
 
 882 
 76118056186574 
 
 
 968 
 76118056186574

In [ ]:
assert col['n'][9] == x

In [ ]:
x = 9

In [ ]:
%%sql
-- Indication. Vous ne projetez pas la colonne `n` de la bonne table.
SELECT B.n
     , salt_043({{x}} + sum(nn(A.hash)) OVER ()) AS token
FROM ints A
JOIN ints B ON A.n = B.n * (B.n + 1) / 2
WHERE B.n < 45
ORDER BY A.n

45 rows affected.

n 
 token 
 
 
 
 
 0 
 103209978926115 
 
 
 1 
 103209978926115 
 
 
 2 
 103209978926115 
 
 
 3 
 103209978926115 
 
 
 4 
 103209978926115 
 
 
 5 
 103209978926115 
 
 
 6 
 103209978926115 
 
 
 7 
 103209978926115 
 
 
 8 
 103209978926115 
 
 
 9 
 103209978926115 
 
 
 10 
 103209978926115 
 
 
 11 
 103209978926115 
 
 
 12 
 103209978926115 
 
 
 13 
 103209978926115 
 
 
 14 
 103209978926115 
 
 
 15 
 103209978926115 
 
 
 16 
 103209978926115 
 
 
 17 
 103209978926115 
 
 
 18 
 103209978926115 
 
 
 19 
 103209978926115 
 
 
 20 
 103209978926115 
 
 
 21 
 103209978926115 
 
 
 22 
 103209978926115 
 
 
 23 
 103209978926115 
 
 
 24 
 103209978926115 
 
 
 25 
 103209978926115 
 
 
 26 
 103209978926115 
 
 
 27 
 103209978926115 
 
 
 28 
 103209978926115 
 
 
 29 
 103209978926115 
 
 
 30 
 103209978926115 
 
 
 31 
 103209978926115 
 
 
 32 
 103209978926115 
 
 
 33 
 103209978926115 
 
 
 34 
 103209978926115 
 
 
 35 
 103209978926115 
 
 
 36 
 103209978926115 
 
 
 37 
 103209978926115 
 
 
 38 
 103209978926115 
 
 
 39 
 103209978926115 
 
 
 40 
 103209978926115 
 
 
 41 
 103209978926115 
 
 
 42 
 103209978926115 
 
 
 43 
 103209978926115 
 
 
 44 
 103209978926115

In [ ]:
assert col['n'][9] == x

### Entiers automorphes

**Atelier [010].** Un entier $n$ est **automorphe** si son carré se termine par $n$ (en écriture décimale).

| Exemple | Carré | Automorphe |
|---:|:--:|:--:|
| $5$ | $25$ | ✅
| $25$ | $625$ | ✅ |
| $7$ | $49$ | ❌ |

_Défi._ Listez par ordre croissant les entiers automorphes inférieurs ou égaux à 1000.

In [ ]:
%%sql
-- Avec la fonction de concaténation et l'opérateur `LIKE`.
SELECT n
     , salt_010(sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE cast(n * n AS CHAR) LIKE concat('%', cast(n AS CHAR))

8 rows affected.

n 
 token 
 
 
 
 
 0 
 155147806452639 
 
 
 1 
 155147806452639 
 
 
 5 
 155147806452639 
 
 
 6 
 155147806452639 
 
 
 25 
 155147806452639 
 
 
 76 
 155147806452639 
 
 
 376 
 155147806452639 
 
 
 625 
 155147806452639

In [ ]:
%%sql
-- Variante. En extrayant le bon nombre de caractères à droite et en comparant. L'observation de l'atelier sur
-- les palindromes reste valable ici : MySQL pourrait se passer des opérations de conversion explicite, ce qui
-- rendrait certainement l'expression plus lisible.
SELECT n
     , salt_010(sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE right(cast(n * n AS CHAR), length(cast(n AS CHAR))) = cast(n AS CHAR)

8 rows affected.

n 
 token 
 
 
 
 
 0 
 155147806452639 
 
 
 1 
 155147806452639 
 
 
 5 
 155147806452639 
 
 
 6 
 155147806452639 
 
 
 25 
 155147806452639 
 
 
 76 
 155147806452639 
 
 
 376 
 155147806452639 
 
 
 625 
 155147806452639

### Nombres bicarrés

**Atelier [032].** Un entier $c$ est **bicarré** si et seulement s'il peut s'écrire sous la forme $a^2+b^2$ avec $a$ et $b$ entiers.

| Exemple | Forme cherchée | Bicarré |
|---:|:--:|:--:|
| $17$ | $$1^2+4^2$$ | ✅ |
| $15$ | aucune | ❌ |

_Défi._ Listez par ordre croissant les entiers bicarrés inférieurs ou égaux à 1000.

_Contrainte._ Faites un produit cartésien de trois tables.

<figure>
  <img src="https://raw.githubusercontent.com/laowantong/sqlab_ints/refs/heads/main/assets/nombre-bigarré.png"/>
  <figcaption>Entier bicarré et bigarré.</figcaption>
</figure>

In [ ]:
x = 8 # le 6e terme de cette suite
# Javascript: result[5]?.n ?? 7_531_148

In [ ]:
%%sql
SELECT DISTINCT C.n
              , salt_032({{x}} + sum(nn(A.hash) + nn(B.hash) + nn(C.hash)) OVER ()) AS token
FROM ints C
JOIN ints A ON A.n * A.n <= C.n
JOIN ints B ON A.n * A.n + B.n * B.n = C.n
ORDER BY 1

331 rows affected.

n 
 token 
 
 
 
 
 0 
 1230160502988882 
 
 
 1 
 1230160502988882 
 
 
 2 
 1230160502988882 
 
 
 4 
 1230160502988882 
 
 
 5 
 1230160502988882 
 
 
 8 
 1230160502988882 
 
 
 9 
 1230160502988882 
 
 
 10 
 1230160502988882 
 
 
 13 
 1230160502988882 
 
 
 16 
 1230160502988882 
 
 
 17 
 1230160502988882 
 
 
 18 
 1230160502988882 
 
 
 20 
 1230160502988882 
 
 
 25 
 1230160502988882 
 
 
 26 
 1230160502988882 
 
 
 29 
 1230160502988882 
 
 
 32 
 1230160502988882 
 
 
 34 
 1230160502988882 
 
 
 36 
 1230160502988882 
 
 
 37 
 1230160502988882 
 
 
 40 
 1230160502988882 
 
 
 41 
 1230160502988882 
 
 
 45 
 1230160502988882 
 
 
 49 
 1230160502988882 
 
 
 50 
 1230160502988882 
 
 
 52 
 1230160502988882 
 
 
 53 
 1230160502988882 
 
 
 58 
 1230160502988882 
 
 
 61 
 1230160502988882 
 
 
 64 
 1230160502988882 
 
 
 65 
 1230160502988882 
 
 
 68 
 1230160502988882 
 
 
 72 
 1230160502988882 
 
 
 73 
 1230160502988882 
 
 
 74 
 1230160502988882 
 
 
 80 
 1230160502988882 
 
 
 81 
 1230160502988882 
 
 
 82 
 1230160502988882 
 
 
 85 
 1230160502988882 
 
 
 89 
 1230160502988882 
 
 
 90 
 1230160502988882 
 
 
 97 
 1230160502988882 
 
 
 98 
 1230160502988882 
 
 
 100 
 1230160502988882 
 
 
 101 
 1230160502988882 
 
 
 104 
 1230160502988882 
 
 
 106 
 1230160502988882 
 
 
 109 
 1230160502988882 
 
 
 113 
 1230160502988882 
 
 
 116 
 1230160502988882 
 
 
 117 
 1230160502988882 
 
 
 121 
 1230160502988882 
 
 
 122 
 1230160502988882 
 
 
 125 
 1230160502988882 
 
 
 128 
 1230160502988882 
 
 
 130 
 1230160502988882 
 
 
 136 
 1230160502988882 
 
 
 137 
 1230160502988882 
 
 
 144 
 1230160502988882 
 
 
 145 
 1230160502988882 
 
 
 146 
 1230160502988882 
 
 
 148 
 1230160502988882 
 
 
 149 
 1230160502988882 
 
 
 153 
 1230160502988882 
 
 
 157 
 1230160502988882 
 
 
 160 
 1230160502988882 
 
 
 162 
 1230160502988882 
 
 
 164 
 1230160502988882 
 
 
 169 
 1230160502988882 
 
 
 170 
 1230160502988882 
 
 
 173 
 1230160502988882 
 
 
 178 
 1230160502988882 
 
 
 180 
 1230160502988882 
 
 
 181 
 1230160502988882 
 
 
 185 
 1230160502988882 
 
 
 193 
 1230160502988882 
 
 
 194 
 1230160502988882 
 
 
 196 
 1230160502988882 
 
 
 197 
 1230160502988882 
 
 
 200 
 1230160502988882 
 
 
 202 
 1230160502988882 
 
 
 205 
 1230160502988882 
 
 
 208 
 1230160502988882 
 
 
 212 
 1230160502988882 
 
 
 218 
 1230160502988882 
 
 
 221 
 1230160502988882 
 
 
 225 
 1230160502988882 
 
 
 226 
 1230160502988882 
 
 
 229 
 1230160502988882 
 
 
 232 
 1230160502988882 
 
 
 233 
 1230160502988882 
 
 
 234 
 1230160502988882 
 
 
 241 
 1230160502988882 
 
 
 242 
 1230160502988882 
 
 
 244 
 1230160502988882 
 
 
 245 
 1230160502988882 
 
 
 250 
 1230160502988882 
 
 
 256 
 1230160502988882 
 
 
 257 
 1230160502988882 
 
 
 260 
 1230160502988882 
 
 
 261 
 1230160502988882 
 
 
 265 
 1230160502988882 
 
 
 269 
 1230160502988882 
 
 
 272 
 1230160502988882 
 
 
 274 
 1230160502988882 
 
 
 277 
 1230160502988882 
 
 
 281 
 1230160502988882 
 
 
 288 
 1230160502988882 
 
 
 289 
 1230160502988882 
 
 
 290 
 1230160502988882 
 
 
 292 
 1230160502988882 
 
 
 293 
 1230160502988882 
 
 
 296 
 1230160502988882 
 
 
 298 
 1230160502988882 
 
 
 305 
 1230160502988882 
 
 
 306 
 1230160502988882 
 
 
 313 
 1230160502988882 
 
 
 314 
 1230160502988882 
 
 
 317 
 1230160502988882 
 
 
 320 
 1230160502988882 
 
 
 324 
 1230160502988882 
 
 
 325 
 1230160502988882 
 
 
 328 
 1230160502988882 
 
 
 333 
 1230160502988882 
 
 
 337 
 1230160502988882 
 
 
 338 
 1230160502988882 
 
 
 340 
 1230160502988882 
 
 
 346 
 1230160502988882 
 
 
 349 
 1230160502988882 
 
 
 353 
 1230160502988882 
 
 
 356 
 1230160502988882 
 
 
 360 
 1230160502988882 
 
 
 361 
 1230160502988882 
 
 
 362 
 1230160502988882 
 
 
 365 
 1230160502988882 
 
 
 369 
 1230160502988882 
 
 
 370 
 1230160502988882 
 
 
 373 
 1230160502988882 
 
 
 377 
 1230160502988882 
 
 


In [ ]:
assert col['n'][5] == x

In [ ]:
x = 4

In [ ]:
%%sql
-- Indication. Supprimez les doublons.
SELECT A.n
     , salt_032({{x}} + sum(nn(A.hash) + nn(B.hash) + nn(C.hash)) OVER ()) AS token
FROM ints A
JOIN ints B ON B.n * B.n <= A.n
JOIN ints C ON C.n * C.n <= A.n
WHERE B.n * B.n + C.n * C.n = A.n
ORDER BY 1

819 rows affected.

n 
 token 
 
 
 
 
 0 
 1230160502988894 
 
 
 1 
 1230160502988894 
 
 
 1 
 1230160502988894 
 
 
 2 
 1230160502988894 
 
 
 4 
 1230160502988894 
 
 
 4 
 1230160502988894 
 
 
 5 
 1230160502988894 
 
 
 5 
 1230160502988894 
 
 
 8 
 1230160502988894 
 
 
 9 
 1230160502988894 
 
 
 9 
 1230160502988894 
 
 
 10 
 1230160502988894 
 
 
 10 
 1230160502988894 
 
 
 13 
 1230160502988894 
 
 
 13 
 1230160502988894 
 
 
 16 
 1230160502988894 
 
 
 16 
 1230160502988894 
 
 
 17 
 1230160502988894 
 
 
 17 
 1230160502988894 
 
 
 18 
 1230160502988894 
 
 
 20 
 1230160502988894 
 
 
 20 
 1230160502988894 
 
 
 25 
 1230160502988894 
 
 
 25 
 1230160502988894 
 
 
 25 
 1230160502988894 
 
 
 25 
 1230160502988894 
 
 
 26 
 1230160502988894 
 
 
 26 
 1230160502988894 
 
 
 29 
 1230160502988894 
 
 
 29 
 1230160502988894 
 
 
 32 
 1230160502988894 
 
 
 34 
 1230160502988894 
 
 
 34 
 1230160502988894 
 
 
 36 
 1230160502988894 
 
 
 36 
 1230160502988894 
 
 
 37 
 1230160502988894 
 
 
 37 
 1230160502988894 
 
 
 40 
 1230160502988894 
 
 
 40 
 1230160502988894 
 
 
 41 
 1230160502988894 
 
 
 41 
 1230160502988894 
 
 
 45 
 1230160502988894 
 
 
 45 
 1230160502988894 
 
 
 49 
 1230160502988894 
 
 
 49 
 1230160502988894 
 
 
 50 
 1230160502988894 
 
 
 50 
 1230160502988894 
 
 
 50 
 1230160502988894 
 
 
 52 
 1230160502988894 
 
 
 52 
 1230160502988894 
 
 
 53 
 1230160502988894 
 
 
 53 
 1230160502988894 
 
 
 58 
 1230160502988894 
 
 
 58 
 1230160502988894 
 
 
 61 
 1230160502988894 
 
 
 61 
 1230160502988894 
 
 
 64 
 1230160502988894 
 
 
 64 
 1230160502988894 
 
 
 65 
 1230160502988894 
 
 
 65 
 1230160502988894 
 
 
 65 
 1230160502988894 
 
 
 65 
 1230160502988894 
 
 
 68 
 1230160502988894 
 
 
 68 
 1230160502988894 
 
 
 72 
 1230160502988894 
 
 
 73 
 1230160502988894 
 
 
 73 
 1230160502988894 
 
 
 74 
 1230160502988894 
 
 
 74 
 1230160502988894 
 
 
 80 
 1230160502988894 
 
 
 80 
 1230160502988894 
 
 
 81 
 1230160502988894 
 
 
 81 
 1230160502988894 
 
 
 82 
 1230160502988894 
 
 
 82 
 1230160502988894 
 
 
 85 
 1230160502988894 
 
 
 85 
 1230160502988894 
 
 
 85 
 1230160502988894 
 
 
 85 
 1230160502988894 
 
 
 89 
 1230160502988894 
 
 
 89 
 1230160502988894 
 
 
 90 
 1230160502988894 
 
 
 90 
 1230160502988894 
 
 
 97 
 1230160502988894 
 
 
 97 
 1230160502988894 
 
 
 98 
 1230160502988894 
 
 
 100 
 1230160502988894 
 
 
 100 
 1230160502988894 
 
 
 100 
 1230160502988894 
 
 
 100 
 1230160502988894 
 
 
 101 
 1230160502988894 
 
 
 101 
 1230160502988894 
 
 
 104 
 1230160502988894 
 
 
 104 
 1230160502988894 
 
 
 106 
 1230160502988894 
 
 
 106 
 1230160502988894 
 
 
 109 
 1230160502988894 
 
 
 109 
 1230160502988894 
 
 
 113 
 1230160502988894 
 
 
 113 
 1230160502988894 
 
 
 116 
 1230160502988894 
 
 
 116 
 1230160502988894 
 
 
 117 
 1230160502988894 
 
 
 117 
 1230160502988894 
 
 
 121 
 1230160502988894 
 
 
 121 
 1230160502988894 
 
 
 122 
 1230160502988894 
 
 
 122 
 1230160502988894 
 
 
 125 
 1230160502988894 
 
 
 125 
 1230160502988894 
 
 
 125 
 1230160502988894 
 
 
 125 
 1230160502988894 
 
 
 128 
 1230160502988894 
 
 
 130 
 1230160502988894 
 
 
 130 
 1230160502988894 
 
 
 130 
 1230160502988894 
 
 
 130 
 1230160502988894 
 
 
 136 
 1230160502988894 
 
 
 136 
 1230160502988894 
 
 
 137 
 1230160502988894 
 
 
 137 
 1230160502988894 
 
 
 144 
 1230160502988894 
 
 
 144 
 1230160502988894 
 
 
 145 
 1230160502988894 
 
 
 145 
 1230160502988894 
 
 
 145 
 1230160502988894 
 
 
 145 
 1230160502988894 
 
 
 146 
 1230160502988894 
 
 
 146 
 1230160502988894 
 
 
 148 
 1230160502988894 
 
 
 148 
 1230160502988894 
 
 
 149 
 1230160502988894 
 
 
 149 
 1230160502988894 
 
 
 153 
 1230160502988894 
 
 
 153 
 1230160502988894 
 
 
 157 
 1230160502988894 
 
 
 157 
 1230160502988894 
 
 
 160 
 1230160502988894 
 
 
 160 
 1230160502988894 
 
 
 162 
 1230160502988894 
 
 
 164 
 12301605029

In [ ]:
assert col['n'][5] == x

In [ ]:
x = 676

In [ ]:
%%sql
-- Indication. Triez ces nombres par ordre croissant.
SELECT DISTINCT A.n
              , salt_032({{x}} + sum(nn(A.hash) + nn(B.hash) + nn(C.hash)) OVER ()) AS token
FROM ints A
JOIN ints B ON B.n * B.n <= A.n
JOIN ints C ON C.n * C.n <= A.n
WHERE B.n * B.n + C.n * C.n = A.n

331 rows affected.

n 
 token 
 
 
 
 
 961 
 1230160502992190 
 
 
 900 
 1230160502992190 
 
 
 841 
 1230160502992190 
 
 
 784 
 1230160502992190 
 
 
 729 
 1230160502992190 
 
 
 676 
 1230160502992190 
 
 
 625 
 1230160502992190 
 
 
 576 
 1230160502992190 
 
 
 529 
 1230160502992190 
 
 
 484 
 1230160502992190 
 
 
 441 
 1230160502992190 
 
 
 400 
 1230160502992190 
 
 
 361 
 1230160502992190 
 
 
 324 
 1230160502992190 
 
 
 289 
 1230160502992190 
 
 
 256 
 1230160502992190 
 
 
 225 
 1230160502992190 
 
 
 196 
 1230160502992190 
 
 
 169 
 1230160502992190 
 
 
 144 
 1230160502992190 
 
 
 121 
 1230160502992190 
 
 
 100 
 1230160502992190 
 
 
 81 
 1230160502992190 
 
 
 64 
 1230160502992190 
 
 
 49 
 1230160502992190 
 
 
 36 
 1230160502992190 
 
 
 25 
 1230160502992190 
 
 
 16 
 1230160502992190 
 
 
 9 
 1230160502992190 
 
 
 4 
 1230160502992190 
 
 
 1 
 1230160502992190 
 
 
 0 
 1230160502992190 
 
 
 962 
 1230160502992190 
 
 
 901 
 1230160502992190 
 
 
 842 
 1230160502992190 
 
 
 785 
 1230160502992190 
 
 
 730 
 1230160502992190 
 
 
 677 
 1230160502992190 
 
 
 626 
 1230160502992190 
 
 
 577 
 1230160502992190 
 
 
 530 
 1230160502992190 
 
 
 485 
 1230160502992190 
 
 
 442 
 1230160502992190 
 
 
 401 
 1230160502992190 
 
 
 362 
 1230160502992190 
 
 
 325 
 1230160502992190 
 
 
 290 
 1230160502992190 
 
 
 257 
 1230160502992190 
 
 
 226 
 1230160502992190 
 
 
 197 
 1230160502992190 
 
 
 170 
 1230160502992190 
 
 
 145 
 1230160502992190 
 
 
 122 
 1230160502992190 
 
 
 101 
 1230160502992190 
 
 
 82 
 1230160502992190 
 
 
 65 
 1230160502992190 
 
 
 50 
 1230160502992190 
 
 
 37 
 1230160502992190 
 
 
 26 
 1230160502992190 
 
 
 17 
 1230160502992190 
 
 
 10 
 1230160502992190 
 
 
 5 
 1230160502992190 
 
 
 2 
 1230160502992190 
 
 
 965 
 1230160502992190 
 
 
 904 
 1230160502992190 
 
 
 845 
 1230160502992190 
 
 
 788 
 1230160502992190 
 
 
 733 
 1230160502992190 
 
 
 680 
 1230160502992190 
 
 
 629 
 1230160502992190 
 
 
 580 
 1230160502992190 
 
 
 533 
 1230160502992190 
 
 
 488 
 1230160502992190 
 
 
 445 
 1230160502992190 
 
 
 404 
 1230160502992190 
 
 
 365 
 1230160502992190 
 
 
 328 
 1230160502992190 
 
 
 293 
 1230160502992190 
 
 
 260 
 1230160502992190 
 
 
 229 
 1230160502992190 
 
 
 200 
 1230160502992190 
 
 
 173 
 1230160502992190 
 
 
 148 
 1230160502992190 
 
 
 125 
 1230160502992190 
 
 
 104 
 1230160502992190 
 
 
 85 
 1230160502992190 
 
 
 68 
 1230160502992190 
 
 
 53 
 1230160502992190 
 
 
 40 
 1230160502992190 
 
 
 29 
 1230160502992190 
 
 
 20 
 1230160502992190 
 
 
 13 
 1230160502992190 
 
 
 8 
 1230160502992190 
 
 
 970 
 1230160502992190 
 
 
 909 
 1230160502992190 
 
 
 850 
 1230160502992190 
 
 
 793 
 1230160502992190 
 
 
 738 
 1230160502992190 
 
 
 685 
 1230160502992190 
 
 
 634 
 1230160502992190 
 
 
 585 
 1230160502992190 
 
 
 538 
 1230160502992190 
 
 
 493 
 1230160502992190 
 
 
 450 
 1230160502992190 
 
 
 409 
 1230160502992190 
 
 
 370 
 1230160502992190 
 
 
 333 
 1230160502992190 
 
 
 298 
 1230160502992190 
 
 
 265 
 1230160502992190 
 
 
 234 
 1230160502992190 
 
 
 205 
 1230160502992190 
 
 
 178 
 1230160502992190 
 
 
 153 
 1230160502992190 
 
 
 130 
 1230160502992190 
 
 
 109 
 1230160502992190 
 
 
 90 
 1230160502992190 
 
 
 73 
 1230160502992190 
 
 
 58 
 1230160502992190 
 
 
 45 
 1230160502992190 
 
 
 34 
 1230160502992190 
 
 
 18 
 1230160502992190 
 
 
 977 
 1230160502992190 
 
 
 916 
 1230160502992190 
 
 
 857 
 1230160502992190 
 
 
 800 
 1230160502992190 
 
 
 745 
 1230160502992190 
 
 
 692 
 1230160502992190 
 
 
 641 
 1230160502992190 
 
 
 592 
 1230160502992190 
 
 
 545 
 1230160502992190 
 
 
 500 
 1230160502992190 
 
 
 457 
 1230160502992190 
 
 
 416 
 1230160502992190 
 
 
 377 
 1230160502992190 
 
 
 340 
 1230160502992190 
 
 
 305 
 1230160502992190 
 
 
 272 
 1230160502992190 
 
 
 241 
 1230160502992190 
 
 
 212 
 123016050299

In [ ]:
assert col['n'][5] == x

**Atelier [033].** Un entier $c$ est **bicarré** si et seulement s'il peut s'écrire sous la forme $a^2+b^2$ avec $a$ et $b$ entiers.

| Exemple | Forme cherchée | Bicarré |
|---:|:--:|:--:|
| $17$ | $$1^2+4^2$$ | ✅ |
| $15$ | aucune | ❌ |

_Défi._ Listez par ordre croissant les entiers bicarrés inférieurs ou égaux à 1000.

_Contrainte._ Faites un produit cartésien de deux tables seulement.

<figure>
  <img src="https://raw.githubusercontent.com/laowantong/sqlab_ints/refs/heads/main/assets/nombre-non-bigarré.png"/>
  <figcaption>Entier non bicarré ni bigarré.</figcaption>
</figure>

In [ ]:
x = 8 # le 6e terme de cette suite
# Javascript: result[5]?.n ?? 7_531_148

In [ ]:
%%sql
-- On fait deux « boucles », l'une sur $a$, l'autre sur $b$.
-- Plutôt que de « parcourir » tous les $c$ possibles, et éliminer ceux qui ne valent pas $a^2 + b^2$,
-- on calcule directement $c = a^2 + b^2$, et on vérifie que cette somme est bien dans la table donnée
-- (pour plus de généralité, on aurait pu écrire `A.n * A.n + B.n * B.n IN (SELECT n FROM ints)`).
-- La deuxième condition du `ON` évite les doublons par symétrie (p. ex., (3, 4) et (4, 3)).
SELECT DISTINCT A.n * A.n + B.n * B.n AS n
              , salt_033({{x}} + sum(nn(A.hash) + nn(B.hash)) OVER ()) AS token
FROM ints A
JOIN ints B ON A.n * A.n + B.n * B.n <= 1000
AND A.n <= B.n
ORDER BY 1

331 rows affected.

n 
 token 
 
 
 
 
 0 
 298774613720463 
 
 
 1 
 298774613720463 
 
 
 2 
 298774613720463 
 
 
 4 
 298774613720463 
 
 
 5 
 298774613720463 
 
 
 8 
 298774613720463 
 
 
 9 
 298774613720463 
 
 
 10 
 298774613720463 
 
 
 13 
 298774613720463 
 
 
 16 
 298774613720463 
 
 
 17 
 298774613720463 
 
 
 18 
 298774613720463 
 
 
 20 
 298774613720463 
 
 
 25 
 298774613720463 
 
 
 26 
 298774613720463 
 
 
 29 
 298774613720463 
 
 
 32 
 298774613720463 
 
 
 34 
 298774613720463 
 
 
 36 
 298774613720463 
 
 
 37 
 298774613720463 
 
 
 40 
 298774613720463 
 
 
 41 
 298774613720463 
 
 
 45 
 298774613720463 
 
 
 49 
 298774613720463 
 
 
 50 
 298774613720463 
 
 
 52 
 298774613720463 
 
 
 53 
 298774613720463 
 
 
 58 
 298774613720463 
 
 
 61 
 298774613720463 
 
 
 64 
 298774613720463 
 
 
 65 
 298774613720463 
 
 
 68 
 298774613720463 
 
 
 72 
 298774613720463 
 
 
 73 
 298774613720463 
 
 
 74 
 298774613720463 
 
 
 80 
 298774613720463 
 
 
 81 
 298774613720463 
 
 
 82 
 298774613720463 
 
 
 85 
 298774613720463 
 
 
 89 
 298774613720463 
 
 
 90 
 298774613720463 
 
 
 97 
 298774613720463 
 
 
 98 
 298774613720463 
 
 
 100 
 298774613720463 
 
 
 101 
 298774613720463 
 
 
 104 
 298774613720463 
 
 
 106 
 298774613720463 
 
 
 109 
 298774613720463 
 
 
 113 
 298774613720463 
 
 
 116 
 298774613720463 
 
 
 117 
 298774613720463 
 
 
 121 
 298774613720463 
 
 
 122 
 298774613720463 
 
 
 125 
 298774613720463 
 
 
 128 
 298774613720463 
 
 
 130 
 298774613720463 
 
 
 136 
 298774613720463 
 
 
 137 
 298774613720463 
 
 
 144 
 298774613720463 
 
 
 145 
 298774613720463 
 
 
 146 
 298774613720463 
 
 
 148 
 298774613720463 
 
 
 149 
 298774613720463 
 
 
 153 
 298774613720463 
 
 
 157 
 298774613720463 
 
 
 160 
 298774613720463 
 
 
 162 
 298774613720463 
 
 
 164 
 298774613720463 
 
 
 169 
 298774613720463 
 
 
 170 
 298774613720463 
 
 
 173 
 298774613720463 
 
 
 178 
 298774613720463 
 
 
 180 
 298774613720463 
 
 
 181 
 298774613720463 
 
 
 185 
 298774613720463 
 
 
 193 
 298774613720463 
 
 
 194 
 298774613720463 
 
 
 196 
 298774613720463 
 
 
 197 
 298774613720463 
 
 
 200 
 298774613720463 
 
 
 202 
 298774613720463 
 
 
 205 
 298774613720463 
 
 
 208 
 298774613720463 
 
 
 212 
 298774613720463 
 
 
 218 
 298774613720463 
 
 
 221 
 298774613720463 
 
 
 225 
 298774613720463 
 
 
 226 
 298774613720463 
 
 
 229 
 298774613720463 
 
 
 232 
 298774613720463 
 
 
 233 
 298774613720463 
 
 
 234 
 298774613720463 
 
 
 241 
 298774613720463 
 
 
 242 
 298774613720463 
 
 
 244 
 298774613720463 
 
 
 245 
 298774613720463 
 
 
 250 
 298774613720463 
 
 
 256 
 298774613720463 
 
 
 257 
 298774613720463 
 
 
 260 
 298774613720463 
 
 
 261 
 298774613720463 
 
 
 265 
 298774613720463 
 
 
 269 
 298774613720463 
 
 
 272 
 298774613720463 
 
 
 274 
 298774613720463 
 
 
 277 
 298774613720463 
 
 
 281 
 298774613720463 
 
 
 288 
 298774613720463 
 
 
 289 
 298774613720463 
 
 
 290 
 298774613720463 
 
 
 292 
 298774613720463 
 
 
 293 
 298774613720463 
 
 
 296 
 298774613720463 
 
 
 298 
 298774613720463 
 
 
 305 
 298774613720463 
 
 
 306 
 298774613720463 
 
 
 313 
 298774613720463 
 
 
 314 
 298774613720463 
 
 
 317 
 298774613720463 
 
 
 320 
 298774613720463 
 
 
 324 
 298774613720463 
 
 
 325 
 298774613720463 
 
 
 328 
 298774613720463 
 
 
 333 
 298774613720463 
 
 
 337 
 298774613720463 
 
 
 338 
 298774613720463 
 
 
 340 
 298774613720463 
 
 
 346 
 298774613720463 
 
 
 349 
 298774613720463 
 
 
 353 
 298774613720463 
 
 
 356 
 298774613720463 
 
 
 360 
 298774613720463 
 
 
 361 
 298774613720463 
 
 
 362 
 298774613720463 
 
 
 365 
 298774613720463 
 
 
 369 
 298774613720463 
 
 
 370 
 298774613720463 
 
 
 373 
 298774613720463 
 
 
 377 
 298774613720463 
 
 
 386 
 298774613720463 
 
 
 388 
 298774613720463 
 
 
 389 
 298774613720463 
 
 
 392 
 298774613720463 
 
 
 394 
 298774613720463 
 
 

In [ ]:
assert col['n'][5] == x

### Nombres premiers

**Atelier [081].** Un entier est **premier** si et seulement s'il a exactement deux diviseurs entiers (1 et lui-même).

| Exemple | Diviseurs | Propriété | Premier |
|---:|:--:|:--:|:--:|
| $13$ | $${1, 13}$$ | exactement deux diviseurs | ✅ |
| $12$ | $${1, 2, 3, 4, 6, 12}$$ | plus de deux diviseurs | ❌ |
| $1$ | $${1}$$ | moins de deux diviseurs | ❌ |

_Défi._ Listez par ordre croissant les nombres premiers inférieurs ou égaux à 1000.

_Contrainte._ N'utilisez pas de regroupement.

In [ ]:
%%sql
SELECT n
     , salt_081(sum(nn(A.hash)) OVER ()) AS token
FROM ints A
WHERE NOT EXISTS
        (SELECT 1
         FROM ints B
         WHERE B.n BETWEEN 2 AND sqrt(A.n)
             AND A.n MOD B.n = 0 )
    AND n > 1

168 rows affected.

n 
 token 
 
 
 
 
 2 
 253352561534995 
 
 
 3 
 253352561534995 
 
 
 5 
 253352561534995 
 
 
 7 
 253352561534995 
 
 
 11 
 253352561534995 
 
 
 13 
 253352561534995 
 
 
 17 
 253352561534995 
 
 
 19 
 253352561534995 
 
 
 23 
 253352561534995 
 
 
 29 
 253352561534995 
 
 
 31 
 253352561534995 
 
 
 37 
 253352561534995 
 
 
 41 
 253352561534995 
 
 
 43 
 253352561534995 
 
 
 47 
 253352561534995 
 
 
 53 
 253352561534995 
 
 
 59 
 253352561534995 
 
 
 61 
 253352561534995 
 
 
 67 
 253352561534995 
 
 
 71 
 253352561534995 
 
 
 73 
 253352561534995 
 
 
 79 
 253352561534995 
 
 
 83 
 253352561534995 
 
 
 89 
 253352561534995 
 
 
 97 
 253352561534995 
 
 
 101 
 253352561534995 
 
 
 103 
 253352561534995 
 
 
 107 
 253352561534995 
 
 
 109 
 253352561534995 
 
 
 113 
 253352561534995 
 
 
 127 
 253352561534995 
 
 
 131 
 253352561534995 
 
 
 137 
 253352561534995 
 
 
 139 
 253352561534995 
 
 
 149 
 253352561534995 
 
 
 151 
 253352561534995 
 
 
 157 
 253352561534995 
 
 
 163 
 253352561534995 
 
 
 167 
 253352561534995 
 
 
 173 
 253352561534995 
 
 
 179 
 253352561534995 
 
 
 181 
 253352561534995 
 
 
 191 
 253352561534995 
 
 
 193 
 253352561534995 
 
 
 197 
 253352561534995 
 
 
 199 
 253352561534995 
 
 
 211 
 253352561534995 
 
 
 223 
 253352561534995 
 
 
 227 
 253352561534995 
 
 
 229 
 253352561534995 
 
 
 233 
 253352561534995 
 
 
 239 
 253352561534995 
 
 
 241 
 253352561534995 
 
 
 251 
 253352561534995 
 
 
 257 
 253352561534995 
 
 
 263 
 253352561534995 
 
 
 269 
 253352561534995 
 
 
 271 
 253352561534995 
 
 
 277 
 253352561534995 
 
 
 281 
 253352561534995 
 
 
 283 
 253352561534995 
 
 
 293 
 253352561534995 
 
 
 307 
 253352561534995 
 
 
 311 
 253352561534995 
 
 
 313 
 253352561534995 
 
 
 317 
 253352561534995 
 
 
 331 
 253352561534995 
 
 
 337 
 253352561534995 
 
 
 347 
 253352561534995 
 
 
 349 
 253352561534995 
 
 
 353 
 253352561534995 
 
 
 359 
 253352561534995 
 
 
 367 
 253352561534995 
 
 
 373 
 253352561534995 
 
 
 379 
 253352561534995 
 
 
 383 
 253352561534995 
 
 
 389 
 253352561534995 
 
 
 397 
 253352561534995 
 
 
 401 
 253352561534995 
 
 
 409 
 253352561534995 
 
 
 419 
 253352561534995 
 
 
 421 
 253352561534995 
 
 
 431 
 253352561534995 
 
 
 433 
 253352561534995 
 
 
 439 
 253352561534995 
 
 
 443 
 253352561534995 
 
 
 449 
 253352561534995 
 
 
 457 
 253352561534995 
 
 
 461 
 253352561534995 
 
 
 463 
 253352561534995 
 
 
 467 
 253352561534995 
 
 
 479 
 253352561534995 
 
 
 487 
 253352561534995 
 
 
 491 
 253352561534995 
 
 
 499 
 253352561534995 
 
 
 503 
 253352561534995 
 
 
 509 
 253352561534995 
 
 
 521 
 253352561534995 
 
 
 523 
 253352561534995 
 
 
 541 
 253352561534995 
 
 
 547 
 253352561534995 
 
 
 557 
 253352561534995 
 
 
 563 
 253352561534995 
 
 
 569 
 253352561534995 
 
 
 571 
 253352561534995 
 
 
 577 
 253352561534995 
 
 
 587 
 253352561534995 
 
 
 593 
 253352561534995 
 
 
 599 
 253352561534995 
 
 
 601 
 253352561534995 
 
 
 607 
 253352561534995 
 
 
 613 
 253352561534995 
 
 
 617 
 253352561534995 
 
 
 619 
 253352561534995 
 
 
 631 
 253352561534995 
 
 
 641 
 253352561534995 
 
 
 643 
 253352561534995 
 
 
 647 
 253352561534995 
 
 
 653 
 253352561534995 
 
 
 659 
 253352561534995 
 
 
 661 
 253352561534995 
 
 
 673 
 253352561534995 
 
 
 677 
 253352561534995 
 
 
 683 
 253352561534995 
 
 
 691 
 253352561534995 
 
 
 701 
 253352561534995 
 
 
 709 
 253352561534995 
 
 
 719 
 253352561534995 
 
 
 727 
 253352561534995 
 
 
 733 
 253352561534995 
 
 
 739 
 253352561534995 
 
 
 743 
 253352561534995 
 
 
 751 
 253352561534995 
 
 
 757 
 253352561534995 
 
 
 761 
 253352561534995 
 
 
 769 
 253352561534995 
 
 
 773 
 253352561534995 
 
 
 787 
 253352561534995 
 
 
 797 
 253352561534995 
 
 
 809 
 253352561534995 
 
 
 811 
 253352561534995 
 
 
 821 
 253352561534995 
 
 
 823 
 253352561534995 
 
 
 827 


In [ ]:
%%sql
-- Variante. Avec une requête imbriquée dans le WHERE.
SELECT A.n
     , salt_081(sum(nn(A.hash)) OVER ()) AS token
FROM ints A
WHERE A.n > 1
    AND A.n NOT IN
        (SELECT A2.n
         FROM ints A2
         JOIN ints B ON B.n BETWEEN 2 AND sqrt(A2.n)
         AND A2.n MOD B.n = 0)

168 rows affected.

n 
 token 
 
 
 
 
 2 
 253352561534995 
 
 
 3 
 253352561534995 
 
 
 5 
 253352561534995 
 
 
 7 
 253352561534995 
 
 
 11 
 253352561534995 
 
 
 13 
 253352561534995 
 
 
 17 
 253352561534995 
 
 
 19 
 253352561534995 
 
 
 23 
 253352561534995 
 
 
 29 
 253352561534995 
 
 
 31 
 253352561534995 
 
 
 37 
 253352561534995 
 
 
 41 
 253352561534995 
 
 
 43 
 253352561534995 
 
 
 47 
 253352561534995 
 
 
 53 
 253352561534995 
 
 
 59 
 253352561534995 
 
 
 61 
 253352561534995 
 
 
 67 
 253352561534995 
 
 
 71 
 253352561534995 
 
 
 73 
 253352561534995 
 
 
 79 
 253352561534995 
 
 
 83 
 253352561534995 
 
 
 89 
 253352561534995 
 
 
 97 
 253352561534995 
 
 
 101 
 253352561534995 
 
 
 103 
 253352561534995 
 
 
 107 
 253352561534995 
 
 
 109 
 253352561534995 
 
 
 113 
 253352561534995 
 
 
 127 
 253352561534995 
 
 
 131 
 253352561534995 
 
 
 137 
 253352561534995 
 
 
 139 
 253352561534995 
 
 
 149 
 253352561534995 
 
 
 151 
 253352561534995 
 
 
 157 
 253352561534995 
 
 
 163 
 253352561534995 
 
 
 167 
 253352561534995 
 
 
 173 
 253352561534995 
 
 
 179 
 253352561534995 
 
 
 181 
 253352561534995 
 
 
 191 
 253352561534995 
 
 
 193 
 253352561534995 
 
 
 197 
 253352561534995 
 
 
 199 
 253352561534995 
 
 
 211 
 253352561534995 
 
 
 223 
 253352561534995 
 
 
 227 
 253352561534995 
 
 
 229 
 253352561534995 
 
 
 233 
 253352561534995 
 
 
 239 
 253352561534995 
 
 
 241 
 253352561534995 
 
 
 251 
 253352561534995 
 
 
 257 
 253352561534995 
 
 
 263 
 253352561534995 
 
 
 269 
 253352561534995 
 
 
 271 
 253352561534995 
 
 
 277 
 253352561534995 
 
 
 281 
 253352561534995 
 
 
 283 
 253352561534995 
 
 
 293 
 253352561534995 
 
 
 307 
 253352561534995 
 
 
 311 
 253352561534995 
 
 
 313 
 253352561534995 
 
 
 317 
 253352561534995 
 
 
 331 
 253352561534995 
 
 
 337 
 253352561534995 
 
 
 347 
 253352561534995 
 
 
 349 
 253352561534995 
 
 
 353 
 253352561534995 
 
 
 359 
 253352561534995 
 
 
 367 
 253352561534995 
 
 
 373 
 253352561534995 
 
 
 379 
 253352561534995 
 
 
 383 
 253352561534995 
 
 
 389 
 253352561534995 
 
 
 397 
 253352561534995 
 
 
 401 
 253352561534995 
 
 
 409 
 253352561534995 
 
 
 419 
 253352561534995 
 
 
 421 
 253352561534995 
 
 
 431 
 253352561534995 
 
 
 433 
 253352561534995 
 
 
 439 
 253352561534995 
 
 
 443 
 253352561534995 
 
 
 449 
 253352561534995 
 
 
 457 
 253352561534995 
 
 
 461 
 253352561534995 
 
 
 463 
 253352561534995 
 
 
 467 
 253352561534995 
 
 
 479 
 253352561534995 
 
 
 487 
 253352561534995 
 
 
 491 
 253352561534995 
 
 
 499 
 253352561534995 
 
 
 503 
 253352561534995 
 
 
 509 
 253352561534995 
 
 
 521 
 253352561534995 
 
 
 523 
 253352561534995 
 
 
 541 
 253352561534995 
 
 
 547 
 253352561534995 
 
 
 557 
 253352561534995 
 
 
 563 
 253352561534995 
 
 
 569 
 253352561534995 
 
 
 571 
 253352561534995 
 
 
 577 
 253352561534995 
 
 
 587 
 253352561534995 
 
 
 593 
 253352561534995 
 
 
 599 
 253352561534995 
 
 
 601 
 253352561534995 
 
 
 607 
 253352561534995 
 
 
 613 
 253352561534995 
 
 
 617 
 253352561534995 
 
 
 619 
 253352561534995 
 
 
 631 
 253352561534995 
 
 
 641 
 253352561534995 
 
 
 643 
 253352561534995 
 
 
 647 
 253352561534995 
 
 
 653 
 253352561534995 
 
 
 659 
 253352561534995 
 
 
 661 
 253352561534995 
 
 
 673 
 253352561534995 
 
 
 677 
 253352561534995 
 
 
 683 
 253352561534995 
 
 
 691 
 253352561534995 
 
 
 701 
 253352561534995 
 
 
 709 
 253352561534995 
 
 
 719 
 253352561534995 
 
 
 727 
 253352561534995 
 
 
 733 
 253352561534995 
 
 
 739 
 253352561534995 
 
 
 743 
 253352561534995 
 
 
 751 
 253352561534995 
 
 
 757 
 253352561534995 
 
 
 761 
 253352561534995 
 
 
 769 
 253352561534995 
 
 
 773 
 253352561534995 
 
 
 787 
 253352561534995 
 
 
 797 
 253352561534995 
 
 
 809 
 253352561534995 
 
 
 811 
 253352561534995 
 
 
 821 
 253352561534995 
 
 
 823 
 253352561534995 
 
 
 827 


**Atelier [082].** Un entier est **premier** si et seulement s'il a exactement deux diviseurs entiers (1 et lui-même).

| Exemple | Diviseurs | Propriété | Premier |
|---:|:--:|:--:|:--:|
| $13$ | $${1, 13}$$ | exactement deux diviseurs | ✅ |
| $12$ | $${1, 2, 3, 4, 6, 12}$$ | plus de deux diviseurs | ❌ |
| $1$ | $${1}$$ | moins de deux diviseurs | ❌ |

_Défi._ Listez par ordre croissant les nombres premiers inférieurs ou égaux à 1000.

_Contrainte._ Utilisez un regroupement.

In [ ]:
%%sql
SELECT A.n
     , salt_082(bit_xor(sum(nn(A.hash))) OVER ()) AS token
FROM ints A
LEFT JOIN ints B ON B.n BETWEEN 2 AND sqrt(A.n)
AND A.n MOD B.n = 0
WHERE A.n > 1
GROUP BY A.n
HAVING count(B.n) = 0

168 rows affected.

n 
 token 
 
 
 
 
 2 
 156364735562291 
 
 
 3 
 156364735562291 
 
 
 5 
 156364735562291 
 
 
 7 
 156364735562291 
 
 
 11 
 156364735562291 
 
 
 13 
 156364735562291 
 
 
 17 
 156364735562291 
 
 
 19 
 156364735562291 
 
 
 23 
 156364735562291 
 
 
 29 
 156364735562291 
 
 
 31 
 156364735562291 
 
 
 37 
 156364735562291 
 
 
 41 
 156364735562291 
 
 
 43 
 156364735562291 
 
 
 47 
 156364735562291 
 
 
 53 
 156364735562291 
 
 
 59 
 156364735562291 
 
 
 61 
 156364735562291 
 
 
 67 
 156364735562291 
 
 
 71 
 156364735562291 
 
 
 73 
 156364735562291 
 
 
 79 
 156364735562291 
 
 
 83 
 156364735562291 
 
 
 89 
 156364735562291 
 
 
 97 
 156364735562291 
 
 
 101 
 156364735562291 
 
 
 103 
 156364735562291 
 
 
 107 
 156364735562291 
 
 
 109 
 156364735562291 
 
 
 113 
 156364735562291 
 
 
 127 
 156364735562291 
 
 
 131 
 156364735562291 
 
 
 137 
 156364735562291 
 
 
 139 
 156364735562291 
 
 
 149 
 156364735562291 
 
 
 151 
 156364735562291 
 
 
 157 
 156364735562291 
 
 
 163 
 156364735562291 
 
 
 167 
 156364735562291 
 
 
 173 
 156364735562291 
 
 
 179 
 156364735562291 
 
 
 181 
 156364735562291 
 
 
 191 
 156364735562291 
 
 
 193 
 156364735562291 
 
 
 197 
 156364735562291 
 
 
 199 
 156364735562291 
 
 
 211 
 156364735562291 
 
 
 223 
 156364735562291 
 
 
 227 
 156364735562291 
 
 
 229 
 156364735562291 
 
 
 233 
 156364735562291 
 
 
 239 
 156364735562291 
 
 
 241 
 156364735562291 
 
 
 251 
 156364735562291 
 
 
 257 
 156364735562291 
 
 
 263 
 156364735562291 
 
 
 269 
 156364735562291 
 
 
 271 
 156364735562291 
 
 
 277 
 156364735562291 
 
 
 281 
 156364735562291 
 
 
 283 
 156364735562291 
 
 
 293 
 156364735562291 
 
 
 307 
 156364735562291 
 
 
 311 
 156364735562291 
 
 
 313 
 156364735562291 
 
 
 317 
 156364735562291 
 
 
 331 
 156364735562291 
 
 
 337 
 156364735562291 
 
 
 347 
 156364735562291 
 
 
 349 
 156364735562291 
 
 
 353 
 156364735562291 
 
 
 359 
 156364735562291 
 
 
 367 
 156364735562291 
 
 
 373 
 156364735562291 
 
 
 379 
 156364735562291 
 
 
 383 
 156364735562291 
 
 
 389 
 156364735562291 
 
 
 397 
 156364735562291 
 
 
 401 
 156364735562291 
 
 
 409 
 156364735562291 
 
 
 419 
 156364735562291 
 
 
 421 
 156364735562291 
 
 
 431 
 156364735562291 
 
 
 433 
 156364735562291 
 
 
 439 
 156364735562291 
 
 
 443 
 156364735562291 
 
 
 449 
 156364735562291 
 
 
 457 
 156364735562291 
 
 
 461 
 156364735562291 
 
 
 463 
 156364735562291 
 
 
 467 
 156364735562291 
 
 
 479 
 156364735562291 
 
 
 487 
 156364735562291 
 
 
 491 
 156364735562291 
 
 
 499 
 156364735562291 
 
 
 503 
 156364735562291 
 
 
 509 
 156364735562291 
 
 
 521 
 156364735562291 
 
 
 523 
 156364735562291 
 
 
 541 
 156364735562291 
 
 
 547 
 156364735562291 
 
 
 557 
 156364735562291 
 
 
 563 
 156364735562291 
 
 
 569 
 156364735562291 
 
 
 571 
 156364735562291 
 
 
 577 
 156364735562291 
 
 
 587 
 156364735562291 
 
 
 593 
 156364735562291 
 
 
 599 
 156364735562291 
 
 
 601 
 156364735562291 
 
 
 607 
 156364735562291 
 
 
 613 
 156364735562291 
 
 
 617 
 156364735562291 
 
 
 619 
 156364735562291 
 
 
 631 
 156364735562291 
 
 
 641 
 156364735562291 
 
 
 643 
 156364735562291 
 
 
 647 
 156364735562291 
 
 
 653 
 156364735562291 
 
 
 659 
 156364735562291 
 
 
 661 
 156364735562291 
 
 
 673 
 156364735562291 
 
 
 677 
 156364735562291 
 
 
 683 
 156364735562291 
 
 
 691 
 156364735562291 
 
 
 701 
 156364735562291 
 
 
 709 
 156364735562291 
 
 
 719 
 156364735562291 
 
 
 727 
 156364735562291 
 
 
 733 
 156364735562291 
 
 
 739 
 156364735562291 
 
 
 743 
 156364735562291 
 
 
 751 
 156364735562291 
 
 
 757 
 156364735562291 
 
 
 761 
 156364735562291 
 
 
 769 
 156364735562291 
 
 
 773 
 156364735562291 
 
 
 787 
 156364735562291 
 
 
 797 
 156364735562291 
 
 
 809 
 156364735562291 
 
 
 811 
 156364735562291 
 
 
 821 
 156364735562291 
 
 
 823 
 156364735562291 
 
 
 827 


In [ ]:
%%sql
-- Indication. 0 et 1 ne sont pas premiers.
SELECT A.n
     , salt_082(bit_xor(sum(nn(A.hash))) OVER ()) AS token
FROM ints A
LEFT JOIN ints B ON B.n BETWEEN 2 AND sqrt(A.n)
AND A.n MOD B.n = 0
GROUP BY A.n
HAVING count(B.n) = 0

170 rows affected.

n 
 token 
 
 
 
 
 0 
 156596690231090 
 
 
 1 
 156596690231090 
 
 
 2 
 156596690231090 
 
 
 3 
 156596690231090 
 
 
 5 
 156596690231090 
 
 
 7 
 156596690231090 
 
 
 11 
 156596690231090 
 
 
 13 
 156596690231090 
 
 
 17 
 156596690231090 
 
 
 19 
 156596690231090 
 
 
 23 
 156596690231090 
 
 
 29 
 156596690231090 
 
 
 31 
 156596690231090 
 
 
 37 
 156596690231090 
 
 
 41 
 156596690231090 
 
 
 43 
 156596690231090 
 
 
 47 
 156596690231090 
 
 
 53 
 156596690231090 
 
 
 59 
 156596690231090 
 
 
 61 
 156596690231090 
 
 
 67 
 156596690231090 
 
 
 71 
 156596690231090 
 
 
 73 
 156596690231090 
 
 
 79 
 156596690231090 
 
 
 83 
 156596690231090 
 
 
 89 
 156596690231090 
 
 
 97 
 156596690231090 
 
 
 101 
 156596690231090 
 
 
 103 
 156596690231090 
 
 
 107 
 156596690231090 
 
 
 109 
 156596690231090 
 
 
 113 
 156596690231090 
 
 
 127 
 156596690231090 
 
 
 131 
 156596690231090 
 
 
 137 
 156596690231090 
 
 
 139 
 156596690231090 
 
 
 149 
 156596690231090 
 
 
 151 
 156596690231090 
 
 
 157 
 156596690231090 
 
 
 163 
 156596690231090 
 
 
 167 
 156596690231090 
 
 
 173 
 156596690231090 
 
 
 179 
 156596690231090 
 
 
 181 
 156596690231090 
 
 
 191 
 156596690231090 
 
 
 193 
 156596690231090 
 
 
 197 
 156596690231090 
 
 
 199 
 156596690231090 
 
 
 211 
 156596690231090 
 
 
 223 
 156596690231090 
 
 
 227 
 156596690231090 
 
 
 229 
 156596690231090 
 
 
 233 
 156596690231090 
 
 
 239 
 156596690231090 
 
 
 241 
 156596690231090 
 
 
 251 
 156596690231090 
 
 
 257 
 156596690231090 
 
 
 263 
 156596690231090 
 
 
 269 
 156596690231090 
 
 
 271 
 156596690231090 
 
 
 277 
 156596690231090 
 
 
 281 
 156596690231090 
 
 
 283 
 156596690231090 
 
 
 293 
 156596690231090 
 
 
 307 
 156596690231090 
 
 
 311 
 156596690231090 
 
 
 313 
 156596690231090 
 
 
 317 
 156596690231090 
 
 
 331 
 156596690231090 
 
 
 337 
 156596690231090 
 
 
 347 
 156596690231090 
 
 
 349 
 156596690231090 
 
 
 353 
 156596690231090 
 
 
 359 
 156596690231090 
 
 
 367 
 156596690231090 
 
 
 373 
 156596690231090 
 
 
 379 
 156596690231090 
 
 
 383 
 156596690231090 
 
 
 389 
 156596690231090 
 
 
 397 
 156596690231090 
 
 
 401 
 156596690231090 
 
 
 409 
 156596690231090 
 
 
 419 
 156596690231090 
 
 
 421 
 156596690231090 
 
 
 431 
 156596690231090 
 
 
 433 
 156596690231090 
 
 
 439 
 156596690231090 
 
 
 443 
 156596690231090 
 
 
 449 
 156596690231090 
 
 
 457 
 156596690231090 
 
 
 461 
 156596690231090 
 
 
 463 
 156596690231090 
 
 
 467 
 156596690231090 
 
 
 479 
 156596690231090 
 
 
 487 
 156596690231090 
 
 
 491 
 156596690231090 
 
 
 499 
 156596690231090 
 
 
 503 
 156596690231090 
 
 
 509 
 156596690231090 
 
 
 521 
 156596690231090 
 
 
 523 
 156596690231090 
 
 
 541 
 156596690231090 
 
 
 547 
 156596690231090 
 
 
 557 
 156596690231090 
 
 
 563 
 156596690231090 
 
 
 569 
 156596690231090 
 
 
 571 
 156596690231090 
 
 
 577 
 156596690231090 
 
 
 587 
 156596690231090 
 
 
 593 
 156596690231090 
 
 
 599 
 156596690231090 
 
 
 601 
 156596690231090 
 
 
 607 
 156596690231090 
 
 
 613 
 156596690231090 
 
 
 617 
 156596690231090 
 
 
 619 
 156596690231090 
 
 
 631 
 156596690231090 
 
 
 641 
 156596690231090 
 
 
 643 
 156596690231090 
 
 
 647 
 156596690231090 
 
 
 653 
 156596690231090 
 
 
 659 
 156596690231090 
 
 
 661 
 156596690231090 
 
 
 673 
 156596690231090 
 
 
 677 
 156596690231090 
 
 
 683 
 156596690231090 
 
 
 691 
 156596690231090 
 
 
 701 
 156596690231090 
 
 
 709 
 156596690231090 
 
 
 719 
 156596690231090 
 
 
 727 
 156596690231090 
 
 
 733 
 156596690231090 
 
 
 739 
 156596690231090 
 
 
 743 
 156596690231090 
 
 
 751 
 156596690231090 
 
 
 757 
 156596690231090 
 
 
 761 
 156596690231090 
 
 
 769 
 156596690231090 
 
 
 773 
 156596690231090 
 
 
 787 
 156596690231090 
 
 
 797 
 156596690231090 
 
 
 809 
 156596690231090 
 
 
 811 
 156596690231090 
 
 
 821 
 156

In [ ]:
%%sql
-- Indication. 1 n'est pas premier.
SELECT A.n
     , salt_082(bit_xor(sum(nn(A.hash))) OVER ()) AS token
FROM ints A
LEFT JOIN ints B ON B.n BETWEEN 2 AND sqrt(A.n)
AND A.n MOD B.n = 0
WHERE A.n != 0
GROUP BY A.n
HAVING count(B.n) = 0

169 rows affected.

n 
 token 
 
 
 
 
 1 
 156189361184507 
 
 
 2 
 156189361184507 
 
 
 3 
 156189361184507 
 
 
 5 
 156189361184507 
 
 
 7 
 156189361184507 
 
 
 11 
 156189361184507 
 
 
 13 
 156189361184507 
 
 
 17 
 156189361184507 
 
 
 19 
 156189361184507 
 
 
 23 
 156189361184507 
 
 
 29 
 156189361184507 
 
 
 31 
 156189361184507 
 
 
 37 
 156189361184507 
 
 
 41 
 156189361184507 
 
 
 43 
 156189361184507 
 
 
 47 
 156189361184507 
 
 
 53 
 156189361184507 
 
 
 59 
 156189361184507 
 
 
 61 
 156189361184507 
 
 
 67 
 156189361184507 
 
 
 71 
 156189361184507 
 
 
 73 
 156189361184507 
 
 
 79 
 156189361184507 
 
 
 83 
 156189361184507 
 
 
 89 
 156189361184507 
 
 
 97 
 156189361184507 
 
 
 101 
 156189361184507 
 
 
 103 
 156189361184507 
 
 
 107 
 156189361184507 
 
 
 109 
 156189361184507 
 
 
 113 
 156189361184507 
 
 
 127 
 156189361184507 
 
 
 131 
 156189361184507 
 
 
 137 
 156189361184507 
 
 
 139 
 156189361184507 
 
 
 149 
 156189361184507 
 
 
 151 
 156189361184507 
 
 
 157 
 156189361184507 
 
 
 163 
 156189361184507 
 
 
 167 
 156189361184507 
 
 
 173 
 156189361184507 
 
 
 179 
 156189361184507 
 
 
 181 
 156189361184507 
 
 
 191 
 156189361184507 
 
 
 193 
 156189361184507 
 
 
 197 
 156189361184507 
 
 
 199 
 156189361184507 
 
 
 211 
 156189361184507 
 
 
 223 
 156189361184507 
 
 
 227 
 156189361184507 
 
 
 229 
 156189361184507 
 
 
 233 
 156189361184507 
 
 
 239 
 156189361184507 
 
 
 241 
 156189361184507 
 
 
 251 
 156189361184507 
 
 
 257 
 156189361184507 
 
 
 263 
 156189361184507 
 
 
 269 
 156189361184507 
 
 
 271 
 156189361184507 
 
 
 277 
 156189361184507 
 
 
 281 
 156189361184507 
 
 
 283 
 156189361184507 
 
 
 293 
 156189361184507 
 
 
 307 
 156189361184507 
 
 
 311 
 156189361184507 
 
 
 313 
 156189361184507 
 
 
 317 
 156189361184507 
 
 
 331 
 156189361184507 
 
 
 337 
 156189361184507 
 
 
 347 
 156189361184507 
 
 
 349 
 156189361184507 
 
 
 353 
 156189361184507 
 
 
 359 
 156189361184507 
 
 
 367 
 156189361184507 
 
 
 373 
 156189361184507 
 
 
 379 
 156189361184507 
 
 
 383 
 156189361184507 
 
 
 389 
 156189361184507 
 
 
 397 
 156189361184507 
 
 
 401 
 156189361184507 
 
 
 409 
 156189361184507 
 
 
 419 
 156189361184507 
 
 
 421 
 156189361184507 
 
 
 431 
 156189361184507 
 
 
 433 
 156189361184507 
 
 
 439 
 156189361184507 
 
 
 443 
 156189361184507 
 
 
 449 
 156189361184507 
 
 
 457 
 156189361184507 
 
 
 461 
 156189361184507 
 
 
 463 
 156189361184507 
 
 
 467 
 156189361184507 
 
 
 479 
 156189361184507 
 
 
 487 
 156189361184507 
 
 
 491 
 156189361184507 
 
 
 499 
 156189361184507 
 
 
 503 
 156189361184507 
 
 
 509 
 156189361184507 
 
 
 521 
 156189361184507 
 
 
 523 
 156189361184507 
 
 
 541 
 156189361184507 
 
 
 547 
 156189361184507 
 
 
 557 
 156189361184507 
 
 
 563 
 156189361184507 
 
 
 569 
 156189361184507 
 
 
 571 
 156189361184507 
 
 
 577 
 156189361184507 
 
 
 587 
 156189361184507 
 
 
 593 
 156189361184507 
 
 
 599 
 156189361184507 
 
 
 601 
 156189361184507 
 
 
 607 
 156189361184507 
 
 
 613 
 156189361184507 
 
 
 617 
 156189361184507 
 
 
 619 
 156189361184507 
 
 
 631 
 156189361184507 
 
 
 641 
 156189361184507 
 
 
 643 
 156189361184507 
 
 
 647 
 156189361184507 
 
 
 653 
 156189361184507 
 
 
 659 
 156189361184507 
 
 
 661 
 156189361184507 
 
 
 673 
 156189361184507 
 
 
 677 
 156189361184507 
 
 
 683 
 156189361184507 
 
 
 691 
 156189361184507 
 
 
 701 
 156189361184507 
 
 
 709 
 156189361184507 
 
 
 719 
 156189361184507 
 
 
 727 
 156189361184507 
 
 
 733 
 156189361184507 
 
 
 739 
 156189361184507 
 
 
 743 
 156189361184507 
 
 
 751 
 156189361184507 
 
 
 757 
 156189361184507 
 
 
 761 
 156189361184507 
 
 
 769 
 156189361184507 
 
 
 773 
 156189361184507 
 
 
 787 
 156189361184507 
 
 
 797 
 156189361184507 
 
 
 809 
 156189361184507 
 
 
 811 
 156189361184507 
 
 
 821 
 156189361184507 
 
 
 823 
 1

**Atelier [062].** Un entier est **composite** si et seulement s'il a plus de deux diviseurs entiers (1 et lui-même).

| n | Diviseurs |
|---:|:--|
|4 | 1 2 4 |
|6 | 1 2 6 |
|8 | 1 2 8 |
|9 | 1 3 9 |
|10 | 1 2 10 |
|12 | 1 2 3 12 |

_Défi._ Listez par ordre croissant les nombres composites inférieurs ou égaux à 1000 avec la liste de leurs diviseurs séparés un espace comme dans la table ci-dessus.

_Aide._ Une simple variation du calcul des nombres premiers pour découvrir la fonction d'agrégation [`group_concat()`](https://dev.mysql.com/doc/refman/8.4/en/aggregate-functions.html#function_group-concat).

In [ ]:
x = '1 2 3 4 24' # la 14e liste de diviseurs, séparés par un espace
# Javascript: result[13]?.divisors ?? 7_531_148

In [ ]:
%%sql
SELECT A.n
     , group_concat(B.n
                    ORDER BY B.n ASC SEPARATOR ' ') AS divisors
     , salt_062(string_hash('{{x}}') + bit_xor(sum(nn(A.hash))) OVER ()) AS token
FROM ints A
JOIN ints B ON A.n MOD B.n = 0
WHERE B.n = A.n
    OR B.n BETWEEN 1 AND sqrt(A.n)
GROUP BY A.n
HAVING count(B.n) > 2

831 rows affected.

n 
 divisors 
 token 
 
 
 
 
 4 
 1 2 4 
 92857264956831 
 
 
 6 
 1 2 6 
 92857264956831 
 
 
 8 
 1 2 8 
 92857264956831 
 
 
 9 
 1 3 9 
 92857264956831 
 
 
 10 
 1 2 10 
 92857264956831 
 
 
 12 
 1 2 3 12 
 92857264956831 
 
 
 14 
 1 2 14 
 92857264956831 
 
 
 15 
 1 3 15 
 92857264956831 
 
 
 16 
 1 2 4 16 
 92857264956831 
 
 
 18 
 1 2 3 18 
 92857264956831 
 
 
 20 
 1 2 4 20 
 92857264956831 
 
 
 21 
 1 3 21 
 92857264956831 
 
 
 22 
 1 2 22 
 92857264956831 
 
 
 24 
 1 2 3 4 24 
 92857264956831 
 
 
 25 
 1 5 25 
 92857264956831 
 
 
 26 
 1 2 26 
 92857264956831 
 
 
 27 
 1 3 27 
 92857264956831 
 
 
 28 
 1 2 4 28 
 92857264956831 
 
 
 30 
 1 2 3 5 30 
 92857264956831 
 
 
 32 
 1 2 4 32 
 92857264956831 
 
 
 33 
 1 3 33 
 92857264956831 
 
 
 34 
 1 2 34 
 92857264956831 
 
 
 35 
 1 5 35 
 92857264956831 
 
 
 36 
 1 2 3 4 6 36 
 92857264956831 
 
 
 38 
 1 2 38 
 92857264956831 
 
 
 39 
 1 3 39 
 92857264956831 
 
 
 40 
 1 2 4 5 40 
 92857264956831 
 
 
 42 
 1 2 3 6 42 
 92857264956831 
 
 
 44 
 1 2 4 44 
 92857264956831 
 
 
 45 
 1 3 5 45 
 92857264956831 
 
 
 46 
 1 2 46 
 92857264956831 
 
 
 48 
 1 2 3 4 6 48 
 92857264956831 
 
 
 49 
 1 7 49 
 92857264956831 
 
 
 50 
 1 2 5 50 
 92857264956831 
 
 
 51 
 1 3 51 
 92857264956831 
 
 
 52 
 1 2 4 52 
 92857264956831 
 
 
 54 
 1 2 3 6 54 
 92857264956831 
 
 
 55 
 1 5 55 
 92857264956831 
 
 
 56 
 1 2 4 7 56 
 92857264956831 
 
 
 57 
 1 3 57 
 92857264956831 
 
 
 58 
 1 2 58 
 92857264956831 
 
 
 60 
 1 2 3 4 5 6 60 
 92857264956831 
 
 
 62 
 1 2 62 
 92857264956831 
 
 
 63 
 1 3 7 63 
 92857264956831 
 
 
 64 
 1 2 4 8 64 
 92857264956831 
 
 
 65 
 1 5 65 
 92857264956831 
 
 
 66 
 1 2 3 6 66 
 92857264956831 
 
 
 68 
 1 2 4 68 
 92857264956831 
 
 
 69 
 1 3 69 
 92857264956831 
 
 
 70 
 1 2 5 7 70 
 92857264956831 
 
 
 72 
 1 2 3 4 6 8 72 
 92857264956831 
 
 
 74 
 1 2 74 
 92857264956831 
 
 
 75 
 1 3 5 75 
 92857264956831 
 
 
 76 
 1 2 4 76 
 92857264956831 
 
 
 77 
 1 7 77 
 92857264956831 
 
 
 78 
 1 2 3 6 78 
 92857264956831 
 
 
 80 
 1 2 4 5 8 80 
 92857264956831 
 
 
 81 
 1 3 9 81 
 92857264956831 
 
 
 82 
 1 2 82 
 92857264956831 
 
 
 84 
 1 2 3 4 6 7 84 
 92857264956831 
 
 
 85 
 1 5 85 
 92857264956831 
 
 
 86 
 1 2 86 
 92857264956831 
 
 
 87 
 1 3 87 
 92857264956831 
 
 
 88 
 1 2 4 8 88 
 92857264956831 
 
 
 90 
 1 2 3 5 6 9 90 
 92857264956831 
 
 
 91 
 1 7 91 
 92857264956831 
 
 
 92 
 1 2 4 92 
 92857264956831 
 
 
 93 
 1 3 93 
 92857264956831 
 
 
 94 
 1 2 94 
 92857264956831 
 
 
 95 
 1 5 95 
 92857264956831 
 
 
 96 
 1 2 3 4 6 8 96 
 92857264956831 
 
 
 98 
 1 2 7 98 
 92857264956831 
 
 
 99 
 1 3 9 99 
 92857264956831 
 
 
 100 
 1 2 4 5 10 100 
 92857264956831 
 
 
 102 
 1 2 3 6 102 
 92857264956831 
 
 
 104 
 1 2 4 8 104 
 92857264956831 
 
 
 105 
 1 3 5 7 105 
 92857264956831 
 
 
 106 
 1 2 106 
 92857264956831 
 
 
 108 
 1 2 3 4 6 9 108 
 92857264956831 
 
 
 110 
 1 2 5 10 110 
 92857264956831 
 
 
 111 
 1 3 111 
 92857264956831 
 
 
 112 
 1 2 4 7 8 112 
 92857264956831 
 
 
 114 
 1 2 3 6 114 
 92857264956831 
 
 
 115 
 1 5 115 
 92857264956831 
 
 
 116 
 1 2 4 116 
 92857264956831 
 
 
 117 
 1 3 9 117 
 92857264956831 
 
 
 118 
 1 2 118 
 92857264956831 
 
 
 119 
 1 7 119 
 92857264956831 
 
 
 120 
 1 2 3 4 5 6 8 10 120 
 92857264956831 
 
 
 121 
 1 11 121 
 92857264956831 
 
 
 122 
 1 2 122 
 92857264956831 
 
 
 123 
 1 3 123 
 92857264956831 
 
 
 124 
 1 2 4 124 
 92857264956831 
 
 
 125 
 1 5 125 
 92857264956831 
 
 
 126 
 1 2 3 6 7 9 126 
 92857264956831 
 
 
 128 
 1 2 4 8 128 
 92857264956831 
 
 
 129 
 1 3 129 
 92857264956831 
 
 
 130 
 1 2 5 10 130 
 92857264956831 
 
 
 132 
 1 2 3 4 6 11 132 
 92857264956831 
 
 
 133 
 1 7 133 
 92857264956831 
 
 
 134 
 1 2 134 
 92857264956831 
 
 
 135 
 1 3 5 9 135 
 92857264956831 
 
 
 136 
 1 2 4 8 136 
 92857264956831 
 
 
 138 
 1 2 3 6 138 
 92857264956831 
 
 
 140 
 1 2 4 5 7 10 140 
 928572649568

In [ ]:
assert col['divisors'][13] == x

### Nombres abondants

**Atelier [023].** Un entier $n$ est **abondant** si et seulement s'il est inférieur à la somme de ses diviseurs stricts (_i.e._, distincts de $n$).

| Exemple | Diviseurs stricts | Propriété | Abondant |
|---:|:--:|:--:|:--:|
| $12$ | $${1, 2, 3, 4, 6}$$ | $$12 < 1+2+3+4+6 = 16$$ | ✅ |
| $16$ | $${1, 2, 4, 8}$$ | $$16 \geq 1+2+4+8 = 15$$ | ❌ |

_Défi._ Listez par ordre croissant les nombres abondants inférieurs ou égaux à 1000.

_Contrainte._ Utilisez une auto-jointure et un regroupement.

In [ ]:
x = 36 # le 6e terme de cette suite
# Javascript: result[5]?.['n'] ?? 7_531_148

In [ ]:
%%sql
SELECT A.n
     , salt_023({{x}} + bit_xor(sum(nn(A.hash) + nn(B.hash))) OVER ()) AS token
FROM ints A
JOIN ints B ON B.n < A.n
AND A.n MOD B.n = 0
GROUP BY A.n
HAVING A.n < sum(B.n)
ORDER BY 1

246 rows affected.

n 
 token 
 
 
 
 
 12 
 5591408610389 
 
 
 18 
 5591408610389 
 
 
 20 
 5591408610389 
 
 
 24 
 5591408610389 
 
 
 30 
 5591408610389 
 
 
 36 
 5591408610389 
 
 
 40 
 5591408610389 
 
 
 42 
 5591408610389 
 
 
 48 
 5591408610389 
 
 
 54 
 5591408610389 
 
 
 56 
 5591408610389 
 
 
 60 
 5591408610389 
 
 
 66 
 5591408610389 
 
 
 70 
 5591408610389 
 
 
 72 
 5591408610389 
 
 
 78 
 5591408610389 
 
 
 80 
 5591408610389 
 
 
 84 
 5591408610389 
 
 
 88 
 5591408610389 
 
 
 90 
 5591408610389 
 
 
 96 
 5591408610389 
 
 
 100 
 5591408610389 
 
 
 102 
 5591408610389 
 
 
 104 
 5591408610389 
 
 
 108 
 5591408610389 
 
 
 112 
 5591408610389 
 
 
 114 
 5591408610389 
 
 
 120 
 5591408610389 
 
 
 126 
 5591408610389 
 
 
 132 
 5591408610389 
 
 
 138 
 5591408610389 
 
 
 140 
 5591408610389 
 
 
 144 
 5591408610389 
 
 
 150 
 5591408610389 
 
 
 156 
 5591408610389 
 
 
 160 
 5591408610389 
 
 
 162 
 5591408610389 
 
 
 168 
 5591408610389 
 
 
 174 
 5591408610389 
 
 
 176 
 5591408610389 
 
 
 180 
 5591408610389 
 
 
 186 
 5591408610389 
 
 
 192 
 5591408610389 
 
 
 196 
 5591408610389 
 
 
 198 
 5591408610389 
 
 
 200 
 5591408610389 
 
 
 204 
 5591408610389 
 
 
 208 
 5591408610389 
 
 
 210 
 5591408610389 
 
 
 216 
 5591408610389 
 
 
 220 
 5591408610389 
 
 
 222 
 5591408610389 
 
 
 224 
 5591408610389 
 
 
 228 
 5591408610389 
 
 
 234 
 5591408610389 
 
 
 240 
 5591408610389 
 
 
 246 
 5591408610389 
 
 
 252 
 5591408610389 
 
 
 258 
 5591408610389 
 
 
 260 
 5591408610389 
 
 
 264 
 5591408610389 
 
 
 270 
 5591408610389 
 
 
 272 
 5591408610389 
 
 
 276 
 5591408610389 
 
 
 280 
 5591408610389 
 
 
 282 
 5591408610389 
 
 
 288 
 5591408610389 
 
 
 294 
 5591408610389 
 
 
 300 
 5591408610389 
 
 
 304 
 5591408610389 
 
 
 306 
 5591408610389 
 
 
 308 
 5591408610389 
 
 
 312 
 5591408610389 
 
 
 318 
 5591408610389 
 
 
 320 
 5591408610389 
 
 
 324 
 5591408610389 
 
 
 330 
 5591408610389 
 
 
 336 
 5591408610389 
 
 
 340 
 5591408610389 
 
 
 342 
 5591408610389 
 
 
 348 
 5591408610389 
 
 
 350 
 5591408610389 
 
 
 352 
 5591408610389 
 
 
 354 
 5591408610389 
 
 
 360 
 5591408610389 
 
 
 364 
 5591408610389 
 
 
 366 
 5591408610389 
 
 
 368 
 5591408610389 
 
 
 372 
 5591408610389 
 
 
 378 
 5591408610389 
 
 
 380 
 5591408610389 
 
 
 384 
 5591408610389 
 
 
 390 
 5591408610389 
 
 
 392 
 5591408610389 
 
 
 396 
 5591408610389 
 
 
 400 
 5591408610389 
 
 
 402 
 5591408610389 
 
 
 408 
 5591408610389 
 
 
 414 
 5591408610389 
 
 
 416 
 5591408610389 
 
 
 420 
 5591408610389 
 
 
 426 
 5591408610389 
 
 
 432 
 5591408610389 
 
 
 438 
 5591408610389 
 
 
 440 
 5591408610389 
 
 
 444 
 5591408610389 
 
 
 448 
 5591408610389 
 
 
 450 
 5591408610389 
 
 
 456 
 5591408610389 
 
 
 460 
 5591408610389 
 
 
 462 
 5591408610389 
 
 
 464 
 5591408610389 
 
 
 468 
 5591408610389 
 
 
 474 
 5591408610389 
 
 
 476 
 5591408610389 
 
 
 480 
 5591408610389 
 
 
 486 
 5591408610389 
 
 
 490 
 5591408610389 
 
 
 492 
 5591408610389 
 
 
 498 
 5591408610389 
 
 
 500 
 5591408610389 
 
 
 504 
 5591408610389 
 
 
 510 
 5591408610389 
 
 
 516 
 5591408610389 
 
 
 520 
 5591408610389 
 
 
 522 
 5591408610389 
 
 
 528 
 5591408610389 
 
 
 532 
 5591408610389 
 
 
 534 
 5591408610389 
 
 
 540 
 5591408610389 
 
 
 544 
 5591408610389 
 
 
 546 
 5591408610389 
 
 
 550 
 5591408610389 
 
 
 552 
 5591408610389 
 
 
 558 
 5591408610389 
 
 
 560 
 5591408610389 
 
 
 564 
 5591408610389 
 
 
 570 
 5591408610389 
 
 
 572 
 5591408610389 
 
 
 576 
 5591408610389 
 
 
 580 
 5591408610389 
 
 
 582 
 5591408610389 
 
 
 588 
 5591408610389 
 
 
 594 
 5591408610389 
 
 
 600 
 5591408610389 
 
 
 606 
 5591408610389 
 
 
 608 
 5591408610389 
 
 
 612 
 5591408610389 
 
 
 616 
 5591408610389 
 
 
 618 
 5591408610389 
 
 
 620 
 5591408610389 
 
 
 624 
 5591408610389 
 
 
 630 
 5591408610389 
 
 
 636 
 5591408610389 
 


In [ ]:
assert col['n'][5] == x

In [ ]:
x = 36

In [ ]:
%%sql
-- Indication. Sommez tous les diviseurs inférieurs à $n$, y compris 1. Le résultat est le même pour les nombres
-- de notre table, mais on peut prouver mathématiquement que cette condition supplémentaire est inutile dans le
-- cas général.
SELECT A.n
     , salt_023({{x}} + bit_xor(sum(nn(A.hash) + nn(B.hash))) OVER ()) AS token
FROM ints A
JOIN ints B ON B.n < A.n
AND B.n > 1
AND A.n MOD B.n = 0
GROUP BY A.n
HAVING A.n < sum(B.n)
ORDER BY 1

246 rows affected.

n 
 token 
 
 
 
 
 12 
 62621691563930 
 
 
 18 
 62621691563930 
 
 
 20 
 62621691563930 
 
 
 24 
 62621691563930 
 
 
 30 
 62621691563930 
 
 
 36 
 62621691563930 
 
 
 40 
 62621691563930 
 
 
 42 
 62621691563930 
 
 
 48 
 62621691563930 
 
 
 54 
 62621691563930 
 
 
 56 
 62621691563930 
 
 
 60 
 62621691563930 
 
 
 66 
 62621691563930 
 
 
 70 
 62621691563930 
 
 
 72 
 62621691563930 
 
 
 78 
 62621691563930 
 
 
 80 
 62621691563930 
 
 
 84 
 62621691563930 
 
 
 88 
 62621691563930 
 
 
 90 
 62621691563930 
 
 
 96 
 62621691563930 
 
 
 100 
 62621691563930 
 
 
 102 
 62621691563930 
 
 
 104 
 62621691563930 
 
 
 108 
 62621691563930 
 
 
 112 
 62621691563930 
 
 
 114 
 62621691563930 
 
 
 120 
 62621691563930 
 
 
 126 
 62621691563930 
 
 
 132 
 62621691563930 
 
 
 138 
 62621691563930 
 
 
 140 
 62621691563930 
 
 
 144 
 62621691563930 
 
 
 150 
 62621691563930 
 
 
 156 
 62621691563930 
 
 
 160 
 62621691563930 
 
 
 162 
 62621691563930 
 
 
 168 
 62621691563930 
 
 
 174 
 62621691563930 
 
 
 176 
 62621691563930 
 
 
 180 
 62621691563930 
 
 
 186 
 62621691563930 
 
 
 192 
 62621691563930 
 
 
 196 
 62621691563930 
 
 
 198 
 62621691563930 
 
 
 200 
 62621691563930 
 
 
 204 
 62621691563930 
 
 
 208 
 62621691563930 
 
 
 210 
 62621691563930 
 
 
 216 
 62621691563930 
 
 
 220 
 62621691563930 
 
 
 222 
 62621691563930 
 
 
 224 
 62621691563930 
 
 
 228 
 62621691563930 
 
 
 234 
 62621691563930 
 
 
 240 
 62621691563930 
 
 
 246 
 62621691563930 
 
 
 252 
 62621691563930 
 
 
 258 
 62621691563930 
 
 
 260 
 62621691563930 
 
 
 264 
 62621691563930 
 
 
 270 
 62621691563930 
 
 
 272 
 62621691563930 
 
 
 276 
 62621691563930 
 
 
 280 
 62621691563930 
 
 
 282 
 62621691563930 
 
 
 288 
 62621691563930 
 
 
 294 
 62621691563930 
 
 
 300 
 62621691563930 
 
 
 304 
 62621691563930 
 
 
 306 
 62621691563930 
 
 
 308 
 62621691563930 
 
 
 312 
 62621691563930 
 
 
 318 
 62621691563930 
 
 
 320 
 62621691563930 
 
 
 324 
 62621691563930 
 
 
 330 
 62621691563930 
 
 
 336 
 62621691563930 
 
 
 340 
 62621691563930 
 
 
 342 
 62621691563930 
 
 
 348 
 62621691563930 
 
 
 350 
 62621691563930 
 
 
 352 
 62621691563930 
 
 
 354 
 62621691563930 
 
 
 360 
 62621691563930 
 
 
 364 
 62621691563930 
 
 
 366 
 62621691563930 
 
 
 368 
 62621691563930 
 
 
 372 
 62621691563930 
 
 
 378 
 62621691563930 
 
 
 380 
 62621691563930 
 
 
 384 
 62621691563930 
 
 
 390 
 62621691563930 
 
 
 392 
 62621691563930 
 
 
 396 
 62621691563930 
 
 
 400 
 62621691563930 
 
 
 402 
 62621691563930 
 
 
 408 
 62621691563930 
 
 
 414 
 62621691563930 
 
 
 416 
 62621691563930 
 
 
 420 
 62621691563930 
 
 
 426 
 62621691563930 
 
 
 432 
 62621691563930 
 
 
 438 
 62621691563930 
 
 
 440 
 62621691563930 
 
 
 444 
 62621691563930 
 
 
 448 
 62621691563930 
 
 
 450 
 62621691563930 
 
 
 456 
 62621691563930 
 
 
 460 
 62621691563930 
 
 
 462 
 62621691563930 
 
 
 464 
 62621691563930 
 
 
 468 
 62621691563930 
 
 
 474 
 62621691563930 
 
 
 476 
 62621691563930 
 
 
 480 
 62621691563930 
 
 
 486 
 62621691563930 
 
 
 490 
 62621691563930 
 
 
 492 
 62621691563930 
 
 
 498 
 62621691563930 
 
 
 500 
 62621691563930 
 
 
 504 
 62621691563930 
 
 
 510 
 62621691563930 
 
 
 516 
 62621691563930 
 
 
 520 
 62621691563930 
 
 
 522 
 62621691563930 
 
 
 528 
 62621691563930 
 
 
 532 
 62621691563930 
 
 
 534 
 62621691563930 
 
 
 540 
 62621691563930 
 
 
 544 
 62621691563930 
 
 
 546 
 62621691563930 
 
 
 550 
 62621691563930 
 
 
 552 
 62621691563930 
 
 
 558 
 62621691563930 
 
 
 560 
 62621691563930 
 
 
 564 
 62621691563930 
 
 
 570 
 62621691563930 
 
 
 572 
 62621691563930 
 
 
 576 
 62621691563930 
 
 
 580 
 62621691563930 
 
 
 582 
 62621691563930 
 
 
 588 
 62621691563930 
 
 
 594 
 62621691563930 
 
 
 600 
 62621691563930 
 
 
 606 
 62621691563930 
 
 
 608 
 62621691563930 
 
 
 612 
 62621691563930 
 
 
 616 


In [ ]:
assert col['n'][5] == x

In [ ]:
x = 7

In [ ]:
%%sql
-- Indication. $n$ n'est pas un diviseur strict de lui-même.
SELECT A.n
     , salt_023({{x}} + bit_xor(sum(nn(A.hash) + nn(B.hash))) OVER ()) AS token
FROM ints A
JOIN ints B ON B.n <= A.n
AND A.n MOD B.n = 0
GROUP BY A.n
HAVING A.n < sum(B.n)
ORDER BY 1

999 rows affected.

n 
 token 
 
 
 
 
 2 
 14110344140782 
 
 
 3 
 14110344140782 
 
 
 4 
 14110344140782 
 
 
 5 
 14110344140782 
 
 
 6 
 14110344140782 
 
 
 7 
 14110344140782 
 
 
 8 
 14110344140782 
 
 
 9 
 14110344140782 
 
 
 10 
 14110344140782 
 
 
 11 
 14110344140782 
 
 
 12 
 14110344140782 
 
 
 13 
 14110344140782 
 
 
 14 
 14110344140782 
 
 
 15 
 14110344140782 
 
 
 16 
 14110344140782 
 
 
 17 
 14110344140782 
 
 
 18 
 14110344140782 
 
 
 19 
 14110344140782 
 
 
 20 
 14110344140782 
 
 
 21 
 14110344140782 
 
 
 22 
 14110344140782 
 
 
 23 
 14110344140782 
 
 
 24 
 14110344140782 
 
 
 25 
 14110344140782 
 
 
 26 
 14110344140782 
 
 
 27 
 14110344140782 
 
 
 28 
 14110344140782 
 
 
 29 
 14110344140782 
 
 
 30 
 14110344140782 
 
 
 31 
 14110344140782 
 
 
 32 
 14110344140782 
 
 
 33 
 14110344140782 
 
 
 34 
 14110344140782 
 
 
 35 
 14110344140782 
 
 
 36 
 14110344140782 
 
 
 37 
 14110344140782 
 
 
 38 
 14110344140782 
 
 
 39 
 14110344140782 
 
 
 40 
 14110344140782 
 
 
 41 
 14110344140782 
 
 
 42 
 14110344140782 
 
 
 43 
 14110344140782 
 
 
 44 
 14110344140782 
 
 
 45 
 14110344140782 
 
 
 46 
 14110344140782 
 
 
 47 
 14110344140782 
 
 
 48 
 14110344140782 
 
 
 49 
 14110344140782 
 
 
 50 
 14110344140782 
 
 
 51 
 14110344140782 
 
 
 52 
 14110344140782 
 
 
 53 
 14110344140782 
 
 
 54 
 14110344140782 
 
 
 55 
 14110344140782 
 
 
 56 
 14110344140782 
 
 
 57 
 14110344140782 
 
 
 58 
 14110344140782 
 
 
 59 
 14110344140782 
 
 
 60 
 14110344140782 
 
 
 61 
 14110344140782 
 
 
 62 
 14110344140782 
 
 
 63 
 14110344140782 
 
 
 64 
 14110344140782 
 
 
 65 
 14110344140782 
 
 
 66 
 14110344140782 
 
 
 67 
 14110344140782 
 
 
 68 
 14110344140782 
 
 
 69 
 14110344140782 
 
 
 70 
 14110344140782 
 
 
 71 
 14110344140782 
 
 
 72 
 14110344140782 
 
 
 73 
 14110344140782 
 
 
 74 
 14110344140782 
 
 
 75 
 14110344140782 
 
 
 76 
 14110344140782 
 
 
 77 
 14110344140782 
 
 
 78 
 14110344140782 
 
 
 79 
 14110344140782 
 
 
 80 
 14110344140782 
 
 
 81 
 14110344140782 
 
 
 82 
 14110344140782 
 
 
 83 
 14110344140782 
 
 
 84 
 14110344140782 
 
 
 85 
 14110344140782 
 
 
 86 
 14110344140782 
 
 
 87 
 14110344140782 
 
 
 88 
 14110344140782 
 
 
 89 
 14110344140782 
 
 
 90 
 14110344140782 
 
 
 91 
 14110344140782 
 
 
 92 
 14110344140782 
 
 
 93 
 14110344140782 
 
 
 94 
 14110344140782 
 
 
 95 
 14110344140782 
 
 
 96 
 14110344140782 
 
 
 97 
 14110344140782 
 
 
 98 
 14110344140782 
 
 
 99 
 14110344140782 
 
 
 100 
 14110344140782 
 
 
 101 
 14110344140782 
 
 
 102 
 14110344140782 
 
 
 103 
 14110344140782 
 
 
 104 
 14110344140782 
 
 
 105 
 14110344140782 
 
 
 106 
 14110344140782 
 
 
 107 
 14110344140782 
 
 
 108 
 14110344140782 
 
 
 109 
 14110344140782 
 
 
 110 
 14110344140782 
 
 
 111 
 14110344140782 
 
 
 112 
 14110344140782 
 
 
 113 
 14110344140782 
 
 
 114 
 14110344140782 
 
 
 115 
 14110344140782 
 
 
 116 
 14110344140782 
 
 
 117 
 14110344140782 
 
 
 118 
 14110344140782 
 
 
 119 
 14110344140782 
 
 
 120 
 14110344140782 
 
 
 121 
 14110344140782 
 
 
 122 
 14110344140782 
 
 
 123 
 14110344140782 
 
 
 124 
 14110344140782 
 
 
 125 
 14110344140782 
 
 
 126 
 14110344140782 
 
 
 127 
 14110344140782 
 
 
 128 
 14110344140782 
 
 
 129 
 14110344140782 
 
 
 130 
 14110344140782 
 
 
 131 
 14110344140782 
 
 
 132 
 14110344140782 
 
 
 133 
 14110344140782 
 
 
 134 
 14110344140782 
 
 
 135 
 14110344140782 
 
 
 136 
 14110344140782 
 
 
 137 
 14110344140782 
 
 
 138 
 14110344140782 
 
 
 139 
 14110344140782 
 
 
 140 
 14110344140782 
 
 
 141 
 14110344140782 
 
 
 142 
 14110344140782 
 
 
 143 
 14110344140782 
 
 
 144 
 14110344140782 
 
 
 145 
 14110344140782 
 
 
 146 
 14110344140782 
 
 
 147 
 14110344140782 
 
 
 148 
 14110344140782 
 
 
 149 
 14110344140782 
 
 
 150 
 14110344140782 
 
 
 151 
 14110344140782 
 
 
 152 
 14110344140782 
 
 
 153 
 141

In [ ]:
assert col['n'][5] == x

**Atelier [024].** Un entier $n$ est **abondant** si et seulement s'il est inférieur à la somme de ses diviseurs stricts (_i.e._, distincts de $n$).

| Exemple | Diviseurs stricts | Propriété | Abondant |
|---:|:--:|:--:|:--:|
| $12$ | $${1, 2, 3, 4, 6}$$ | $$12 < 1+2+3+4+6 = 16$$ | ✅ |
| $16$ | $${1, 2, 4, 8}$$ | $$16 \geq 1+2+4+8 = 15$$ | ❌ |

_Défi._ Listez par ordre croissant les nombres abondants inférieurs ou égaux à 1000.

_Contrainte._ Utilisez une sous-requête corrélée, et pas de regroupement.

In [ ]:
x = 36 # le 6e terme de cette suite
# Javascript: result[5]?.n ?? 7_531_148

In [ ]:
%%sql
SELECT A.n
     , salt_024({{x}} + sum(nn(A.hash)) OVER ()) AS token
FROM ints A
WHERE A.n <
        (SELECT sum(B.n)
         FROM ints B
         WHERE B.n < A.n
             AND A.n MOD B.n = 0 )
ORDER BY 1

246 rows affected.

n 
 token 
 
 
 
 
 12 
 248960157567190 
 
 
 18 
 248960157567190 
 
 
 20 
 248960157567190 
 
 
 24 
 248960157567190 
 
 
 30 
 248960157567190 
 
 
 36 
 248960157567190 
 
 
 40 
 248960157567190 
 
 
 42 
 248960157567190 
 
 
 48 
 248960157567190 
 
 
 54 
 248960157567190 
 
 
 56 
 248960157567190 
 
 
 60 
 248960157567190 
 
 
 66 
 248960157567190 
 
 
 70 
 248960157567190 
 
 
 72 
 248960157567190 
 
 
 78 
 248960157567190 
 
 
 80 
 248960157567190 
 
 
 84 
 248960157567190 
 
 
 88 
 248960157567190 
 
 
 90 
 248960157567190 
 
 
 96 
 248960157567190 
 
 
 100 
 248960157567190 
 
 
 102 
 248960157567190 
 
 
 104 
 248960157567190 
 
 
 108 
 248960157567190 
 
 
 112 
 248960157567190 
 
 
 114 
 248960157567190 
 
 
 120 
 248960157567190 
 
 
 126 
 248960157567190 
 
 
 132 
 248960157567190 
 
 
 138 
 248960157567190 
 
 
 140 
 248960157567190 
 
 
 144 
 248960157567190 
 
 
 150 
 248960157567190 
 
 
 156 
 248960157567190 
 
 
 160 
 248960157567190 
 
 
 162 
 248960157567190 
 
 
 168 
 248960157567190 
 
 
 174 
 248960157567190 
 
 
 176 
 248960157567190 
 
 
 180 
 248960157567190 
 
 
 186 
 248960157567190 
 
 
 192 
 248960157567190 
 
 
 196 
 248960157567190 
 
 
 198 
 248960157567190 
 
 
 200 
 248960157567190 
 
 
 204 
 248960157567190 
 
 
 208 
 248960157567190 
 
 
 210 
 248960157567190 
 
 
 216 
 248960157567190 
 
 
 220 
 248960157567190 
 
 
 222 
 248960157567190 
 
 
 224 
 248960157567190 
 
 
 228 
 248960157567190 
 
 
 234 
 248960157567190 
 
 
 240 
 248960157567190 
 
 
 246 
 248960157567190 
 
 
 252 
 248960157567190 
 
 
 258 
 248960157567190 
 
 
 260 
 248960157567190 
 
 
 264 
 248960157567190 
 
 
 270 
 248960157567190 
 
 
 272 
 248960157567190 
 
 
 276 
 248960157567190 
 
 
 280 
 248960157567190 
 
 
 282 
 248960157567190 
 
 
 288 
 248960157567190 
 
 
 294 
 248960157567190 
 
 
 300 
 248960157567190 
 
 
 304 
 248960157567190 
 
 
 306 
 248960157567190 
 
 
 308 
 248960157567190 
 
 
 312 
 248960157567190 
 
 
 318 
 248960157567190 
 
 
 320 
 248960157567190 
 
 
 324 
 248960157567190 
 
 
 330 
 248960157567190 
 
 
 336 
 248960157567190 
 
 
 340 
 248960157567190 
 
 
 342 
 248960157567190 
 
 
 348 
 248960157567190 
 
 
 350 
 248960157567190 
 
 
 352 
 248960157567190 
 
 
 354 
 248960157567190 
 
 
 360 
 248960157567190 
 
 
 364 
 248960157567190 
 
 
 366 
 248960157567190 
 
 
 368 
 248960157567190 
 
 
 372 
 248960157567190 
 
 
 378 
 248960157567190 
 
 
 380 
 248960157567190 
 
 
 384 
 248960157567190 
 
 
 390 
 248960157567190 
 
 
 392 
 248960157567190 
 
 
 396 
 248960157567190 
 
 
 400 
 248960157567190 
 
 
 402 
 248960157567190 
 
 
 408 
 248960157567190 
 
 
 414 
 248960157567190 
 
 
 416 
 248960157567190 
 
 
 420 
 248960157567190 
 
 
 426 
 248960157567190 
 
 
 432 
 248960157567190 
 
 
 438 
 248960157567190 
 
 
 440 
 248960157567190 
 
 
 444 
 248960157567190 
 
 
 448 
 248960157567190 
 
 
 450 
 248960157567190 
 
 
 456 
 248960157567190 
 
 
 460 
 248960157567190 
 
 
 462 
 248960157567190 
 
 
 464 
 248960157567190 
 
 
 468 
 248960157567190 
 
 
 474 
 248960157567190 
 
 
 476 
 248960157567190 
 
 
 480 
 248960157567190 
 
 
 486 
 248960157567190 
 
 
 490 
 248960157567190 
 
 
 492 
 248960157567190 
 
 
 498 
 248960157567190 
 
 
 500 
 248960157567190 
 
 
 504 
 248960157567190 
 
 
 510 
 248960157567190 
 
 
 516 
 248960157567190 
 
 
 520 
 248960157567190 
 
 
 522 
 248960157567190 
 
 
 528 
 248960157567190 
 
 
 532 
 248960157567190 
 
 
 534 
 248960157567190 
 
 
 540 
 248960157567190 
 
 
 544 
 248960157567190 
 
 
 546 
 248960157567190 
 
 
 550 
 248960157567190 
 
 
 552 
 248960157567190 
 
 
 558 
 248960157567190 
 
 
 560 
 248960157567190 
 
 
 564 
 248960157567190 
 
 
 570 
 248960157567190 
 
 
 572 
 248960157567190 
 
 
 576 
 248960157567190 
 
 
 580 
 248960157567190 
 
 
 582 
 248960157567190 
 
 
 588 
 248960157567190 
 


In [ ]:
assert col['n'][5] == x

### Entiers sans facteurs carrés

**Atelier [037].** Un entier est **sans facteur carré** si et seulement si aucun des nombres de sa décomposition en facteurs premiers n'apparaît plus d'une fois.

| Exemple | Décomposition | Propriété | Sans facteur carré |
|---:|:--:|:--:|:--:|
| $30$ | $$2 \times 3 \times 5$$ | aucun facteur dupliqué | ✅ |
| $12$ | $$2 \times 2 \times 3$$ | $2$ apparaît plus d'une fois | ❌ |

_Défi._ Listez par ordre croissant les entiers sans facteurs carrés inférieurs ou égaux à 1000.

In [ ]:
%%sql
-- Pour chaque entier $i_a$, on vérifie qu'il n'existe aucun entier $i_s$ dont le carré divise $i_a$.
SELECT n
     , salt_037(sum(nn(hash)) OVER ()) AS token
FROM ints A
WHERE n > 0
  AND NOT EXISTS (
    SELECT 1
    FROM ints AS S
    WHERE S.n >= 2
      AND S.n * S.n <= A.n
      AND A.n MOD (S.n * S.n) = 0
  )

608 rows affected.

n 
 token 
 
 
 
 
 1 
 436819829846544 
 
 
 2 
 436819829846544 
 
 
 3 
 436819829846544 
 
 
 5 
 436819829846544 
 
 
 6 
 436819829846544 
 
 
 7 
 436819829846544 
 
 
 10 
 436819829846544 
 
 
 11 
 436819829846544 
 
 
 13 
 436819829846544 
 
 
 14 
 436819829846544 
 
 
 15 
 436819829846544 
 
 
 17 
 436819829846544 
 
 
 19 
 436819829846544 
 
 
 21 
 436819829846544 
 
 
 22 
 436819829846544 
 
 
 23 
 436819829846544 
 
 
 26 
 436819829846544 
 
 
 29 
 436819829846544 
 
 
 30 
 436819829846544 
 
 
 31 
 436819829846544 
 
 
 33 
 436819829846544 
 
 
 34 
 436819829846544 
 
 
 35 
 436819829846544 
 
 
 37 
 436819829846544 
 
 
 38 
 436819829846544 
 
 
 39 
 436819829846544 
 
 
 41 
 436819829846544 
 
 
 42 
 436819829846544 
 
 
 43 
 436819829846544 
 
 
 46 
 436819829846544 
 
 
 47 
 436819829846544 
 
 
 51 
 436819829846544 
 
 
 53 
 436819829846544 
 
 
 55 
 436819829846544 
 
 
 57 
 436819829846544 
 
 
 58 
 436819829846544 
 
 
 59 
 436819829846544 
 
 
 61 
 436819829846544 
 
 
 62 
 436819829846544 
 
 
 65 
 436819829846544 
 
 
 66 
 436819829846544 
 
 
 67 
 436819829846544 
 
 
 69 
 436819829846544 
 
 
 70 
 436819829846544 
 
 
 71 
 436819829846544 
 
 
 73 
 436819829846544 
 
 
 74 
 436819829846544 
 
 
 77 
 436819829846544 
 
 
 78 
 436819829846544 
 
 
 79 
 436819829846544 
 
 
 82 
 436819829846544 
 
 
 83 
 436819829846544 
 
 
 85 
 436819829846544 
 
 
 86 
 436819829846544 
 
 
 87 
 436819829846544 
 
 
 89 
 436819829846544 
 
 
 91 
 436819829846544 
 
 
 93 
 436819829846544 
 
 
 94 
 436819829846544 
 
 
 95 
 436819829846544 
 
 
 97 
 436819829846544 
 
 
 101 
 436819829846544 
 
 
 102 
 436819829846544 
 
 
 103 
 436819829846544 
 
 
 105 
 436819829846544 
 
 
 106 
 436819829846544 
 
 
 107 
 436819829846544 
 
 
 109 
 436819829846544 
 
 
 110 
 436819829846544 
 
 
 111 
 436819829846544 
 
 
 113 
 436819829846544 
 
 
 114 
 436819829846544 
 
 
 115 
 436819829846544 
 
 
 118 
 436819829846544 
 
 
 119 
 436819829846544 
 
 
 122 
 436819829846544 
 
 
 123 
 436819829846544 
 
 
 127 
 436819829846544 
 
 
 129 
 436819829846544 
 
 
 130 
 436819829846544 
 
 
 131 
 436819829846544 
 
 
 133 
 436819829846544 
 
 
 134 
 436819829846544 
 
 
 137 
 436819829846544 
 
 
 138 
 436819829846544 
 
 
 139 
 436819829846544 
 
 
 141 
 436819829846544 
 
 
 142 
 436819829846544 
 
 
 143 
 436819829846544 
 
 
 145 
 436819829846544 
 
 
 146 
 436819829846544 
 
 
 149 
 436819829846544 
 
 
 151 
 436819829846544 
 
 
 154 
 436819829846544 
 
 
 155 
 436819829846544 
 
 
 157 
 436819829846544 
 
 
 158 
 436819829846544 
 
 
 159 
 436819829846544 
 
 
 161 
 436819829846544 
 
 
 163 
 436819829846544 
 
 
 165 
 436819829846544 
 
 
 166 
 436819829846544 
 
 
 167 
 436819829846544 
 
 
 170 
 436819829846544 
 
 
 173 
 436819829846544 
 
 
 174 
 436819829846544 
 
 
 177 
 436819829846544 
 
 
 178 
 436819829846544 
 
 
 179 
 436819829846544 
 
 
 181 
 436819829846544 
 
 
 182 
 436819829846544 
 
 
 183 
 436819829846544 
 
 
 185 
 436819829846544 
 
 
 186 
 436819829846544 
 
 
 187 
 436819829846544 
 
 
 190 
 436819829846544 
 
 
 191 
 436819829846544 
 
 
 193 
 436819829846544 
 
 
 194 
 436819829846544 
 
 
 195 
 436819829846544 
 
 
 197 
 436819829846544 
 
 
 199 
 436819829846544 
 
 
 201 
 436819829846544 
 
 
 202 
 436819829846544 
 
 
 203 
 436819829846544 
 
 
 205 
 436819829846544 
 
 
 206 
 436819829846544 
 
 
 209 
 436819829846544 
 
 
 210 
 436819829846544 
 
 
 211 
 436819829846544 
 
 
 213 
 436819829846544 
 
 
 214 
 436819829846544 
 
 
 215 
 436819829846544 
 
 
 217 
 436819829846544 
 
 
 218 
 436819829846544 
 
 
 219 
 436819829846544 
 
 
 221 
 436819829846544 
 
 
 222 
 436819829846544 
 
 
 223 
 436819829846544 
 
 
 226 
 436819829846544 
 
 
 227 
 436819829846544 
 
 
 229 
 436819829846544 
 
 
 230 
 436819829846544 
 
 
 231 
 436819829846544 
 
 
 233 
 436819829

In [ ]:
%%sql
-- Variante. Une CTE calcule la table `squares` des carrés susceptibles d'être facteurs d'entiers de `ints`.
-- On met ensuite chaque ligne de `ints` en face de chacun de ses diviseurs carrés. La jointure externe permet
-- de garder les lignes pour lesquelles aucune correspondance n'est possible : ce sont celles qui nous intéressent.
WITH
squares AS (
    SELECT DISTINCT n * n AS i2
    FROM ints
    WHERE n > 1 AND n * n <= 1000
)
SELECT n
     , salt_037(sum(nn(hash)) OVER ()) AS token
FROM ints
LEFT JOIN squares ON n MOD i2 = 0
WHERE i2 is NULL

608 rows affected.

n 
 token 
 
 
 
 
 1 
 436819829846544 
 
 
 2 
 436819829846544 
 
 
 3 
 436819829846544 
 
 
 5 
 436819829846544 
 
 
 6 
 436819829846544 
 
 
 7 
 436819829846544 
 
 
 10 
 436819829846544 
 
 
 11 
 436819829846544 
 
 
 13 
 436819829846544 
 
 
 14 
 436819829846544 
 
 
 15 
 436819829846544 
 
 
 17 
 436819829846544 
 
 
 19 
 436819829846544 
 
 
 21 
 436819829846544 
 
 
 22 
 436819829846544 
 
 
 23 
 436819829846544 
 
 
 26 
 436819829846544 
 
 
 29 
 436819829846544 
 
 
 30 
 436819829846544 
 
 
 31 
 436819829846544 
 
 
 33 
 436819829846544 
 
 
 34 
 436819829846544 
 
 
 35 
 436819829846544 
 
 
 37 
 436819829846544 
 
 
 38 
 436819829846544 
 
 
 39 
 436819829846544 
 
 
 41 
 436819829846544 
 
 
 42 
 436819829846544 
 
 
 43 
 436819829846544 
 
 
 46 
 436819829846544 
 
 
 47 
 436819829846544 
 
 
 51 
 436819829846544 
 
 
 53 
 436819829846544 
 
 
 55 
 436819829846544 
 
 
 57 
 436819829846544 
 
 
 58 
 436819829846544 
 
 
 59 
 436819829846544 
 
 
 61 
 436819829846544 
 
 
 62 
 436819829846544 
 
 
 65 
 436819829846544 
 
 
 66 
 436819829846544 
 
 
 67 
 436819829846544 
 
 
 69 
 436819829846544 
 
 
 70 
 436819829846544 
 
 
 71 
 436819829846544 
 
 
 73 
 436819829846544 
 
 
 74 
 436819829846544 
 
 
 77 
 436819829846544 
 
 
 78 
 436819829846544 
 
 
 79 
 436819829846544 
 
 
 82 
 436819829846544 
 
 
 83 
 436819829846544 
 
 
 85 
 436819829846544 
 
 
 86 
 436819829846544 
 
 
 87 
 436819829846544 
 
 
 89 
 436819829846544 
 
 
 91 
 436819829846544 
 
 
 93 
 436819829846544 
 
 
 94 
 436819829846544 
 
 
 95 
 436819829846544 
 
 
 97 
 436819829846544 
 
 
 101 
 436819829846544 
 
 
 102 
 436819829846544 
 
 
 103 
 436819829846544 
 
 
 105 
 436819829846544 
 
 
 106 
 436819829846544 
 
 
 107 
 436819829846544 
 
 
 109 
 436819829846544 
 
 
 110 
 436819829846544 
 
 
 111 
 436819829846544 
 
 
 113 
 436819829846544 
 
 
 114 
 436819829846544 
 
 
 115 
 436819829846544 
 
 
 118 
 436819829846544 
 
 
 119 
 436819829846544 
 
 
 122 
 436819829846544 
 
 
 123 
 436819829846544 
 
 
 127 
 436819829846544 
 
 
 129 
 436819829846544 
 
 
 130 
 436819829846544 
 
 
 131 
 436819829846544 
 
 
 133 
 436819829846544 
 
 
 134 
 436819829846544 
 
 
 137 
 436819829846544 
 
 
 138 
 436819829846544 
 
 
 139 
 436819829846544 
 
 
 141 
 436819829846544 
 
 
 142 
 436819829846544 
 
 
 143 
 436819829846544 
 
 
 145 
 436819829846544 
 
 
 146 
 436819829846544 
 
 
 149 
 436819829846544 
 
 
 151 
 436819829846544 
 
 
 154 
 436819829846544 
 
 
 155 
 436819829846544 
 
 
 157 
 436819829846544 
 
 
 158 
 436819829846544 
 
 
 159 
 436819829846544 
 
 
 161 
 436819829846544 
 
 
 163 
 436819829846544 
 
 
 165 
 436819829846544 
 
 
 166 
 436819829846544 
 
 
 167 
 436819829846544 
 
 
 170 
 436819829846544 
 
 
 173 
 436819829846544 
 
 
 174 
 436819829846544 
 
 
 177 
 436819829846544 
 
 
 178 
 436819829846544 
 
 
 179 
 436819829846544 
 
 
 181 
 436819829846544 
 
 
 182 
 436819829846544 
 
 
 183 
 436819829846544 
 
 
 185 
 436819829846544 
 
 
 186 
 436819829846544 
 
 
 187 
 436819829846544 
 
 
 190 
 436819829846544 
 
 
 191 
 436819829846544 
 
 
 193 
 436819829846544 
 
 
 194 
 436819829846544 
 
 
 195 
 436819829846544 
 
 
 197 
 436819829846544 
 
 
 199 
 436819829846544 
 
 
 201 
 436819829846544 
 
 
 202 
 436819829846544 
 
 
 203 
 436819829846544 
 
 
 205 
 436819829846544 
 
 
 206 
 436819829846544 
 
 
 209 
 436819829846544 
 
 
 210 
 436819829846544 
 
 
 211 
 436819829846544 
 
 
 213 
 436819829846544 
 
 
 214 
 436819829846544 
 
 
 215 
 436819829846544 
 
 
 217 
 436819829846544 
 
 
 218 
 436819829846544 
 
 
 219 
 436819829846544 
 
 
 221 
 436819829846544 
 
 
 222 
 436819829846544 
 
 
 223 
 436819829846544 
 
 
 226 
 436819829846544 
 
 
 227 
 436819829846544 
 
 
 229 
 436819829846544 
 
 
 230 
 436819829846544 
 
 
 231 
 436819829846544 
 
 
 233 
 436819829

In [ ]:
%%sql
-- Variante. Même idée avec une sous-requête non corrélée. Mais il faut se méfier de la forme `NOT IN table` :
-- si `table` contient ne serait-ce qu'un `NULL`, la condition renverra toujours `NULL` !
-- Pour vous en convaincre, testez avec `SELECT 3 NOT IN (1, 2, NULL), 3 NOT IN (1, 2)`.
-- Ici, aucun `NULL` n'apparaît dans le résultat de la sous-requête, mais de façon générale évitez ce genre de
-- requête au comportement potentiellement déroutant.
SELECT n
     , salt_037(sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE n NOT IN (
    SELECT A.n
    FROM ints AS A
    JOIN ints AS S ON A.n MOD (S.n * S.n) = 0
    WHERE S.n > 1 AND S.n * S.n <= 1000
)

608 rows affected.

n 
 token 
 
 
 
 
 1 
 436819829846544 
 
 
 2 
 436819829846544 
 
 
 3 
 436819829846544 
 
 
 5 
 436819829846544 
 
 
 6 
 436819829846544 
 
 
 7 
 436819829846544 
 
 
 10 
 436819829846544 
 
 
 11 
 436819829846544 
 
 
 13 
 436819829846544 
 
 
 14 
 436819829846544 
 
 
 15 
 436819829846544 
 
 
 17 
 436819829846544 
 
 
 19 
 436819829846544 
 
 
 21 
 436819829846544 
 
 
 22 
 436819829846544 
 
 
 23 
 436819829846544 
 
 
 26 
 436819829846544 
 
 
 29 
 436819829846544 
 
 
 30 
 436819829846544 
 
 
 31 
 436819829846544 
 
 
 33 
 436819829846544 
 
 
 34 
 436819829846544 
 
 
 35 
 436819829846544 
 
 
 37 
 436819829846544 
 
 
 38 
 436819829846544 
 
 
 39 
 436819829846544 
 
 
 41 
 436819829846544 
 
 
 42 
 436819829846544 
 
 
 43 
 436819829846544 
 
 
 46 
 436819829846544 
 
 
 47 
 436819829846544 
 
 
 51 
 436819829846544 
 
 
 53 
 436819829846544 
 
 
 55 
 436819829846544 
 
 
 57 
 436819829846544 
 
 
 58 
 436819829846544 
 
 
 59 
 436819829846544 
 
 
 61 
 436819829846544 
 
 
 62 
 436819829846544 
 
 
 65 
 436819829846544 
 
 
 66 
 436819829846544 
 
 
 67 
 436819829846544 
 
 
 69 
 436819829846544 
 
 
 70 
 436819829846544 
 
 
 71 
 436819829846544 
 
 
 73 
 436819829846544 
 
 
 74 
 436819829846544 
 
 
 77 
 436819829846544 
 
 
 78 
 436819829846544 
 
 
 79 
 436819829846544 
 
 
 82 
 436819829846544 
 
 
 83 
 436819829846544 
 
 
 85 
 436819829846544 
 
 
 86 
 436819829846544 
 
 
 87 
 436819829846544 
 
 
 89 
 436819829846544 
 
 
 91 
 436819829846544 
 
 
 93 
 436819829846544 
 
 
 94 
 436819829846544 
 
 
 95 
 436819829846544 
 
 
 97 
 436819829846544 
 
 
 101 
 436819829846544 
 
 
 102 
 436819829846544 
 
 
 103 
 436819829846544 
 
 
 105 
 436819829846544 
 
 
 106 
 436819829846544 
 
 
 107 
 436819829846544 
 
 
 109 
 436819829846544 
 
 
 110 
 436819829846544 
 
 
 111 
 436819829846544 
 
 
 113 
 436819829846544 
 
 
 114 
 436819829846544 
 
 
 115 
 436819829846544 
 
 
 118 
 436819829846544 
 
 
 119 
 436819829846544 
 
 
 122 
 436819829846544 
 
 
 123 
 436819829846544 
 
 
 127 
 436819829846544 
 
 
 129 
 436819829846544 
 
 
 130 
 436819829846544 
 
 
 131 
 436819829846544 
 
 
 133 
 436819829846544 
 
 
 134 
 436819829846544 
 
 
 137 
 436819829846544 
 
 
 138 
 436819829846544 
 
 
 139 
 436819829846544 
 
 
 141 
 436819829846544 
 
 
 142 
 436819829846544 
 
 
 143 
 436819829846544 
 
 
 145 
 436819829846544 
 
 
 146 
 436819829846544 
 
 
 149 
 436819829846544 
 
 
 151 
 436819829846544 
 
 
 154 
 436819829846544 
 
 
 155 
 436819829846544 
 
 
 157 
 436819829846544 
 
 
 158 
 436819829846544 
 
 
 159 
 436819829846544 
 
 
 161 
 436819829846544 
 
 
 163 
 436819829846544 
 
 
 165 
 436819829846544 
 
 
 166 
 436819829846544 
 
 
 167 
 436819829846544 
 
 
 170 
 436819829846544 
 
 
 173 
 436819829846544 
 
 
 174 
 436819829846544 
 
 
 177 
 436819829846544 
 
 
 178 
 436819829846544 
 
 
 179 
 436819829846544 
 
 
 181 
 436819829846544 
 
 
 182 
 436819829846544 
 
 
 183 
 436819829846544 
 
 
 185 
 436819829846544 
 
 
 186 
 436819829846544 
 
 
 187 
 436819829846544 
 
 
 190 
 436819829846544 
 
 
 191 
 436819829846544 
 
 
 193 
 436819829846544 
 
 
 194 
 436819829846544 
 
 
 195 
 436819829846544 
 
 
 197 
 436819829846544 
 
 
 199 
 436819829846544 
 
 
 201 
 436819829846544 
 
 
 202 
 436819829846544 
 
 
 203 
 436819829846544 
 
 
 205 
 436819829846544 
 
 
 206 
 436819829846544 
 
 
 209 
 436819829846544 
 
 
 210 
 436819829846544 
 
 
 211 
 436819829846544 
 
 
 213 
 436819829846544 
 
 
 214 
 436819829846544 
 
 
 215 
 436819829846544 
 
 
 217 
 436819829846544 
 
 
 218 
 436819829846544 
 
 
 219 
 436819829846544 
 
 
 221 
 436819829846544 
 
 
 222 
 436819829846544 
 
 
 223 
 436819829846544 
 
 
 226 
 436819829846544 
 
 
 227 
 436819829846544 
 
 
 229 
 436819829846544 
 
 
 230 
 436819829846544 
 
 
 231 
 436819829846544 
 
 
 233 
 436819829

In [ ]:
%%sql
-- Indication. Vous renvoyez tous les `n`.
-- Ne gardez que ceux que vous ne pouvez mettre en correspondance avec **aucun** diviseur carré.
WITH
squares AS (
    SELECT DISTINCT n * n AS i2
    FROM ints
    WHERE n > 1 AND n * n <= 1000
)
SELECT DISTINCT n
     , salt_037(sum(nn(hash)) OVER ()) AS token
FROM ints
LEFT JOIN squares ON n MOD i2 = 0

1001 rows affected.

n 
 token 
 
 
 
 
 0 
 836962415998811 
 
 
 1 
 836962415998811 
 
 
 2 
 836962415998811 
 
 
 3 
 836962415998811 
 
 
 4 
 836962415998811 
 
 
 5 
 836962415998811 
 
 
 6 
 836962415998811 
 
 
 7 
 836962415998811 
 
 
 8 
 836962415998811 
 
 
 9 
 836962415998811 
 
 
 10 
 836962415998811 
 
 
 11 
 836962415998811 
 
 
 12 
 836962415998811 
 
 
 13 
 836962415998811 
 
 
 14 
 836962415998811 
 
 
 15 
 836962415998811 
 
 
 16 
 836962415998811 
 
 
 17 
 836962415998811 
 
 
 18 
 836962415998811 
 
 
 19 
 836962415998811 
 
 
 20 
 836962415998811 
 
 
 21 
 836962415998811 
 
 
 22 
 836962415998811 
 
 
 23 
 836962415998811 
 
 
 24 
 836962415998811 
 
 
 25 
 836962415998811 
 
 
 26 
 836962415998811 
 
 
 27 
 836962415998811 
 
 
 28 
 836962415998811 
 
 
 29 
 836962415998811 
 
 
 30 
 836962415998811 
 
 
 31 
 836962415998811 
 
 
 32 
 836962415998811 
 
 
 33 
 836962415998811 
 
 
 34 
 836962415998811 
 
 
 35 
 836962415998811 
 
 
 36 
 836962415998811 
 
 
 37 
 836962415998811 
 
 
 38 
 836962415998811 
 
 
 39 
 836962415998811 
 
 
 40 
 836962415998811 
 
 
 41 
 836962415998811 
 
 
 42 
 836962415998811 
 
 
 43 
 836962415998811 
 
 
 44 
 836962415998811 
 
 
 45 
 836962415998811 
 
 
 46 
 836962415998811 
 
 
 47 
 836962415998811 
 
 
 48 
 836962415998811 
 
 
 49 
 836962415998811 
 
 
 50 
 836962415998811 
 
 
 51 
 836962415998811 
 
 
 52 
 836962415998811 
 
 
 53 
 836962415998811 
 
 
 54 
 836962415998811 
 
 
 55 
 836962415998811 
 
 
 56 
 836962415998811 
 
 
 57 
 836962415998811 
 
 
 58 
 836962415998811 
 
 
 59 
 836962415998811 
 
 
 60 
 836962415998811 
 
 
 61 
 836962415998811 
 
 
 62 
 836962415998811 
 
 
 63 
 836962415998811 
 
 
 64 
 836962415998811 
 
 
 65 
 836962415998811 
 
 
 66 
 836962415998811 
 
 
 67 
 836962415998811 
 
 
 68 
 836962415998811 
 
 
 69 
 836962415998811 
 
 
 70 
 836962415998811 
 
 
 71 
 836962415998811 
 
 
 72 
 836962415998811 
 
 
 73 
 836962415998811 
 
 
 74 
 836962415998811 
 
 
 75 
 836962415998811 
 
 
 76 
 836962415998811 
 
 
 77 
 836962415998811 
 
 
 78 
 836962415998811 
 
 
 79 
 836962415998811 
 
 
 80 
 836962415998811 
 
 
 81 
 836962415998811 
 
 
 82 
 836962415998811 
 
 
 83 
 836962415998811 
 
 
 84 
 836962415998811 
 
 
 85 
 836962415998811 
 
 
 86 
 836962415998811 
 
 
 87 
 836962415998811 
 
 
 88 
 836962415998811 
 
 
 89 
 836962415998811 
 
 
 90 
 836962415998811 
 
 
 91 
 836962415998811 
 
 
 92 
 836962415998811 
 
 
 93 
 836962415998811 
 
 
 94 
 836962415998811 
 
 
 95 
 836962415998811 
 
 
 96 
 836962415998811 
 
 
 97 
 836962415998811 
 
 
 98 
 836962415998811 
 
 
 99 
 836962415998811 
 
 
 100 
 836962415998811 
 
 
 101 
 836962415998811 
 
 
 102 
 836962415998811 
 
 
 103 
 836962415998811 
 
 
 104 
 836962415998811 
 
 
 105 
 836962415998811 
 
 
 106 
 836962415998811 
 
 
 107 
 836962415998811 
 
 
 108 
 836962415998811 
 
 
 109 
 836962415998811 
 
 
 110 
 836962415998811 
 
 
 111 
 836962415998811 
 
 
 112 
 836962415998811 
 
 
 113 
 836962415998811 
 
 
 114 
 836962415998811 
 
 
 115 
 836962415998811 
 
 
 116 
 836962415998811 
 
 
 117 
 836962415998811 
 
 
 118 
 836962415998811 
 
 
 119 
 836962415998811 
 
 
 120 
 836962415998811 
 
 
 121 
 836962415998811 
 
 
 122 
 836962415998811 
 
 
 123 
 836962415998811 
 
 
 124 
 836962415998811 
 
 
 125 
 836962415998811 
 
 
 126 
 836962415998811 
 
 
 127 
 836962415998811 
 
 
 128 
 836962415998811 
 
 
 129 
 836962415998811 
 
 
 130 
 836962415998811 
 
 
 131 
 836962415998811 
 
 
 132 
 836962415998811 
 
 
 133 
 836962415998811 
 
 
 134 
 836962415998811 
 
 
 135 
 836962415998811 
 
 
 136 
 836962415998811 
 
 
 137 
 836962415998811 
 
 
 138 
 836962415998811 
 
 
 139 
 836962415998811 
 
 
 140 
 836962415998811 
 
 
 141 
 836962415998811 
 
 
 142 
 836962415998811 
 
 
 143 
 836962415998811 
 
 
 144 
 836962415998811 
 
 
 145 
 836962415998811 
 
 
 14

In [ ]:
%%sql
-- Indication. Vous renvoyez tous les entiers de 1 à 1000. Si vous avez utilisé une sous-requête corrélée,
-- vérifiez que vous avez bien préfixé tous les noms de colonnes par le nom de leur table (on dit « qualifier »
-- une colonne). Sans cela, il se peut que SQL n'arrive pas à faire la corrélation correctement.
SELECT n
     , salt_037(sum(nn(hash)) OVER ()) AS token
FROM ints A
WHERE n > 0
  AND NOT EXISTS (
    SELECT 1
    FROM ints AS S
    WHERE S.n >= 2
      AND S.n * S.n <= n
      AND n MOD (S.n * S.n) = 0
  )

1000 rows affected.

n 
 token 
 
 
 
 
 1 
 378179076514973 
 
 
 2 
 378179076514973 
 
 
 3 
 378179076514973 
 
 
 4 
 378179076514973 
 
 
 5 
 378179076514973 
 
 
 6 
 378179076514973 
 
 
 7 
 378179076514973 
 
 
 8 
 378179076514973 
 
 
 9 
 378179076514973 
 
 
 10 
 378179076514973 
 
 
 11 
 378179076514973 
 
 
 12 
 378179076514973 
 
 
 13 
 378179076514973 
 
 
 14 
 378179076514973 
 
 
 15 
 378179076514973 
 
 
 16 
 378179076514973 
 
 
 17 
 378179076514973 
 
 
 18 
 378179076514973 
 
 
 19 
 378179076514973 
 
 
 20 
 378179076514973 
 
 
 21 
 378179076514973 
 
 
 22 
 378179076514973 
 
 
 23 
 378179076514973 
 
 
 24 
 378179076514973 
 
 
 25 
 378179076514973 
 
 
 26 
 378179076514973 
 
 
 27 
 378179076514973 
 
 
 28 
 378179076514973 
 
 
 29 
 378179076514973 
 
 
 30 
 378179076514973 
 
 
 31 
 378179076514973 
 
 
 32 
 378179076514973 
 
 
 33 
 378179076514973 
 
 
 34 
 378179076514973 
 
 
 35 
 378179076514973 
 
 
 36 
 378179076514973 
 
 
 37 
 378179076514973 
 
 
 38 
 378179076514973 
 
 
 39 
 378179076514973 
 
 
 40 
 378179076514973 
 
 
 41 
 378179076514973 
 
 
 42 
 378179076514973 
 
 
 43 
 378179076514973 
 
 
 44 
 378179076514973 
 
 
 45 
 378179076514973 
 
 
 46 
 378179076514973 
 
 
 47 
 378179076514973 
 
 
 48 
 378179076514973 
 
 
 49 
 378179076514973 
 
 
 50 
 378179076514973 
 
 
 51 
 378179076514973 
 
 
 52 
 378179076514973 
 
 
 53 
 378179076514973 
 
 
 54 
 378179076514973 
 
 
 55 
 378179076514973 
 
 
 56 
 378179076514973 
 
 
 57 
 378179076514973 
 
 
 58 
 378179076514973 
 
 
 59 
 378179076514973 
 
 
 60 
 378179076514973 
 
 
 61 
 378179076514973 
 
 
 62 
 378179076514973 
 
 
 63 
 378179076514973 
 
 
 64 
 378179076514973 
 
 
 65 
 378179076514973 
 
 
 66 
 378179076514973 
 
 
 67 
 378179076514973 
 
 
 68 
 378179076514973 
 
 
 69 
 378179076514973 
 
 
 70 
 378179076514973 
 
 
 71 
 378179076514973 
 
 
 72 
 378179076514973 
 
 
 73 
 378179076514973 
 
 
 74 
 378179076514973 
 
 
 75 
 378179076514973 
 
 
 76 
 378179076514973 
 
 
 77 
 378179076514973 
 
 
 78 
 378179076514973 
 
 
 79 
 378179076514973 
 
 
 80 
 378179076514973 
 
 
 81 
 378179076514973 
 
 
 82 
 378179076514973 
 
 
 83 
 378179076514973 
 
 
 84 
 378179076514973 
 
 
 85 
 378179076514973 
 
 
 86 
 378179076514973 
 
 
 87 
 378179076514973 
 
 
 88 
 378179076514973 
 
 
 89 
 378179076514973 
 
 
 90 
 378179076514973 
 
 
 91 
 378179076514973 
 
 
 92 
 378179076514973 
 
 
 93 
 378179076514973 
 
 
 94 
 378179076514973 
 
 
 95 
 378179076514973 
 
 
 96 
 378179076514973 
 
 
 97 
 378179076514973 
 
 
 98 
 378179076514973 
 
 
 99 
 378179076514973 
 
 
 100 
 378179076514973 
 
 
 101 
 378179076514973 
 
 
 102 
 378179076514973 
 
 
 103 
 378179076514973 
 
 
 104 
 378179076514973 
 
 
 105 
 378179076514973 
 
 
 106 
 378179076514973 
 
 
 107 
 378179076514973 
 
 
 108 
 378179076514973 
 
 
 109 
 378179076514973 
 
 
 110 
 378179076514973 
 
 
 111 
 378179076514973 
 
 
 112 
 378179076514973 
 
 
 113 
 378179076514973 
 
 
 114 
 378179076514973 
 
 
 115 
 378179076514973 
 
 
 116 
 378179076514973 
 
 
 117 
 378179076514973 
 
 
 118 
 378179076514973 
 
 
 119 
 378179076514973 
 
 
 120 
 378179076514973 
 
 
 121 
 378179076514973 
 
 
 122 
 378179076514973 
 
 
 123 
 378179076514973 
 
 
 124 
 378179076514973 
 
 
 125 
 378179076514973 
 
 
 126 
 378179076514973 
 
 
 127 
 378179076514973 
 
 
 128 
 378179076514973 
 
 
 129 
 378179076514973 
 
 
 130 
 378179076514973 
 
 
 131 
 378179076514973 
 
 
 132 
 378179076514973 
 
 
 133 
 378179076514973 
 
 
 134 
 378179076514973 
 
 
 135 
 378179076514973 
 
 
 136 
 378179076514973 
 
 
 137 
 378179076514973 
 
 
 138 
 378179076514973 
 
 
 139 
 378179076514973 
 
 
 140 
 378179076514973 
 
 
 141 
 378179076514973 
 
 
 142 
 378179076514973 
 
 
 143 
 378179076514973 
 
 
 144 
 378179076514973 
 
 
 145 
 378179076514973 
 
 
 146 
 378179076514973 
 
 
 

In [ ]:
%%sql
-- Indication. Vous renvoyez tous les entiers de 0 à 1000. Si vous avez utilisé une sous-requête corrélée,
-- vérifiez que vous avez bien préfixé tous les noms de colonnes par le nom de leur table (on dit « qualifier »
-- une colonne). Sans cela, il se peut que SQL n'arrive pas à faire la corrélation correctement.
SELECT n
     , salt_037(sum(nn(hash)) OVER ()) AS token
FROM ints A
WHERE NOT EXISTS (
    SELECT 1
    FROM ints AS S
    WHERE S.n >= 2
      AND S.n * S.n <= n
      AND n MOD (S.n * S.n) = 0
  )

1001 rows affected.

n 
 token 
 
 
 
 
 0 
 374196928538196 
 
 
 1 
 374196928538196 
 
 
 2 
 374196928538196 
 
 
 3 
 374196928538196 
 
 
 4 
 374196928538196 
 
 
 5 
 374196928538196 
 
 
 6 
 374196928538196 
 
 
 7 
 374196928538196 
 
 
 8 
 374196928538196 
 
 
 9 
 374196928538196 
 
 
 10 
 374196928538196 
 
 
 11 
 374196928538196 
 
 
 12 
 374196928538196 
 
 
 13 
 374196928538196 
 
 
 14 
 374196928538196 
 
 
 15 
 374196928538196 
 
 
 16 
 374196928538196 
 
 
 17 
 374196928538196 
 
 
 18 
 374196928538196 
 
 
 19 
 374196928538196 
 
 
 20 
 374196928538196 
 
 
 21 
 374196928538196 
 
 
 22 
 374196928538196 
 
 
 23 
 374196928538196 
 
 
 24 
 374196928538196 
 
 
 25 
 374196928538196 
 
 
 26 
 374196928538196 
 
 
 27 
 374196928538196 
 
 
 28 
 374196928538196 
 
 
 29 
 374196928538196 
 
 
 30 
 374196928538196 
 
 
 31 
 374196928538196 
 
 
 32 
 374196928538196 
 
 
 33 
 374196928538196 
 
 
 34 
 374196928538196 
 
 
 35 
 374196928538196 
 
 
 36 
 374196928538196 
 
 
 37 
 374196928538196 
 
 
 38 
 374196928538196 
 
 
 39 
 374196928538196 
 
 
 40 
 374196928538196 
 
 
 41 
 374196928538196 
 
 
 42 
 374196928538196 
 
 
 43 
 374196928538196 
 
 
 44 
 374196928538196 
 
 
 45 
 374196928538196 
 
 
 46 
 374196928538196 
 
 
 47 
 374196928538196 
 
 
 48 
 374196928538196 
 
 
 49 
 374196928538196 
 
 
 50 
 374196928538196 
 
 
 51 
 374196928538196 
 
 
 52 
 374196928538196 
 
 
 53 
 374196928538196 
 
 
 54 
 374196928538196 
 
 
 55 
 374196928538196 
 
 
 56 
 374196928538196 
 
 
 57 
 374196928538196 
 
 
 58 
 374196928538196 
 
 
 59 
 374196928538196 
 
 
 60 
 374196928538196 
 
 
 61 
 374196928538196 
 
 
 62 
 374196928538196 
 
 
 63 
 374196928538196 
 
 
 64 
 374196928538196 
 
 
 65 
 374196928538196 
 
 
 66 
 374196928538196 
 
 
 67 
 374196928538196 
 
 
 68 
 374196928538196 
 
 
 69 
 374196928538196 
 
 
 70 
 374196928538196 
 
 
 71 
 374196928538196 
 
 
 72 
 374196928538196 
 
 
 73 
 374196928538196 
 
 
 74 
 374196928538196 
 
 
 75 
 374196928538196 
 
 
 76 
 374196928538196 
 
 
 77 
 374196928538196 
 
 
 78 
 374196928538196 
 
 
 79 
 374196928538196 
 
 
 80 
 374196928538196 
 
 
 81 
 374196928538196 
 
 
 82 
 374196928538196 
 
 
 83 
 374196928538196 
 
 
 84 
 374196928538196 
 
 
 85 
 374196928538196 
 
 
 86 
 374196928538196 
 
 
 87 
 374196928538196 
 
 
 88 
 374196928538196 
 
 
 89 
 374196928538196 
 
 
 90 
 374196928538196 
 
 
 91 
 374196928538196 
 
 
 92 
 374196928538196 
 
 
 93 
 374196928538196 
 
 
 94 
 374196928538196 
 
 
 95 
 374196928538196 
 
 
 96 
 374196928538196 
 
 
 97 
 374196928538196 
 
 
 98 
 374196928538196 
 
 
 99 
 374196928538196 
 
 
 100 
 374196928538196 
 
 
 101 
 374196928538196 
 
 
 102 
 374196928538196 
 
 
 103 
 374196928538196 
 
 
 104 
 374196928538196 
 
 
 105 
 374196928538196 
 
 
 106 
 374196928538196 
 
 
 107 
 374196928538196 
 
 
 108 
 374196928538196 
 
 
 109 
 374196928538196 
 
 
 110 
 374196928538196 
 
 
 111 
 374196928538196 
 
 
 112 
 374196928538196 
 
 
 113 
 374196928538196 
 
 
 114 
 374196928538196 
 
 
 115 
 374196928538196 
 
 
 116 
 374196928538196 
 
 
 117 
 374196928538196 
 
 
 118 
 374196928538196 
 
 
 119 
 374196928538196 
 
 
 120 
 374196928538196 
 
 
 121 
 374196928538196 
 
 
 122 
 374196928538196 
 
 
 123 
 374196928538196 
 
 
 124 
 374196928538196 
 
 
 125 
 374196928538196 
 
 
 126 
 374196928538196 
 
 
 127 
 374196928538196 
 
 
 128 
 374196928538196 
 
 
 129 
 374196928538196 
 
 
 130 
 374196928538196 
 
 
 131 
 374196928538196 
 
 
 132 
 374196928538196 
 
 
 133 
 374196928538196 
 
 
 134 
 374196928538196 
 
 
 135 
 374196928538196 
 
 
 136 
 374196928538196 
 
 
 137 
 374196928538196 
 
 
 138 
 374196928538196 
 
 
 139 
 374196928538196 
 
 
 140 
 374196928538196 
 
 
 141 
 374196928538196 
 
 
 142 
 374196928538196 
 
 
 143 
 374196928538196 
 
 
 144 
 374196928538196 
 
 
 145 
 374196928538196 
 
 
 14

In [ ]:
%%sql
-- Indication. Vous renvoyez tous les `n` que vous pouvez mettre en correspondance avec au moins un diviseur
-- carré. On demande le contraire.
WITH
squares AS (
    SELECT DISTINCT n * n AS i2
    FROM ints
    WHERE n > 1 AND n * n <= 1000
)
SELECT DISTINCT n
     , salt_037(sum(nn(hash)) OVER ()) AS token
FROM ints
LEFT JOIN squares ON n MOD i2 = 0
WHERE i2 IS NOT NULL

393 rows affected.

n 
 token 
 
 
 
 
 0 
 446356723589658 
 
 
 4 
 446356723589658 
 
 
 8 
 446356723589658 
 
 
 9 
 446356723589658 
 
 
 12 
 446356723589658 
 
 
 16 
 446356723589658 
 
 
 18 
 446356723589658 
 
 
 20 
 446356723589658 
 
 
 24 
 446356723589658 
 
 
 25 
 446356723589658 
 
 
 27 
 446356723589658 
 
 
 28 
 446356723589658 
 
 
 32 
 446356723589658 
 
 
 36 
 446356723589658 
 
 
 40 
 446356723589658 
 
 
 44 
 446356723589658 
 
 
 45 
 446356723589658 
 
 
 48 
 446356723589658 
 
 
 49 
 446356723589658 
 
 
 50 
 446356723589658 
 
 
 52 
 446356723589658 
 
 
 54 
 446356723589658 
 
 
 56 
 446356723589658 
 
 
 60 
 446356723589658 
 
 
 63 
 446356723589658 
 
 
 64 
 446356723589658 
 
 
 68 
 446356723589658 
 
 
 72 
 446356723589658 
 
 
 75 
 446356723589658 
 
 
 76 
 446356723589658 
 
 
 80 
 446356723589658 
 
 
 81 
 446356723589658 
 
 
 84 
 446356723589658 
 
 
 88 
 446356723589658 
 
 
 90 
 446356723589658 
 
 
 92 
 446356723589658 
 
 
 96 
 446356723589658 
 
 
 98 
 446356723589658 
 
 
 99 
 446356723589658 
 
 
 100 
 446356723589658 
 
 
 104 
 446356723589658 
 
 
 108 
 446356723589658 
 
 
 112 
 446356723589658 
 
 
 116 
 446356723589658 
 
 
 117 
 446356723589658 
 
 
 120 
 446356723589658 
 
 
 121 
 446356723589658 
 
 
 124 
 446356723589658 
 
 
 125 
 446356723589658 
 
 
 126 
 446356723589658 
 
 
 128 
 446356723589658 
 
 
 132 
 446356723589658 
 
 
 135 
 446356723589658 
 
 
 136 
 446356723589658 
 
 
 140 
 446356723589658 
 
 
 144 
 446356723589658 
 
 
 147 
 446356723589658 
 
 
 148 
 446356723589658 
 
 
 150 
 446356723589658 
 
 
 152 
 446356723589658 
 
 
 153 
 446356723589658 
 
 
 156 
 446356723589658 
 
 
 160 
 446356723589658 
 
 
 162 
 446356723589658 
 
 
 164 
 446356723589658 
 
 
 168 
 446356723589658 
 
 
 169 
 446356723589658 
 
 
 171 
 446356723589658 
 
 
 172 
 446356723589658 
 
 
 175 
 446356723589658 
 
 
 176 
 446356723589658 
 
 
 180 
 446356723589658 
 
 
 184 
 446356723589658 
 
 
 188 
 446356723589658 
 
 
 189 
 446356723589658 
 
 
 192 
 446356723589658 
 
 
 196 
 446356723589658 
 
 
 198 
 446356723589658 
 
 
 200 
 446356723589658 
 
 
 204 
 446356723589658 
 
 
 207 
 446356723589658 
 
 
 208 
 446356723589658 
 
 
 212 
 446356723589658 
 
 
 216 
 446356723589658 
 
 
 220 
 446356723589658 
 
 
 224 
 446356723589658 
 
 
 225 
 446356723589658 
 
 
 228 
 446356723589658 
 
 
 232 
 446356723589658 
 
 
 234 
 446356723589658 
 
 
 236 
 446356723589658 
 
 
 240 
 446356723589658 
 
 
 242 
 446356723589658 
 
 
 243 
 446356723589658 
 
 
 244 
 446356723589658 
 
 
 245 
 446356723589658 
 
 
 248 
 446356723589658 
 
 
 250 
 446356723589658 
 
 
 252 
 446356723589658 
 
 
 256 
 446356723589658 
 
 
 260 
 446356723589658 
 
 
 261 
 446356723589658 
 
 
 264 
 446356723589658 
 
 
 268 
 446356723589658 
 
 
 270 
 446356723589658 
 
 
 272 
 446356723589658 
 
 
 275 
 446356723589658 
 
 
 276 
 446356723589658 
 
 
 279 
 446356723589658 
 
 
 280 
 446356723589658 
 
 
 284 
 446356723589658 
 
 
 288 
 446356723589658 
 
 
 289 
 446356723589658 
 
 
 292 
 446356723589658 
 
 
 294 
 446356723589658 
 
 
 296 
 446356723589658 
 
 
 297 
 446356723589658 
 
 
 300 
 446356723589658 
 
 
 304 
 446356723589658 
 
 
 306 
 446356723589658 
 
 
 308 
 446356723589658 
 
 
 312 
 446356723589658 
 
 
 315 
 446356723589658 
 
 
 316 
 446356723589658 
 
 
 320 
 446356723589658 
 
 
 324 
 446356723589658 
 
 
 325 
 446356723589658 
 
 
 328 
 446356723589658 
 
 
 332 
 446356723589658 
 
 
 333 
 446356723589658 
 
 
 336 
 446356723589658 
 
 
 338 
 446356723589658 
 
 
 340 
 446356723589658 
 
 
 342 
 446356723589658 
 
 
 343 
 446356723589658 
 
 
 344 
 446356723589658 
 
 
 348 
 446356723589658 
 
 
 350 
 446356723589658 
 
 
 351 
 446356723589658 
 
 
 352 
 446356723589658 
 
 
 356 
 446356723589658 
 
 
 360 
 446356723589658 
 
 
 361 
 446356723589658 
 
 
 363 
 4463567235896

In [ ]:
%%sql
-- Indication. Excluez zéro : il n'a pas de décomposition en facteurs premiers.
SELECT n
     , salt_037(sum(nn(hash)) OVER ()) AS token
FROM ints A
WHERE NOT EXISTS (
    SELECT 1
    FROM ints AS S
    WHERE S.n >= 2
      AND S.n * S.n <= A.n
      AND A.n MOD (S.n * S.n) = 0
  )

609 rows affected.

n 
 token 
 
 
 
 
 0 
 437237875864615 
 
 
 1 
 437237875864615 
 
 
 2 
 437237875864615 
 
 
 3 
 437237875864615 
 
 
 5 
 437237875864615 
 
 
 6 
 437237875864615 
 
 
 7 
 437237875864615 
 
 
 10 
 437237875864615 
 
 
 11 
 437237875864615 
 
 
 13 
 437237875864615 
 
 
 14 
 437237875864615 
 
 
 15 
 437237875864615 
 
 
 17 
 437237875864615 
 
 
 19 
 437237875864615 
 
 
 21 
 437237875864615 
 
 
 22 
 437237875864615 
 
 
 23 
 437237875864615 
 
 
 26 
 437237875864615 
 
 
 29 
 437237875864615 
 
 
 30 
 437237875864615 
 
 
 31 
 437237875864615 
 
 
 33 
 437237875864615 
 
 
 34 
 437237875864615 
 
 
 35 
 437237875864615 
 
 
 37 
 437237875864615 
 
 
 38 
 437237875864615 
 
 
 39 
 437237875864615 
 
 
 41 
 437237875864615 
 
 
 42 
 437237875864615 
 
 
 43 
 437237875864615 
 
 
 46 
 437237875864615 
 
 
 47 
 437237875864615 
 
 
 51 
 437237875864615 
 
 
 53 
 437237875864615 
 
 
 55 
 437237875864615 
 
 
 57 
 437237875864615 
 
 
 58 
 437237875864615 
 
 
 59 
 437237875864615 
 
 
 61 
 437237875864615 
 
 
 62 
 437237875864615 
 
 
 65 
 437237875864615 
 
 
 66 
 437237875864615 
 
 
 67 
 437237875864615 
 
 
 69 
 437237875864615 
 
 
 70 
 437237875864615 
 
 
 71 
 437237875864615 
 
 
 73 
 437237875864615 
 
 
 74 
 437237875864615 
 
 
 77 
 437237875864615 
 
 
 78 
 437237875864615 
 
 
 79 
 437237875864615 
 
 
 82 
 437237875864615 
 
 
 83 
 437237875864615 
 
 
 85 
 437237875864615 
 
 
 86 
 437237875864615 
 
 
 87 
 437237875864615 
 
 
 89 
 437237875864615 
 
 
 91 
 437237875864615 
 
 
 93 
 437237875864615 
 
 
 94 
 437237875864615 
 
 
 95 
 437237875864615 
 
 
 97 
 437237875864615 
 
 
 101 
 437237875864615 
 
 
 102 
 437237875864615 
 
 
 103 
 437237875864615 
 
 
 105 
 437237875864615 
 
 
 106 
 437237875864615 
 
 
 107 
 437237875864615 
 
 
 109 
 437237875864615 
 
 
 110 
 437237875864615 
 
 
 111 
 437237875864615 
 
 
 113 
 437237875864615 
 
 
 114 
 437237875864615 
 
 
 115 
 437237875864615 
 
 
 118 
 437237875864615 
 
 
 119 
 437237875864615 
 
 
 122 
 437237875864615 
 
 
 123 
 437237875864615 
 
 
 127 
 437237875864615 
 
 
 129 
 437237875864615 
 
 
 130 
 437237875864615 
 
 
 131 
 437237875864615 
 
 
 133 
 437237875864615 
 
 
 134 
 437237875864615 
 
 
 137 
 437237875864615 
 
 
 138 
 437237875864615 
 
 
 139 
 437237875864615 
 
 
 141 
 437237875864615 
 
 
 142 
 437237875864615 
 
 
 143 
 437237875864615 
 
 
 145 
 437237875864615 
 
 
 146 
 437237875864615 
 
 
 149 
 437237875864615 
 
 
 151 
 437237875864615 
 
 
 154 
 437237875864615 
 
 
 155 
 437237875864615 
 
 
 157 
 437237875864615 
 
 
 158 
 437237875864615 
 
 
 159 
 437237875864615 
 
 
 161 
 437237875864615 
 
 
 163 
 437237875864615 
 
 
 165 
 437237875864615 
 
 
 166 
 437237875864615 
 
 
 167 
 437237875864615 
 
 
 170 
 437237875864615 
 
 
 173 
 437237875864615 
 
 
 174 
 437237875864615 
 
 
 177 
 437237875864615 
 
 
 178 
 437237875864615 
 
 
 179 
 437237875864615 
 
 
 181 
 437237875864615 
 
 
 182 
 437237875864615 
 
 
 183 
 437237875864615 
 
 
 185 
 437237875864615 
 
 
 186 
 437237875864615 
 
 
 187 
 437237875864615 
 
 
 190 
 437237875864615 
 
 
 191 
 437237875864615 
 
 
 193 
 437237875864615 
 
 
 194 
 437237875864615 
 
 
 195 
 437237875864615 
 
 
 197 
 437237875864615 
 
 
 199 
 437237875864615 
 
 
 201 
 437237875864615 
 
 
 202 
 437237875864615 
 
 
 203 
 437237875864615 
 
 
 205 
 437237875864615 
 
 
 206 
 437237875864615 
 
 
 209 
 437237875864615 
 
 
 210 
 437237875864615 
 
 
 211 
 437237875864615 
 
 
 213 
 437237875864615 
 
 
 214 
 437237875864615 
 
 
 215 
 437237875864615 
 
 
 217 
 437237875864615 
 
 
 218 
 437237875864615 
 
 
 219 
 437237875864615 
 
 
 221 
 437237875864615 
 
 
 222 
 437237875864615 
 
 
 223 
 437237875864615 
 
 
 226 
 437237875864615 
 
 
 227 
 437237875864615 
 
 
 229 
 437237875864615 
 
 
 230 
 437237875864615 
 
 
 231 
 43723787586

### Nombres de Kaprekar

**Atelier [009].** Un entier $n$ est un **nombre de Kaprekar** si et seulement si son carré peut être séparé en une partie gauche et une partie droite dont la somme vaut $n$. La partie gauche peut être vide. La partie droite ne peut être vide ou nulle.

| Exemple | Carré | Découpage       | Somme | Kaprekar                 |
|--------:|------:|----------------:|------:|:-------------------------|
| 1       | 1     | `"" + "1"`      | 1     | ✅ (NB : partie gauche vide)  |
| 5       | 25    | `"" + "25"` <br> `"2" + "5"`    | 25 <br> 7 | ❌                       |
| 9       | 81    | `"8" + "1"`     | 9     | ✅                       |
| 45      | 2025  | `"20" + "25"`   | 45    | ✅                       |
| 10      | 100   | `"10" + "0"`    | 10    | ❌ (partie droite nulle) |
| 99      | 9801  | `"98" + "01"`   | 99    | ✅                       |

_Défi._ Listez par ordre croissant les nombres de Kaprekar inférieurs ou égaux à 1000.

_Aide._ Utilisez les fonctions `left(str, len)` et `right(str, len)`.

**Annotation.**
On parcourt tous les entiers $A_i$ candidats, en excluant immédiatement les multiples de $10$
(`n MOD 10 != 0`).

Pour chaque $A_i$, on vérifie si c'est un nombre de Kaprekar via la sous-requête `EXISTS` :

- On prend le même entier $A_i$ sous l'alias $B_i$.
- On parcourt toutes les positions de coupe jusque avant le dernier caractère de $B_i^2$.
- On découpe $B_i^2$ et on somme les parties.
- On s'assure que cette somme est égale à $A_i$.

In [ ]:
%%sql
SELECT n
     , salt_009(sum(nn(hash)) OVER ()) AS token
FROM ints AS A
WHERE n MOD 10 != 0
    AND EXISTS
        (SELECT 1
         FROM ints AS cut
         JOIN ints AS B ON cut.n < length(B.n * B.n)
         WHERE A.n = B.n
             AND A.n = left(B.n * B.n, cut.n) + right(B.n * B.n, length(B.n * B.n) - cut.n) )

8 rows affected.

n 
 token 
 
 
 
 
 1 
 253600606633879 
 
 
 9 
 253600606633879 
 
 
 45 
 253600606633879 
 
 
 55 
 253600606633879 
 
 
 99 
 253600606633879 
 
 
 297 
 253600606633879 
 
 
 703 
 253600606633879 
 
 
 999 
 253600606633879

In [ ]:
%%sql
-- Variante. Avec une CTE qui précalcule les carrés une fois pour toutes.
WITH squares AS
    (SELECT n
          , n * n AS I2
     FROM ints)
SELECT n
     , salt_009(sum(nn(hash)) OVER ()) AS token
FROM ints AS A
WHERE n MOD 10 != 0
    AND EXISTS
        (SELECT 1
         FROM ints AS cut
         JOIN squares ON cut.n < length(I2)
         WHERE A.n = squares.n
             AND A.n = left(I2, cut.n) + right(I2, length(I2) - cut.n) )

8 rows affected.

n 
 token 
 
 
 
 
 1 
 253600606633879 
 
 
 9 
 253600606633879 
 
 
 45 
 253600606633879 
 
 
 55 
 253600606633879 
 
 
 99 
 253600606633879 
 
 
 297 
 253600606633879 
 
 
 703 
 253600606633879 
 
 
 999 
 253600606633879

In [ ]:
%%sql
-- Indication. Vérifiez les positions de coupe.
WITH squares AS
    (SELECT n
          , n * n AS I2
     FROM ints)
SELECT n
     , salt_009(sum(nn(hash)) OVER ()) AS token
FROM ints AS A
WHERE n MOD 10 != 0
    AND EXISTS
        (SELECT 1
         FROM ints AS cut
         JOIN squares ON cut.n < length(I2)
         WHERE A.n = squares.n
             AND A.n = left(I2, cut.n - 1) + right(I2, length(I2) - cut.n + 1) )

7 rows affected.

n 
 token 
 
 
 
 
 1 
 253974688626775 
 
 
 45 
 253974688626775 
 
 
 55 
 253974688626775 
 
 
 99 
 253974688626775 
 
 
 297 
 253974688626775 
 
 
 703 
 253974688626775 
 
 
 999 
 253974688626775

In [ ]:
%%sql
-- Indication. La partie gauche peut avoir comme longueur 1.
WITH squares AS
    (SELECT n
          , n * n AS I2
     FROM ints)
SELECT n
     , salt_009(sum(nn(hash)) OVER ()) AS token
FROM ints AS A
WHERE n MOD 10 != 0
    AND EXISTS
        (SELECT 1
         FROM ints AS cut
         JOIN squares ON cut.n < length(I2) - 1
         WHERE A.n = squares.n
             AND A.n = left(I2, cut.n) + right(I2, length(I2) - cut.n) )

6 rows affected.

n 
 token 
 
 
 
 
 45 
 254220120595727 
 
 
 55 
 254220120595727 
 
 
 99 
 254220120595727 
 
 
 297 
 254220120595727 
 
 
 703 
 254220120595727 
 
 
 999 
 254220120595727

In [ ]:
%%sql
-- Indication. Une suite de zéros n'est pas autorisée pour la partie droite.
SELECT n
     , salt_009(sum(nn(hash)) OVER ()) AS token
FROM ints AS base
WHERE EXISTS
        (SELECT 1
         FROM
             (SELECT base.n
                   , cast(left(sq, cut.n) AS UNSIGNED) AS left_part
                   , cast(right(sq, length(sq) - cut.n) AS UNSIGNED) AS right_part
              FROM
                  (SELECT n
                        , cast(n * n AS CHAR) AS sq
                   FROM ints) AS base
              JOIN ints AS cut ON cut.n BETWEEN 1 AND length(base.sq) - 1) AS parts
         WHERE parts.left_part + parts.right_part = parts.n
             AND parts.n = base.n )

10 rows affected.

n 
 token 
 
 
 
 
 9 
 253352804744747 
 
 
 10 
 253352804744747 
 
 
 45 
 253352804744747 
 
 
 55 
 253352804744747 
 
 
 99 
 253352804744747 
 
 
 100 
 253352804744747 
 
 
 297 
 253352804744747 
 
 
 703 
 253352804744747 
 
 
 999 
 253352804744747 
 
 
 1000 
 253352804744747

In [ ]:
%%sql
-- Indication. Le premier nombre de Kaprekar est 1.
SELECT n
     , salt_009(sum(nn(hash)) OVER ()) AS token
FROM ints AS base
WHERE n MOD 10 != 0
    AND EXISTS
        (SELECT 1
         FROM
             (SELECT base.n
                   , cast(left(sq, cut.n) AS UNSIGNED) AS left_part
                   , cast(right(sq, length(sq) - cut.n) AS UNSIGNED) AS right_part
              FROM
                  (SELECT n
                        , cast(n * n AS CHAR) AS sq
                   FROM ints) AS base
              JOIN ints AS cut ON cut.n BETWEEN 1 AND length(base.sq) - 1) AS parts
         WHERE parts.left_part + parts.right_part = parts.n
             AND parts.n = base.n )

7 rows affected.

n 
 token 
 
 
 
 
 9 
 253843891117135 
 
 
 45 
 253843891117135 
 
 
 55 
 253843891117135 
 
 
 99 
 253843891117135 
 
 
 297 
 253843891117135 
 
 
 703 
 253843891117135 
 
 
 999 
 253843891117135

In [ ]:
%%sql
-- Indication. Une suite de zéros n'est pas autorisée pour la partie droite.
SELECT n
     , salt_009(sum(nn(hash)) OVER ()) AS token
FROM ints AS base
WHERE n = 1
    OR EXISTS
        (SELECT 1
         FROM
             (SELECT base.n
                   , cast(left(sq, cut.n) AS UNSIGNED) AS left_part
                   , cast(right(sq, length(sq) - cut.n) AS UNSIGNED) AS right_part
              FROM
                  (SELECT n
                        , cast(n * n AS CHAR) AS sq
                   FROM ints) AS base
              JOIN ints AS cut ON cut.n BETWEEN 1 AND length(base.sq) - 1) AS parts
         WHERE parts.left_part + parts.right_part = parts.n
             AND parts.n = base.n )

11 rows affected.

n 
 token 
 
 
 
 
 1 
 253109520226675 
 
 
 9 
 253109520226675 
 
 
 10 
 253109520226675 
 
 
 45 
 253109520226675 
 
 
 55 
 253109520226675 
 
 
 99 
 253109520226675 
 
 
 100 
 253109520226675 
 
 
 297 
 253109520226675 
 
 
 703 
 253109520226675 
 
 
 999 
 253109520226675 
 
 
 1000 
 253109520226675

### Pics de Collatz

**Atelier [025].** On part d'un entier $n$ strictement positif. On le remplace par $n/2$ s'il est pair, et par $3n+1$ s'il est impair. On recommence le processus jusqu'à atteindre $1$. Les nombres ainsi générés constituent la **trajectoire de Collatz** de $n$. Le plus grand est le **pic de Collatz** de $n$. Par exemple :

| Terme | Trajectoire | Pic |
|-------:|-----------:|----:|
| 1 | **1** | 1 |
| 2 | **2**, 1 | 2 |
| 3 | 10, 5, **16**, 8, 4, 2, 1 | 16 |
| 4 | **4**, 2, 1 | 4 |
| 5 | 5, **16**, 8, 4, 2, 1 | 16 |
| 6 | 6, 3, 10, 5, **16**, 8, 4, 2, 1 | 16 |
| 7 | 7, 22, 11, 34, 17, **52**, 26, 13, 40, 20, 10, 5, 16, 8, 4, 2, 1 | 52 |
| ⋮ |  |  |

_Défi._ Listez les pics de tous les entiers de 1 à 1000.

_Aide._ Utilisez une CTE (_Common Table Expression_) récursive à deux colonnes.

In [ ]:
x = '1000.1.2.16.4.16.16.52.8.52.16.52.16.40.52.160.16.52.52.88.20' # concaténation du nombre de lignes et des vingt premiers pics
# Javascript: [result.length].concat(result.slice(0, 20).col('peak')).join('.')

In [ ]:
%%sql
-- La CTE récursive applique la suite de Collatz à chaque entier strictement positif de `ints`. Une ligne de
-- `steps` stocke à la fois l'entier d’origine ($i$) et la valeur courante ($n$). La partie récursive remplace la
-- le $n$ par $C(n)$, et continue jusqu’à atteindre 1. La requête finale regroupe les lignes par entier initial $i$,
-- et calcule le maximum des $n$ de la trajectoire correspondante.
WITH RECURSIVE steps (i, n) AS (
    SELECT n, n
    FROM ints
    WHERE n > 0
    
    UNION ALL
    
    SELECT
        i, 
        CASE n mod 2 WHEN 0 THEN n DIV 2 ELSE 3 * n + 1 END
    FROM steps
    WHERE n > 1
)
SELECT max(n) as peak
     , salt_025(sum(string_hash('{{x}}')) OVER ()) AS token
FROM steps
GROUP BY i

1000 rows affected.

peak 
 token 
 
 
 
 
 1 
 876450356392193 
 
 
 2 
 876450356392193 
 
 
 16 
 876450356392193 
 
 
 4 
 876450356392193 
 
 
 16 
 876450356392193 
 
 
 16 
 876450356392193 
 
 
 52 
 876450356392193 
 
 
 8 
 876450356392193 
 
 
 52 
 876450356392193 
 
 
 16 
 876450356392193 
 
 
 52 
 876450356392193 
 
 
 16 
 876450356392193 
 
 
 40 
 876450356392193 
 
 
 52 
 876450356392193 
 
 
 160 
 876450356392193 
 
 
 16 
 876450356392193 
 
 
 52 
 876450356392193 
 
 
 52 
 876450356392193 
 
 
 88 
 876450356392193 
 
 
 20 
 876450356392193 
 
 
 64 
 876450356392193 
 
 
 52 
 876450356392193 
 
 
 160 
 876450356392193 
 
 
 24 
 876450356392193 
 
 
 88 
 876450356392193 
 
 
 40 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 52 
 876450356392193 
 
 
 88 
 876450356392193 
 
 
 160 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 32 
 876450356392193 
 
 
 100 
 876450356392193 
 
 
 52 
 876450356392193 
 
 
 160 
 876450356392193 
 
 
 52 
 876450356392193 
 
 
 112 
 876450356392193 
 
 
 88 
 876450356392193 
 
 
 304 
 876450356392193 
 
 
 40 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 64 
 876450356392193 
 
 
 196 
 876450356392193 
 
 
 52 
 876450356392193 
 
 
 136 
 876450356392193 
 
 
 160 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 48 
 876450356392193 
 
 
 148 
 876450356392193 
 
 
 88 
 876450356392193 
 
 
 232 
 876450356392193 
 
 
 52 
 876450356392193 
 
 
 160 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 56 
 876450356392193 
 
 
 196 
 876450356392193 
 
 
 88 
 876450356392193 
 
 
 304 
 876450356392193 
 
 
 160 
 876450356392193 
 
 
 184 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 64 
 876450356392193 
 
 
 196 
 876450356392193 
 
 
 100 
 876450356392193 
 
 
 304 
 876450356392193 
 
 
 68 
 876450356392193 
 
 
 208 
 876450356392193 
 
 
 160 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 72 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 112 
 876450356392193 
 
 
 340 
 876450356392193 
 
 
 88 
 876450356392193 
 
 
 232 
 876450356392193 
 
 
 304 
 876450356392193 
 
 
 808 
 876450356392193 
 
 
 80 
 876450356392193 
 
 
 244 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 84 
 876450356392193 
 
 
 256 
 876450356392193 
 
 
 196 
 876450356392193 
 
 
 592 
 876450356392193 
 
 
 88 
 876450356392193 
 
 
 304 
 876450356392193 
 
 
 136 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 160 
 876450356392193 
 
 
 280 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 96 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 148 
 876450356392193 
 
 
 448 
 876450356392193 
 
 
 100 
 876450356392193 
 
 
 304 
 876450356392193 
 
 
 232 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 104 
 876450356392193 
 
 
 808 
 876450356392193 
 
 
 160 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 112 
 876450356392193 
 
 
 340 
 876450356392193 
 
 
 196 
 876450356392193 
 
 
 520 
 876450356392193 
 
 
 116 
 876450356392193 
 
 
 352 
 876450356392193 
 
 
 304 
 876450356392193 
 
 
 808 
 876450356392193 
 
 
 160 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 184 
 876450356392193 
 
 
 628 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 4372 
 876450356392193 
 
 
 128 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 196 
 876450356392193 
 
 
 592 
 876450356392193 
 
 
 132 
 876450356392193 
 
 
 400 
 876450356392193 
 
 
 304 
 876450356392193 
 
 
 916 
 876450356392193 
 
 
 136 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 208 
 876450356392193 
 
 
 628 
 876450356392193 
 
 
 160 
 876450356392193 
 
 
 424 
 876450356392193 
 
 
 9232 
 876450356392193 
 
 
 9232 
 87645035639219

In [ ]:
assert '.'.join(map(str, [len(_)] + col['peak'][:20])) == x

In [ ]:
x = '1001.0.1.2.16.4.16.16.52.8.52.16.52.16.40.52.160.16.52.52.88'

In [ ]:
%%sql
-- Indication. Le plus petit entier de départ devrait être 1.
WITH RECURSIVE steps (i, n) AS (
    SELECT n, n
    FROM ints
    
    UNION ALL
    
    SELECT
        i, 
        CASE n mod 2 WHEN 0 THEN n DIV 2 ELSE 3 * n + 1 END
    FROM steps
    WHERE n > 1
)
SELECT max(n) as peak
     , salt_025(sum(string_hash('{{x}}')) OVER ()) AS token
FROM steps
GROUP BY i

1001 rows affected.

peak 
 token 
 
 
 
 
 0 
 1101605527154113 
 
 
 1 
 1101605527154113 
 
 
 2 
 1101605527154113 
 
 
 16 
 1101605527154113 
 
 
 4 
 1101605527154113 
 
 
 16 
 1101605527154113 
 
 
 16 
 1101605527154113 
 
 
 52 
 1101605527154113 
 
 
 8 
 1101605527154113 
 
 
 52 
 1101605527154113 
 
 
 16 
 1101605527154113 
 
 
 52 
 1101605527154113 
 
 
 16 
 1101605527154113 
 
 
 40 
 1101605527154113 
 
 
 52 
 1101605527154113 
 
 
 160 
 1101605527154113 
 
 
 16 
 1101605527154113 
 
 
 52 
 1101605527154113 
 
 
 52 
 1101605527154113 
 
 
 88 
 1101605527154113 
 
 
 20 
 1101605527154113 
 
 
 64 
 1101605527154113 
 
 
 52 
 1101605527154113 
 
 
 160 
 1101605527154113 
 
 
 24 
 1101605527154113 
 
 
 88 
 1101605527154113 
 
 
 40 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 52 
 1101605527154113 
 
 
 88 
 1101605527154113 
 
 
 160 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 32 
 1101605527154113 
 
 
 100 
 1101605527154113 
 
 
 52 
 1101605527154113 
 
 
 160 
 1101605527154113 
 
 
 52 
 1101605527154113 
 
 
 112 
 1101605527154113 
 
 
 88 
 1101605527154113 
 
 
 304 
 1101605527154113 
 
 
 40 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 64 
 1101605527154113 
 
 
 196 
 1101605527154113 
 
 
 52 
 1101605527154113 
 
 
 136 
 1101605527154113 
 
 
 160 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 48 
 1101605527154113 
 
 
 148 
 1101605527154113 
 
 
 88 
 1101605527154113 
 
 
 232 
 1101605527154113 
 
 
 52 
 1101605527154113 
 
 
 160 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 56 
 1101605527154113 
 
 
 196 
 1101605527154113 
 
 
 88 
 1101605527154113 
 
 
 304 
 1101605527154113 
 
 
 160 
 1101605527154113 
 
 
 184 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 64 
 1101605527154113 
 
 
 196 
 1101605527154113 
 
 
 100 
 1101605527154113 
 
 
 304 
 1101605527154113 
 
 
 68 
 1101605527154113 
 
 
 208 
 1101605527154113 
 
 
 160 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 72 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 112 
 1101605527154113 
 
 
 340 
 1101605527154113 
 
 
 88 
 1101605527154113 
 
 
 232 
 1101605527154113 
 
 
 304 
 1101605527154113 
 
 
 808 
 1101605527154113 
 
 
 80 
 1101605527154113 
 
 
 244 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 84 
 1101605527154113 
 
 
 256 
 1101605527154113 
 
 
 196 
 1101605527154113 
 
 
 592 
 1101605527154113 
 
 
 88 
 1101605527154113 
 
 
 304 
 1101605527154113 
 
 
 136 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 160 
 1101605527154113 
 
 
 280 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 96 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 148 
 1101605527154113 
 
 
 448 
 1101605527154113 
 
 
 100 
 1101605527154113 
 
 
 304 
 1101605527154113 
 
 
 232 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 104 
 1101605527154113 
 
 
 808 
 1101605527154113 
 
 
 160 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 112 
 1101605527154113 
 
 
 340 
 1101605527154113 
 
 
 196 
 1101605527154113 
 
 
 520 
 1101605527154113 
 
 
 116 
 1101605527154113 
 
 
 352 
 1101605527154113 
 
 
 304 
 1101605527154113 
 
 
 808 
 1101605527154113 
 
 
 160 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 184 
 1101605527154113 
 
 
 628 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 4372 
 1101605527154113 
 
 
 128 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 
 196 
 1101605527154113 
 
 
 592 
 1101605527154113 
 
 
 132 
 1101605527154113 
 
 
 400 
 1101605527154113 
 
 
 304 
 1101605527154113 
 
 
 916 
 1101605527154113 
 
 
 136 
 1101605527154113 
 
 
 9232 
 1101605527154113 
 
 

In [ ]:
assert '.'.join(map(str, [len(_)] + col['peak'][:20])) == x

### Suite de Fibonacci

**Atelier [019].** La **suite de Fibonacci** commence par 0 et 1, ensuite chaque terme est la somme des deux précédents :

| Terme | Explication |
|-------:|:-------:|
| $0$      | (donné) |
| $1$      | (donné) |
| $1$      | $$0 + 1 = 1$$ |
| $2$      | $$1 + 1 = 2$$ |
| $3$      | $$1 + 2 = 3$$ |
| $5$      | $$2 + 3 = 5$$ |
| $8$      | $$3 + 5 = 8$$ |
| $13$     | $$5 + 8 = 13$$ |
|  ⋮  |   |

_Défi._ Listez par ordre croissant tous les nombres de Fibonacci inférieurs ou égaux à 1000.

_Aide._ Utilisez une CTE (_Common Table Expression_) récursive.

_NB._ Cette suite comportant une répétion, vous ne pouvez pas l'exprimer comme une sous-séquence de la suite des entiers naturels. Ici, exceptionnellement, passez-vous de la table `ints`.

In [ ]:
x = '0.1.1.2.3.5.8.13.21.34.55.89.144.233.377.610.987' # la concaténation de ces nombres.
# Javascript: result.col('n').join('.') || '7_531_148'

In [ ]:
%%sql
WITH RECURSIVE
fib (a, b) AS (
    SELECT 0, 1

    UNION ALL

    SELECT b, a + b
    FROM fib
    WHERE b <= 1000 )
SELECT a as n
     , salt_019(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM fib

17 rows affected.

n 
 token 
 
 
 
 
 0 
 149114173335496 
 
 
 1 
 149114173335496 
 
 
 1 
 149114173335496 
 
 
 2 
 149114173335496 
 
 
 3 
 149114173335496 
 
 
 5 
 149114173335496 
 
 
 8 
 149114173335496 
 
 
 13 
 149114173335496 
 
 
 21 
 149114173335496 
 
 
 34 
 149114173335496 
 
 
 55 
 149114173335496 
 
 
 89 
 149114173335496 
 
 
 144 
 149114173335496 
 
 
 233 
 149114173335496 
 
 
 377 
 149114173335496 
 
 
 610 
 149114173335496 
 
 
 987 
 149114173335496

In [ ]:
assert '.'.join(map(str, col['n'])) == x

In [ ]:
x = '0.1.1.2.3.5.8.13.21.34.55.89.144.233.377.610.987.1597'

In [ ]:
%%sql
-- Indication. Vous stoppez la récursion une itération trop tard.
WITH RECURSIVE
fib (a, b) AS (
    SELECT 0, 1

    UNION ALL

    SELECT b, a + b
     FROM fib
     WHERE a <= 1000 )
SELECT a as n
     , salt_019(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM fib

18 rows affected.

n 
 token 
 
 
 
 
 0 
 148611824478556 
 
 
 1 
 148611824478556 
 
 
 1 
 148611824478556 
 
 
 2 
 148611824478556 
 
 
 3 
 148611824478556 
 
 
 5 
 148611824478556 
 
 
 8 
 148611824478556 
 
 
 13 
 148611824478556 
 
 
 21 
 148611824478556 
 
 
 34 
 148611824478556 
 
 
 55 
 148611824478556 
 
 
 89 
 148611824478556 
 
 
 144 
 148611824478556 
 
 
 233 
 148611824478556 
 
 
 377 
 148611824478556 
 
 
 610 
 148611824478556 
 
 
 987 
 148611824478556 
 
 
 1597 
 148611824478556

In [ ]:
assert '.'.join(map(str, col['n'])) == x

In [ ]:
x = '1.1.2.3.5.8.13.21.34.55.89.144.233.377.610.987'

In [ ]:
%%sql
-- Indication. Le premier terme devrait être 0.
WITH RECURSIVE
fib (a, b) AS (
    SELECT 1, 1

    UNION ALL

    SELECT b, a + b
     FROM fib
     WHERE b <= 1000 )
SELECT a as n
     , salt_019(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM fib

16 rows affected.

n 
 token 
 
 
 
 
 1 
 148879872816411 
 
 
 1 
 148879872816411 
 
 
 2 
 148879872816411 
 
 
 3 
 148879872816411 
 
 
 5 
 148879872816411 
 
 
 8 
 148879872816411 
 
 
 13 
 148879872816411 
 
 
 21 
 148879872816411 
 
 
 34 
 148879872816411 
 
 
 55 
 148879872816411 
 
 
 89 
 148879872816411 
 
 
 144 
 148879872816411 
 
 
 233 
 148879872816411 
 
 
 377 
 148879872816411 
 
 
 610 
 148879872816411 
 
 
 987 
 148879872816411

In [ ]:
assert '.'.join(map(str, col['n'])) == x

In [ ]:
x = '1.1.2.3.5.8.13.21.34.55.89.144.233.377.610.987.1597'

In [ ]:
%%sql
-- Indication. Votre séquence semble décalée de 1. Projetez-vous la bonne colonne du résultat de la CTE ?
WITH RECURSIVE
fib (a, b) AS (
    SELECT 0, 1

    UNION ALL

    SELECT b, a + b
     FROM fib
     WHERE b <= 1000 )
SELECT b as n
     , salt_019(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM fib

17 rows affected.

n 
 token 
 
 
 
 
 1 
 148669601188638 
 
 
 1 
 148669601188638 
 
 
 2 
 148669601188638 
 
 
 3 
 148669601188638 
 
 
 5 
 148669601188638 
 
 
 8 
 148669601188638 
 
 
 13 
 148669601188638 
 
 
 21 
 148669601188638 
 
 
 34 
 148669601188638 
 
 
 55 
 148669601188638 
 
 
 89 
 148669601188638 
 
 
 144 
 148669601188638 
 
 
 233 
 148669601188638 
 
 
 377 
 148669601188638 
 
 
 610 
 148669601188638 
 
 
 987 
 148669601188638 
 
 
 1597 
 148669601188638

In [ ]:
assert '.'.join(map(str, col['n'])) == x

In [ ]:
x = '0.1.2.3.5.8.13.21.34.55.89.144.233.377.610.987'

In [ ]:
%%sql
-- Indication. Deux 1 devraient apparaître. Auriez-vous malencontreusement éliminé les redondances du résultat
-- de votre CTE ?
WITH RECURSIVE
fib (a, b) AS (
    SELECT 0, 1

    UNION ALL

    SELECT b, a + b
    FROM fib
    WHERE b <= 1000 )
SELECT n
     , salt_019(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM ints
WHERE n in (SELECT a FROM fib)

16 rows affected.

n 
 token 
 
 
 
 
 0 
 148515034955604 
 
 
 1 
 148515034955604 
 
 
 2 
 148515034955604 
 
 
 3 
 148515034955604 
 
 
 5 
 148515034955604 
 
 
 8 
 148515034955604 
 
 
 13 
 148515034955604 
 
 
 21 
 148515034955604 
 
 
 34 
 148515034955604 
 
 
 55 
 148515034955604 
 
 
 89 
 148515034955604 
 
 
 144 
 148515034955604 
 
 
 233 
 148515034955604 
 
 
 377 
 148515034955604 
 
 
 610 
 148515034955604 
 
 
 987 
 148515034955604

In [ ]:
assert '.'.join(map(str, col['n'])) == x

In [ ]:
x = '0.1.2.3.6.11.20.37.68.125.230.423.778'

In [ ]:
%%sql
-- Indication. Vous êtes en train de réinventer les [nombres de « Tribonacci »](https://oeis.org/A001590),
-- une récurrence d'ordre 3 (au lieu de 2 pour Fibonacci). Écrivez une CTE à deux colonnes.
WITH RECURSIVE
fib (a, b, c) AS (
    SELECT 0, 1, 1

    UNION ALL

    SELECT b, b+c, a+b
    FROM fib
    WHERE b <= 1000 )
SELECT a as n
     , salt_019(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM fib

13 rows affected.

n 
 token 
 
 
 
 
 0 
 149468789687598 
 
 
 1 
 149468789687598 
 
 
 2 
 149468789687598 
 
 
 3 
 149468789687598 
 
 
 6 
 149468789687598 
 
 
 11 
 149468789687598 
 
 
 20 
 149468789687598 
 
 
 37 
 149468789687598 
 
 
 68 
 149468789687598 
 
 
 125 
 149468789687598 
 
 
 230 
 149468789687598 
 
 
 423 
 149468789687598 
 
 
 778 
 149468789687598

In [ ]:
assert '.'.join(map(str, col['n'])) == x

In [ ]:
x = '0.0.1.1.2.4.7.13.24.44.81.149.274.504.927'

In [ ]:
%%sql
-- Indication. Vous êtes en train de réinventer les [nombres de « Tribonacci »](https://oeis.org/A000073),
-- une récurrence d'ordre 3 (au lieu de 2 pour Fibonacci). Écrivez une CTE à deux colonnes.
WITH RECURSIVE
fib (a, b, c) AS (
    SELECT 0, 0, 1

    UNION ALL

    SELECT b, b+c, a+b
    FROM fib
    WHERE b <= 1000 )
SELECT a as n
     , salt_019(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM fib

15 rows affected.

n 
 token 
 
 
 
 
 0 
 149210280710509 
 
 
 0 
 149210280710509 
 
 
 1 
 149210280710509 
 
 
 1 
 149210280710509 
 
 
 2 
 149210280710509 
 
 
 4 
 149210280710509 
 
 
 7 
 149210280710509 
 
 
 13 
 149210280710509 
 
 
 24 
 149210280710509 
 
 
 44 
 149210280710509 
 
 
 81 
 149210280710509 
 
 
 149 
 149210280710509 
 
 
 274 
 149210280710509 
 
 
 504 
 149210280710509 
 
 
 927 
 149210280710509

In [ ]:
assert '.'.join(map(str, col['n'])) == x

In [ ]:
x = '0.1.1.2.4.7.13.24.44.81.149.274.504.927'

In [ ]:
%%sql
-- Indication. Vous êtes en train de réinventer les [nombres de « Tribonacci »](https://oeis.org/A000073),
-- une récurrence d'ordre 3 (au lieu de 2 pour Fibonacci). Écrivez une CTE à deux colonnes.
WITH RECURSIVE
fib (a, b, c) AS (
    SELECT 0, 1, 0

    UNION ALL

    SELECT b, b+c, a+b
    FROM fib
    WHERE b <= 1000 )
SELECT a as n
     , salt_019(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM fib

14 rows affected.

n 
 token 
 
 
 
 
 0 
 149003955203329 
 
 
 1 
 149003955203329 
 
 
 1 
 149003955203329 
 
 
 2 
 149003955203329 
 
 
 4 
 149003955203329 
 
 
 7 
 149003955203329 
 
 
 13 
 149003955203329 
 
 
 24 
 149003955203329 
 
 
 44 
 149003955203329 
 
 
 81 
 149003955203329 
 
 
 149 
 149003955203329 
 
 
 274 
 149003955203329 
 
 
 504 
 149003955203329 
 
 
 927 
 149003955203329

In [ ]:
assert '.'.join(map(str, col['n'])) == x

### Nombres de Harshad

**Atelier [039].** Un entier est un **nombre de Harshad** si et seulement s'il est divisible par la somme de ses chiffres (en écriture décimale).

| Exemple | Chiffres | Somme | Propriété | Harshad |
|---:|:--:|:--:|:--:|:--:|
| $42$ | $${4, 2}$$ | $6$ | divisible | ✅ |
| $11$ | $${1, 1}$$ | $2$ | non divisible | ❌ |

_Défi._ Listez par ordre croissant les nombres de Harshad inférieurs ou égaux à 1000.

_Contrainte._ Utilisez une CTE récursive.

In [ ]:
x = '213.1.2.3.4.5.6.7.8.9.10.12.18.20.21.24.27.30.36.40.42' # concaténation du nombre de lignes et des vingt premiers n
# Javascript: [result.length].concat(result.slice(0, 20).col('n')).join('.')

In [ ]:
%%sql
-- On construit récursivement une table avec tous les chiffres de chaque nombre. Ensuite, on regroupe par
-- nombre. Enfin, on teste la propriété de divisibilité avec la somme des chiffres de chaque nombre.
WITH RECURSIVE
digits (n, q, r) AS
    (SELECT n
          , n MOD 10
          , n DIV 10
     FROM ints

     UNION ALL

     SELECT n
          , r MOD 10
          , r DIV 10
     FROM digits
     WHERE r > 0 )
SELECT n
     , salt_039(sum(string_hash('{{x}}')) OVER ()) AS token
FROM digits
GROUP BY n
HAVING n MOD sum(q) = 0

213 rows affected.

n 
 token 
 
 
 
 
 1 
 243582352371835 
 
 
 2 
 243582352371835 
 
 
 3 
 243582352371835 
 
 
 4 
 243582352371835 
 
 
 5 
 243582352371835 
 
 
 6 
 243582352371835 
 
 
 7 
 243582352371835 
 
 
 8 
 243582352371835 
 
 
 9 
 243582352371835 
 
 
 10 
 243582352371835 
 
 
 12 
 243582352371835 
 
 
 18 
 243582352371835 
 
 
 20 
 243582352371835 
 
 
 21 
 243582352371835 
 
 
 24 
 243582352371835 
 
 
 27 
 243582352371835 
 
 
 30 
 243582352371835 
 
 
 36 
 243582352371835 
 
 
 40 
 243582352371835 
 
 
 42 
 243582352371835 
 
 
 45 
 243582352371835 
 
 
 48 
 243582352371835 
 
 
 50 
 243582352371835 
 
 
 54 
 243582352371835 
 
 
 60 
 243582352371835 
 
 
 63 
 243582352371835 
 
 
 70 
 243582352371835 
 
 
 72 
 243582352371835 
 
 
 80 
 243582352371835 
 
 
 81 
 243582352371835 
 
 
 84 
 243582352371835 
 
 
 90 
 243582352371835 
 
 
 100 
 243582352371835 
 
 
 102 
 243582352371835 
 
 
 108 
 243582352371835 
 
 
 110 
 243582352371835 
 
 
 111 
 243582352371835 
 
 
 112 
 243582352371835 
 
 
 114 
 243582352371835 
 
 
 117 
 243582352371835 
 
 
 120 
 243582352371835 
 
 
 126 
 243582352371835 
 
 
 132 
 243582352371835 
 
 
 133 
 243582352371835 
 
 
 135 
 243582352371835 
 
 
 140 
 243582352371835 
 
 
 144 
 243582352371835 
 
 
 150 
 243582352371835 
 
 
 152 
 243582352371835 
 
 
 153 
 243582352371835 
 
 
 156 
 243582352371835 
 
 
 162 
 243582352371835 
 
 
 171 
 243582352371835 
 
 
 180 
 243582352371835 
 
 
 190 
 243582352371835 
 
 
 192 
 243582352371835 
 
 
 195 
 243582352371835 
 
 
 198 
 243582352371835 
 
 
 200 
 243582352371835 
 
 
 201 
 243582352371835 
 
 
 204 
 243582352371835 
 
 
 207 
 243582352371835 
 
 
 209 
 243582352371835 
 
 
 210 
 243582352371835 
 
 
 216 
 243582352371835 
 
 
 220 
 243582352371835 
 
 
 222 
 243582352371835 
 
 
 224 
 243582352371835 
 
 
 225 
 243582352371835 
 
 
 228 
 243582352371835 
 
 
 230 
 243582352371835 
 
 
 234 
 243582352371835 
 
 
 240 
 243582352371835 
 
 
 243 
 243582352371835 
 
 
 247 
 243582352371835 
 
 
 252 
 243582352371835 
 
 
 261 
 243582352371835 
 
 
 264 
 243582352371835 
 
 
 266 
 243582352371835 
 
 
 270 
 243582352371835 
 
 
 280 
 243582352371835 
 
 
 285 
 243582352371835 
 
 
 288 
 243582352371835 
 
 
 300 
 243582352371835 
 
 
 306 
 243582352371835 
 
 
 308 
 243582352371835 
 
 
 312 
 243582352371835 
 
 
 315 
 243582352371835 
 
 
 320 
 243582352371835 
 
 
 322 
 243582352371835 
 
 
 324 
 243582352371835 
 
 
 330 
 243582352371835 
 
 
 333 
 243582352371835 
 
 
 336 
 243582352371835 
 
 
 342 
 243582352371835 
 
 
 351 
 243582352371835 
 
 
 360 
 243582352371835 
 
 
 364 
 243582352371835 
 
 
 370 
 243582352371835 
 
 
 372 
 243582352371835 
 
 
 375 
 243582352371835 
 
 
 378 
 243582352371835 
 
 
 392 
 243582352371835 
 
 
 396 
 243582352371835 
 
 
 399 
 243582352371835 
 
 
 400 
 243582352371835 
 
 
 402 
 243582352371835 
 
 
 405 
 243582352371835 
 
 
 407 
 243582352371835 
 
 
 408 
 243582352371835 
 
 
 410 
 243582352371835 
 
 
 414 
 243582352371835 
 
 
 420 
 243582352371835 
 
 
 423 
 243582352371835 
 
 
 432 
 243582352371835 
 
 
 440 
 243582352371835 
 
 
 441 
 243582352371835 
 
 
 444 
 243582352371835 
 
 
 448 
 243582352371835 
 
 
 450 
 243582352371835 
 
 
 460 
 243582352371835 
 
 
 465 
 243582352371835 
 
 
 468 
 243582352371835 
 
 
 476 
 243582352371835 
 
 
 480 
 243582352371835 
 
 
 481 
 243582352371835 
 
 
 486 
 243582352371835 
 
 
 500 
 243582352371835 
 
 
 504 
 243582352371835 
 
 
 506 
 243582352371835 
 
 
 510 
 243582352371835 
 
 
 511 
 243582352371835 
 
 
 512 
 243582352371835 
 
 
 513 
 243582352371835 
 
 
 516 
 243582352371835 
 
 
 518 
 243582352371835 
 
 
 522 
 243582352371835 
 
 
 531 
 243582352371835 
 
 
 540 
 243582352371835 
 
 
 550 
 243582352371835 
 
 
 552 
 243582352371835 
 
 
 555 
 243582352371835 
 
 
 558 
 243582352371835 
 
 
 576 
 24358235237

In [ ]:
assert '.'.join(map(str, [len(col['n'])] + col['n'][:20])) == x

In [ ]:
%%sql
-- Variante. On peut calculer la somme au fur et à mesure de la récursion au lieu de reparcourir la table
-- après coup. La table construite récursivement associe, à chaque nombre de $d$ chiffres, $d$ sommes
-- intermédiaires. Attention : seule la dernière (`r = 0`) nous intéresse.
WITH RECURSIVE
digits(n, digit_sum, r) AS (
    SELECT n, n MOD 10, n DIV 10
    FROM ints
    
    UNION ALL
    
    SELECT n, digit_sum + (r MOD 10), r DIV 10
    FROM digits
    WHERE r > 0
)
SELECT n
     , salt_039(sum(string_hash('{{x}}')) OVER ()) AS token
FROM digits
WHERE r = 0 AND n MOD digit_sum = 0

213 rows affected.

n 
 token 
 
 
 
 
 1 
 243582352371835 
 
 
 2 
 243582352371835 
 
 
 3 
 243582352371835 
 
 
 4 
 243582352371835 
 
 
 5 
 243582352371835 
 
 
 6 
 243582352371835 
 
 
 7 
 243582352371835 
 
 
 8 
 243582352371835 
 
 
 9 
 243582352371835 
 
 
 10 
 243582352371835 
 
 
 12 
 243582352371835 
 
 
 18 
 243582352371835 
 
 
 20 
 243582352371835 
 
 
 21 
 243582352371835 
 
 
 24 
 243582352371835 
 
 
 27 
 243582352371835 
 
 
 30 
 243582352371835 
 
 
 36 
 243582352371835 
 
 
 40 
 243582352371835 
 
 
 42 
 243582352371835 
 
 
 45 
 243582352371835 
 
 
 48 
 243582352371835 
 
 
 50 
 243582352371835 
 
 
 54 
 243582352371835 
 
 
 60 
 243582352371835 
 
 
 63 
 243582352371835 
 
 
 70 
 243582352371835 
 
 
 72 
 243582352371835 
 
 
 80 
 243582352371835 
 
 
 81 
 243582352371835 
 
 
 84 
 243582352371835 
 
 
 90 
 243582352371835 
 
 
 100 
 243582352371835 
 
 
 102 
 243582352371835 
 
 
 108 
 243582352371835 
 
 
 110 
 243582352371835 
 
 
 111 
 243582352371835 
 
 
 112 
 243582352371835 
 
 
 114 
 243582352371835 
 
 
 117 
 243582352371835 
 
 
 120 
 243582352371835 
 
 
 126 
 243582352371835 
 
 
 132 
 243582352371835 
 
 
 133 
 243582352371835 
 
 
 135 
 243582352371835 
 
 
 140 
 243582352371835 
 
 
 144 
 243582352371835 
 
 
 150 
 243582352371835 
 
 
 152 
 243582352371835 
 
 
 153 
 243582352371835 
 
 
 156 
 243582352371835 
 
 
 162 
 243582352371835 
 
 
 171 
 243582352371835 
 
 
 180 
 243582352371835 
 
 
 190 
 243582352371835 
 
 
 192 
 243582352371835 
 
 
 195 
 243582352371835 
 
 
 198 
 243582352371835 
 
 
 200 
 243582352371835 
 
 
 201 
 243582352371835 
 
 
 204 
 243582352371835 
 
 
 207 
 243582352371835 
 
 
 209 
 243582352371835 
 
 
 210 
 243582352371835 
 
 
 216 
 243582352371835 
 
 
 220 
 243582352371835 
 
 
 222 
 243582352371835 
 
 
 224 
 243582352371835 
 
 
 225 
 243582352371835 
 
 
 228 
 243582352371835 
 
 
 230 
 243582352371835 
 
 
 234 
 243582352371835 
 
 
 240 
 243582352371835 
 
 
 243 
 243582352371835 
 
 
 247 
 243582352371835 
 
 
 252 
 243582352371835 
 
 
 261 
 243582352371835 
 
 
 264 
 243582352371835 
 
 
 266 
 243582352371835 
 
 
 270 
 243582352371835 
 
 
 280 
 243582352371835 
 
 
 285 
 243582352371835 
 
 
 288 
 243582352371835 
 
 
 300 
 243582352371835 
 
 
 306 
 243582352371835 
 
 
 308 
 243582352371835 
 
 
 312 
 243582352371835 
 
 
 315 
 243582352371835 
 
 
 320 
 243582352371835 
 
 
 322 
 243582352371835 
 
 
 324 
 243582352371835 
 
 
 330 
 243582352371835 
 
 
 333 
 243582352371835 
 
 
 336 
 243582352371835 
 
 
 342 
 243582352371835 
 
 
 351 
 243582352371835 
 
 
 360 
 243582352371835 
 
 
 364 
 243582352371835 
 
 
 370 
 243582352371835 
 
 
 372 
 243582352371835 
 
 
 375 
 243582352371835 
 
 
 378 
 243582352371835 
 
 
 392 
 243582352371835 
 
 
 396 
 243582352371835 
 
 
 399 
 243582352371835 
 
 
 400 
 243582352371835 
 
 
 402 
 243582352371835 
 
 
 405 
 243582352371835 
 
 
 407 
 243582352371835 
 
 
 408 
 243582352371835 
 
 
 410 
 243582352371835 
 
 
 414 
 243582352371835 
 
 
 420 
 243582352371835 
 
 
 423 
 243582352371835 
 
 
 432 
 243582352371835 
 
 
 440 
 243582352371835 
 
 
 441 
 243582352371835 
 
 
 444 
 243582352371835 
 
 
 448 
 243582352371835 
 
 
 450 
 243582352371835 
 
 
 460 
 243582352371835 
 
 
 465 
 243582352371835 
 
 
 468 
 243582352371835 
 
 
 476 
 243582352371835 
 
 
 480 
 243582352371835 
 
 
 481 
 243582352371835 
 
 
 486 
 243582352371835 
 
 
 500 
 243582352371835 
 
 
 504 
 243582352371835 
 
 
 506 
 243582352371835 
 
 
 510 
 243582352371835 
 
 
 511 
 243582352371835 
 
 
 512 
 243582352371835 
 
 
 513 
 243582352371835 
 
 
 516 
 243582352371835 
 
 
 518 
 243582352371835 
 
 
 522 
 243582352371835 
 
 
 531 
 243582352371835 
 
 
 540 
 243582352371835 
 
 
 550 
 243582352371835 
 
 
 552 
 243582352371835 
 
 
 555 
 243582352371835 
 
 
 558 
 243582352371835 
 
 
 576 
 24358235237

In [ ]:
assert '.'.join(map(str, [len(col['n'])] + col['n'][:20])) == x

In [ ]:
x = '9.1.2.3.4.5.6.7.8.9'

In [ ]:
%%sql
-- Indication. Il y a quelque chose de louche ! Les opérandes du modulo sont-ils dans le bon sens ? C'est le
-- même que celui de la division entière.
WITH RECURSIVE digits(n, q, r) AS
    (SELECT n
          , n MOD 10
          , n DIV 10
     FROM ints

     UNION ALL

     SELECT n
          , r MOD 10
          , r DIV 10
     FROM digits
     WHERE r > 0 )
SELECT n
     , salt_039(sum(string_hash('{{x}}')) OVER ()) AS token
FROM digits
GROUP BY n
HAVING sum(q) MOD n = 0

9 rows affected.

n 
 token 
 
 
 
 
 1 
 226313462278852 
 
 
 2 
 226313462278852 
 
 
 3 
 226313462278852 
 
 
 4 
 226313462278852 
 
 
 5 
 226313462278852 
 
 
 6 
 226313462278852 
 
 
 7 
 226313462278852 
 
 
 8 
 226313462278852 
 
 
 9 
 226313462278852

In [ ]:
assert '.'.join(map(str, [len(col['n'])] + col['n'][:20])) == x

In [ ]:
x = '204.1.2.3.4.5.6.7.8.9.11.12.15.21.22.24.25.31.32.33.35'

In [ ]:
%%sql
-- Indication. Il semble que vous arrêtiez la récursion trop tôt, ce qui vous fait manquer certains nombres de
-- Harshad, par exemple 10.
WITH RECURSIVE digits(n, q, r) AS
    (SELECT n
          , n MOD 10
          , n DIV 10
     FROM ints

     UNION ALL

     SELECT n
          , r MOD 10
          , r DIV 10
     FROM digits
     WHERE r > 10 )
SELECT n
     , salt_039(sum(string_hash('{{x}}')) OVER ()) AS token
FROM digits
GROUP BY n
HAVING n MOD sum(q) = 0

204 rows affected.

n 
 token 
 
 
 
 
 1 
 165717715346964 
 
 
 2 
 165717715346964 
 
 
 3 
 165717715346964 
 
 
 4 
 165717715346964 
 
 
 5 
 165717715346964 
 
 
 6 
 165717715346964 
 
 
 7 
 165717715346964 
 
 
 8 
 165717715346964 
 
 
 9 
 165717715346964 
 
 
 11 
 165717715346964 
 
 
 12 
 165717715346964 
 
 
 15 
 165717715346964 
 
 
 21 
 165717715346964 
 
 
 22 
 165717715346964 
 
 
 24 
 165717715346964 
 
 
 25 
 165717715346964 
 
 
 31 
 165717715346964 
 
 
 32 
 165717715346964 
 
 
 33 
 165717715346964 
 
 
 35 
 165717715346964 
 
 
 36 
 165717715346964 
 
 
 41 
 165717715346964 
 
 
 42 
 165717715346964 
 
 
 44 
 165717715346964 
 
 
 45 
 165717715346964 
 
 
 48 
 165717715346964 
 
 
 51 
 165717715346964 
 
 
 52 
 165717715346964 
 
 
 55 
 165717715346964 
 
 
 61 
 165717715346964 
 
 
 62 
 165717715346964 
 
 
 63 
 165717715346964 
 
 
 64 
 165717715346964 
 
 
 65 
 165717715346964 
 
 
 66 
 165717715346964 
 
 
 71 
 165717715346964 
 
 
 72 
 165717715346964 
 
 
 75 
 165717715346964 
 
 
 77 
 165717715346964 
 
 
 81 
 165717715346964 
 
 
 82 
 165717715346964 
 
 
 84 
 165717715346964 
 
 
 85 
 165717715346964 
 
 
 88 
 165717715346964 
 
 
 91 
 165717715346964 
 
 
 92 
 165717715346964 
 
 
 93 
 165717715346964 
 
 
 95 
 165717715346964 
 
 
 96 
 165717715346964 
 
 
 99 
 165717715346964 
 
 
 101 
 165717715346964 
 
 
 102 
 165717715346964 
 
 
 104 
 165717715346964 
 
 
 105 
 165717715346964 
 
 
 110 
 165717715346964 
 
 
 120 
 165717715346964 
 
 
 140 
 165717715346964 
 
 
 144 
 165717715346964 
 
 
 150 
 165717715346964 
 
 
 161 
 165717715346964 
 
 
 165 
 165717715346964 
 
 
 168 
 165717715346964 
 
 
 201 
 165717715346964 
 
 
 202 
 165717715346964 
 
 
 204 
 165717715346964 
 
 
 205 
 165717715346964 
 
 
 208 
 165717715346964 
 
 
 210 
 165717715346964 
 
 
 220 
 165717715346964 
 
 
 240 
 165717715346964 
 
 
 250 
 165717715346964 
 
 
 252 
 165717715346964 
 
 
 280 
 165717715346964 
 
 
 288 
 165717715346964 
 
 
 289 
 165717715346964 
 
 
 301 
 165717715346964 
 
 
 302 
 165717715346964 
 
 
 303 
 165717715346964 
 
 
 304 
 165717715346964 
 
 
 305 
 165717715346964 
 
 
 306 
 165717715346964 
 
 
 310 
 165717715346964 
 
 
 312 
 165717715346964 
 
 
 320 
 165717715346964 
 
 
 321 
 165717715346964 
 
 
 324 
 165717715346964 
 
 
 330 
 165717715346964 
 
 
 340 
 165717715346964 
 
 
 342 
 165717715346964 
 
 
 343 
 165717715346964 
 
 
 344 
 165717715346964 
 
 
 348 
 165717715346964 
 
 
 350 
 165717715346964 
 
 
 360 
 165717715346964 
 
 
 374 
 165717715346964 
 
 
 384 
 165717715346964 
 
 
 401 
 165717715346964 
 
 
 402 
 165717715346964 
 
 
 404 
 165717715346964 
 
 
 405 
 165717715346964 
 
 
 408 
 165717715346964 
 
 
 410 
 165717715346964 
 
 
 420 
 165717715346964 
 
 
 429 
 165717715346964 
 
 
 434 
 165717715346964 
 
 
 440 
 165717715346964 
 
 
 450 
 165717715346964 
 
 
 480 
 165717715346964 
 
 
 494 
 165717715346964 
 
 
 501 
 165717715346964 
 
 
 502 
 165717715346964 
 
 
 504 
 165717715346964 
 
 
 505 
 165717715346964 
 
 
 510 
 165717715346964 
 
 
 520 
 165717715346964 
 
 
 525 
 165717715346964 
 
 
 540 
 165717715346964 
 
 
 544 
 165717715346964 
 
 
 550 
 165717715346964 
 
 
 583 
 165717715346964 
 
 
 585 
 165717715346964 
 
 
 601 
 165717715346964 
 
 
 602 
 165717715346964 
 
 
 603 
 165717715346964 
 
 
 604 
 165717715346964 
 
 
 605 
 165717715346964 
 
 
 606 
 165717715346964 
 
 
 608 
 165717715346964 
 
 
 610 
 165717715346964 
 
 
 612 
 165717715346964 
 
 
 616 
 165717715346964 
 
 
 620 
 165717715346964 
 
 
 621 
 165717715346964 
 
 
 624 
 165717715346964 
 
 
 630 
 165717715346964 
 
 
 638 
 165717715346964 
 
 
 640 
 165717715346964 
 
 
 642 
 165717715346964 
 
 
 648 
 165717715346964 
 
 
 650 
 165717715346964 
 
 
 660 
 165717715346964 
 
 
 676 
 165717715346964 
 
 
 680 
 165717715346964 
 
 
 684 
 165717715346964 
 
 
 686 
 1

In [ ]:
assert '.'.join(map(str, [len(col['n'])] + col['n'][:20])) == x

In [ ]:
x = '841.1.2.3.4.5.6.7.8.9.12.15.21.24.25.31.32.35.36.41.42'

In [ ]:
%%sql
-- Indication. Ne regroupez que sur la colonne des entiers cherchés.
WITH RECURSIVE digits(n, q, r) AS
    (SELECT n
          , n MOD 10
          , n DIV 10
     FROM ints

     UNION ALL

     SELECT n
          , r MOD 10
          , r DIV 10
     FROM digits
     WHERE r > 0 )
SELECT n
     , salt_039(sum(string_hash('{{x}}')) OVER ()) AS token
FROM digits
GROUP BY n, q
HAVING n MOD sum(q) = 0

841 rows affected.

n 
 token 
 
 
 
 
 1 
 198102760205823 
 
 
 2 
 198102760205823 
 
 
 3 
 198102760205823 
 
 
 4 
 198102760205823 
 
 
 5 
 198102760205823 
 
 
 6 
 198102760205823 
 
 
 7 
 198102760205823 
 
 
 8 
 198102760205823 
 
 
 9 
 198102760205823 
 
 
 12 
 198102760205823 
 
 
 15 
 198102760205823 
 
 
 21 
 198102760205823 
 
 
 24 
 198102760205823 
 
 
 25 
 198102760205823 
 
 
 31 
 198102760205823 
 
 
 32 
 198102760205823 
 
 
 35 
 198102760205823 
 
 
 36 
 198102760205823 
 
 
 41 
 198102760205823 
 
 
 42 
 198102760205823 
 
 
 45 
 198102760205823 
 
 
 48 
 198102760205823 
 
 
 51 
 198102760205823 
 
 
 52 
 198102760205823 
 
 
 61 
 198102760205823 
 
 
 62 
 198102760205823 
 
 
 63 
 198102760205823 
 
 
 64 
 198102760205823 
 
 
 65 
 198102760205823 
 
 
 71 
 198102760205823 
 
 
 72 
 198102760205823 
 
 
 75 
 198102760205823 
 
 
 81 
 198102760205823 
 
 
 82 
 198102760205823 
 
 
 84 
 198102760205823 
 
 
 85 
 198102760205823 
 
 
 91 
 198102760205823 
 
 
 92 
 198102760205823 
 
 
 93 
 198102760205823 
 
 
 95 
 198102760205823 
 
 
 96 
 198102760205823 
 
 
 102 
 198102760205823 
 
 
 104 
 198102760205823 
 
 
 105 
 198102760205823 
 
 
 111 
 198102760205823 
 
 
 112 
 198102760205823 
 
 
 115 
 198102760205823 
 
 
 123 
 198102760205823 
 
 
 124 
 198102760205823 
 
 
 125 
 198102760205823 
 
 
 126 
 198102760205823 
 
 
 128 
 198102760205823 
 
 
 132 
 198102760205823 
 
 
 135 
 198102760205823 
 
 
 142 
 198102760205823 
 
 
 144 
 198102760205823 
 
 
 145 
 198102760205823 
 
 
 147 
 198102760205823 
 
 
 152 
 198102760205823 
 
 
 153 
 198102760205823 
 
 
 156 
 198102760205823 
 
 
 162 
 198102760205823 
 
 
 164 
 198102760205823 
 
 
 165 
 198102760205823 
 
 
 168 
 198102760205823 
 
 
 172 
 198102760205823 
 
 
 175 
 198102760205823 
 
 
 182 
 198102760205823 
 
 
 183 
 198102760205823 
 
 
 184 
 198102760205823 
 
 
 185 
 198102760205823 
 
 
 186 
 198102760205823 
 
 
 189 
 198102760205823 
 
 
 192 
 198102760205823 
 
 
 195 
 198102760205823 
 
 
 201 
 198102760205823 
 
 
 204 
 198102760205823 
 
 
 205 
 198102760205823 
 
 
 208 
 198102760205823 
 
 
 212 
 198102760205823 
 
 
 213 
 198102760205823 
 
 
 215 
 198102760205823 
 
 
 216 
 198102760205823 
 
 
 217 
 198102760205823 
 
 
 221 
 198102760205823 
 
 
 222 
 198102760205823 
 
 
 224 
 198102760205823 
 
 
 225 
 198102760205823 
 
 
 231 
 198102760205823 
 
 
 232 
 198102760205823 
 
 
 235 
 198102760205823 
 
 
 241 
 198102760205823 
 
 
 243 
 198102760205823 
 
 
 245 
 198102760205823 
 
 
 246 
 198102760205823 
 
 
 248 
 198102760205823 
 
 
 251 
 198102760205823 
 
 
 252 
 198102760205823 
 
 
 261 
 198102760205823 
 
 
 264 
 198102760205823 
 
 
 265 
 198102760205823 
 
 
 271 
 198102760205823 
 
 
 272 
 198102760205823 
 
 
 273 
 198102760205823 
 
 
 275 
 198102760205823 
 
 
 276 
 198102760205823 
 
 
 279 
 198102760205823 
 
 
 281 
 198102760205823 
 
 
 284 
 198102760205823 
 
 
 285 
 198102760205823 
 
 
 287 
 198102760205823 
 
 
 288 
 198102760205823 
 
 
 291 
 198102760205823 
 
 
 292 
 198102760205823 
 
 
 295 
 198102760205823 
 
 
 301 
 198102760205823 
 
 
 302 
 198102760205823 
 
 
 304 
 198102760205823 
 
 
 305 
 198102760205823 
 
 
 306 
 198102760205823 
 
 
 312 
 198102760205823 
 
 
 315 
 198102760205823 
 
 
 321 
 198102760205823 
 
 
 324 
 198102760205823 
 
 
 325 
 198102760205823 
 
 
 328 
 198102760205823 
 
 
 331 
 198102760205823 
 
 
 332 
 198102760205823 
 
 
 333 
 198102760205823 
 
 
 335 
 198102760205823 
 
 
 336 
 198102760205823 
 
 
 341 
 198102760205823 
 
 
 342 
 198102760205823 
 
 
 344 
 198102760205823 
 
 
 345 
 198102760205823 
 
 
 351 
 198102760205823 
 
 
 352 
 198102760205823 
 
 
 357 
 198102760205823 
 
 
 361 
 198102760205823 
 
 
 362 
 198102760205823 
 
 
 364 
 198102760205823 
 
 
 365 
 198102760205823 
 
 
 368 
 198102760205823 
 
 
 369 
 198102760205823 
 
 

In [ ]:
assert '.'.join(map(str, [len(col['n'])] + col['n'][:20])) == x

In [ ]:
x = '1049.1.2.3.4.5.6.7.8.9.11.12.15.21.22.24.25.31.32.33.35'

In [ ]:
%%sql
-- Indication. Ne regroupez que sur la colonne des entiers cherchés.
WITH RECURSIVE digits(n, q, r) AS
    (SELECT n
          , n MOD 10
          , n DIV 10
     FROM ints

     UNION ALL

     SELECT n
          , r MOD 10
          , r DIV 10
     FROM digits
     WHERE r > 0 )
SELECT n
     , salt_039(sum(string_hash('{{x}}')) OVER ()) AS token
FROM digits
GROUP BY n, r
HAVING n MOD sum(q) = 0

1049 rows affected.

n 
 token 
 
 
 
 
 1 
 583015109991402 
 
 
 2 
 583015109991402 
 
 
 3 
 583015109991402 
 
 
 4 
 583015109991402 
 
 
 5 
 583015109991402 
 
 
 6 
 583015109991402 
 
 
 7 
 583015109991402 
 
 
 8 
 583015109991402 
 
 
 9 
 583015109991402 
 
 
 11 
 583015109991402 
 
 
 12 
 583015109991402 
 
 
 15 
 583015109991402 
 
 
 21 
 583015109991402 
 
 
 22 
 583015109991402 
 
 
 24 
 583015109991402 
 
 
 25 
 583015109991402 
 
 
 31 
 583015109991402 
 
 
 32 
 583015109991402 
 
 
 33 
 583015109991402 
 
 
 35 
 583015109991402 
 
 
 36 
 583015109991402 
 
 
 41 
 583015109991402 
 
 
 42 
 583015109991402 
 
 
 44 
 583015109991402 
 
 
 45 
 583015109991402 
 
 
 48 
 583015109991402 
 
 
 51 
 583015109991402 
 
 
 52 
 583015109991402 
 
 
 55 
 583015109991402 
 
 
 61 
 583015109991402 
 
 
 62 
 583015109991402 
 
 
 63 
 583015109991402 
 
 
 64 
 583015109991402 
 
 
 65 
 583015109991402 
 
 
 66 
 583015109991402 
 
 
 71 
 583015109991402 
 
 
 72 
 583015109991402 
 
 
 75 
 583015109991402 
 
 
 77 
 583015109991402 
 
 
 81 
 583015109991402 
 
 
 82 
 583015109991402 
 
 
 84 
 583015109991402 
 
 
 85 
 583015109991402 
 
 
 88 
 583015109991402 
 
 
 91 
 583015109991402 
 
 
 92 
 583015109991402 
 
 
 93 
 583015109991402 
 
 
 95 
 583015109991402 
 
 
 96 
 583015109991402 
 
 
 99 
 583015109991402 
 
 
 101 
 583015109991402 
 
 
 102 
 583015109991402 
 
 
 104 
 583015109991402 
 
 
 105 
 583015109991402 
 
 
 111 
 583015109991402 
 
 
 112 
 583015109991402 
 
 
 115 
 583015109991402 
 
 
 121 
 583015109991402 
 
 
 122 
 583015109991402 
 
 
 123 
 583015109991402 
 
 
 124 
 583015109991402 
 
 
 125 
 583015109991402 
 
 
 126 
 583015109991402 
 
 
 128 
 583015109991402 
 
 
 131 
 583015109991402 
 
 
 132 
 583015109991402 
 
 
 135 
 583015109991402 
 
 
 141 
 583015109991402 
 
 
 142 
 583015109991402 
 
 
 144 
 583015109991402 
 
 
 145 
 583015109991402 
 
 
 147 
 583015109991402 
 
 
 151 
 583015109991402 
 
 
 152 
 583015109991402 
 
 
 153 
 583015109991402 
 
 
 155 
 583015109991402 
 
 
 156 
 583015109991402 
 
 
 161 
 583015109991402 
 
 
 162 
 583015109991402 
 
 
 164 
 583015109991402 
 
 
 165 
 583015109991402 
 
 
 168 
 583015109991402 
 
 
 171 
 583015109991402 
 
 
 172 
 583015109991402 
 
 
 175 
 583015109991402 
 
 
 181 
 583015109991402 
 
 
 182 
 583015109991402 
 
 
 183 
 583015109991402 
 
 
 184 
 583015109991402 
 
 
 185 
 583015109991402 
 
 
 186 
 583015109991402 
 
 
 189 
 583015109991402 
 
 
 191 
 583015109991402 
 
 
 192 
 583015109991402 
 
 
 195 
 583015109991402 
 
 
 201 
 583015109991402 
 
 
 202 
 583015109991402 
 
 
 204 
 583015109991402 
 
 
 205 
 583015109991402 
 
 
 208 
 583015109991402 
 
 
 211 
 583015109991402 
 
 
 212 
 583015109991402 
 
 
 213 
 583015109991402 
 
 
 215 
 583015109991402 
 
 
 216 
 583015109991402 
 
 
 217 
 583015109991402 
 
 
 221 
 583015109991402 
 
 
 222 
 583015109991402 
 
 
 224 
 583015109991402 
 
 
 225 
 583015109991402 
 
 
 231 
 583015109991402 
 
 
 232 
 583015109991402 
 
 
 235 
 583015109991402 
 
 
 241 
 583015109991402 
 
 
 242 
 583015109991402 
 
 
 243 
 583015109991402 
 
 
 244 
 583015109991402 
 
 
 245 
 583015109991402 
 
 
 246 
 583015109991402 
 
 
 248 
 583015109991402 
 
 
 251 
 583015109991402 
 
 
 252 
 583015109991402 
 
 
 255 
 583015109991402 
 
 
 261 
 583015109991402 
 
 
 262 
 583015109991402 
 
 
 264 
 583015109991402 
 
 
 265 
 583015109991402 
 
 
 271 
 583015109991402 
 
 
 272 
 583015109991402 
 
 
 273 
 583015109991402 
 
 
 275 
 583015109991402 
 
 
 276 
 583015109991402 
 
 
 279 
 583015109991402 
 
 
 281 
 583015109991402 
 
 
 282 
 583015109991402 
 
 
 284 
 583015109991402 
 
 
 285 
 583015109991402 
 
 
 287 
 583015109991402 
 
 
 288 
 583015109991402 
 
 
 291 
 583015109991402 
 
 
 292 
 583015109991402 
 
 
 295 
 583015109991402 
 
 
 301 
 583015109991402 
 
 
 302 
 583015109991402 
 
 
 303 
 5

In [ ]:
assert '.'.join(map(str, [len(col['n'])] + col['n'][:20])) == x

In [ ]:
x = '140.1.2.3.4.5.6.7.8.9.10.12.18.20.21.24.27.30.36.40.42'

In [ ]:
%%sql
-- Indication. Veillez à la cohérence entre l'ordre des arguments de votre fonction et celui de ses appels.
WITH RECURSIVE digits(n, q, r) AS
    (SELECT n
          , n DIV 10
          , n MOD 10
     FROM ints

     UNION ALL

     SELECT n
          , r MOD 10
          , r DIV 10
     FROM digits
     WHERE r > 0 )
SELECT n
     , salt_039(sum(string_hash('{{x}}')) OVER ()) AS token
FROM digits
GROUP BY n
HAVING n MOD sum(q) = 0

140 rows affected.

n 
 token 
 
 
 
 
 1 
 189105737194104 
 
 
 2 
 189105737194104 
 
 
 3 
 189105737194104 
 
 
 4 
 189105737194104 
 
 
 5 
 189105737194104 
 
 
 6 
 189105737194104 
 
 
 7 
 189105737194104 
 
 
 8 
 189105737194104 
 
 
 9 
 189105737194104 
 
 
 10 
 189105737194104 
 
 
 12 
 189105737194104 
 
 
 18 
 189105737194104 
 
 
 20 
 189105737194104 
 
 
 21 
 189105737194104 
 
 
 24 
 189105737194104 
 
 
 27 
 189105737194104 
 
 
 30 
 189105737194104 
 
 
 36 
 189105737194104 
 
 
 40 
 189105737194104 
 
 
 42 
 189105737194104 
 
 
 45 
 189105737194104 
 
 
 48 
 189105737194104 
 
 
 50 
 189105737194104 
 
 
 54 
 189105737194104 
 
 
 60 
 189105737194104 
 
 
 63 
 189105737194104 
 
 
 70 
 189105737194104 
 
 
 72 
 189105737194104 
 
 
 80 
 189105737194104 
 
 
 81 
 189105737194104 
 
 
 84 
 189105737194104 
 
 
 90 
 189105737194104 
 
 
 100 
 189105737194104 
 
 
 105 
 189105737194104 
 
 
 108 
 189105737194104 
 
 
 110 
 189105737194104 
 
 
 120 
 189105737194104 
 
 
 126 
 189105737194104 
 
 
 130 
 189105737194104 
 
 
 140 
 189105737194104 
 
 
 144 
 189105737194104 
 
 
 147 
 189105737194104 
 
 
 150 
 189105737194104 
 
 
 160 
 189105737194104 
 
 
 162 
 189105737194104 
 
 
 168 
 189105737194104 
 
 
 170 
 189105737194104 
 
 
 180 
 189105737194104 
 
 
 189 
 189105737194104 
 
 
 190 
 189105737194104 
 
 
 200 
 189105737194104 
 
 
 210 
 189105737194104 
 
 
 216 
 189105737194104 
 
 
 220 
 189105737194104 
 
 
 230 
 189105737194104 
 
 
 240 
 189105737194104 
 
 
 243 
 189105737194104 
 
 
 250 
 189105737194104 
 
 
 260 
 189105737194104 
 
 
 270 
 189105737194104 
 
 
 280 
 189105737194104 
 
 
 288 
 189105737194104 
 
 
 290 
 189105737194104 
 
 
 300 
 189105737194104 
 
 
 310 
 189105737194104 
 
 
 320 
 189105737194104 
 
 
 324 
 189105737194104 
 
 
 330 
 189105737194104 
 
 
 340 
 189105737194104 
 
 
 350 
 189105737194104 
 
 
 360 
 189105737194104 
 
 
 370 
 189105737194104 
 
 
 380 
 189105737194104 
 
 
 390 
 189105737194104 
 
 
 400 
 189105737194104 
 
 
 405 
 189105737194104 
 
 
 410 
 189105737194104 
 
 
 420 
 189105737194104 
 
 
 430 
 189105737194104 
 
 
 440 
 189105737194104 
 
 
 450 
 189105737194104 
 
 
 460 
 189105737194104 
 
 
 470 
 189105737194104 
 
 
 480 
 189105737194104 
 
 
 486 
 189105737194104 
 
 
 490 
 189105737194104 
 
 
 500 
 189105737194104 
 
 
 510 
 189105737194104 
 
 
 520 
 189105737194104 
 
 
 530 
 189105737194104 
 
 
 540 
 189105737194104 
 
 
 550 
 189105737194104 
 
 
 560 
 189105737194104 
 
 
 567 
 189105737194104 
 
 
 570 
 189105737194104 
 
 
 580 
 189105737194104 
 
 
 590 
 189105737194104 
 
 
 600 
 189105737194104 
 
 
 610 
 189105737194104 
 
 
 620 
 189105737194104 
 
 
 630 
 189105737194104 
 
 
 640 
 189105737194104 
 
 
 648 
 189105737194104 
 
 
 650 
 189105737194104 
 
 
 660 
 189105737194104 
 
 
 670 
 189105737194104 
 
 
 680 
 189105737194104 
 
 
 690 
 189105737194104 
 
 
 700 
 189105737194104 
 
 
 710 
 189105737194104 
 
 
 720 
 189105737194104 
 
 
 729 
 189105737194104 
 
 
 730 
 189105737194104 
 
 
 740 
 189105737194104 
 
 
 750 
 189105737194104 
 
 
 760 
 189105737194104 
 
 
 770 
 189105737194104 
 
 
 780 
 189105737194104 
 
 
 790 
 189105737194104 
 
 
 800 
 189105737194104 
 
 
 810 
 189105737194104 
 
 
 820 
 189105737194104 
 
 
 830 
 189105737194104 
 
 
 840 
 189105737194104 
 
 
 850 
 189105737194104 
 
 
 860 
 189105737194104 
 
 
 870 
 189105737194104 
 
 
 880 
 189105737194104 
 
 
 890 
 189105737194104 
 
 
 900 
 189105737194104 
 
 
 910 
 189105737194104 
 
 
 920 
 189105737194104 
 
 
 930 
 189105737194104 
 
 
 940 
 189105737194104 
 
 
 950 
 189105737194104 
 
 
 960 
 189105737194104 
 
 
 970 
 189105737194104 
 
 
 980 
 189105737194104 
 
 
 990 
 189105737194104 
 
 
 1000 
 189105737194104

In [ ]:
assert '.'.join(map(str, [len(col['n'])] + col['n'][:20])) == x

In [ ]:
x = '470.1.2.3.4.5.6.7.8.9.11.12.15.21.22.24.25.31.32.33.35'

In [ ]:
%%sql
-- Indication. Avez-vous une CTE récursive?
SELECT n
     , salt_039(sum(string_hash('{{x}}')) OVER ()) AS token
FROM ints  
WHERE n MOD (n MOD 10) = 0

470 rows affected.

n 
 token 
 
 
 
 
 1 
 237984121642486 
 
 
 2 
 237984121642486 
 
 
 3 
 237984121642486 
 
 
 4 
 237984121642486 
 
 
 5 
 237984121642486 
 
 
 6 
 237984121642486 
 
 
 7 
 237984121642486 
 
 
 8 
 237984121642486 
 
 
 9 
 237984121642486 
 
 
 11 
 237984121642486 
 
 
 12 
 237984121642486 
 
 
 15 
 237984121642486 
 
 
 21 
 237984121642486 
 
 
 22 
 237984121642486 
 
 
 24 
 237984121642486 
 
 
 25 
 237984121642486 
 
 
 31 
 237984121642486 
 
 
 32 
 237984121642486 
 
 
 33 
 237984121642486 
 
 
 35 
 237984121642486 
 
 
 36 
 237984121642486 
 
 
 41 
 237984121642486 
 
 
 42 
 237984121642486 
 
 
 44 
 237984121642486 
 
 
 45 
 237984121642486 
 
 
 48 
 237984121642486 
 
 
 51 
 237984121642486 
 
 
 52 
 237984121642486 
 
 
 55 
 237984121642486 
 
 
 61 
 237984121642486 
 
 
 62 
 237984121642486 
 
 
 63 
 237984121642486 
 
 
 64 
 237984121642486 
 
 
 65 
 237984121642486 
 
 
 66 
 237984121642486 
 
 
 71 
 237984121642486 
 
 
 72 
 237984121642486 
 
 
 75 
 237984121642486 
 
 
 77 
 237984121642486 
 
 
 81 
 237984121642486 
 
 
 82 
 237984121642486 
 
 
 84 
 237984121642486 
 
 
 85 
 237984121642486 
 
 
 88 
 237984121642486 
 
 
 91 
 237984121642486 
 
 
 92 
 237984121642486 
 
 
 93 
 237984121642486 
 
 
 95 
 237984121642486 
 
 
 96 
 237984121642486 
 
 
 99 
 237984121642486 
 
 
 101 
 237984121642486 
 
 
 102 
 237984121642486 
 
 
 104 
 237984121642486 
 
 
 105 
 237984121642486 
 
 
 111 
 237984121642486 
 
 
 112 
 237984121642486 
 
 
 115 
 237984121642486 
 
 
 121 
 237984121642486 
 
 
 122 
 237984121642486 
 
 
 123 
 237984121642486 
 
 
 124 
 237984121642486 
 
 
 125 
 237984121642486 
 
 
 126 
 237984121642486 
 
 
 128 
 237984121642486 
 
 
 131 
 237984121642486 
 
 
 132 
 237984121642486 
 
 
 135 
 237984121642486 
 
 
 141 
 237984121642486 
 
 
 142 
 237984121642486 
 
 
 144 
 237984121642486 
 
 
 145 
 237984121642486 
 
 
 147 
 237984121642486 
 
 
 151 
 237984121642486 
 
 
 152 
 237984121642486 
 
 
 153 
 237984121642486 
 
 
 155 
 237984121642486 
 
 
 156 
 237984121642486 
 
 
 161 
 237984121642486 
 
 
 162 
 237984121642486 
 
 
 164 
 237984121642486 
 
 
 165 
 237984121642486 
 
 
 168 
 237984121642486 
 
 
 171 
 237984121642486 
 
 
 172 
 237984121642486 
 
 
 175 
 237984121642486 
 
 
 181 
 237984121642486 
 
 
 182 
 237984121642486 
 
 
 183 
 237984121642486 
 
 
 184 
 237984121642486 
 
 
 185 
 237984121642486 
 
 
 186 
 237984121642486 
 
 
 189 
 237984121642486 
 
 
 191 
 237984121642486 
 
 
 192 
 237984121642486 
 
 
 195 
 237984121642486 
 
 
 201 
 237984121642486 
 
 
 202 
 237984121642486 
 
 
 204 
 237984121642486 
 
 
 205 
 237984121642486 
 
 
 208 
 237984121642486 
 
 
 211 
 237984121642486 
 
 
 212 
 237984121642486 
 
 
 213 
 237984121642486 
 
 
 215 
 237984121642486 
 
 
 216 
 237984121642486 
 
 
 217 
 237984121642486 
 
 
 221 
 237984121642486 
 
 
 222 
 237984121642486 
 
 
 224 
 237984121642486 
 
 
 225 
 237984121642486 
 
 
 231 
 237984121642486 
 
 
 232 
 237984121642486 
 
 
 235 
 237984121642486 
 
 
 241 
 237984121642486 
 
 
 242 
 237984121642486 
 
 
 243 
 237984121642486 
 
 
 244 
 237984121642486 
 
 
 245 
 237984121642486 
 
 
 246 
 237984121642486 
 
 
 248 
 237984121642486 
 
 
 251 
 237984121642486 
 
 
 252 
 237984121642486 
 
 
 255 
 237984121642486 
 
 
 261 
 237984121642486 
 
 
 262 
 237984121642486 
 
 
 264 
 237984121642486 
 
 
 265 
 237984121642486 
 
 
 271 
 237984121642486 
 
 
 272 
 237984121642486 
 
 
 273 
 237984121642486 
 
 
 275 
 237984121642486 
 
 
 276 
 237984121642486 
 
 
 279 
 237984121642486 
 
 
 281 
 237984121642486 
 
 
 282 
 237984121642486 
 
 
 284 
 237984121642486 
 
 
 285 
 237984121642486 
 
 
 287 
 237984121642486 
 
 
 288 
 237984121642486 
 
 
 291 
 237984121642486 
 
 
 292 
 237984121642486 
 
 
 295 
 237984121642486 
 
 
 301 
 237984121642486 
 
 
 302 
 237984121642486 
 
 
 303 
 2

In [ ]:
assert '.'.join(map(str, [len(col['n'])] + col['n'][:20])) == x

In [ ]:
x = '828.1.2.3.4.5.6.7.8.9.11.12.15.21.22.24.25.31.32.33.35'

In [ ]:
%%sql
-- Indication. La table construite récursivement est correcte, mais attention, elle associe à chaque nombre
-- toutes les sommes intermédiaires de ses chiffres. Seule la dernière nous intéresse.
WITH RECURSIVE digits(n, digit_sum, r) AS (
    SELECT n, n MOD 10, n DIV 10
    FROM ints
    
    UNION ALL
    
    SELECT n, digit_sum + (r MOD 10), r DIV 10
    FROM digits
    WHERE r > 0
)
SELECT n
     , salt_039(sum(string_hash('{{x}}')) OVER ()) AS token
FROM digits
WHERE n MOD digit_sum = 0;

828 rows affected.

n 
 token 
 
 
 
 
 1 
 1076677401390944 
 
 
 2 
 1076677401390944 
 
 
 3 
 1076677401390944 
 
 
 4 
 1076677401390944 
 
 
 5 
 1076677401390944 
 
 
 6 
 1076677401390944 
 
 
 7 
 1076677401390944 
 
 
 8 
 1076677401390944 
 
 
 9 
 1076677401390944 
 
 
 11 
 1076677401390944 
 
 
 12 
 1076677401390944 
 
 
 15 
 1076677401390944 
 
 
 21 
 1076677401390944 
 
 
 22 
 1076677401390944 
 
 
 24 
 1076677401390944 
 
 
 25 
 1076677401390944 
 
 
 31 
 1076677401390944 
 
 
 32 
 1076677401390944 
 
 
 33 
 1076677401390944 
 
 
 35 
 1076677401390944 
 
 
 36 
 1076677401390944 
 
 
 41 
 1076677401390944 
 
 
 42 
 1076677401390944 
 
 
 44 
 1076677401390944 
 
 
 45 
 1076677401390944 
 
 
 48 
 1076677401390944 
 
 
 51 
 1076677401390944 
 
 
 52 
 1076677401390944 
 
 
 55 
 1076677401390944 
 
 
 61 
 1076677401390944 
 
 
 62 
 1076677401390944 
 
 
 63 
 1076677401390944 
 
 
 64 
 1076677401390944 
 
 
 65 
 1076677401390944 
 
 
 66 
 1076677401390944 
 
 
 71 
 1076677401390944 
 
 
 72 
 1076677401390944 
 
 
 75 
 1076677401390944 
 
 
 77 
 1076677401390944 
 
 
 81 
 1076677401390944 
 
 
 82 
 1076677401390944 
 
 
 84 
 1076677401390944 
 
 
 85 
 1076677401390944 
 
 
 88 
 1076677401390944 
 
 
 91 
 1076677401390944 
 
 
 92 
 1076677401390944 
 
 
 93 
 1076677401390944 
 
 
 95 
 1076677401390944 
 
 
 96 
 1076677401390944 
 
 
 99 
 1076677401390944 
 
 
 101 
 1076677401390944 
 
 
 102 
 1076677401390944 
 
 
 104 
 1076677401390944 
 
 
 105 
 1076677401390944 
 
 
 111 
 1076677401390944 
 
 
 112 
 1076677401390944 
 
 
 115 
 1076677401390944 
 
 
 121 
 1076677401390944 
 
 
 122 
 1076677401390944 
 
 
 123 
 1076677401390944 
 
 
 124 
 1076677401390944 
 
 
 125 
 1076677401390944 
 
 
 126 
 1076677401390944 
 
 
 128 
 1076677401390944 
 
 
 131 
 1076677401390944 
 
 
 132 
 1076677401390944 
 
 
 135 
 1076677401390944 
 
 
 141 
 1076677401390944 
 
 
 142 
 1076677401390944 
 
 
 144 
 1076677401390944 
 
 
 145 
 1076677401390944 
 
 
 147 
 1076677401390944 
 
 
 151 
 1076677401390944 
 
 
 152 
 1076677401390944 
 
 
 153 
 1076677401390944 
 
 
 155 
 1076677401390944 
 
 
 156 
 1076677401390944 
 
 
 161 
 1076677401390944 
 
 
 162 
 1076677401390944 
 
 
 164 
 1076677401390944 
 
 
 165 
 1076677401390944 
 
 
 168 
 1076677401390944 
 
 
 171 
 1076677401390944 
 
 
 172 
 1076677401390944 
 
 
 175 
 1076677401390944 
 
 
 181 
 1076677401390944 
 
 
 182 
 1076677401390944 
 
 
 183 
 1076677401390944 
 
 
 184 
 1076677401390944 
 
 
 185 
 1076677401390944 
 
 
 186 
 1076677401390944 
 
 
 189 
 1076677401390944 
 
 
 191 
 1076677401390944 
 
 
 192 
 1076677401390944 
 
 
 195 
 1076677401390944 
 
 
 201 
 1076677401390944 
 
 
 202 
 1076677401390944 
 
 
 204 
 1076677401390944 
 
 
 205 
 1076677401390944 
 
 
 208 
 1076677401390944 
 
 
 211 
 1076677401390944 
 
 
 212 
 1076677401390944 
 
 
 213 
 1076677401390944 
 
 
 215 
 1076677401390944 
 
 
 216 
 1076677401390944 
 
 
 217 
 1076677401390944 
 
 
 221 
 1076677401390944 
 
 
 222 
 1076677401390944 
 
 
 224 
 1076677401390944 
 
 
 225 
 1076677401390944 
 
 
 231 
 1076677401390944 
 
 
 232 
 1076677401390944 
 
 
 235 
 1076677401390944 
 
 
 241 
 1076677401390944 
 
 
 242 
 1076677401390944 
 
 
 243 
 1076677401390944 
 
 
 244 
 1076677401390944 
 
 
 245 
 1076677401390944 
 
 
 246 
 1076677401390944 
 
 
 248 
 1076677401390944 
 
 
 251 
 1076677401390944 
 
 
 252 
 1076677401390944 
 
 
 255 
 1076677401390944 
 
 
 261 
 1076677401390944 
 
 
 262 
 1076677401390944 
 
 
 264 
 1076677401390944 
 
 
 265 
 1076677401390944 
 
 
 271 
 1076677401390944 
 
 
 272 
 1076677401390944 
 
 
 273 
 1076677401390944 
 
 
 275 
 1076677401390944 
 
 
 276 
 1076677401390944 
 
 
 279 
 1076677401390944 
 
 
 281 
 1076677401390944 
 
 
 282 
 1076677401390944 
 
 
 284 
 1076677401390944 
 
 
 285 
 1076677401390944 
 
 
 287 
 1076677401390944 
 
 
 288 
 1076677401390944 
 
 
 291 
 10

In [ ]:
assert '.'.join(map(str, [len(col['n'])] + col['n'][:20])) == x

## Mélanges

Utilisez une liste d'entiers comme support de création de tables intéressantes ou amusantes.

### Code de Gray

**Atelier [056].** Le **code de Gray** est un codage binaire où les valeurs successives ne diffèrent que d'un seul bit. Il est utile pour éviter les modifications « catastrophiques » potentiellement produites par l'incrémentation dans les codages usuels (p. ex., en décimal, ajouter 1 à 9999 revient à modifier 5 chiffres, ce qui serait une catastrophe dans certaines applications).

<figure>
  <img src="https://raw.githubusercontent.com/laowantong/sqlab_ints/refs/heads/main/assets/bin.png"/>
  <br>
  <img src="https://raw.githubusercontent.com/laowantong/sqlab_ints/refs/heads/main/assets/gray.png"/>
  <figcaption><p>128 valeurs sur 7 bits en binaire (en haut) et dans le code de Gray (en bas). Chaque entier est représenté par une colonne de bits (blanc = 0, rouge = 1) qui se lit de bas en haut. Vous pouvez vérifier qu'avec le code de Gray, un et un seul bit est modifié entre deux colonnes successives (<a href='http://datagenetics.com/blog/november32014/' target='_blank'>source de ces diagrammes</a>).</p></figcaption>
</figure>


Voici les codes de Gray sur 3 bits :

| n | Code binaire | Code de Gray |
|---|--------------|--------------|
| 0 | 000          | 000          |
| 1 | 001          | 001          |
| 2 | 010          | 011          |
| 3 | 011          | 010          |
| 4 | 100          | 110          |
| 5 | 101          | 111          |
| 6 | 110          | 101          |
| 7 | 111          | 100          |

Pour convertir un code binaire `n` en code de Gray, il suffit de faire un _ou exclusif_ entre `n` et `n` décalé d'un bit vers la droite.

_Défi._ Listez les 256 premiers codes de Gray en les formatant sur 8 bits (complétés avec des zéros à gauche si nécessaire).

_Aide._ Immédiat avec les [fonctions](https://dev.mysql.com/doc/refman/8.4/en/string-functions.html) et les [opérateurs](https://dev.mysql.com/doc/refman/8.4/en/bit-functions.html) fournis par MySQL.

In [ ]:
x = '00000000 00111111 01111110 01000001 11111100 10111011 10000010' # la concaténation des codes de Gray de 42 en 42, séparés par des espaces.
# Javascript: (result.col('Gray').slice3(undefined, undefined, 42).join(' ')) || '7_531_148'

In [ ]:
%%sql
SELECT n, lpad(bin(n ^ (n >> 1)), 8, '0') as Gray
     , salt_056(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM ints
WHERE n < 256

256 rows affected.

n 
 Gray 
 token 
 
 
 
 
 0 
 00000000 
 165618471384997 
 
 
 1 
 00000001 
 165618471384997 
 
 
 2 
 00000011 
 165618471384997 
 
 
 3 
 00000010 
 165618471384997 
 
 
 4 
 00000110 
 165618471384997 
 
 
 5 
 00000111 
 165618471384997 
 
 
 6 
 00000101 
 165618471384997 
 
 
 7 
 00000100 
 165618471384997 
 
 
 8 
 00001100 
 165618471384997 
 
 
 9 
 00001101 
 165618471384997 
 
 
 10 
 00001111 
 165618471384997 
 
 
 11 
 00001110 
 165618471384997 
 
 
 12 
 00001010 
 165618471384997 
 
 
 13 
 00001011 
 165618471384997 
 
 
 14 
 00001001 
 165618471384997 
 
 
 15 
 00001000 
 165618471384997 
 
 
 16 
 00011000 
 165618471384997 
 
 
 17 
 00011001 
 165618471384997 
 
 
 18 
 00011011 
 165618471384997 
 
 
 19 
 00011010 
 165618471384997 
 
 
 20 
 00011110 
 165618471384997 
 
 
 21 
 00011111 
 165618471384997 
 
 
 22 
 00011101 
 165618471384997 
 
 
 23 
 00011100 
 165618471384997 
 
 
 24 
 00010100 
 165618471384997 
 
 
 25 
 00010101 
 165618471384997 
 
 
 26 
 00010111 
 165618471384997 
 
 
 27 
 00010110 
 165618471384997 
 
 
 28 
 00010010 
 165618471384997 
 
 
 29 
 00010011 
 165618471384997 
 
 
 30 
 00010001 
 165618471384997 
 
 
 31 
 00010000 
 165618471384997 
 
 
 32 
 00110000 
 165618471384997 
 
 
 33 
 00110001 
 165618471384997 
 
 
 34 
 00110011 
 165618471384997 
 
 
 35 
 00110010 
 165618471384997 
 
 
 36 
 00110110 
 165618471384997 
 
 
 37 
 00110111 
 165618471384997 
 
 
 38 
 00110101 
 165618471384997 
 
 
 39 
 00110100 
 165618471384997 
 
 
 40 
 00111100 
 165618471384997 
 
 
 41 
 00111101 
 165618471384997 
 
 
 42 
 00111111 
 165618471384997 
 
 
 43 
 00111110 
 165618471384997 
 
 
 44 
 00111010 
 165618471384997 
 
 
 45 
 00111011 
 165618471384997 
 
 
 46 
 00111001 
 165618471384997 
 
 
 47 
 00111000 
 165618471384997 
 
 
 48 
 00101000 
 165618471384997 
 
 
 49 
 00101001 
 165618471384997 
 
 
 50 
 00101011 
 165618471384997 
 
 
 51 
 00101010 
 165618471384997 
 
 
 52 
 00101110 
 165618471384997 
 
 
 53 
 00101111 
 165618471384997 
 
 
 54 
 00101101 
 165618471384997 
 
 
 55 
 00101100 
 165618471384997 
 
 
 56 
 00100100 
 165618471384997 
 
 
 57 
 00100101 
 165618471384997 
 
 
 58 
 00100111 
 165618471384997 
 
 
 59 
 00100110 
 165618471384997 
 
 
 60 
 00100010 
 165618471384997 
 
 
 61 
 00100011 
 165618471384997 
 
 
 62 
 00100001 
 165618471384997 
 
 
 63 
 00100000 
 165618471384997 
 
 
 64 
 01100000 
 165618471384997 
 
 
 65 
 01100001 
 165618471384997 
 
 
 66 
 01100011 
 165618471384997 
 
 
 67 
 01100010 
 165618471384997 
 
 
 68 
 01100110 
 165618471384997 
 
 
 69 
 01100111 
 165618471384997 
 
 
 70 
 01100101 
 165618471384997 
 
 
 71 
 01100100 
 165618471384997 
 
 
 72 
 01101100 
 165618471384997 
 
 
 73 
 01101101 
 165618471384997 
 
 
 74 
 01101111 
 165618471384997 
 
 
 75 
 01101110 
 165618471384997 
 
 
 76 
 01101010 
 165618471384997 
 
 
 77 
 01101011 
 165618471384997 
 
 
 78 
 01101001 
 165618471384997 
 
 
 79 
 01101000 
 165618471384997 
 
 
 80 
 01111000 
 165618471384997 
 
 
 81 
 01111001 
 165618471384997 
 
 
 82 
 01111011 
 165618471384997 
 
 
 83 
 01111010 
 165618471384997 
 
 
 84 
 01111110 
 165618471384997 
 
 
 85 
 01111111 
 165618471384997 
 
 
 86 
 01111101 
 165618471384997 
 
 
 87 
 01111100 
 165618471384997 
 
 
 88 
 01110100 
 165618471384997 
 
 
 89 
 01110101 
 165618471384997 
 
 
 90 
 01110111 
 165618471384997 
 
 
 91 
 01110110 
 165618471384997 
 
 
 92 
 01110010 
 165618471384997 
 
 
 93 
 01110011 
 165618471384997 
 
 
 94 
 01110001 
 165618471384997 
 
 
 95 
 01110000 
 165618471384997 
 
 
 96 
 01010000 
 165618471384997 
 
 
 97 
 01010001 
 165618471384997 
 
 
 98 
 01010011 
 165618471384997 
 
 
 99 
 01010010 
 165618471384997 
 
 
 100 
 01010110 
 165618471384997 
 
 
 101 
 01010111 
 165618471384997 
 
 
 102 
 01010101 
 165618471384997 
 
 
 103 
 01010100 
 165618471384997 
 
 
 104 
 01011100 
 1656184713

In [ ]:
assert " ".join(map(str, col['Gray'][::42])) == x

In [ ]:
x = '0 111111 1111110 1000001 11111100 10111011 10000010'

In [ ]:
%%sql
-- Indication. Chaque code de Gray doit être complété par des zéros à gauche jusqu'à occuper 8 bits.
SELECT n, bin(n ^ (n >> 1)) as Gray
     , salt_056(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM ints
WHERE n < 256

256 rows affected.

n 
 Gray 
 token 
 
 
 
 
 0 
 0 
 165084830099319 
 
 
 1 
 1 
 165084830099319 
 
 
 2 
 11 
 165084830099319 
 
 
 3 
 10 
 165084830099319 
 
 
 4 
 110 
 165084830099319 
 
 
 5 
 111 
 165084830099319 
 
 
 6 
 101 
 165084830099319 
 
 
 7 
 100 
 165084830099319 
 
 
 8 
 1100 
 165084830099319 
 
 
 9 
 1101 
 165084830099319 
 
 
 10 
 1111 
 165084830099319 
 
 
 11 
 1110 
 165084830099319 
 
 
 12 
 1010 
 165084830099319 
 
 
 13 
 1011 
 165084830099319 
 
 
 14 
 1001 
 165084830099319 
 
 
 15 
 1000 
 165084830099319 
 
 
 16 
 11000 
 165084830099319 
 
 
 17 
 11001 
 165084830099319 
 
 
 18 
 11011 
 165084830099319 
 
 
 19 
 11010 
 165084830099319 
 
 
 20 
 11110 
 165084830099319 
 
 
 21 
 11111 
 165084830099319 
 
 
 22 
 11101 
 165084830099319 
 
 
 23 
 11100 
 165084830099319 
 
 
 24 
 10100 
 165084830099319 
 
 
 25 
 10101 
 165084830099319 
 
 
 26 
 10111 
 165084830099319 
 
 
 27 
 10110 
 165084830099319 
 
 
 28 
 10010 
 165084830099319 
 
 
 29 
 10011 
 165084830099319 
 
 
 30 
 10001 
 165084830099319 
 
 
 31 
 10000 
 165084830099319 
 
 
 32 
 110000 
 165084830099319 
 
 
 33 
 110001 
 165084830099319 
 
 
 34 
 110011 
 165084830099319 
 
 
 35 
 110010 
 165084830099319 
 
 
 36 
 110110 
 165084830099319 
 
 
 37 
 110111 
 165084830099319 
 
 
 38 
 110101 
 165084830099319 
 
 
 39 
 110100 
 165084830099319 
 
 
 40 
 111100 
 165084830099319 
 
 
 41 
 111101 
 165084830099319 
 
 
 42 
 111111 
 165084830099319 
 
 
 43 
 111110 
 165084830099319 
 
 
 44 
 111010 
 165084830099319 
 
 
 45 
 111011 
 165084830099319 
 
 
 46 
 111001 
 165084830099319 
 
 
 47 
 111000 
 165084830099319 
 
 
 48 
 101000 
 165084830099319 
 
 
 49 
 101001 
 165084830099319 
 
 
 50 
 101011 
 165084830099319 
 
 
 51 
 101010 
 165084830099319 
 
 
 52 
 101110 
 165084830099319 
 
 
 53 
 101111 
 165084830099319 
 
 
 54 
 101101 
 165084830099319 
 
 
 55 
 101100 
 165084830099319 
 
 
 56 
 100100 
 165084830099319 
 
 
 57 
 100101 
 165084830099319 
 
 
 58 
 100111 
 165084830099319 
 
 
 59 
 100110 
 165084830099319 
 
 
 60 
 100010 
 165084830099319 
 
 
 61 
 100011 
 165084830099319 
 
 
 62 
 100001 
 165084830099319 
 
 
 63 
 100000 
 165084830099319 
 
 
 64 
 1100000 
 165084830099319 
 
 
 65 
 1100001 
 165084830099319 
 
 
 66 
 1100011 
 165084830099319 
 
 
 67 
 1100010 
 165084830099319 
 
 
 68 
 1100110 
 165084830099319 
 
 
 69 
 1100111 
 165084830099319 
 
 
 70 
 1100101 
 165084830099319 
 
 
 71 
 1100100 
 165084830099319 
 
 
 72 
 1101100 
 165084830099319 
 
 
 73 
 1101101 
 165084830099319 
 
 
 74 
 1101111 
 165084830099319 
 
 
 75 
 1101110 
 165084830099319 
 
 
 76 
 1101010 
 165084830099319 
 
 
 77 
 1101011 
 165084830099319 
 
 
 78 
 1101001 
 165084830099319 
 
 
 79 
 1101000 
 165084830099319 
 
 
 80 
 1111000 
 165084830099319 
 
 
 81 
 1111001 
 165084830099319 
 
 
 82 
 1111011 
 165084830099319 
 
 
 83 
 1111010 
 165084830099319 
 
 
 84 
 1111110 
 165084830099319 
 
 
 85 
 1111111 
 165084830099319 
 
 
 86 
 1111101 
 165084830099319 
 
 
 87 
 1111100 
 165084830099319 
 
 
 88 
 1110100 
 165084830099319 
 
 
 89 
 1110101 
 165084830099319 
 
 
 90 
 1110111 
 165084830099319 
 
 
 91 
 1110110 
 165084830099319 
 
 
 92 
 1110010 
 165084830099319 
 
 
 93 
 1110011 
 165084830099319 
 
 
 94 
 1110001 
 165084830099319 
 
 
 95 
 1110000 
 165084830099319 
 
 
 96 
 1010000 
 165084830099319 
 
 
 97 
 1010001 
 165084830099319 
 
 
 98 
 1010011 
 165084830099319 
 
 
 99 
 1010010 
 165084830099319 
 
 
 100 
 1010110 
 165084830099319 
 
 
 101 
 1010111 
 165084830099319 
 
 
 102 
 1010101 
 165084830099319 
 
 
 103 
 1010100 
 165084830099319 
 
 
 104 
 1011100 
 165084830099319 
 
 
 105 
 1011101 
 165084830099319 
 
 
 106 
 1011111 
 165084830099319 
 
 
 107 
 1011110 
 165084830099319 
 
 
 108 
 1011010 
 165084830099319 
 
 
 109 
 1011011 
 165084830099319 
 
 
 110 
 1011001 
 1650848300993

In [ ]:
assert " ".join(map(str, col['Gray'][::42])) == x

In [ ]:
x = '0 63 126 65 252 187 130'

In [ ]:
%%sql
-- Indication. Vous obtenez les bons codes de Gray. Reste à les convertir en binaire.
SELECT n, n ^ (n >> 1) as Gray
     , salt_056(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM ints
WHERE n < 256

256 rows affected.

n 
 Gray 
 token 
 
 
 
 
 0 
 0 
 165229563321814 
 
 
 1 
 1 
 165229563321814 
 
 
 2 
 3 
 165229563321814 
 
 
 3 
 2 
 165229563321814 
 
 
 4 
 6 
 165229563321814 
 
 
 5 
 7 
 165229563321814 
 
 
 6 
 5 
 165229563321814 
 
 
 7 
 4 
 165229563321814 
 
 
 8 
 12 
 165229563321814 
 
 
 9 
 13 
 165229563321814 
 
 
 10 
 15 
 165229563321814 
 
 
 11 
 14 
 165229563321814 
 
 
 12 
 10 
 165229563321814 
 
 
 13 
 11 
 165229563321814 
 
 
 14 
 9 
 165229563321814 
 
 
 15 
 8 
 165229563321814 
 
 
 16 
 24 
 165229563321814 
 
 
 17 
 25 
 165229563321814 
 
 
 18 
 27 
 165229563321814 
 
 
 19 
 26 
 165229563321814 
 
 
 20 
 30 
 165229563321814 
 
 
 21 
 31 
 165229563321814 
 
 
 22 
 29 
 165229563321814 
 
 
 23 
 28 
 165229563321814 
 
 
 24 
 20 
 165229563321814 
 
 
 25 
 21 
 165229563321814 
 
 
 26 
 23 
 165229563321814 
 
 
 27 
 22 
 165229563321814 
 
 
 28 
 18 
 165229563321814 
 
 
 29 
 19 
 165229563321814 
 
 
 30 
 17 
 165229563321814 
 
 
 31 
 16 
 165229563321814 
 
 
 32 
 48 
 165229563321814 
 
 
 33 
 49 
 165229563321814 
 
 
 34 
 51 
 165229563321814 
 
 
 35 
 50 
 165229563321814 
 
 
 36 
 54 
 165229563321814 
 
 
 37 
 55 
 165229563321814 
 
 
 38 
 53 
 165229563321814 
 
 
 39 
 52 
 165229563321814 
 
 
 40 
 60 
 165229563321814 
 
 
 41 
 61 
 165229563321814 
 
 
 42 
 63 
 165229563321814 
 
 
 43 
 62 
 165229563321814 
 
 
 44 
 58 
 165229563321814 
 
 
 45 
 59 
 165229563321814 
 
 
 46 
 57 
 165229563321814 
 
 
 47 
 56 
 165229563321814 
 
 
 48 
 40 
 165229563321814 
 
 
 49 
 41 
 165229563321814 
 
 
 50 
 43 
 165229563321814 
 
 
 51 
 42 
 165229563321814 
 
 
 52 
 46 
 165229563321814 
 
 
 53 
 47 
 165229563321814 
 
 
 54 
 45 
 165229563321814 
 
 
 55 
 44 
 165229563321814 
 
 
 56 
 36 
 165229563321814 
 
 
 57 
 37 
 165229563321814 
 
 
 58 
 39 
 165229563321814 
 
 
 59 
 38 
 165229563321814 
 
 
 60 
 34 
 165229563321814 
 
 
 61 
 35 
 165229563321814 
 
 
 62 
 33 
 165229563321814 
 
 
 63 
 32 
 165229563321814 
 
 
 64 
 96 
 165229563321814 
 
 
 65 
 97 
 165229563321814 
 
 
 66 
 99 
 165229563321814 
 
 
 67 
 98 
 165229563321814 
 
 
 68 
 102 
 165229563321814 
 
 
 69 
 103 
 165229563321814 
 
 
 70 
 101 
 165229563321814 
 
 
 71 
 100 
 165229563321814 
 
 
 72 
 108 
 165229563321814 
 
 
 73 
 109 
 165229563321814 
 
 
 74 
 111 
 165229563321814 
 
 
 75 
 110 
 165229563321814 
 
 
 76 
 106 
 165229563321814 
 
 
 77 
 107 
 165229563321814 
 
 
 78 
 105 
 165229563321814 
 
 
 79 
 104 
 165229563321814 
 
 
 80 
 120 
 165229563321814 
 
 
 81 
 121 
 165229563321814 
 
 
 82 
 123 
 165229563321814 
 
 
 83 
 122 
 165229563321814 
 
 
 84 
 126 
 165229563321814 
 
 
 85 
 127 
 165229563321814 
 
 
 86 
 125 
 165229563321814 
 
 
 87 
 124 
 165229563321814 
 
 
 88 
 116 
 165229563321814 
 
 
 89 
 117 
 165229563321814 
 
 
 90 
 119 
 165229563321814 
 
 
 91 
 118 
 165229563321814 
 
 
 92 
 114 
 165229563321814 
 
 
 93 
 115 
 165229563321814 
 
 
 94 
 113 
 165229563321814 
 
 
 95 
 112 
 165229563321814 
 
 
 96 
 80 
 165229563321814 
 
 
 97 
 81 
 165229563321814 
 
 
 98 
 83 
 165229563321814 
 
 
 99 
 82 
 165229563321814 
 
 
 100 
 86 
 165229563321814 
 
 
 101 
 87 
 165229563321814 
 
 
 102 
 85 
 165229563321814 
 
 
 103 
 84 
 165229563321814 
 
 
 104 
 92 
 165229563321814 
 
 
 105 
 93 
 165229563321814 
 
 
 106 
 95 
 165229563321814 
 
 
 107 
 94 
 165229563321814 
 
 
 108 
 90 
 165229563321814 
 
 
 109 
 91 
 165229563321814 
 
 
 110 
 89 
 165229563321814 
 
 
 111 
 88 
 165229563321814 
 
 
 112 
 72 
 165229563321814 
 
 
 113 
 73 
 165229563321814 
 
 
 114 
 75 
 165229563321814 
 
 
 115 
 74 
 165229563321814 
 
 
 116 
 78 
 165229563321814 
 
 
 117 
 79 
 165229563321814 
 
 
 118 
 77 
 165229563321814 
 
 
 119 
 76 
 165229563321814 
 
 
 120 
 68 
 165229563321814 
 
 
 121 
 69 
 165229563321814 
 
 
 122 
 71 
 165229563321814 
 
 
 123 
 

In [ ]:
assert " ".join(map(str, col['Gray'][::42])) == x

### FizzBuzz

**Atelier [088].** La suite **FizzBuzz** est une transformation des entiers naturels strictement positifs où :

- tout multiple de 3 est remplacé par `'Fizz'` ;
- tout multiple de 5 est remplacé par `'Buzz'` ;
- tout multiple de 15 est remplacé par `'FizzBuzz'` ;
- les autres nombres restent inchangés.

<figure>
  <img src="https://raw.githubusercontent.com/laowantong/sqlab_ints/refs/heads/main/assets/fizzbuzz.jpg"/>
  <figcaption>FizzBuzz, un jeu d'enfants !</figcaption>
</figure>


_Défi._ Listez par ordre croissant les termes de FizzBuzz jusqu'à 1000 : 1, 2, Fizz, 4, Buzz, etc.

_Aide._ L'opérateur `CASE` fera ici merveille sous la forme suivante :

```sql
CASE
    WHEN condition_1 THEN result_1
    WHEN condition_2 THEN result_2
    ...
    ELSE default_result
END
```

In [ ]:
x = "fizz.buzz.11.fizz.13.14.fizzbuzz.16" # la concaténation des 9e au 16e termes, séparés par des points, en minuscules.
# Javascript: (result.slice(8, 16).col('fizzbuzz').join('.')).toLowerCase() || '7_531_148'

In [ ]:
%%sql
SELECT CASE
           WHEN n MOD 15 = 0 THEN 'FizzBuzz'
           WHEN n MOD 3 = 0 THEN 'Fizz'
           WHEN n MOD 5 = 0 THEN 'Buzz'
           ELSE n
       END AS fizzbuzz
     , salt_088(string_hash('{{x}}') + sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE n > 0

1000 rows affected.

fizzbuzz 
 token 
 
 
 
 
 1 
 360051049043076 
 
 
 2 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 4 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 7 
 360051049043076 
 
 
 8 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 11 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 13 
 360051049043076 
 
 
 14 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 16 
 360051049043076 
 
 
 17 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 19 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 22 
 360051049043076 
 
 
 23 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 26 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 28 
 360051049043076 
 
 
 29 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 31 
 360051049043076 
 
 
 32 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 34 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 37 
 360051049043076 
 
 
 38 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 41 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 43 
 360051049043076 
 
 
 44 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 46 
 360051049043076 
 
 
 47 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 49 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 52 
 360051049043076 
 
 
 53 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 56 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 58 
 360051049043076 
 
 
 59 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 61 
 360051049043076 
 
 
 62 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 64 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 67 
 360051049043076 
 
 
 68 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 71 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 73 
 360051049043076 
 
 
 74 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 76 
 360051049043076 
 
 
 77 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 79 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 82 
 360051049043076 
 
 
 83 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 86 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 88 
 360051049043076 
 
 
 89 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 91 
 360051049043076 
 
 
 92 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 94 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 97 
 360051049043076 
 
 
 98 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 101 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 103 
 360051049043076 
 
 
 104 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 106 
 360051049043076 
 
 
 107 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 109 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 112 
 360051049043076 
 
 
 113 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 116 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 118 
 360051049043076 
 
 
 119 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 121 
 360051049043076 
 
 
 122 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 124 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 127 
 360051049043076 
 
 
 128 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 131 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 133 
 360051049043076 
 
 
 134 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 136 
 360051049043076 
 
 
 137 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 139 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360

In [ ]:
assert '.'.join(col['fizzbuzz'][8:16]).lower() == x

In [ ]:
%%sql
-- Variante. En générant dynamiquement la chaîne.
SELECT coalesce(nullif(concat(if(n MOD 3 = 0, 'Fizz', ''), if(n MOD 5 = 0, 'Buzz', '')), ''), n) AS fizzbuzz
     , salt_088(string_hash('{{x}}') + sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE n > 0

1000 rows affected.

fizzbuzz 
 token 
 
 
 
 
 1 
 360051049043076 
 
 
 2 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 4 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 7 
 360051049043076 
 
 
 8 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 11 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 13 
 360051049043076 
 
 
 14 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 16 
 360051049043076 
 
 
 17 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 19 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 22 
 360051049043076 
 
 
 23 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 26 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 28 
 360051049043076 
 
 
 29 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 31 
 360051049043076 
 
 
 32 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 34 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 37 
 360051049043076 
 
 
 38 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 41 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 43 
 360051049043076 
 
 
 44 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 46 
 360051049043076 
 
 
 47 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 49 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 52 
 360051049043076 
 
 
 53 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 56 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 58 
 360051049043076 
 
 
 59 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 61 
 360051049043076 
 
 
 62 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 64 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 67 
 360051049043076 
 
 
 68 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 71 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 73 
 360051049043076 
 
 
 74 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 76 
 360051049043076 
 
 
 77 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 79 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 82 
 360051049043076 
 
 
 83 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 86 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 88 
 360051049043076 
 
 
 89 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 91 
 360051049043076 
 
 
 92 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 94 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 97 
 360051049043076 
 
 
 98 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 101 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 103 
 360051049043076 
 
 
 104 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 106 
 360051049043076 
 
 
 107 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 109 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 112 
 360051049043076 
 
 
 113 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 116 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 118 
 360051049043076 
 
 
 119 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 121 
 360051049043076 
 
 
 122 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 124 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 127 
 360051049043076 
 
 
 128 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 131 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 133 
 360051049043076 
 
 
 134 
 360051049043076 
 
 
 FizzBuzz 
 360051049043076 
 
 
 136 
 360051049043076 
 
 
 137 
 360051049043076 
 
 
 Fizz 
 360051049043076 
 
 
 139 
 360051049043076 
 
 
 Buzz 
 360051049043076 
 
 
 Fizz 
 360

In [ ]:
assert '.'.join(col['fizzbuzz'][8:16]).lower() == x

In [ ]:
x = '8.fizz.buzz.11.fizz.13.14.fizzbuzz'

In [ ]:
%%sql
-- Indication. La véritable suite FizzBuzz™️ commence à 1.
SELECT CASE
           WHEN n MOD 15 = 0 THEN 'FizzBuzz'
           WHEN n MOD 3 = 0 THEN 'Fizz'
           WHEN n MOD 5 = 0 THEN 'Buzz'
           ELSE n
       END AS fizzbuzz
     , salt_088(string_hash('{{x}}') + sum(nn(hash)) OVER ()) AS token
FROM ints

1001 rows affected.

fizzbuzz 
 token 
 
 
 
 
 FizzBuzz 
 360247014033845 
 
 
 1 
 360247014033845 
 
 
 2 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 4 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 7 
 360247014033845 
 
 
 8 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 11 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 13 
 360247014033845 
 
 
 14 
 360247014033845 
 
 
 FizzBuzz 
 360247014033845 
 
 
 16 
 360247014033845 
 
 
 17 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 19 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 22 
 360247014033845 
 
 
 23 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 26 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 28 
 360247014033845 
 
 
 29 
 360247014033845 
 
 
 FizzBuzz 
 360247014033845 
 
 
 31 
 360247014033845 
 
 
 32 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 34 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 37 
 360247014033845 
 
 
 38 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 41 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 43 
 360247014033845 
 
 
 44 
 360247014033845 
 
 
 FizzBuzz 
 360247014033845 
 
 
 46 
 360247014033845 
 
 
 47 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 49 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 52 
 360247014033845 
 
 
 53 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 56 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 58 
 360247014033845 
 
 
 59 
 360247014033845 
 
 
 FizzBuzz 
 360247014033845 
 
 
 61 
 360247014033845 
 
 
 62 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 64 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 67 
 360247014033845 
 
 
 68 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 71 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 73 
 360247014033845 
 
 
 74 
 360247014033845 
 
 
 FizzBuzz 
 360247014033845 
 
 
 76 
 360247014033845 
 
 
 77 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 79 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 82 
 360247014033845 
 
 
 83 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 86 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 88 
 360247014033845 
 
 
 89 
 360247014033845 
 
 
 FizzBuzz 
 360247014033845 
 
 
 91 
 360247014033845 
 
 
 92 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 94 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 97 
 360247014033845 
 
 
 98 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 101 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 103 
 360247014033845 
 
 
 104 
 360247014033845 
 
 
 FizzBuzz 
 360247014033845 
 
 
 106 
 360247014033845 
 
 
 107 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 109 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 112 
 360247014033845 
 
 
 113 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 116 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 118 
 360247014033845 
 
 
 119 
 360247014033845 
 
 
 FizzBuzz 
 360247014033845 
 
 
 121 
 360247014033845 
 
 
 122 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 124 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 127 
 360247014033845 
 
 
 128 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 Buzz 
 360247014033845 
 
 
 131 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 133 
 360247014033845 
 
 
 134 
 360247014033845 
 
 
 FizzBuzz 
 360247014033845 
 
 
 136 
 360247014033845 
 
 
 137 
 360247014033845 
 
 
 Fizz 
 360247014033845 
 
 
 139 
 360247014033845 
 
 
 Buzz 


In [ ]:
assert '.'.join(col['fizzbuzz'][8:16]).lower() == x

In [ ]:
x = 'buzz.11.fizz.13.14.fizzbuzz.16.17'

In [ ]:
%%sql
-- Indication. La véritable suite FizzBuzz™️ commence à 1.
SELECT CASE
           WHEN n MOD 15 = 0 THEN 'FizzBuzz'
           WHEN n MOD 3 = 0 THEN 'Fizz'
           WHEN n MOD 5 = 0 THEN 'Buzz'
           ELSE n
       END AS fizzbuzz
     , salt_088(string_hash('{{x}}') + sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE n > 1

999 rows affected.

fizzbuzz 
 token 
 
 
 
 
 2 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 4 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 7 
 359749191076977 
 
 
 8 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 11 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 13 
 359749191076977 
 
 
 14 
 359749191076977 
 
 
 FizzBuzz 
 359749191076977 
 
 
 16 
 359749191076977 
 
 
 17 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 19 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 22 
 359749191076977 
 
 
 23 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 26 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 28 
 359749191076977 
 
 
 29 
 359749191076977 
 
 
 FizzBuzz 
 359749191076977 
 
 
 31 
 359749191076977 
 
 
 32 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 34 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 37 
 359749191076977 
 
 
 38 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 41 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 43 
 359749191076977 
 
 
 44 
 359749191076977 
 
 
 FizzBuzz 
 359749191076977 
 
 
 46 
 359749191076977 
 
 
 47 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 49 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 52 
 359749191076977 
 
 
 53 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 56 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 58 
 359749191076977 
 
 
 59 
 359749191076977 
 
 
 FizzBuzz 
 359749191076977 
 
 
 61 
 359749191076977 
 
 
 62 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 64 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 67 
 359749191076977 
 
 
 68 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 71 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 73 
 359749191076977 
 
 
 74 
 359749191076977 
 
 
 FizzBuzz 
 359749191076977 
 
 
 76 
 359749191076977 
 
 
 77 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 79 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 82 
 359749191076977 
 
 
 83 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 86 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 88 
 359749191076977 
 
 
 89 
 359749191076977 
 
 
 FizzBuzz 
 359749191076977 
 
 
 91 
 359749191076977 
 
 
 92 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 94 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 97 
 359749191076977 
 
 
 98 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 101 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 103 
 359749191076977 
 
 
 104 
 359749191076977 
 
 
 FizzBuzz 
 359749191076977 
 
 
 106 
 359749191076977 
 
 
 107 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 109 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 112 
 359749191076977 
 
 
 113 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 116 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 118 
 359749191076977 
 
 
 119 
 359749191076977 
 
 
 FizzBuzz 
 359749191076977 
 
 
 121 
 359749191076977 
 
 
 122 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 124 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 127 
 359749191076977 
 
 
 128 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 131 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 133 
 359749191076977 
 
 
 134 
 359749191076977 
 
 
 FizzBuzz 
 359749191076977 
 
 
 136 
 359749191076977 
 
 
 137 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 139 
 359749191076977 
 
 
 Buzz 
 359749191076977 
 
 
 Fizz 
 359749191076977 
 
 
 142 
 3

In [ ]:
assert '.'.join(col['fizzbuzz'][8:16]).lower() == x

In [ ]:
x = "fizz.buzz.11.fizz.13.14.fizz.16"

In [ ]:
%%sql
-- Indication. Avez-vous pensé au fait qu'un nombre divisible par 15 l'est également par 4 et 5 ?
SELECT CASE
           WHEN n MOD 3 = 0 THEN 'Fizz'
           WHEN n MOD 5 = 0 THEN 'Buzz'
           WHEN n MOD 15 = 0 THEN 'FizzBuzz'
           ELSE n
       END AS fizzbuzz
     , salt_088(string_hash('{{x}}') + sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE n > 0
LIMIT 20

20 rows affected.

fizzbuzz 
 token 
 
 
 
 
 1 
 360186567754554 
 
 
 2 
 360186567754554 
 
 
 Fizz 
 360186567754554 
 
 
 4 
 360186567754554 
 
 
 Buzz 
 360186567754554 
 
 
 Fizz 
 360186567754554 
 
 
 7 
 360186567754554 
 
 
 8 
 360186567754554 
 
 
 Fizz 
 360186567754554 
 
 
 Buzz 
 360186567754554 
 
 
 11 
 360186567754554 
 
 
 Fizz 
 360186567754554 
 
 
 13 
 360186567754554 
 
 
 14 
 360186567754554 
 
 
 Fizz 
 360186567754554 
 
 
 16 
 360186567754554 
 
 
 17 
 360186567754554 
 
 
 Fizz 
 360186567754554 
 
 
 19 
 360186567754554 
 
 
 Buzz 
 360186567754554

In [ ]:
assert '.'.join(col['fizzbuzz'][8:16]).lower() == x

In [ ]:
x = "fizz.buzz.11.fizz.13.14.buzz.16"

In [ ]:
%%sql
-- Indication. Avez-vous pensé au fait qu'un nombre divisible par 15 l'est également par 4 et 5 ?
SELECT CASE
           WHEN n MOD 5 = 0 THEN 'Buzz'
           WHEN n MOD 3 = 0 THEN 'Fizz'
           WHEN n MOD 15 = 0 THEN 'FizzBuzz'
           ELSE n
       END AS fizzbuzz
     , salt_088(string_hash('{{x}}') + sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE n > 0
LIMIT 20

20 rows affected.

fizzbuzz 
 token 
 
 
 
 
 1 
 359943398969027 
 
 
 2 
 359943398969027 
 
 
 Fizz 
 359943398969027 
 
 
 4 
 359943398969027 
 
 
 Buzz 
 359943398969027 
 
 
 Fizz 
 359943398969027 
 
 
 7 
 359943398969027 
 
 
 8 
 359943398969027 
 
 
 Fizz 
 359943398969027 
 
 
 Buzz 
 359943398969027 
 
 
 11 
 359943398969027 
 
 
 Fizz 
 359943398969027 
 
 
 13 
 359943398969027 
 
 
 14 
 359943398969027 
 
 
 Buzz 
 359943398969027 
 
 
 16 
 359943398969027 
 
 
 17 
 359943398969027 
 
 
 Fizz 
 359943398969027 
 
 
 19 
 359943398969027 
 
 
 Buzz 
 359943398969027

In [ ]:
assert '.'.join(col['fizzbuzz'][8:16]).lower() == x

In [ ]:
x = "fizz.buzz.11.fizz.13.14.fizzbuzz.16"

In [ ]:
%%sql
-- Indication. Votre suite comporte un terme de trop.
SELECT CASE
           WHEN (n + 1) MOD 15 = 0 THEN 'FizzBuzz'
           WHEN (n + 1) MOD 3 = 0 THEN 'Fizz'
           WHEN (n + 1) MOD 5 = 0 THEN 'Buzz'
           ELSE (n + 1)
       END AS fizzbuzz
     , salt_088(string_hash('{{x}}') + sum(nn(hash)) OVER ()) AS token
FROM ints

1001 rows affected.

fizzbuzz 
 token 
 
 
 
 
 1 
 359642314904307 
 
 
 2 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 4 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 7 
 359642314904307 
 
 
 8 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 11 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 13 
 359642314904307 
 
 
 14 
 359642314904307 
 
 
 FizzBuzz 
 359642314904307 
 
 
 16 
 359642314904307 
 
 
 17 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 19 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 22 
 359642314904307 
 
 
 23 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 26 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 28 
 359642314904307 
 
 
 29 
 359642314904307 
 
 
 FizzBuzz 
 359642314904307 
 
 
 31 
 359642314904307 
 
 
 32 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 34 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 37 
 359642314904307 
 
 
 38 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 41 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 43 
 359642314904307 
 
 
 44 
 359642314904307 
 
 
 FizzBuzz 
 359642314904307 
 
 
 46 
 359642314904307 
 
 
 47 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 49 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 52 
 359642314904307 
 
 
 53 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 56 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 58 
 359642314904307 
 
 
 59 
 359642314904307 
 
 
 FizzBuzz 
 359642314904307 
 
 
 61 
 359642314904307 
 
 
 62 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 64 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 67 
 359642314904307 
 
 
 68 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 71 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 73 
 359642314904307 
 
 
 74 
 359642314904307 
 
 
 FizzBuzz 
 359642314904307 
 
 
 76 
 359642314904307 
 
 
 77 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 79 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 82 
 359642314904307 
 
 
 83 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 86 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 88 
 359642314904307 
 
 
 89 
 359642314904307 
 
 
 FizzBuzz 
 359642314904307 
 
 
 91 
 359642314904307 
 
 
 92 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 94 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 97 
 359642314904307 
 
 
 98 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 101 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 103 
 359642314904307 
 
 
 104 
 359642314904307 
 
 
 FizzBuzz 
 359642314904307 
 
 
 106 
 359642314904307 
 
 
 107 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 109 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 112 
 359642314904307 
 
 
 113 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 116 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 118 
 359642314904307 
 
 
 119 
 359642314904307 
 
 
 FizzBuzz 
 359642314904307 
 
 
 121 
 359642314904307 
 
 
 122 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 124 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 127 
 359642314904307 
 
 
 128 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 131 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 133 
 359642314904307 
 
 
 134 
 359642314904307 
 
 
 FizzBuzz 
 359642314904307 
 
 
 136 
 359642314904307 
 
 
 137 
 359642314904307 
 
 
 Fizz 
 359642314904307 
 
 
 139 
 359642314904307 
 
 
 Buzz 
 359642314904307 
 
 
 Fizz 
 359

In [ ]:
assert '.'.join(col['fizzbuzz'][8:16]).lower() == x

In [ ]:
x = "fizz.buzz.11.fizz.13.14.fizzbuzz.16"

In [ ]:
%%sql
-- Indication. Vous pouvez éviter d'incrémenter chaque `n` : laissez tomber le premier `n` au lieu du dernier.
SELECT CASE
           WHEN (n + 1) MOD 15 = 0 THEN 'FizzBuzz'
           WHEN (n + 1) MOD 3 = 0 THEN 'Fizz'
           WHEN (n + 1) MOD 5 = 0 THEN 'Buzz'
           ELSE (n + 1)
       END AS fizzbuzz
     , salt_088(string_hash('{{x}}') + sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE n < 1000

1000 rows affected.

fizzbuzz 
 token 
 
 
 
 
 1 
 359813838431707 
 
 
 2 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 4 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 7 
 359813838431707 
 
 
 8 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 11 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 13 
 359813838431707 
 
 
 14 
 359813838431707 
 
 
 FizzBuzz 
 359813838431707 
 
 
 16 
 359813838431707 
 
 
 17 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 19 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 22 
 359813838431707 
 
 
 23 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 26 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 28 
 359813838431707 
 
 
 29 
 359813838431707 
 
 
 FizzBuzz 
 359813838431707 
 
 
 31 
 359813838431707 
 
 
 32 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 34 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 37 
 359813838431707 
 
 
 38 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 41 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 43 
 359813838431707 
 
 
 44 
 359813838431707 
 
 
 FizzBuzz 
 359813838431707 
 
 
 46 
 359813838431707 
 
 
 47 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 49 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 52 
 359813838431707 
 
 
 53 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 56 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 58 
 359813838431707 
 
 
 59 
 359813838431707 
 
 
 FizzBuzz 
 359813838431707 
 
 
 61 
 359813838431707 
 
 
 62 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 64 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 67 
 359813838431707 
 
 
 68 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 71 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 73 
 359813838431707 
 
 
 74 
 359813838431707 
 
 
 FizzBuzz 
 359813838431707 
 
 
 76 
 359813838431707 
 
 
 77 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 79 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 82 
 359813838431707 
 
 
 83 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 86 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 88 
 359813838431707 
 
 
 89 
 359813838431707 
 
 
 FizzBuzz 
 359813838431707 
 
 
 91 
 359813838431707 
 
 
 92 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 94 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 97 
 359813838431707 
 
 
 98 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 101 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 103 
 359813838431707 
 
 
 104 
 359813838431707 
 
 
 FizzBuzz 
 359813838431707 
 
 
 106 
 359813838431707 
 
 
 107 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 109 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 112 
 359813838431707 
 
 
 113 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 116 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 118 
 359813838431707 
 
 
 119 
 359813838431707 
 
 
 FizzBuzz 
 359813838431707 
 
 
 121 
 359813838431707 
 
 
 122 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 124 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 127 
 359813838431707 
 
 
 128 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 131 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 133 
 359813838431707 
 
 
 134 
 359813838431707 
 
 
 FizzBuzz 
 359813838431707 
 
 
 136 
 359813838431707 
 
 
 137 
 359813838431707 
 
 
 Fizz 
 359813838431707 
 
 
 139 
 359813838431707 
 
 
 Buzz 
 359813838431707 
 
 
 Fizz 
 359

In [ ]:
assert '.'.join(col['fizzbuzz'][8:16]).lower() == x

In [ ]:
x = "fizz.buzz.11.fizz.13.14.fizz buzz.16"

In [ ]:
%%sql
-- Indication. N'insérez pas d'espace dans `'FizzBuzz'`.
SELECT CASE
           WHEN n MOD 15 = 0 THEN 'Fizz Buzz'
           WHEN n MOD 3 = 0 THEN 'Fizz'
           WHEN n MOD 5 = 0 THEN 'Buzz'
           ELSE n
       END AS fizzbuzz
     , salt_088(string_hash('{{x}}') + sum(nn(hash)) OVER ()) AS token
FROM ints
WHERE n > 0

1000 rows affected.

fizzbuzz 
 token 
 
 
 
 
 1 
 359590657654446 
 
 
 2 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 4 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 7 
 359590657654446 
 
 
 8 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 11 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 13 
 359590657654446 
 
 
 14 
 359590657654446 
 
 
 Fizz Buzz 
 359590657654446 
 
 
 16 
 359590657654446 
 
 
 17 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 19 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 22 
 359590657654446 
 
 
 23 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 26 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 28 
 359590657654446 
 
 
 29 
 359590657654446 
 
 
 Fizz Buzz 
 359590657654446 
 
 
 31 
 359590657654446 
 
 
 32 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 34 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 37 
 359590657654446 
 
 
 38 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 41 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 43 
 359590657654446 
 
 
 44 
 359590657654446 
 
 
 Fizz Buzz 
 359590657654446 
 
 
 46 
 359590657654446 
 
 
 47 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 49 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 52 
 359590657654446 
 
 
 53 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 56 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 58 
 359590657654446 
 
 
 59 
 359590657654446 
 
 
 Fizz Buzz 
 359590657654446 
 
 
 61 
 359590657654446 
 
 
 62 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 64 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 67 
 359590657654446 
 
 
 68 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 71 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 73 
 359590657654446 
 
 
 74 
 359590657654446 
 
 
 Fizz Buzz 
 359590657654446 
 
 
 76 
 359590657654446 
 
 
 77 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 79 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 82 
 359590657654446 
 
 
 83 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 86 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 88 
 359590657654446 
 
 
 89 
 359590657654446 
 
 
 Fizz Buzz 
 359590657654446 
 
 
 91 
 359590657654446 
 
 
 92 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 94 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 97 
 359590657654446 
 
 
 98 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 101 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 103 
 359590657654446 
 
 
 104 
 359590657654446 
 
 
 Fizz Buzz 
 359590657654446 
 
 
 106 
 359590657654446 
 
 
 107 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 109 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 112 
 359590657654446 
 
 
 113 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 116 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 118 
 359590657654446 
 
 
 119 
 359590657654446 
 
 
 Fizz Buzz 
 359590657654446 
 
 
 121 
 359590657654446 
 
 
 122 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 124 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 127 
 359590657654446 
 
 
 128 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 131 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 133 
 359590657654446 
 
 
 134 
 359590657654446 
 
 
 Fizz Buzz 
 359590657654446 
 
 
 136 
 359590657654446 
 
 
 137 
 359590657654446 
 
 
 Fizz 
 359590657654446 
 
 
 139 
 359590657654446 
 
 
 Buzz 
 359590657654446 
 
 
 F

In [ ]:
assert '.'.join(col['fizzbuzz'][8:16]).lower() == x

### Les deux aiguilles superposées

**Atelier [060].** À quels horaires l'aiguille des heures et celle des minutes sont-elles superposées ?

<figure>
  <img src="https://raw.githubusercontent.com/laowantong/sqlab_ints/refs/heads/main/assets/clocks.png"/>
  <figcaption><p>Les cinq premiers horaires de superposition des aiguilles des heures et des minutes. Attention, l'aiguille des secondes ne peut se superposer qu'à midi ou minuit ; ci-dessus, elle est à la position qui minimise la différence angulaire entre les deux autres aiguilles. Cadrans générés avec <a href='https://onlinetools.com/time/draw-analog-clock' target='_blank'>Analog Clock Maker</a>.</p></figcaption>
</figure>

_Défi._ Listez, par ordre croissant et à la seconde près, tous les horaires de superposition compris entre 00:00:00 et 11:59:59.

_Aide._ Vous aurez à convertir les mesures de temps en degrés d'angle. Pour produire toutes les heures, minutes et secondes candidates, faites un triple produit cartésien. Deux CTE sont recommandées, l'une pour les calculs, l'autre pour la sélection des résultats. Les [fonctions de date et heure](https://dev.mysql.com/doc/refman/8.4/en/date-and-time-functions.html) de MySQL vous aideront à présenter les horaires au format attendu (`HH:MM:SS`).

In [ ]:
x = '00:00:00 01:05:27 02:10:55 03:16:22 04:21:49 05:27:16 06:32:44 07:38:11 08:43:38 09:49:05 10:54:33' # la concaténation de ces nombres séparés par un espace.
# Javascript: result.col('time').join(' ') || '7_531_148'

In [ ]:
%%sql
WITH
T1 AS (
    SELECT
        time_format(sec_to_time(h * 3600 + m * 60 + s), '%H:%i:%s') AS time,
        abs(h * 30 - m * 11/2 - s * 11/120) AS angle
    FROM (SELECT n AS h FROM ints WHERE n < 12) A,
         (SELECT n AS m FROM ints WHERE n < 60) B,
         (SELECT n AS s FROM ints WHERE n < 60) C
),
T2 AS (
    SELECT time
    FROM T1
    WHERE round(angle) = 0
    ORDER BY angle
    LIMIT 11
)
SELECT time
     , salt_060(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM T2
ORDER BY time

11 rows affected.

time 
 token 
 
 
 
 
 00:00:00 
 111684804833911 
 
 
 01:05:27 
 111684804833911 
 
 
 02:10:55 
 111684804833911 
 
 
 03:16:22 
 111684804833911 
 
 
 04:21:49 
 111684804833911 
 
 
 05:27:16 
 111684804833911 
 
 
 06:32:44 
 111684804833911 
 
 
 07:38:11 
 111684804833911 
 
 
 08:43:38 
 111684804833911 
 
 
 09:49:05 
 111684804833911 
 
 
 10:54:33 
 111684804833911

In [ ]:
assert ' '.join(col['time']) == x

In [ ]:
x = '00:00:00 07:38:11 04:21:49 03:16:22 08:43:38 01:05:27 10:54:33 05:27:16 06:32:44 02:10:55 09:49:05'

In [ ]:
%%sql
-- Indication. Triez encore ces horaires par ordre croissant.
WITH
T1 AS (
    SELECT
        time_format(sec_to_time(h * 3600 + m * 60 + s), '%H:%i:%s') AS time,
        abs(h * 30 - m * 11/2 - s * 11/120) AS angle
    FROM (SELECT n AS h FROM ints WHERE n < 12) A,
         (SELECT n AS m FROM ints WHERE n < 60) B,
         (SELECT n AS s FROM ints WHERE n < 60) C
),
T2 AS (
    SELECT time
    FROM T1
    WHERE round(angle) = 0
    ORDER BY angle
    LIMIT 11
)
SELECT time
     , salt_060(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM T2

11 rows affected.

time 
 token 
 
 
 
 
 00:00:00 
 111432449994756 
 
 
 07:38:11 
 111432449994756 
 
 
 04:21:49 
 111432449994756 
 
 
 03:16:22 
 111432449994756 
 
 
 08:43:38 
 111432449994756 
 
 
 01:05:27 
 111432449994756 
 
 
 10:54:33 
 111432449994756 
 
 
 05:27:16 
 111432449994756 
 
 
 06:32:44 
 111432449994756 
 
 
 02:10:55 
 111432449994756 
 
 
 09:49:05 
 111432449994756

In [ ]:
assert ' '.join(col['time']) == x

### Prévalence des vendredis 13

**Atelier [078].** Pas de bol : les vendredis 13 sont comparativement plus nombreux que les lundis 13, mardis 13, etc.

<figure>
  <img src="https://raw.githubusercontent.com/laowantong/sqlab_ints/refs/heads/main/assets/Schopenhauer-fr.jpg" width=450/>
  <figcaption><p>Arthur Schopenhauer, Parerga und Paralipomena, Band II, Kapitel XXXI: Zur Metaphysik des Aberglaubens, § 394. Erste Ausgabe, A. W. Hayn, Berlin, 1851, S. 663. <a href="https://www.youtube.com/watch?v=dQw4w9WgXcQ" target="__blank">Source</a>.</p></figcaption>
</figure>

_Défi_. Confirmez cette malédiction en donnant, pour chaque jour de la semaine (à commencer par le lundi), le nombre de fois où il tombe le 13 du mois dans un cycle grégorien complet (400 ans).

_Aide_. Vous pouvez (ou non) utiliser les [fonctions de date et heure](https://dev.mysql.com/doc/refman/8.4/en/date-and-time-functions.html) de MySQL.

_Avertissement_. Choisissez une année de départ postérieure au début du calendrier grégorien (1582).

“Es ist ein weiterer Beweis für die grundlegende Bosheit des Willens, daß der dreizehnte Tag eines Monats öfter auf einen Freitag fällt als auf jeden anderen Wochentag. Die Natur selbst scheint sich gegen uns verschworen zu haben, indem sie unseren Aberglauben mit mathematischer Präzision nährt. Welch grausame Ironie, daß selbst der Kalender zum Werkzeug unseres Leidens wird!”

In [ ]:
x = "685 685 687 684 688 684 687" # la concaténation de ces nombres séparés par un espace.
# Javascript: result.col('occurrences').join(' ') || '7_531_148'

In [ ]:
%%sql
WITH 
years AS (
    SELECT 1583 + n AS year_number
    FROM ints
    WHERE n < 400
),
days AS (
    SELECT n AS day_number
    FROM ints
    WHERE n BETWEEN 1 AND 366
),
dates AS (
    SELECT makedate(year_number, day_number) AS D
    FROM years, days
)
SELECT dayname(D) AS day
     , count(*) AS occurrences
     , salt_078(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM dates
WHERE day(D) = 13
GROUP BY weekday(D)
       , dayname(D)
ORDER BY weekday(D)

7 rows affected.

day 
 occurrences 
 token 
 
 
 
 
 Monday 
 685 
 33460752933766 
 
 
 Tuesday 
 685 
 33460752933766 
 
 
 Wednesday 
 687 
 33460752933766 
 
 
 Thursday 
 684 
 33460752933766 
 
 
 Friday 
 688 
 33460752933766 
 
 
 Saturday 
 684 
 33460752933766 
 
 
 Sunday 
 687 
 33460752933766

In [ ]:
assert ' '.join(map(str, col['occurrences'])) == x

In [ ]:
%%sql
-- Variante. Même principe, mais en calculant les dates du 13 des 4800 mois qui commencent au 13 d'un mois
-- arbitraire d'une année arbitraire.
WITH dates AS
    (SELECT date_add('1583-01-13', INTERVAL A.n + 1000 * B.n MONTH) AS D
     FROM ints AS A
     CROSS JOIN ints AS B
     WHERE A.n < 1000
         AND A.n + 1000 * B.n < 4800 )
SELECT dayname(D) AS `day`
     , count(D) AS `occurrences`
     , salt_078(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM dates
GROUP BY weekday(D)
       , dayname(D)
ORDER BY weekday(D)

7 rows affected.

day 
 occurrences 
 token 
 
 
 
 
 Monday 
 685 
 33460752933766 
 
 
 Tuesday 
 685 
 33460752933766 
 
 
 Wednesday 
 687 
 33460752933766 
 
 
 Thursday 
 684 
 33460752933766 
 
 
 Friday 
 688 
 33460752933766 
 
 
 Saturday 
 684 
 33460752933766 
 
 
 Sunday 
 687 
 33460752933766

In [ ]:
assert ' '.join(map(str, col['occurrences'])) == x

### Numération chinoise

**Atelier [036].** Les signes fondamentaux de la numération chinoise moderne sont les suivants :

| Arabe | 0 | 1 | 2 | 3 | 4 | 5 | 6 | 7 | 8 | 9 | 10 | 100 | 1000 | 10000 |
|---|---|---|---|---|---|---|---|---|---|---|----|-----|------|-------|
| **Chinois** | 零 | 一 | 二 | 三 | 四 | 五 | 六 | 七 | 八 | 九 | 十 | 百 | 千 | 万 |

Elle repose sur un système simple de multiplications (pour les dizaines, centaines, etc.) et d'additions. Par exemple :

$$
\begin{array}{rcccccccccccccc}
1968 & = & 1 & \times & 1000 & + & 9 & \times & 100 & + & 6 & \times & 10 & + & 8 \\
一千九百六十八 & = & 一 &  & 千 &  & 九 & & 百 &  & 六 &  & 十 &  & 八
\end{array}
$$

Cette règle ne connaît que deux exceptions :
- La multiplication par un est omise pour les nombres de $10$ à $19$ : $1\times 10$ (一十) s'abrège alors en $10$ (十).
  - On écrira donc 十三 (13) et non 一十三.
  - Pas d'exception au-delà de $100$ : on écrit bien 一百一十三 (113) et non 百十三.
- Les multiplications par zéro sont remplacées par des $0$ intercalaires :
    - $105 = 1 \times 100 + 0 \times 10 + 5$ (一百零十五) s'abrège en $1 \times 100 + 0 + 5$ (一百零五) ;
    - $1005 = 1 \times 100 + 0 \times 100 + 0 \times 10 + 5$ (一万零百零十五) s'abrège en $1 \times 1000 + 0 + 0 + 5$ (一万零零五).
    
_Défi._ Générer une table des nombres chinois de 0 (零) à 1000 (一千).

_Aide._ Pas besoin de récursivité ici. Comme on se limite arbitraitement à 1000, tout l'algorithme tient dans la clause `SELECT`.

_Astuce._ Utilisez `SUBSTRING('一二三四五六七八九', i, 1)` pour renvoyer directement le chiffre chinois pour $i$ sans passer par d'encombrants `CASE ... END` à chaque fois. Notez que `SUBSTRING` renvoie une chaine vide quand son deuxième argument est 0.

In [ ]:
def num_to_chinese(num):
    if num == 0:
        return '零'
    if num == 1000:
        return '一千'
    
    digits = '零一二三四五六七八九'
    
    result = []
    s = str(num)
    
    # Handle hundreds
    if len(s) == 3:
        result.append(digits[int(s[0])] + '百')
        if s[1] != '0':
            result.append(digits[int(s[1])] + '十')
        elif s[2] != '0':
            result.append('零')
        if s[2] != '0':
            result.append(digits[int(s[2])])
    
    # Handle tens
    elif len(s) == 2:
        if s[0] == '1':
            result.append('十')
        else:
            result.append(digits[int(s[0])] + '十')
        if s[1] != '0':
            result.append(digits[int(s[1])])
    
    # Handle single digits
    else:
        result.append(digits[int(s)])
    
    return ''.join(result)

In [ ]:
x = ' '.join(num_to_chinese(i) for i in range(0, 1001, 8)) # la concaténation des nombres chinois, pris de 8 en 8 et séparés par des espaces.
# Javascript: (result.col('chinese').slice3(undefined, undefined, 8).join(' ')) || '7_531_148'

In [ ]:
%%sql
-- Ici, pour éviter les répétitions, on précalcule un certain nombre de variables utiles dans une CTE.
WITH variables AS (
  SELECT 
    n,
    (n MOD 1000) DIV 100 AS hundreds,
    (n MOD 100) DIV 10 AS tens,
    n MOD 10 AS ones
  FROM ints
)
SELECT n AS arabic,
    CASE n
        WHEN 0 THEN '零'
        WHEN 1000 THEN '一千'
        ELSE CONCAT(
            CASE
                WHEN hundreds = 0 THEN ''
                ELSE CONCAT(SUBSTRING('一二三四五六七八九', hundreds, 1), '百')
            END,
            CASE
                WHEN hundreds > 0 AND tens = 0 AND ones > 0 THEN '零'
                WHEN tens = 0 THEN ''
                WHEN hundreds = 0 AND tens = 1 THEN '十'
                ELSE CONCAT(SUBSTRING('一二三四五六七八九', tens, 1), '十')
            END,
            SUBSTRING('一二三四五六七八九', ones, 1)
        )
    END AS chinese
     , salt_036(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM variables

1001 rows affected.

arabic 
 chinese 
 token 
 
 
 
 
 0 
 零 
 123998439794056 
 
 
 1 
 一 
 123998439794056 
 
 
 2 
 二 
 123998439794056 
 
 
 3 
 三 
 123998439794056 
 
 
 4 
 四 
 123998439794056 
 
 
 5 
 五 
 123998439794056 
 
 
 6 
 六 
 123998439794056 
 
 
 7 
 七 
 123998439794056 
 
 
 8 
 八 
 123998439794056 
 
 
 9 
 九 
 123998439794056 
 
 
 10 
 十 
 123998439794056 
 
 
 11 
 十一 
 123998439794056 
 
 
 12 
 十二 
 123998439794056 
 
 
 13 
 十三 
 123998439794056 
 
 
 14 
 十四 
 123998439794056 
 
 
 15 
 十五 
 123998439794056 
 
 
 16 
 十六 
 123998439794056 
 
 
 17 
 十七 
 123998439794056 
 
 
 18 
 十八 
 123998439794056 
 
 
 19 
 十九 
 123998439794056 
 
 
 20 
 二十 
 123998439794056 
 
 
 21 
 二十一 
 123998439794056 
 
 
 22 
 二十二 
 123998439794056 
 
 
 23 
 二十三 
 123998439794056 
 
 
 24 
 二十四 
 123998439794056 
 
 
 25 
 二十五 
 123998439794056 
 
 
 26 
 二十六 
 123998439794056 
 
 
 27 
 二十七 
 123998439794056 
 
 
 28 
 二十八 
 123998439794056 
 
 
 29 
 二十九 
 123998439794056 
 
 
 30 
 三十 
 123998439794056 
 
 
 31 
 三十一 
 123998439794056 
 
 
 32 
 三十二 
 123998439794056 
 
 
 33 
 三十三 
 123998439794056 
 
 
 34 
 三十四 
 123998439794056 
 
 
 35 
 三十五 
 123998439794056 
 
 
 36 
 三十六 
 123998439794056 
 
 
 37 
 三十七 
 123998439794056 
 
 
 38 
 三十八 
 123998439794056 
 
 
 39 
 三十九 
 123998439794056 
 
 
 40 
 四十 
 123998439794056 
 
 
 41 
 四十一 
 123998439794056 
 
 
 42 
 四十二 
 123998439794056 
 
 
 43 
 四十三 
 123998439794056 
 
 
 44 
 四十四 
 123998439794056 
 
 
 45 
 四十五 
 123998439794056 
 
 
 46 
 四十六 
 123998439794056 
 
 
 47 
 四十七 
 123998439794056 
 
 
 48 
 四十八 
 123998439794056 
 
 
 49 
 四十九 
 123998439794056 
 
 
 50 
 五十 
 123998439794056 
 
 
 51 
 五十一 
 123998439794056 
 
 
 52 
 五十二 
 123998439794056 
 
 
 53 
 五十三 
 123998439794056 
 
 
 54 
 五十四 
 123998439794056 
 
 
 55 
 五十五 
 123998439794056 
 
 
 56 
 五十六 
 123998439794056 
 
 
 57 
 五十七 
 123998439794056 
 
 
 58 
 五十八 
 123998439794056 
 
 
 59 
 五十九 
 123998439794056 
 
 
 60 
 六十 
 123998439794056 
 
 
 61 
 六十一 
 123998439794056 
 
 
 62 
 六十二 
 123998439794056 
 
 
 63 
 六十三 
 123998439794056 
 
 
 64 
 六十四 
 123998439794056 
 
 
 65 
 六十五 
 123998439794056 
 
 
 66 
 六十六 
 123998439794056 
 
 
 67 
 六十七 
 123998439794056 
 
 
 68 
 六十八 
 123998439794056 
 
 
 69 
 六十九 
 123998439794056 
 
 
 70 
 七十 
 123998439794056 
 
 
 71 
 七十一 
 123998439794056 
 
 
 72 
 七十二 
 123998439794056 
 
 
 73 
 七十三 
 123998439794056 
 
 
 74 
 七十四 
 123998439794056 
 
 
 75 
 七十五 
 123998439794056 
 
 
 76 
 七十六 
 123998439794056 
 
 
 77 
 七十七 
 123998439794056 
 
 
 78 
 七十八 
 123998439794056 
 
 
 79 
 七十九 
 123998439794056 
 
 
 80 
 八十 
 123998439794056 
 
 
 81 
 八十一 
 123998439794056 
 
 
 82 
 八十二 
 123998439794056 
 
 
 83 
 八十三 
 123998439794056 
 
 
 84 
 八十四 
 123998439794056 
 
 
 85 
 八十五 
 123998439794056 
 
 
 86 
 八十六 
 123998439794056 
 
 
 87 
 八十七 
 123998439794056 
 
 
 88 
 八十八 
 123998439794056 
 
 
 89 
 八十九 
 123998439794056 
 
 
 90 
 九十 
 123998439794056 
 
 
 91 
 九十一 
 123998439794056 
 
 
 92 
 九十二 
 123998439794056 
 
 
 93 
 九十三 
 123998439794056 
 
 
 94 
 九十四 
 123998439794056 
 
 
 95 
 九十五 
 123998439794056 
 
 
 96 
 九十六 
 123998439794056 
 
 
 97 
 九十七 
 123998439794056 
 
 
 98 
 九十八 
 123998439794056 
 
 
 99 
 九十九 
 123998439794056 
 
 
 100 
 一百 
 123998439794056 
 
 
 101 
 一百零一 
 123998439794056 
 
 
 102 
 一百零二 
 123998439794056 
 
 
 103 
 一百零三 
 123998439794056 
 
 
 104 
 一百零四 
 123998439794056 
 
 
 105 
 一百零五 
 123998439794056 
 
 
 106 
 一百零六 
 123998439794056 
 
 
 107 
 一百零七 
 123998439794056 
 
 
 108 
 一百零八 
 123998439794056 
 
 
 109 
 一百零九 
 123998439794056 
 
 
 110 
 一百一十 
 123998439794056 
 
 
 111 
 一百一十一 
 123998439794056 
 
 
 112 
 一百一十二 
 123998439794056 
 
 
 113 
 一百一十三 
 123998439794056 
 
 
 114 
 一百一十四 
 123998439794056 
 
 
 115 
 一百一十五 
 123998439794056 
 
 
 116 
 一百一十六 
 123998439794056 
 
 
 117 
 一百一十七 
 123998439794056 
 
 
 118 
 一百一十八 
 123998439794056 
 
 
 119 
 一百一十九 
 123998439794056 
 
 
 120 
 一

In [ ]:
assert ' '.join(col['chinese'][::8]) == x

In [ ]:
x = '零 八 十六 二十四 三十二 四十 四十八 五十六 六十四 七十二 八十 八十八 九十六 一百零四 一百一十二 一百二十 一百二十八 一百三十六 一百四十四 一百五十二 一百六十 一百六十八 一百七十六 一百八十四 一百九十二 二百 二百零八 二百一十六 二百二十四 二百三十二 二百四十 二百四十八 二百五十六 二百六十四 二百七十二 二百八十 二百八十八 二百九十六 三百零四 三百一十二 三百二十 三百二十八 三百三十六 三百四十四 三百五十二 三百六十 三百六十八 三百七十六 三百八十四 三百九十二 四百 四百零八 四百一十六 四百二十四 四百三十二 四百四十 四百四十八 四百五十六 四百六十四 四百七十二 四百八十 四百八十八 四百九十六 五百零四 五百一十二 五百二十 五百二十八 五百三十六 五百四十四 五百五十二 五百六十 五百六十八 五百七十六 五百八十四 五百九十二 六百 六百零八 六百一十六 六百二十四 六百三十二 六百四十 六百四十八 六百五十六 六百六十四 六百七十二 六百八十 六百八十八 六百九十六 七百零四 七百一十二 七百二十 七百二十八 七百三十六 七百四十四 七百五十二 七百六十 七百六十八 七百七十六 七百八十四 七百九十二 八百 八百零八 八百一十六 八百二十四 八百三十二 八百四十 八百四十八 八百五十六 八百六十四 八百七十二 八百八十 八百八十八 八百九十六 九百零四 九百一十二 九百二十 九百二十八 九百三十六 九百四十四 九百五十二 九百六十 九百六十八 九百七十六 九百八十四 九百九十二 千'

In [ ]:
%%sql
-- Indication. Le nombre 1000 s'écrit 一千 et non 千.
WITH variables AS (
  SELECT 
    n,
    (n MOD 1000) DIV 100 AS hundreds,
    (n MOD 100) DIV 10 AS tens,
    n MOD 10 AS ones
  FROM ints
)
SELECT n AS arabic,
    CASE n
        WHEN 0 THEN '零'
        WHEN 1000 THEN '千'
        ELSE CONCAT(
            CASE
                WHEN hundreds = 0 THEN ''
                ELSE CONCAT(SUBSTRING('一二三四五六七八九', hundreds, 1), '百')
            END,
            CASE
                WHEN tens = 0 AND hundreds > 0 AND ones > 0 THEN '零'
                WHEN tens = 0 THEN ''
                WHEN tens = 1 AND hundreds = 0 THEN '十'
                ELSE CONCAT(SUBSTRING('一二三四五六七八九', tens, 1), '十')
            END,
            SUBSTRING('一二三四五六七八九', ones, 1)
        )
    END AS "chinese"
     , salt_036(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM variables

1001 rows affected.

arabic 
 chinese 
 token 
 
 
 
 
 0 
 零 
 123397572119962 
 
 
 1 
 一 
 123397572119962 
 
 
 2 
 二 
 123397572119962 
 
 
 3 
 三 
 123397572119962 
 
 
 4 
 四 
 123397572119962 
 
 
 5 
 五 
 123397572119962 
 
 
 6 
 六 
 123397572119962 
 
 
 7 
 七 
 123397572119962 
 
 
 8 
 八 
 123397572119962 
 
 
 9 
 九 
 123397572119962 
 
 
 10 
 十 
 123397572119962 
 
 
 11 
 十一 
 123397572119962 
 
 
 12 
 十二 
 123397572119962 
 
 
 13 
 十三 
 123397572119962 
 
 
 14 
 十四 
 123397572119962 
 
 
 15 
 十五 
 123397572119962 
 
 
 16 
 十六 
 123397572119962 
 
 
 17 
 十七 
 123397572119962 
 
 
 18 
 十八 
 123397572119962 
 
 
 19 
 十九 
 123397572119962 
 
 
 20 
 二十 
 123397572119962 
 
 
 21 
 二十一 
 123397572119962 
 
 
 22 
 二十二 
 123397572119962 
 
 
 23 
 二十三 
 123397572119962 
 
 
 24 
 二十四 
 123397572119962 
 
 
 25 
 二十五 
 123397572119962 
 
 
 26 
 二十六 
 123397572119962 
 
 
 27 
 二十七 
 123397572119962 
 
 
 28 
 二十八 
 123397572119962 
 
 
 29 
 二十九 
 123397572119962 
 
 
 30 
 三十 
 123397572119962 
 
 
 31 
 三十一 
 123397572119962 
 
 
 32 
 三十二 
 123397572119962 
 
 
 33 
 三十三 
 123397572119962 
 
 
 34 
 三十四 
 123397572119962 
 
 
 35 
 三十五 
 123397572119962 
 
 
 36 
 三十六 
 123397572119962 
 
 
 37 
 三十七 
 123397572119962 
 
 
 38 
 三十八 
 123397572119962 
 
 
 39 
 三十九 
 123397572119962 
 
 
 40 
 四十 
 123397572119962 
 
 
 41 
 四十一 
 123397572119962 
 
 
 42 
 四十二 
 123397572119962 
 
 
 43 
 四十三 
 123397572119962 
 
 
 44 
 四十四 
 123397572119962 
 
 
 45 
 四十五 
 123397572119962 
 
 
 46 
 四十六 
 123397572119962 
 
 
 47 
 四十七 
 123397572119962 
 
 
 48 
 四十八 
 123397572119962 
 
 
 49 
 四十九 
 123397572119962 
 
 
 50 
 五十 
 123397572119962 
 
 
 51 
 五十一 
 123397572119962 
 
 
 52 
 五十二 
 123397572119962 
 
 
 53 
 五十三 
 123397572119962 
 
 
 54 
 五十四 
 123397572119962 
 
 
 55 
 五十五 
 123397572119962 
 
 
 56 
 五十六 
 123397572119962 
 
 
 57 
 五十七 
 123397572119962 
 
 
 58 
 五十八 
 123397572119962 
 
 
 59 
 五十九 
 123397572119962 
 
 
 60 
 六十 
 123397572119962 
 
 
 61 
 六十一 
 123397572119962 
 
 
 62 
 六十二 
 123397572119962 
 
 
 63 
 六十三 
 123397572119962 
 
 
 64 
 六十四 
 123397572119962 
 
 
 65 
 六十五 
 123397572119962 
 
 
 66 
 六十六 
 123397572119962 
 
 
 67 
 六十七 
 123397572119962 
 
 
 68 
 六十八 
 123397572119962 
 
 
 69 
 六十九 
 123397572119962 
 
 
 70 
 七十 
 123397572119962 
 
 
 71 
 七十一 
 123397572119962 
 
 
 72 
 七十二 
 123397572119962 
 
 
 73 
 七十三 
 123397572119962 
 
 
 74 
 七十四 
 123397572119962 
 
 
 75 
 七十五 
 123397572119962 
 
 
 76 
 七十六 
 123397572119962 
 
 
 77 
 七十七 
 123397572119962 
 
 
 78 
 七十八 
 123397572119962 
 
 
 79 
 七十九 
 123397572119962 
 
 
 80 
 八十 
 123397572119962 
 
 
 81 
 八十一 
 123397572119962 
 
 
 82 
 八十二 
 123397572119962 
 
 
 83 
 八十三 
 123397572119962 
 
 
 84 
 八十四 
 123397572119962 
 
 
 85 
 八十五 
 123397572119962 
 
 
 86 
 八十六 
 123397572119962 
 
 
 87 
 八十七 
 123397572119962 
 
 
 88 
 八十八 
 123397572119962 
 
 
 89 
 八十九 
 123397572119962 
 
 
 90 
 九十 
 123397572119962 
 
 
 91 
 九十一 
 123397572119962 
 
 
 92 
 九十二 
 123397572119962 
 
 
 93 
 九十三 
 123397572119962 
 
 
 94 
 九十四 
 123397572119962 
 
 
 95 
 九十五 
 123397572119962 
 
 
 96 
 九十六 
 123397572119962 
 
 
 97 
 九十七 
 123397572119962 
 
 
 98 
 九十八 
 123397572119962 
 
 
 99 
 九十九 
 123397572119962 
 
 
 100 
 一百 
 123397572119962 
 
 
 101 
 一百零一 
 123397572119962 
 
 
 102 
 一百零二 
 123397572119962 
 
 
 103 
 一百零三 
 123397572119962 
 
 
 104 
 一百零四 
 123397572119962 
 
 
 105 
 一百零五 
 123397572119962 
 
 
 106 
 一百零六 
 123397572119962 
 
 
 107 
 一百零七 
 123397572119962 
 
 
 108 
 一百零八 
 123397572119962 
 
 
 109 
 一百零九 
 123397572119962 
 
 
 110 
 一百一十 
 123397572119962 
 
 
 111 
 一百一十一 
 123397572119962 
 
 
 112 
 一百一十二 
 123397572119962 
 
 
 113 
 一百一十三 
 123397572119962 
 
 
 114 
 一百一十四 
 123397572119962 
 
 
 115 
 一百一十五 
 123397572119962 
 
 
 116 
 一百一十六 
 123397572119962 
 
 
 117 
 一百一十七 
 123397572119962 
 
 
 118 
 一百一十八 
 123397572119962 
 
 
 119 
 一百一十九 
 123397572119962 
 
 
 120 
 一

In [ ]:
assert ' '.join(col['chinese'][::8]) == x

In [ ]:
x = '零 八 十六 二十四 三十二 四十 四十八 五十六 六十四 七十二 八十 八十八 九十六 一百零四 一百一十二 一百二十 一百二十八 一百三十六 一百四十四 一百五十二 一百六十 一百六十八 一百七十六 一百八十四 一百九十二 二百 二百零八 二百一十六 二百二十四 二百三十二 二百四十 二百四十八 二百五十六 二百六十四 二百七十二 二百八十 二百八十八 二百九十六 三百零四 三百一十二 三百二十 三百二十八 三百三十六 三百四十四 三百五十二 三百六十 三百六十八 三百七十六 三百八十四 三百九十二 四百 四百零八 四百一十六 四百二十四 四百三十二 四百四十 四百四十八 四百五十六 四百六十四 四百七十二 四百八十 四百八十八 四百九十六 五百零四 五百一十二 五百二十 五百二十八 五百三十六 五百四十四 五百五十二 五百六十 五百六十八 五百七十六 五百八十四 五百九十二 六百 六百零八 六百一十六 六百二十四 六百三十二 六百四十 六百四十八 六百五十六 六百六十四 六百七十二 六百八十 六百八十八 六百九十六 七百零四 七百一十二 七百二十 七百二十八 七百三十六 七百四十四 七百五十二 七百六十 七百六十八 七百七十六 七百八十四 七百九十二 八百 八百零八 八百一十六 八百二十四 八百三十二 八百四十 八百四十八 八百五十六 八百六十四 八百七十二 八百八十 八百八十八 八百九十六 九百零四 九百一十二 九百二十 九百二十八 九百三十六 九百四十四 九百五十二 九百六十 九百六十八 九百七十六 九百八十四 九百九十二 '

In [ ]:
%%sql
-- Indication. N'oubliez pas le nombre 1000, qui s'écrit 一千.
WITH variables AS (
  SELECT 
    n,
    (n MOD 1000) DIV 100 AS hundreds,
    (n MOD 100) DIV 10 AS tens,
    n MOD 10 AS ones
  FROM ints
)
SELECT n AS arabic,
    CASE n
        WHEN 0 THEN '零'
        ELSE CONCAT(
            CASE
                WHEN hundreds = 0 THEN ''
                ELSE CONCAT(SUBSTRING('一二三四五六七八九', hundreds, 1), '百')
            END,
            CASE
                WHEN tens = 0 AND hundreds > 0 AND ones > 0 THEN '零'
                WHEN tens = 0 THEN ''
                WHEN tens = 1 AND hundreds = 0 THEN '十'
                ELSE CONCAT(SUBSTRING('一二三四五六七八九', tens, 1), '十')
            END,
            SUBSTRING('一二三四五六七八九', ones, 1)
        )
    END AS "chinese"
     , salt_036(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM variables

1001 rows affected.

arabic 
 chinese 
 token 
 
 
 
 
 0 
 零 
 123244131805666 
 
 
 1 
 一 
 123244131805666 
 
 
 2 
 二 
 123244131805666 
 
 
 3 
 三 
 123244131805666 
 
 
 4 
 四 
 123244131805666 
 
 
 5 
 五 
 123244131805666 
 
 
 6 
 六 
 123244131805666 
 
 
 7 
 七 
 123244131805666 
 
 
 8 
 八 
 123244131805666 
 
 
 9 
 九 
 123244131805666 
 
 
 10 
 十 
 123244131805666 
 
 
 11 
 十一 
 123244131805666 
 
 
 12 
 十二 
 123244131805666 
 
 
 13 
 十三 
 123244131805666 
 
 
 14 
 十四 
 123244131805666 
 
 
 15 
 十五 
 123244131805666 
 
 
 16 
 十六 
 123244131805666 
 
 
 17 
 十七 
 123244131805666 
 
 
 18 
 十八 
 123244131805666 
 
 
 19 
 十九 
 123244131805666 
 
 
 20 
 二十 
 123244131805666 
 
 
 21 
 二十一 
 123244131805666 
 
 
 22 
 二十二 
 123244131805666 
 
 
 23 
 二十三 
 123244131805666 
 
 
 24 
 二十四 
 123244131805666 
 
 
 25 
 二十五 
 123244131805666 
 
 
 26 
 二十六 
 123244131805666 
 
 
 27 
 二十七 
 123244131805666 
 
 
 28 
 二十八 
 123244131805666 
 
 
 29 
 二十九 
 123244131805666 
 
 
 30 
 三十 
 123244131805666 
 
 
 31 
 三十一 
 123244131805666 
 
 
 32 
 三十二 
 123244131805666 
 
 
 33 
 三十三 
 123244131805666 
 
 
 34 
 三十四 
 123244131805666 
 
 
 35 
 三十五 
 123244131805666 
 
 
 36 
 三十六 
 123244131805666 
 
 
 37 
 三十七 
 123244131805666 
 
 
 38 
 三十八 
 123244131805666 
 
 
 39 
 三十九 
 123244131805666 
 
 
 40 
 四十 
 123244131805666 
 
 
 41 
 四十一 
 123244131805666 
 
 
 42 
 四十二 
 123244131805666 
 
 
 43 
 四十三 
 123244131805666 
 
 
 44 
 四十四 
 123244131805666 
 
 
 45 
 四十五 
 123244131805666 
 
 
 46 
 四十六 
 123244131805666 
 
 
 47 
 四十七 
 123244131805666 
 
 
 48 
 四十八 
 123244131805666 
 
 
 49 
 四十九 
 123244131805666 
 
 
 50 
 五十 
 123244131805666 
 
 
 51 
 五十一 
 123244131805666 
 
 
 52 
 五十二 
 123244131805666 
 
 
 53 
 五十三 
 123244131805666 
 
 
 54 
 五十四 
 123244131805666 
 
 
 55 
 五十五 
 123244131805666 
 
 
 56 
 五十六 
 123244131805666 
 
 
 57 
 五十七 
 123244131805666 
 
 
 58 
 五十八 
 123244131805666 
 
 
 59 
 五十九 
 123244131805666 
 
 
 60 
 六十 
 123244131805666 
 
 
 61 
 六十一 
 123244131805666 
 
 
 62 
 六十二 
 123244131805666 
 
 
 63 
 六十三 
 123244131805666 
 
 
 64 
 六十四 
 123244131805666 
 
 
 65 
 六十五 
 123244131805666 
 
 
 66 
 六十六 
 123244131805666 
 
 
 67 
 六十七 
 123244131805666 
 
 
 68 
 六十八 
 123244131805666 
 
 
 69 
 六十九 
 123244131805666 
 
 
 70 
 七十 
 123244131805666 
 
 
 71 
 七十一 
 123244131805666 
 
 
 72 
 七十二 
 123244131805666 
 
 
 73 
 七十三 
 123244131805666 
 
 
 74 
 七十四 
 123244131805666 
 
 
 75 
 七十五 
 123244131805666 
 
 
 76 
 七十六 
 123244131805666 
 
 
 77 
 七十七 
 123244131805666 
 
 
 78 
 七十八 
 123244131805666 
 
 
 79 
 七十九 
 123244131805666 
 
 
 80 
 八十 
 123244131805666 
 
 
 81 
 八十一 
 123244131805666 
 
 
 82 
 八十二 
 123244131805666 
 
 
 83 
 八十三 
 123244131805666 
 
 
 84 
 八十四 
 123244131805666 
 
 
 85 
 八十五 
 123244131805666 
 
 
 86 
 八十六 
 123244131805666 
 
 
 87 
 八十七 
 123244131805666 
 
 
 88 
 八十八 
 123244131805666 
 
 
 89 
 八十九 
 123244131805666 
 
 
 90 
 九十 
 123244131805666 
 
 
 91 
 九十一 
 123244131805666 
 
 
 92 
 九十二 
 123244131805666 
 
 
 93 
 九十三 
 123244131805666 
 
 
 94 
 九十四 
 123244131805666 
 
 
 95 
 九十五 
 123244131805666 
 
 
 96 
 九十六 
 123244131805666 
 
 
 97 
 九十七 
 123244131805666 
 
 
 98 
 九十八 
 123244131805666 
 
 
 99 
 九十九 
 123244131805666 
 
 
 100 
 一百 
 123244131805666 
 
 
 101 
 一百零一 
 123244131805666 
 
 
 102 
 一百零二 
 123244131805666 
 
 
 103 
 一百零三 
 123244131805666 
 
 
 104 
 一百零四 
 123244131805666 
 
 
 105 
 一百零五 
 123244131805666 
 
 
 106 
 一百零六 
 123244131805666 
 
 
 107 
 一百零七 
 123244131805666 
 
 
 108 
 一百零八 
 123244131805666 
 
 
 109 
 一百零九 
 123244131805666 
 
 
 110 
 一百一十 
 123244131805666 
 
 
 111 
 一百一十一 
 123244131805666 
 
 
 112 
 一百一十二 
 123244131805666 
 
 
 113 
 一百一十三 
 123244131805666 
 
 
 114 
 一百一十四 
 123244131805666 
 
 
 115 
 一百一十五 
 123244131805666 
 
 
 116 
 一百一十六 
 123244131805666 
 
 
 117 
 一百一十七 
 123244131805666 
 
 
 118 
 一百一十八 
 123244131805666 
 
 
 119 
 一百一十九 
 123244131805666 
 
 
 120 
 一

In [ ]:
assert ' '.join(col['chinese'][::8]) == x

In [ ]:
x = '零 百八 百十六 百二十四 百三十二 百四十 百四十八 百五十六 百六十四 百七十二 百八十 百八十八 百九十六 一百零四 一百一十二 一百二十 一百二十八 一百三十六 一百四十四 一百五十二 一百六十 一百六十八 一百七十六 一百八十四 一百九十二 二百 二百零八 二百一十六 二百二十四 二百三十二 二百四十 二百四十八 二百五十六 二百六十四 二百七十二 二百八十 二百八十八 二百九十六 三百零四 三百一十二 三百二十 三百二十八 三百三十六 三百四十四 三百五十二 三百六十 三百六十八 三百七十六 三百八十四 三百九十二 四百 四百零八 四百一十六 四百二十四 四百三十二 四百四十 四百四十八 四百五十六 四百六十四 四百七十二 四百八十 四百八十八 四百九十六 五百零四 五百一十二 五百二十 五百二十八 五百三十六 五百四十四 五百五十二 五百六十 五百六十八 五百七十六 五百八十四 五百九十二 六百 六百零八 六百一十六 六百二十四 六百三十二 六百四十 六百四十八 六百五十六 六百六十四 六百七十二 六百八十 六百八十八 六百九十六 七百零四 七百一十二 七百二十 七百二十八 七百三十六 七百四十四 七百五十二 七百六十 七百六十八 七百七十六 七百八十四 七百九十二 八百 八百零八 八百一十六 八百二十四 八百三十二 八百四十 八百四十八 八百五十六 八百六十四 八百七十二 八百八十 八百八十八 八百九十六 九百零四 九百一十二 九百二十 九百二十八 九百三十六 九百四十四 九百五十二 九百六十 九百六十八 九百七十六 九百八十四 九百九十二 一千'

In [ ]:
%%sql
-- Indication. Éliminez le 百 au-dessous de 100.
WITH variables AS (
  SELECT 
    n,
    (n MOD 1000) DIV 100 AS hundreds,
    (n MOD 100) DIV 10 AS tens,
    n MOD 10 AS ones
  FROM ints
)
SELECT n AS arabic,
    CASE n
        WHEN 0 THEN '零'
        WHEN 1000 THEN '一千'
        ELSE CONCAT(
            CONCAT(SUBSTRING('一二三四五六七八九', hundreds, 1), '百'),
            CASE
                WHEN tens = 0 AND hundreds > 0 AND ones > 0 THEN '零'
                WHEN tens = 0 THEN ''
                WHEN tens = 1 AND hundreds = 0 THEN '十'
                ELSE CONCAT(SUBSTRING('一二三四五六七八九', tens, 1), '十')
            END,
            SUBSTRING('一二三四五六七八九', ones, 1)
        )
    END AS "chinese"
     , salt_036(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM variables

1001 rows affected.

arabic 
 chinese 
 token 
 
 
 
 
 0 
 零 
 123281337243369 
 
 
 1 
 百一 
 123281337243369 
 
 
 2 
 百二 
 123281337243369 
 
 
 3 
 百三 
 123281337243369 
 
 
 4 
 百四 
 123281337243369 
 
 
 5 
 百五 
 123281337243369 
 
 
 6 
 百六 
 123281337243369 
 
 
 7 
 百七 
 123281337243369 
 
 
 8 
 百八 
 123281337243369 
 
 
 9 
 百九 
 123281337243369 
 
 
 10 
 百十 
 123281337243369 
 
 
 11 
 百十一 
 123281337243369 
 
 
 12 
 百十二 
 123281337243369 
 
 
 13 
 百十三 
 123281337243369 
 
 
 14 
 百十四 
 123281337243369 
 
 
 15 
 百十五 
 123281337243369 
 
 
 16 
 百十六 
 123281337243369 
 
 
 17 
 百十七 
 123281337243369 
 
 
 18 
 百十八 
 123281337243369 
 
 
 19 
 百十九 
 123281337243369 
 
 
 20 
 百二十 
 123281337243369 
 
 
 21 
 百二十一 
 123281337243369 
 
 
 22 
 百二十二 
 123281337243369 
 
 
 23 
 百二十三 
 123281337243369 
 
 
 24 
 百二十四 
 123281337243369 
 
 
 25 
 百二十五 
 123281337243369 
 
 
 26 
 百二十六 
 123281337243369 
 
 
 27 
 百二十七 
 123281337243369 
 
 
 28 
 百二十八 
 123281337243369 
 
 
 29 
 百二十九 
 123281337243369 
 
 
 30 
 百三十 
 123281337243369 
 
 
 31 
 百三十一 
 123281337243369 
 
 
 32 
 百三十二 
 123281337243369 
 
 
 33 
 百三十三 
 123281337243369 
 
 
 34 
 百三十四 
 123281337243369 
 
 
 35 
 百三十五 
 123281337243369 
 
 
 36 
 百三十六 
 123281337243369 
 
 
 37 
 百三十七 
 123281337243369 
 
 
 38 
 百三十八 
 123281337243369 
 
 
 39 
 百三十九 
 123281337243369 
 
 
 40 
 百四十 
 123281337243369 
 
 
 41 
 百四十一 
 123281337243369 
 
 
 42 
 百四十二 
 123281337243369 
 
 
 43 
 百四十三 
 123281337243369 
 
 
 44 
 百四十四 
 123281337243369 
 
 
 45 
 百四十五 
 123281337243369 
 
 
 46 
 百四十六 
 123281337243369 
 
 
 47 
 百四十七 
 123281337243369 
 
 
 48 
 百四十八 
 123281337243369 
 
 
 49 
 百四十九 
 123281337243369 
 
 
 50 
 百五十 
 123281337243369 
 
 
 51 
 百五十一 
 123281337243369 
 
 
 52 
 百五十二 
 123281337243369 
 
 
 53 
 百五十三 
 123281337243369 
 
 
 54 
 百五十四 
 123281337243369 
 
 
 55 
 百五十五 
 123281337243369 
 
 
 56 
 百五十六 
 123281337243369 
 
 
 57 
 百五十七 
 123281337243369 
 
 
 58 
 百五十八 
 123281337243369 
 
 
 59 
 百五十九 
 123281337243369 
 
 
 60 
 百六十 
 123281337243369 
 
 
 61 
 百六十一 
 123281337243369 
 
 
 62 
 百六十二 
 123281337243369 
 
 
 63 
 百六十三 
 123281337243369 
 
 
 64 
 百六十四 
 123281337243369 
 
 
 65 
 百六十五 
 123281337243369 
 
 
 66 
 百六十六 
 123281337243369 
 
 
 67 
 百六十七 
 123281337243369 
 
 
 68 
 百六十八 
 123281337243369 
 
 
 69 
 百六十九 
 123281337243369 
 
 
 70 
 百七十 
 123281337243369 
 
 
 71 
 百七十一 
 123281337243369 
 
 
 72 
 百七十二 
 123281337243369 
 
 
 73 
 百七十三 
 123281337243369 
 
 
 74 
 百七十四 
 123281337243369 
 
 
 75 
 百七十五 
 123281337243369 
 
 
 76 
 百七十六 
 123281337243369 
 
 
 77 
 百七十七 
 123281337243369 
 
 
 78 
 百七十八 
 123281337243369 
 
 
 79 
 百七十九 
 123281337243369 
 
 
 80 
 百八十 
 123281337243369 
 
 
 81 
 百八十一 
 123281337243369 
 
 
 82 
 百八十二 
 123281337243369 
 
 
 83 
 百八十三 
 123281337243369 
 
 
 84 
 百八十四 
 123281337243369 
 
 
 85 
 百八十五 
 123281337243369 
 
 
 86 
 百八十六 
 123281337243369 
 
 
 87 
 百八十七 
 123281337243369 
 
 
 88 
 百八十八 
 123281337243369 
 
 
 89 
 百八十九 
 123281337243369 
 
 
 90 
 百九十 
 123281337243369 
 
 
 91 
 百九十一 
 123281337243369 
 
 
 92 
 百九十二 
 123281337243369 
 
 
 93 
 百九十三 
 123281337243369 
 
 
 94 
 百九十四 
 123281337243369 
 
 
 95 
 百九十五 
 123281337243369 
 
 
 96 
 百九十六 
 123281337243369 
 
 
 97 
 百九十七 
 123281337243369 
 
 
 98 
 百九十八 
 123281337243369 
 
 
 99 
 百九十九 
 123281337243369 
 
 
 100 
 一百 
 123281337243369 
 
 
 101 
 一百零一 
 123281337243369 
 
 
 102 
 一百零二 
 123281337243369 
 
 
 103 
 一百零三 
 123281337243369 
 
 
 104 
 一百零四 
 123281337243369 
 
 
 105 
 一百零五 
 123281337243369 
 
 
 106 
 一百零六 
 123281337243369 
 
 
 107 
 一百零七 
 123281337243369 
 
 
 108 
 一百零八 
 123281337243369 
 
 
 109 
 一百零九 
 123281337243369 
 
 
 110 
 一百一十 
 123281337243369 
 
 
 111 
 一百一十一 
 123281337243369 
 
 
 112 
 一百一十二 
 123281337243369 
 
 
 113 
 一百一十三 
 123281337243369 
 
 
 114 
 一百一十四 
 123281337243369 
 
 
 115 
 一百一十五 
 123281337243369 
 
 
 116 
 一百一十六 
 123281337243369 
 
 
 117 
 一百一十七 
 12

In [ ]:
assert ' '.join(col['chinese'][::8]) == x

In [ ]:
x = '零 八 一十六 二十四 三十二 四十 四十八 五十六 六十四 七十二 八十 八十八 九十六 一百零四 一百一十二 一百二十 一百二十八 一百三十六 一百四十四 一百五十二 一百六十 一百六十八 一百七十六 一百八十四 一百九十二 二百 二百零八 二百一十六 二百二十四 二百三十二 二百四十 二百四十八 二百五十六 二百六十四 二百七十二 二百八十 二百八十八 二百九十六 三百零四 三百一十二 三百二十 三百二十八 三百三十六 三百四十四 三百五十二 三百六十 三百六十八 三百七十六 三百八十四 三百九十二 四百 四百零八 四百一十六 四百二十四 四百三十二 四百四十 四百四十八 四百五十六 四百六十四 四百七十二 四百八十 四百八十八 四百九十六 五百零四 五百一十二 五百二十 五百二十八 五百三十六 五百四十四 五百五十二 五百六十 五百六十八 五百七十六 五百八十四 五百九十二 六百 六百零八 六百一十六 六百二十四 六百三十二 六百四十 六百四十八 六百五十六 六百六十四 六百七十二 六百八十 六百八十八 六百九十六 七百零四 七百一十二 七百二十 七百二十八 七百三十六 七百四十四 七百五十二 七百六十 七百六十八 七百七十六 七百八十四 七百九十二 八百 八百零八 八百一十六 八百二十四 八百三十二 八百四十 八百四十八 八百五十六 八百六十四 八百七十二 八百八十 八百八十八 八百九十六 九百零四 九百一十二 九百二十 九百二十八 九百三十六 九百四十四 九百五十二 九百六十 九百六十八 九百七十六 九百八十四 九百九十二 一千'

In [ ]:
%%sql
-- Indication. Tenez compte de l'exception mentionnée dans l'énoncé concernant les nombres de 10 à 19.
-- Ils s'écrivent 十, 十一, 十二, etc. et non 一十, 一十一, 一十二, etc.
WITH variables AS (
  SELECT 
    n,
    (n MOD 1000) DIV 100 AS hundreds,
    (n MOD 100) DIV 10 AS tens,
    n MOD 10 AS ones
  FROM ints
)
SELECT n AS arabic,
    CASE n
        WHEN 0 THEN '零'
        WHEN 1000 THEN '一千'
        ELSE CONCAT(
            CASE
                WHEN hundreds = 0 THEN ''
                ELSE CONCAT(SUBSTRING('一二三四五六七八九', hundreds, 1), '百')
            END,
            CASE
                WHEN tens = 0 AND hundreds > 0 AND ones > 0 THEN '零'
                WHEN tens = 0 THEN ''
                ELSE CONCAT(SUBSTRING('一二三四五六七八九', tens, 1), '十')
            END,
            SUBSTRING('一二三四五六七八九', ones, 1)
        )
    END AS "chinese"
     , salt_036(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM variables

1001 rows affected.

arabic 
 chinese 
 token 
 
 
 
 
 0 
 零 
 123273422358431 
 
 
 1 
 一 
 123273422358431 
 
 
 2 
 二 
 123273422358431 
 
 
 3 
 三 
 123273422358431 
 
 
 4 
 四 
 123273422358431 
 
 
 5 
 五 
 123273422358431 
 
 
 6 
 六 
 123273422358431 
 
 
 7 
 七 
 123273422358431 
 
 
 8 
 八 
 123273422358431 
 
 
 9 
 九 
 123273422358431 
 
 
 10 
 一十 
 123273422358431 
 
 
 11 
 一十一 
 123273422358431 
 
 
 12 
 一十二 
 123273422358431 
 
 
 13 
 一十三 
 123273422358431 
 
 
 14 
 一十四 
 123273422358431 
 
 
 15 
 一十五 
 123273422358431 
 
 
 16 
 一十六 
 123273422358431 
 
 
 17 
 一十七 
 123273422358431 
 
 
 18 
 一十八 
 123273422358431 
 
 
 19 
 一十九 
 123273422358431 
 
 
 20 
 二十 
 123273422358431 
 
 
 21 
 二十一 
 123273422358431 
 
 
 22 
 二十二 
 123273422358431 
 
 
 23 
 二十三 
 123273422358431 
 
 
 24 
 二十四 
 123273422358431 
 
 
 25 
 二十五 
 123273422358431 
 
 
 26 
 二十六 
 123273422358431 
 
 
 27 
 二十七 
 123273422358431 
 
 
 28 
 二十八 
 123273422358431 
 
 
 29 
 二十九 
 123273422358431 
 
 
 30 
 三十 
 123273422358431 
 
 
 31 
 三十一 
 123273422358431 
 
 
 32 
 三十二 
 123273422358431 
 
 
 33 
 三十三 
 123273422358431 
 
 
 34 
 三十四 
 123273422358431 
 
 
 35 
 三十五 
 123273422358431 
 
 
 36 
 三十六 
 123273422358431 
 
 
 37 
 三十七 
 123273422358431 
 
 
 38 
 三十八 
 123273422358431 
 
 
 39 
 三十九 
 123273422358431 
 
 
 40 
 四十 
 123273422358431 
 
 
 41 
 四十一 
 123273422358431 
 
 
 42 
 四十二 
 123273422358431 
 
 
 43 
 四十三 
 123273422358431 
 
 
 44 
 四十四 
 123273422358431 
 
 
 45 
 四十五 
 123273422358431 
 
 
 46 
 四十六 
 123273422358431 
 
 
 47 
 四十七 
 123273422358431 
 
 
 48 
 四十八 
 123273422358431 
 
 
 49 
 四十九 
 123273422358431 
 
 
 50 
 五十 
 123273422358431 
 
 
 51 
 五十一 
 123273422358431 
 
 
 52 
 五十二 
 123273422358431 
 
 
 53 
 五十三 
 123273422358431 
 
 
 54 
 五十四 
 123273422358431 
 
 
 55 
 五十五 
 123273422358431 
 
 
 56 
 五十六 
 123273422358431 
 
 
 57 
 五十七 
 123273422358431 
 
 
 58 
 五十八 
 123273422358431 
 
 
 59 
 五十九 
 123273422358431 
 
 
 60 
 六十 
 123273422358431 
 
 
 61 
 六十一 
 123273422358431 
 
 
 62 
 六十二 
 123273422358431 
 
 
 63 
 六十三 
 123273422358431 
 
 
 64 
 六十四 
 123273422358431 
 
 
 65 
 六十五 
 123273422358431 
 
 
 66 
 六十六 
 123273422358431 
 
 
 67 
 六十七 
 123273422358431 
 
 
 68 
 六十八 
 123273422358431 
 
 
 69 
 六十九 
 123273422358431 
 
 
 70 
 七十 
 123273422358431 
 
 
 71 
 七十一 
 123273422358431 
 
 
 72 
 七十二 
 123273422358431 
 
 
 73 
 七十三 
 123273422358431 
 
 
 74 
 七十四 
 123273422358431 
 
 
 75 
 七十五 
 123273422358431 
 
 
 76 
 七十六 
 123273422358431 
 
 
 77 
 七十七 
 123273422358431 
 
 
 78 
 七十八 
 123273422358431 
 
 
 79 
 七十九 
 123273422358431 
 
 
 80 
 八十 
 123273422358431 
 
 
 81 
 八十一 
 123273422358431 
 
 
 82 
 八十二 
 123273422358431 
 
 
 83 
 八十三 
 123273422358431 
 
 
 84 
 八十四 
 123273422358431 
 
 
 85 
 八十五 
 123273422358431 
 
 
 86 
 八十六 
 123273422358431 
 
 
 87 
 八十七 
 123273422358431 
 
 
 88 
 八十八 
 123273422358431 
 
 
 89 
 八十九 
 123273422358431 
 
 
 90 
 九十 
 123273422358431 
 
 
 91 
 九十一 
 123273422358431 
 
 
 92 
 九十二 
 123273422358431 
 
 
 93 
 九十三 
 123273422358431 
 
 
 94 
 九十四 
 123273422358431 
 
 
 95 
 九十五 
 123273422358431 
 
 
 96 
 九十六 
 123273422358431 
 
 
 97 
 九十七 
 123273422358431 
 
 
 98 
 九十八 
 123273422358431 
 
 
 99 
 九十九 
 123273422358431 
 
 
 100 
 一百 
 123273422358431 
 
 
 101 
 一百零一 
 123273422358431 
 
 
 102 
 一百零二 
 123273422358431 
 
 
 103 
 一百零三 
 123273422358431 
 
 
 104 
 一百零四 
 123273422358431 
 
 
 105 
 一百零五 
 123273422358431 
 
 
 106 
 一百零六 
 123273422358431 
 
 
 107 
 一百零七 
 123273422358431 
 
 
 108 
 一百零八 
 123273422358431 
 
 
 109 
 一百零九 
 123273422358431 
 
 
 110 
 一百一十 
 123273422358431 
 
 
 111 
 一百一十一 
 123273422358431 
 
 
 112 
 一百一十二 
 123273422358431 
 
 
 113 
 一百一十三 
 123273422358431 
 
 
 114 
 一百一十四 
 123273422358431 
 
 
 115 
 一百一十五 
 123273422358431 
 
 
 116 
 一百一十六 
 123273422358431 
 
 
 117 
 一百一十七 
 123273422358431 
 
 
 118 
 一百一十八 
 123273422358431 
 
 
 119 
 一百一十九 
 123273422358431 
 


In [ ]:
assert ' '.join(col['chinese'][::8]) == x

In [ ]:
x = '零 八 十六 二十四 三十二 四十 四十八 五十六 六十四 七十二 八十 八十八 九十六 一百四 一百一十二 一百二十 一百二十八 一百三十六 一百四十四 一百五十二 一百六十 一百六十八 一百七十六 一百八十四 一百九十二 二百 二百八 二百一十六 二百二十四 二百三十二 二百四十 二百四十八 二百五十六 二百六十四 二百七十二 二百八十 二百八十八 二百九十六 三百四 三百一十二 三百二十 三百二十八 三百三十六 三百四十四 三百五十二 三百六十 三百六十八 三百七十六 三百八十四 三百九十二 四百 四百八 四百一十六 四百二十四 四百三十二 四百四十 四百四十八 四百五十六 四百六十四 四百七十二 四百八十 四百八十八 四百九十六 五百四 五百一十二 五百二十 五百二十八 五百三十六 五百四十四 五百五十二 五百六十 五百六十八 五百七十六 五百八十四 五百九十二 六百 六百八 六百一十六 六百二十四 六百三十二 六百四十 六百四十八 六百五十六 六百六十四 六百七十二 六百八十 六百八十八 六百九十六 七百四 七百一十二 七百二十 七百二十八 七百三十六 七百四十四 七百五十二 七百六十 七百六十八 七百七十六 七百八十四 七百九十二 八百 八百八 八百一十六 八百二十四 八百三十二 八百四十 八百四十八 八百五十六 八百六十四 八百七十二 八百八十 八百八十八 八百九十六 九百四 九百一十二 九百二十 九百二十八 九百三十六 九百四十四 九百五十二 九百六十 九百六十八 九百七十六 九百八十四 九百九十二 一千'

In [ ]:
%%sql
-- Indication. N'oubliez pas les 零 (zéros) intercalaires.
-- Par exemple, 101 s'écrit 一百零一 et non pas 一百一.
-- (Techniquement, ces zéros intercalaires sont superflus, mais leur usage s'est imposé en chinois moderne.)
WITH variables AS (
  SELECT 
    n,
    (n MOD 1000) DIV 100 AS hundreds,
    (n MOD 100) DIV 10 AS tens,
    n MOD 10 AS ones
  FROM ints
)
SELECT n AS arabic,
    CASE n
        WHEN 0 THEN '零'
        WHEN 1000 THEN '一千'
        ELSE CONCAT(
            CASE
                WHEN hundreds = 0 THEN ''
                ELSE CONCAT(SUBSTRING('一二三四五六七八九', hundreds, 1), '百')
            END,
            CASE
                WHEN tens = 0 THEN ''
                WHEN tens = 1 AND hundreds = 0 THEN '十'
                ELSE CONCAT(SUBSTRING('一二三四五六七八九', tens, 1), '十')
            END,
            SUBSTRING('一二三四五六七八九', ones, 1)
        )
    END AS "chinese"
     , salt_036(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM variables

1001 rows affected.

arabic 
 chinese 
 token 
 
 
 
 
 0 
 零 
 123664506337580 
 
 
 1 
 一 
 123664506337580 
 
 
 2 
 二 
 123664506337580 
 
 
 3 
 三 
 123664506337580 
 
 
 4 
 四 
 123664506337580 
 
 
 5 
 五 
 123664506337580 
 
 
 6 
 六 
 123664506337580 
 
 
 7 
 七 
 123664506337580 
 
 
 8 
 八 
 123664506337580 
 
 
 9 
 九 
 123664506337580 
 
 
 10 
 十 
 123664506337580 
 
 
 11 
 十一 
 123664506337580 
 
 
 12 
 十二 
 123664506337580 
 
 
 13 
 十三 
 123664506337580 
 
 
 14 
 十四 
 123664506337580 
 
 
 15 
 十五 
 123664506337580 
 
 
 16 
 十六 
 123664506337580 
 
 
 17 
 十七 
 123664506337580 
 
 
 18 
 十八 
 123664506337580 
 
 
 19 
 十九 
 123664506337580 
 
 
 20 
 二十 
 123664506337580 
 
 
 21 
 二十一 
 123664506337580 
 
 
 22 
 二十二 
 123664506337580 
 
 
 23 
 二十三 
 123664506337580 
 
 
 24 
 二十四 
 123664506337580 
 
 
 25 
 二十五 
 123664506337580 
 
 
 26 
 二十六 
 123664506337580 
 
 
 27 
 二十七 
 123664506337580 
 
 
 28 
 二十八 
 123664506337580 
 
 
 29 
 二十九 
 123664506337580 
 
 
 30 
 三十 
 123664506337580 
 
 
 31 
 三十一 
 123664506337580 
 
 
 32 
 三十二 
 123664506337580 
 
 
 33 
 三十三 
 123664506337580 
 
 
 34 
 三十四 
 123664506337580 
 
 
 35 
 三十五 
 123664506337580 
 
 
 36 
 三十六 
 123664506337580 
 
 
 37 
 三十七 
 123664506337580 
 
 
 38 
 三十八 
 123664506337580 
 
 
 39 
 三十九 
 123664506337580 
 
 
 40 
 四十 
 123664506337580 
 
 
 41 
 四十一 
 123664506337580 
 
 
 42 
 四十二 
 123664506337580 
 
 
 43 
 四十三 
 123664506337580 
 
 
 44 
 四十四 
 123664506337580 
 
 
 45 
 四十五 
 123664506337580 
 
 
 46 
 四十六 
 123664506337580 
 
 
 47 
 四十七 
 123664506337580 
 
 
 48 
 四十八 
 123664506337580 
 
 
 49 
 四十九 
 123664506337580 
 
 
 50 
 五十 
 123664506337580 
 
 
 51 
 五十一 
 123664506337580 
 
 
 52 
 五十二 
 123664506337580 
 
 
 53 
 五十三 
 123664506337580 
 
 
 54 
 五十四 
 123664506337580 
 
 
 55 
 五十五 
 123664506337580 
 
 
 56 
 五十六 
 123664506337580 
 
 
 57 
 五十七 
 123664506337580 
 
 
 58 
 五十八 
 123664506337580 
 
 
 59 
 五十九 
 123664506337580 
 
 
 60 
 六十 
 123664506337580 
 
 
 61 
 六十一 
 123664506337580 
 
 
 62 
 六十二 
 123664506337580 
 
 
 63 
 六十三 
 123664506337580 
 
 
 64 
 六十四 
 123664506337580 
 
 
 65 
 六十五 
 123664506337580 
 
 
 66 
 六十六 
 123664506337580 
 
 
 67 
 六十七 
 123664506337580 
 
 
 68 
 六十八 
 123664506337580 
 
 
 69 
 六十九 
 123664506337580 
 
 
 70 
 七十 
 123664506337580 
 
 
 71 
 七十一 
 123664506337580 
 
 
 72 
 七十二 
 123664506337580 
 
 
 73 
 七十三 
 123664506337580 
 
 
 74 
 七十四 
 123664506337580 
 
 
 75 
 七十五 
 123664506337580 
 
 
 76 
 七十六 
 123664506337580 
 
 
 77 
 七十七 
 123664506337580 
 
 
 78 
 七十八 
 123664506337580 
 
 
 79 
 七十九 
 123664506337580 
 
 
 80 
 八十 
 123664506337580 
 
 
 81 
 八十一 
 123664506337580 
 
 
 82 
 八十二 
 123664506337580 
 
 
 83 
 八十三 
 123664506337580 
 
 
 84 
 八十四 
 123664506337580 
 
 
 85 
 八十五 
 123664506337580 
 
 
 86 
 八十六 
 123664506337580 
 
 
 87 
 八十七 
 123664506337580 
 
 
 88 
 八十八 
 123664506337580 
 
 
 89 
 八十九 
 123664506337580 
 
 
 90 
 九十 
 123664506337580 
 
 
 91 
 九十一 
 123664506337580 
 
 
 92 
 九十二 
 123664506337580 
 
 
 93 
 九十三 
 123664506337580 
 
 
 94 
 九十四 
 123664506337580 
 
 
 95 
 九十五 
 123664506337580 
 
 
 96 
 九十六 
 123664506337580 
 
 
 97 
 九十七 
 123664506337580 
 
 
 98 
 九十八 
 123664506337580 
 
 
 99 
 九十九 
 123664506337580 
 
 
 100 
 一百 
 123664506337580 
 
 
 101 
 一百一 
 123664506337580 
 
 
 102 
 一百二 
 123664506337580 
 
 
 103 
 一百三 
 123664506337580 
 
 
 104 
 一百四 
 123664506337580 
 
 
 105 
 一百五 
 123664506337580 
 
 
 106 
 一百六 
 123664506337580 
 
 
 107 
 一百七 
 123664506337580 
 
 
 108 
 一百八 
 123664506337580 
 
 
 109 
 一百九 
 123664506337580 
 
 
 110 
 一百一十 
 123664506337580 
 
 
 111 
 一百一十一 
 123664506337580 
 
 
 112 
 一百一十二 
 123664506337580 
 
 
 113 
 一百一十三 
 123664506337580 
 
 
 114 
 一百一十四 
 123664506337580 
 
 
 115 
 一百一十五 
 123664506337580 
 
 
 116 
 一百一十六 
 123664506337580 
 
 
 117 
 一百一十七 
 123664506337580 
 
 
 118 
 一百一十八 
 123664506337580 
 
 
 119 
 一百一十九 
 123664506337580 
 
 
 120 
 一百二十 
 123

In [ ]:
assert ' '.join(col['chinese'][::8]) == x

In [ ]:
' '.join(col['chinese'][::8])

'零 八 十六 二十四 三十二 四十 四十八 五十六 六十四 七十二 八十 八十八 九十六 一百四 一百一十二 一百二十 一百二十八 一百三十六 一百四十四 一百五十二 一百六十 一百六十八 一百七十六 一百八十四 一百九十二 二百 二百八 二百一十六 二百二十四 二百三十二 二百四十 二百四十八 二百五十六 二百六十四 二百七十二 二百八十 二百八十八 二百九十六 三百四 三百一十二 三百二十 三百二十八 三百三十六 三百四十四 三百五十二 三百六十 三百六十八 三百七十六 三百八十四 三百九十二 四百 四百八 四百一十六 四百二十四 四百三十二 四百四十 四百四十八 四百五十六 四百六十四 四百七十二 四百八十 四百八十八 四百九十六 五百四 五百一十二 五百二十 五百二十八 五百三十六 五百四十四 五百五十二 五百六十 五百六十八 五百七十六 五百八十四 五百九十二 六百 六百八 六百一十六 六百二十四 六百三十二 六百四十 六百四十八 六百五十六 六百六十四 六百七十二 六百八十 六百八十八 六百九十六 七百四 七百一十二 七百二十 七百二十八 七百三十六 七百四十四 七百五十二 七百六十 七百六十八 七百七十六 七百八十四 七百九十二 八百 八百八 八百一十六 八百二十四 八百三十二 八百四十 八百四十八 八百五十六 八百六十四 八百七十二 八百八十 八百八十八 八百九十六 九百四 九百一十二 九百二十 九百二十八 九百三十六 九百四十四 九百五十二 九百六十 九百六十八 九百七十六 九百八十四 九百九十二 一千'

### Numération romaine

**Atelier [047].** On se donne une table associant une sélection d'entiers à leur représentation en chiffres romains, dans cet ordre :

| Position | 1  | 2  | 3 | 4  | 5 | 6 | 7 | 8  | 9 | 10 | 11 | 12 | 13 |
|----------|----|----|---|----|---|---|---|----|---|----|----|----|----|
| **Arabe** |1000|900|500|400|100|90|50|40|10|9|5|4|1|
| **Romain** | M  | CM | D | CD | C |XC| L | XL | X | IX | V | IV | I |

Pour convertir un entier $n$ quelconque, on applique l'algorithme suivant (code Python [ici](https://stackoverflow.com/a/47713392/173003)) :

1. Un accumulateur est initialisé à la chaîne vide.
2. Pour chaque ligne $(a, r)$ de la table d'association :
    - la division entière de $n$ par $a$ donne un quotient $q$ et un reste $m$ ;
    - $n$ devient $q$ ;
    - l'accumulateur est suffixé $m$ fois par $r$.
3. l'accumulateur contient la représentation désirée.

<figure>
  <img src="https://raw.githubusercontent.com/laowantong/sqlab_ints/refs/heads/main/assets/loba-capitolina.jpg"/>
  <figcaption><p>La Louve capitoline du 18 Gran Vía, à Madrid, surplombe le célèbre emblème du pouvoir législatif romain, <i>Senatusque Quiritium Lex</i> (la loi du Sénat et du peuple).<p></figcaption>
</figure>

_Défi._ Donnez, pour chaque entier de 1 à 1000, sa représentation en chiffres romains.

_Aide._ La numération romaine est plus complexe que la numération chinoise. Ici, vous aurez besoin de deux CTE :
1. La première construit la table d'association. Utilisez `VALUES`. La colonne `position` sert à rester en complexité linéaire lors de la conversion.
2. La seconde est récursive, et crée une table avec un certain nombre de colonnes (à déterminer) et dont certaines lignes (à déterminer) contiendront les résultats. Initialisez l'accumulateur à `CAST('' AS CHAR(20))` pour réserver l'espace nécessaire à sa croissance, et utilisez `CONCAT` et `REPEAT` pour le mettre à jour.

In [ ]:
x = 'XI.LIV.XCVII.CXL.CLXXXIII.CCXXVI.CCLXIX.CCCXII.CCCLV.CCCXCVIII.CDXLI.CDLXXXIV.DXXVII.DLXX.DCXIII.DCLVI.DCXCIX.DCCXLII.DCCLXXXV.DCCCXXVIII.DCCCLXXI.CMXIV.CMLVII.M' # la concaténation des nombres romains en partant du 11e et par pas de 43
# Javascript: (result.slice3(10, undefined, 43).col('roman').join('.'))  || '7_531_148'

In [ ]:
%%sql
WITH RECURSIVE

map (pos, arabic, roman) AS (
    SELECT 1, 1000, 'M'
    UNION ALL SELECT 2, 900, 'CM'
    UNION ALL SELECT 3, 500, 'D'
    UNION ALL SELECT 4, 400, 'CD'
    UNION ALL SELECT 5, 100, 'C'
    UNION ALL SELECT 6, 90, 'XC'
    UNION ALL SELECT 7, 50, 'L'
    UNION ALL SELECT 8, 40, 'XL'
    UNION ALL SELECT 9, 10, 'X'
    UNION ALL SELECT 10, 9, 'IX'
    UNION ALL SELECT 11, 5, 'V'
    UNION ALL SELECT 12, 4, 'IV'
    UNION ALL SELECT 13, 1, 'I'
),

conversion (n, remaining, acc, pos) AS (
    SELECT n, n, CAST('' AS CHAR(20)), 1
    FROM ints
    WHERE n > 0
    
    UNION ALL
    
    SELECT 
        n,
        remaining MOD arabic,
        CONCAT(acc, REPEAT(roman, remaining DIV arabic)),
        pos + 1
    FROM conversion
    JOIN map USING (pos)
)

SELECT
    n,
    acc as roman,
    salt_047(sum(string_hash('{{x}}')) OVER ()) AS token
FROM conversion
WHERE pos = 14

1000 rows affected.

n 
 roman 
 token 
 
 
 
 
 1 
 I 
 393035298143192 
 
 
 2 
 II 
 393035298143192 
 
 
 3 
 III 
 393035298143192 
 
 
 4 
 IV 
 393035298143192 
 
 
 5 
 V 
 393035298143192 
 
 
 6 
 VI 
 393035298143192 
 
 
 7 
 VII 
 393035298143192 
 
 
 8 
 VIII 
 393035298143192 
 
 
 9 
 IX 
 393035298143192 
 
 
 10 
 X 
 393035298143192 
 
 
 11 
 XI 
 393035298143192 
 
 
 12 
 XII 
 393035298143192 
 
 
 13 
 XIII 
 393035298143192 
 
 
 14 
 XIV 
 393035298143192 
 
 
 15 
 XV 
 393035298143192 
 
 
 16 
 XVI 
 393035298143192 
 
 
 17 
 XVII 
 393035298143192 
 
 
 18 
 XVIII 
 393035298143192 
 
 
 19 
 XIX 
 393035298143192 
 
 
 20 
 XX 
 393035298143192 
 
 
 21 
 XXI 
 393035298143192 
 
 
 22 
 XXII 
 393035298143192 
 
 
 23 
 XXIII 
 393035298143192 
 
 
 24 
 XXIV 
 393035298143192 
 
 
 25 
 XXV 
 393035298143192 
 
 
 26 
 XXVI 
 393035298143192 
 
 
 27 
 XXVII 
 393035298143192 
 
 
 28 
 XXVIII 
 393035298143192 
 
 
 29 
 XXIX 
 393035298143192 
 
 
 30 
 XXX 
 393035298143192 
 
 
 31 
 XXXI 
 393035298143192 
 
 
 32 
 XXXII 
 393035298143192 
 
 
 33 
 XXXIII 
 393035298143192 
 
 
 34 
 XXXIV 
 393035298143192 
 
 
 35 
 XXXV 
 393035298143192 
 
 
 36 
 XXXVI 
 393035298143192 
 
 
 37 
 XXXVII 
 393035298143192 
 
 
 38 
 XXXVIII 
 393035298143192 
 
 
 39 
 XXXIX 
 393035298143192 
 
 
 40 
 XL 
 393035298143192 
 
 
 41 
 XLI 
 393035298143192 
 
 
 42 
 XLII 
 393035298143192 
 
 
 43 
 XLIII 
 393035298143192 
 
 
 44 
 XLIV 
 393035298143192 
 
 
 45 
 XLV 
 393035298143192 
 
 
 46 
 XLVI 
 393035298143192 
 
 
 47 
 XLVII 
 393035298143192 
 
 
 48 
 XLVIII 
 393035298143192 
 
 
 49 
 XLIX 
 393035298143192 
 
 
 50 
 L 
 393035298143192 
 
 
 51 
 LI 
 393035298143192 
 
 
 52 
 LII 
 393035298143192 
 
 
 53 
 LIII 
 393035298143192 
 
 
 54 
 LIV 
 393035298143192 
 
 
 55 
 LV 
 393035298143192 
 
 
 56 
 LVI 
 393035298143192 
 
 
 57 
 LVII 
 393035298143192 
 
 
 58 
 LVIII 
 393035298143192 
 
 
 59 
 LIX 
 393035298143192 
 
 
 60 
 LX 
 393035298143192 
 
 
 61 
 LXI 
 393035298143192 
 
 
 62 
 LXII 
 393035298143192 
 
 
 63 
 LXIII 
 393035298143192 
 
 
 64 
 LXIV 
 393035298143192 
 
 
 65 
 LXV 
 393035298143192 
 
 
 66 
 LXVI 
 393035298143192 
 
 
 67 
 LXVII 
 393035298143192 
 
 
 68 
 LXVIII 
 393035298143192 
 
 
 69 
 LXIX 
 393035298143192 
 
 
 70 
 LXX 
 393035298143192 
 
 
 71 
 LXXI 
 393035298143192 
 
 
 72 
 LXXII 
 393035298143192 
 
 
 73 
 LXXIII 
 393035298143192 
 
 
 74 
 LXXIV 
 393035298143192 
 
 
 75 
 LXXV 
 393035298143192 
 
 
 76 
 LXXVI 
 393035298143192 
 
 
 77 
 LXXVII 
 393035298143192 
 
 
 78 
 LXXVIII 
 393035298143192 
 
 
 79 
 LXXIX 
 393035298143192 
 
 
 80 
 LXXX 
 393035298143192 
 
 
 81 
 LXXXI 
 393035298143192 
 
 
 82 
 LXXXII 
 393035298143192 
 
 
 83 
 LXXXIII 
 393035298143192 
 
 
 84 
 LXXXIV 
 393035298143192 
 
 
 85 
 LXXXV 
 393035298143192 
 
 
 86 
 LXXXVI 
 393035298143192 
 
 
 87 
 LXXXVII 
 393035298143192 
 
 
 88 
 LXXXVIII 
 393035298143192 
 
 
 89 
 LXXXIX 
 393035298143192 
 
 
 90 
 XC 
 393035298143192 
 
 
 91 
 XCI 
 393035298143192 
 
 
 92 
 XCII 
 393035298143192 
 
 
 93 
 XCIII 
 393035298143192 
 
 
 94 
 XCIV 
 393035298143192 
 
 
 95 
 XCV 
 393035298143192 
 
 
 96 
 XCVI 
 393035298143192 
 
 
 97 
 XCVII 
 393035298143192 
 
 
 98 
 XCVIII 
 393035298143192 
 
 
 99 
 XCIX 
 393035298143192 
 
 
 100 
 C 
 393035298143192 
 
 
 101 
 CI 
 393035298143192 
 
 
 102 
 CII 
 393035298143192 
 
 
 103 
 CIII 
 393035298143192 
 
 
 104 
 CIV 
 393035298143192 
 
 
 105 
 CV 
 393035298143192 
 
 
 106 
 CVI 
 393035298143192 
 
 
 107 
 CVII 
 393035298143192 
 
 
 108 
 CVIII 
 393035298143192 
 
 
 109 
 CIX 
 393035298143192 
 
 
 110 
 CX 
 393035298143192 
 
 
 111 
 CXI 
 393035298143192 
 
 
 112 
 CXII 
 393035298143192 
 
 
 113 
 CXIII 
 393035298143192 
 
 
 114 
 CXIV 
 393035298143192 
 
 
 115 
 CXV 
 393035298143192 
 
 
 116 
 CXVI 
 393035298143192 
 
 
 117 
 CXVII 
 393035298143192

In [ ]:
assert '.'.join(col['roman'][10::43]) == x

In [ ]:
%%sql
-- Variante. Syntaxe plus moderne, mais moins portable.
WITH RECURSIVE

map (pos, arabic, roman) AS (
    VALUES 
    ROW( 1, 1000, 'M'),
    ROW( 2,  900, 'CM'),
    ROW( 3,  500, 'D'),
    ROW( 4,  400, 'CD'),
    ROW( 5,  100, 'C'),
    ROW( 6,   90, 'XC'),
    ROW( 7,   50, 'L'),
    ROW( 8,   40, 'XL'),
    ROW( 9,   10, 'X'),
    ROW(10,    9, 'IX'),
    ROW(11,    5, 'V'),
    ROW(12,    4, 'IV'),
    ROW(13,    1, 'I')
),

conversion (n, remaining, acc, pos) AS (
    SELECT n, n, CAST('' AS CHAR(20)), 1
    FROM ints
    WHERE n > 0
    
    UNION ALL
    
    SELECT 
        n,
        remaining MOD arabic,
        CONCAT(acc, REPEAT(roman, remaining DIV arabic)),
        pos + 1
    FROM conversion
    JOIN map USING (pos)
)

SELECT
    n,
    acc as roman,
    salt_047(sum(string_hash('{{x}}')) OVER ()) AS token
FROM conversion
WHERE pos = 14

1000 rows affected.

n 
 roman 
 token 
 
 
 
 
 1 
 I 
 393035298143192 
 
 
 2 
 II 
 393035298143192 
 
 
 3 
 III 
 393035298143192 
 
 
 4 
 IV 
 393035298143192 
 
 
 5 
 V 
 393035298143192 
 
 
 6 
 VI 
 393035298143192 
 
 
 7 
 VII 
 393035298143192 
 
 
 8 
 VIII 
 393035298143192 
 
 
 9 
 IX 
 393035298143192 
 
 
 10 
 X 
 393035298143192 
 
 
 11 
 XI 
 393035298143192 
 
 
 12 
 XII 
 393035298143192 
 
 
 13 
 XIII 
 393035298143192 
 
 
 14 
 XIV 
 393035298143192 
 
 
 15 
 XV 
 393035298143192 
 
 
 16 
 XVI 
 393035298143192 
 
 
 17 
 XVII 
 393035298143192 
 
 
 18 
 XVIII 
 393035298143192 
 
 
 19 
 XIX 
 393035298143192 
 
 
 20 
 XX 
 393035298143192 
 
 
 21 
 XXI 
 393035298143192 
 
 
 22 
 XXII 
 393035298143192 
 
 
 23 
 XXIII 
 393035298143192 
 
 
 24 
 XXIV 
 393035298143192 
 
 
 25 
 XXV 
 393035298143192 
 
 
 26 
 XXVI 
 393035298143192 
 
 
 27 
 XXVII 
 393035298143192 
 
 
 28 
 XXVIII 
 393035298143192 
 
 
 29 
 XXIX 
 393035298143192 
 
 
 30 
 XXX 
 393035298143192 
 
 
 31 
 XXXI 
 393035298143192 
 
 
 32 
 XXXII 
 393035298143192 
 
 
 33 
 XXXIII 
 393035298143192 
 
 
 34 
 XXXIV 
 393035298143192 
 
 
 35 
 XXXV 
 393035298143192 
 
 
 36 
 XXXVI 
 393035298143192 
 
 
 37 
 XXXVII 
 393035298143192 
 
 
 38 
 XXXVIII 
 393035298143192 
 
 
 39 
 XXXIX 
 393035298143192 
 
 
 40 
 XL 
 393035298143192 
 
 
 41 
 XLI 
 393035298143192 
 
 
 42 
 XLII 
 393035298143192 
 
 
 43 
 XLIII 
 393035298143192 
 
 
 44 
 XLIV 
 393035298143192 
 
 
 45 
 XLV 
 393035298143192 
 
 
 46 
 XLVI 
 393035298143192 
 
 
 47 
 XLVII 
 393035298143192 
 
 
 48 
 XLVIII 
 393035298143192 
 
 
 49 
 XLIX 
 393035298143192 
 
 
 50 
 L 
 393035298143192 
 
 
 51 
 LI 
 393035298143192 
 
 
 52 
 LII 
 393035298143192 
 
 
 53 
 LIII 
 393035298143192 
 
 
 54 
 LIV 
 393035298143192 
 
 
 55 
 LV 
 393035298143192 
 
 
 56 
 LVI 
 393035298143192 
 
 
 57 
 LVII 
 393035298143192 
 
 
 58 
 LVIII 
 393035298143192 
 
 
 59 
 LIX 
 393035298143192 
 
 
 60 
 LX 
 393035298143192 
 
 
 61 
 LXI 
 393035298143192 
 
 
 62 
 LXII 
 393035298143192 
 
 
 63 
 LXIII 
 393035298143192 
 
 
 64 
 LXIV 
 393035298143192 
 
 
 65 
 LXV 
 393035298143192 
 
 
 66 
 LXVI 
 393035298143192 
 
 
 67 
 LXVII 
 393035298143192 
 
 
 68 
 LXVIII 
 393035298143192 
 
 
 69 
 LXIX 
 393035298143192 
 
 
 70 
 LXX 
 393035298143192 
 
 
 71 
 LXXI 
 393035298143192 
 
 
 72 
 LXXII 
 393035298143192 
 
 
 73 
 LXXIII 
 393035298143192 
 
 
 74 
 LXXIV 
 393035298143192 
 
 
 75 
 LXXV 
 393035298143192 
 
 
 76 
 LXXVI 
 393035298143192 
 
 
 77 
 LXXVII 
 393035298143192 
 
 
 78 
 LXXVIII 
 393035298143192 
 
 
 79 
 LXXIX 
 393035298143192 
 
 
 80 
 LXXX 
 393035298143192 
 
 
 81 
 LXXXI 
 393035298143192 
 
 
 82 
 LXXXII 
 393035298143192 
 
 
 83 
 LXXXIII 
 393035298143192 
 
 
 84 
 LXXXIV 
 393035298143192 
 
 
 85 
 LXXXV 
 393035298143192 
 
 
 86 
 LXXXVI 
 393035298143192 
 
 
 87 
 LXXXVII 
 393035298143192 
 
 
 88 
 LXXXVIII 
 393035298143192 
 
 
 89 
 LXXXIX 
 393035298143192 
 
 
 90 
 XC 
 393035298143192 
 
 
 91 
 XCI 
 393035298143192 
 
 
 92 
 XCII 
 393035298143192 
 
 
 93 
 XCIII 
 393035298143192 
 
 
 94 
 XCIV 
 393035298143192 
 
 
 95 
 XCV 
 393035298143192 
 
 
 96 
 XCVI 
 393035298143192 
 
 
 97 
 XCVII 
 393035298143192 
 
 
 98 
 XCVIII 
 393035298143192 
 
 
 99 
 XCIX 
 393035298143192 
 
 
 100 
 C 
 393035298143192 
 
 
 101 
 CI 
 393035298143192 
 
 
 102 
 CII 
 393035298143192 
 
 
 103 
 CIII 
 393035298143192 
 
 
 104 
 CIV 
 393035298143192 
 
 
 105 
 CV 
 393035298143192 
 
 
 106 
 CVI 
 393035298143192 
 
 
 107 
 CVII 
 393035298143192 
 
 
 108 
 CVIII 
 393035298143192 
 
 
 109 
 CIX 
 393035298143192 
 
 
 110 
 CX 
 393035298143192 
 
 
 111 
 CXI 
 393035298143192 
 
 
 112 
 CXII 
 393035298143192 
 
 
 113 
 CXIII 
 393035298143192 
 
 
 114 
 CXIV 
 393035298143192 
 
 
 115 
 CXV 
 393035298143192 
 
 
 116 
 CXVI 
 393035298143192 
 
 
 117 
 CXVII 
 393035298143192

### Le convoyeur d'entiers

**Atelier [020].** Un tapis roulant range une suite d'entiers dans des conteneurs de capacité fixe $K$.

<figure>
  <img src="https://raw.githubusercontent.com/laowantong/sqlab_ints/refs/heads/main/assets/int-bins.svg"/>
  <figcaption>Rangement des entiers de 1 à 10 (pris dans cet ordre) dans quatre conteneurs.</figcaption>
</figure>

L'ordre est imposé, et la somme des entiers placés dans un conteneur ne peut excéder $K$. Voici un exemple du résultat attendu avec $K=20$ pour les entiers de 1 à 10 :


| bin | mini | maxi | total |
|----------:|-----:|-----:|------:|
| 1 | 1 | 5 | 15 |
| 2 | 6 | 7 | 13 |
| 3 | 8 | 9 | 17 |
| 4 | 10 | 10 | 10 |

_Défi._ Prenez les entiers de 1 à 1000 par ordre croissant et répartissez-les dans des conteneurs de capacité 2000. N'affichez pas les contenus _in extenso_, mais donnez juste leurs bornes `mini` et `maxi` sur deux colonnes comme ci-dessus.

_Aide._ Utilisez une CTE récursive. Ici, à nouveau, vous n'avez pas besoin de la table `ints`.

_NB._ Du fait de la contrainte d'ordonnancement, ceci n'est **pas** le [problème du Bin Packing](https://fr.wikipedia.org/wiki/Problème_de_bin_packing) (dont une solution optimale serait : [1, 9, 10], [2, 3, 7, 8] et [1, 2, 4, 5, 6]).

In [ ]:
x = "194537195246500500" # la concaténation des sommes des colonnes `mini`, `maxi` et `total`
# Javascript: (['mini', 'maxi', 'total'].map(name => result.col(name).sum()).join('')) || '7_531_148'

In [ ]:
%%sql
WITH RECURSIVE cte (bin, running_sum, i) AS (
  SELECT 1, 1, 1
  UNION ALL
  SELECT
    CASE WHEN running_sum + i < 2000 THEN bin ELSE bin + 1 END,
    CASE WHEN running_sum + i < 2000 THEN running_sum + i+1 ELSE i+1 END,
    i+1
  FROM cte
  WHERE i < 1000
)
SELECT
    bin,
    min(i) as mini,
    max(i) as maxi,
    max(running_sum) as total,
    salt_020(bit_xor(string_hash('{{x}}')) OVER ()) AS token
FROM cte
GROUP BY 1

291 rows affected.

bin 
 mini 
 maxi 
 total 
 token 
 
 
 
 
 1 
 1 
 62 
 1953 
 24528728837243 
 
 
 2 
 63 
 88 
 1963 
 24528728837243 
 
 
 3 
 89 
 108 
 1970 
 24528728837243 
 
 
 4 
 109 
 125 
 1989 
 24528728837243 
 
 
 5 
 126 
 140 
 1995 
 24528728837243 
 
 
 6 
 141 
 153 
 1911 
 24528728837243 
 
 
 7 
 154 
 165 
 1914 
 24528728837243 
 
 
 8 
 166 
 176 
 1881 
 24528728837243 
 
 
 9 
 177 
 186 
 1815 
 24528728837243 
 
 
 10 
 187 
 196 
 1915 
 24528728837243 
 
 
 11 
 197 
 205 
 1809 
 24528728837243 
 
 
 12 
 206 
 214 
 1890 
 24528728837243 
 
 
 13 
 215 
 223 
 1971 
 24528728837243 
 
 
 14 
 224 
 231 
 1820 
 24528728837243 
 
 
 15 
 232 
 239 
 1884 
 24528728837243 
 
 
 16 
 240 
 247 
 1948 
 24528728837243 
 
 
 17 
 248 
 254 
 1757 
 24528728837243 
 
 
 18 
 255 
 261 
 1806 
 24528728837243 
 
 
 19 
 262 
 268 
 1855 
 24528728837243 
 
 
 20 
 269 
 275 
 1904 
 24528728837243 
 
 
 21 
 276 
 282 
 1953 
 24528728837243 
 
 
 22 
 283 
 288 
 1713 
 24528728837243 
 
 
 23 
 289 
 294 
 1749 
 24528728837243 
 
 
 24 
 295 
 300 
 1785 
 24528728837243 
 
 
 25 
 301 
 306 
 1821 
 24528728837243 
 
 
 26 
 307 
 312 
 1857 
 24528728837243 
 
 
 27 
 313 
 318 
 1893 
 24528728837243 
 
 
 28 
 319 
 324 
 1929 
 24528728837243 
 
 
 29 
 325 
 330 
 1965 
 24528728837243 
 
 
 30 
 331 
 335 
 1665 
 24528728837243 
 
 
 31 
 336 
 340 
 1690 
 24528728837243 
 
 
 32 
 341 
 345 
 1715 
 24528728837243 
 
 
 33 
 346 
 350 
 1740 
 24528728837243 
 
 
 34 
 351 
 355 
 1765 
 24528728837243 
 
 
 35 
 356 
 360 
 1790 
 24528728837243 
 
 
 36 
 361 
 365 
 1815 
 24528728837243 
 
 
 37 
 366 
 370 
 1840 
 24528728837243 
 
 
 38 
 371 
 375 
 1865 
 24528728837243 
 
 
 39 
 376 
 380 
 1890 
 24528728837243 
 
 
 40 
 381 
 385 
 1915 
 24528728837243 
 
 
 41 
 386 
 390 
 1940 
 24528728837243 
 
 
 42 
 391 
 395 
 1965 
 24528728837243 
 
 
 43 
 396 
 400 
 1990 
 24528728837243 
 
 
 44 
 401 
 404 
 1610 
 24528728837243 
 
 
 45 
 405 
 408 
 1626 
 24528728837243 
 
 
 46 
 409 
 412 
 1642 
 24528728837243 
 
 
 47 
 413 
 416 
 1658 
 24528728837243 
 
 
 48 
 417 
 420 
 1674 
 24528728837243 
 
 
 49 
 421 
 424 
 1690 
 24528728837243 
 
 
 50 
 425 
 428 
 1706 
 24528728837243 
 
 
 51 
 429 
 432 
 1722 
 24528728837243 
 
 
 52 
 433 
 436 
 1738 
 24528728837243 
 
 
 53 
 437 
 440 
 1754 
 24528728837243 
 
 
 54 
 441 
 444 
 1770 
 24528728837243 
 
 
 55 
 445 
 448 
 1786 
 24528728837243 
 
 
 56 
 449 
 452 
 1802 
 24528728837243 
 
 
 57 
 453 
 456 
 1818 
 24528728837243 
 
 
 58 
 457 
 460 
 1834 
 24528728837243 
 
 
 59 
 461 
 464 
 1850 
 24528728837243 
 
 
 60 
 465 
 468 
 1866 
 24528728837243 
 
 
 61 
 469 
 472 
 1882 
 24528728837243 
 
 
 62 
 473 
 476 
 1898 
 24528728837243 
 
 
 63 
 477 
 480 
 1914 
 24528728837243 
 
 
 64 
 481 
 484 
 1930 
 24528728837243 
 
 
 65 
 485 
 488 
 1946 
 24528728837243 
 
 
 66 
 489 
 492 
 1962 
 24528728837243 
 
 
 67 
 493 
 496 
 1978 
 24528728837243 
 
 
 68 
 497 
 500 
 1994 
 24528728837243 
 
 
 69 
 501 
 503 
 1506 
 24528728837243 
 
 
 70 
 504 
 506 
 1515 
 24528728837243 
 
 
 71 
 507 
 509 
 1524 
 24528728837243 
 
 
 72 
 510 
 512 
 1533 
 24528728837243 
 
 
 73 
 513 
 515 
 1542 
 24528728837243 
 
 
 74 
 516 
 518 
 1551 
 24528728837243 
 
 
 75 
 519 
 521 
 1560 
 24528728837243 
 
 
 76 
 522 
 524 
 1569 
 24528728837243 
 
 
 77 
 525 
 527 
 1578 
 24528728837243 
 
 
 78 
 528 
 530 
 1587 
 24528728837243 
 
 
 79 
 531 
 533 
 1596 
 24528728837243 
 
 
 80 
 534 
 536 
 1605 
 24528728837243 
 
 
 81 
 537 
 539 
 1614 
 24528728837243 
 
 
 82 
 540 
 542 
 1623 
 24528728837243 
 
 
 83 
 543 
 545 
 1632 
 24528728837243 
 
 
 84 
 546 
 548 
 1641 
 24528728837243 
 
 
 85 
 549 
 551 
 1650 
 24528728837243 
 
 
 86 
 552 
 554 
 1659 
 24528728837243 
 
 
 87 
 555 
 557 
 1668 
 24528728837243 
 
 
 88 
 558 
 560 
 1677 
 24528728837243 
 
 
 89 
 561 
 

In [ ]:
assert str(sum(col['mini'])) + str(sum(col['maxi'])) + str(sum(col['total'])) == x

In [ ]:
BOUND = 2000

buffer = []
running_sum = 0
for i in range(1, 1001):
    if running_sum + i > BOUND:
        print(running_sum, buffer)
        buffer = []
        running_sum = 0
    buffer.append(i)
    running_sum += i
print(running_sum, buffer)

1953 [1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62]
1963 [63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88]
1970 [89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108]
1989 [109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125]
1995 [126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140]
1911 [141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153]
1914 [154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165]
1881 [166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176]
1815 [177, 178, 179, 180, 181, 182, 183, 184, 185, 186]
1915 [187, 188, 189, 190, 191, 192, 193, 194, 195, 196]
1809 [197, 198, 199, 200, 201, 202, 203, 204, 205]
1890 [206, 207, 2

### Théorème Eureka

**Atelier [003].** Tout entier positif peut s'écrire comme la somme de trois nombres triangulaires (cf. atelier 3).

<figure>
<img alt="Gauss&#039;s diary entry, ΕΥΡΗΚΑ! num = Δ + Δ + Δ" src="https://upload.wikimedia.org/wikipedia/commons/c/cd/Eureka_Gauss.png?20211009172716"></a>
  <figcaption><p>La mention « ΕΥΡΗΚΑ. num = Δ + Δ + Δ » dans le journal de Gauss de 1796. Ce résultat est parfois appelé théorème Eureka (« J'ai trouvé » en grec). <a title="Göttinger Digitalisierungszentrum, Public domain, via Wikimedia Commons" href="https://commons.wikimedia.org/wiki/File:Eureka_Gauss.png" target='_blank'>Source de l'image</a>.</p></figcaption>
</figure>

_Défi._ Listez par ordre croissant les entiers de 0 à 1000. En face de chacun d'eux, listez ses décompositions sous la forme $n_1 + n_2 + n_3$, triées par $n_1$, puis $n_2$ croissants. Par exemple :
```
        0 + 0 + 91
        0 + 36 + 55
        1 + 45 + 45
91      3 + 10 + 78
        10 + 15 + 66
        10 + 36 + 45
        15 + 21 + 55
```

_Aide._ Définissez en CTE la requête de l'atelier « nombres triangulaires ». Utilisez `group_concat` avec `ORDER BY` et `SEPARATOR`.

In [ ]:
x = '0619009110533190101517110661201528153154513621551203655105' # la concaténation de tous les chiffres des décompositions de 196
# Javascript: result[196]?.sums?.replace(/\D/g, '') || '7_531_148'

In [ ]:
%%sql
-- L'idée est de calculer toutes les combinaisons de trois nombres triangulaires $n_1$, $n_2$ et $n_3$ qui vérifient
-- un certain nombre de propriétés : leur somme n'excède pas 1000, on a $n_1 \le n_2 \le n_3$ (élimination des
-- doublons par commutativité de l'addition) et, plus subtilement, $n_1\le333$ et $n_2\le500$.
WITH T3 AS (
    SELECT A.n AS n3
    FROM ints A
    JOIN ints B ON A.n = B.n * (B.n + 1) / 2
    WHERE B.n < 45
    ORDER BY A.n
),
T2 AS (
    SELECT n3 AS n2
    FROM T3
    WHERE n3 <= 500
),
T1 AS (
    SELECT n2 AS n1
    FROM T2
    WHERE n2 <= 333
),
raw AS (
    SELECT
        n1 + n2 + n3 AS n,
        concat(n1, ' + ', n2, ' + ', n3) AS s,
        n1,
        n2
    FROM T1
    JOIN T2 ON n1 <= n2
    JOIN T3 ON n2 <= n3
)
SELECT
    n,
    group_concat(s ORDER BY n1, n2 SEPARATOR '\n') AS sums,
    salt_003(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM raw
WHERE n <= 1000
GROUP BY n

1001 rows affected.

n 
 sums 
 token 
 
 
 
 
 0 
 0 + 0 + 0 
 78791083293165 
 
 
 1 
 0 + 0 + 1 
 78791083293165 
 
 
 2 
 0 + 1 + 1 
 78791083293165 
 
 
 3 
 0 + 0 + 3 1 + 1 + 1 
 78791083293165 
 
 
 4 
 0 + 1 + 3 
 78791083293165 
 
 
 5 
 1 + 1 + 3 
 78791083293165 
 
 
 6 
 0 + 0 + 6 0 + 3 + 3 
 78791083293165 
 
 
 7 
 0 + 1 + 6 1 + 3 + 3 
 78791083293165 
 
 
 8 
 1 + 1 + 6 
 78791083293165 
 
 
 9 
 0 + 3 + 6 3 + 3 + 3 
 78791083293165 
 
 
 10 
 0 + 0 + 10 1 + 3 + 6 
 78791083293165 
 
 
 11 
 0 + 1 + 10 
 78791083293165 
 
 
 12 
 0 + 6 + 6 1 + 1 + 10 3 + 3 + 6 
 78791083293165 
 
 
 13 
 0 + 3 + 10 1 + 6 + 6 
 78791083293165 
 
 
 14 
 1 + 3 + 10 
 78791083293165 
 
 
 15 
 0 + 0 + 15 3 + 6 + 6 
 78791083293165 
 
 
 16 
 0 + 1 + 15 0 + 6 + 10 3 + 3 + 10 
 78791083293165 
 
 
 17 
 1 + 1 + 15 1 + 6 + 10 
 78791083293165 
 
 
 18 
 0 + 3 + 15 6 + 6 + 6 
 78791083293165 
 
 
 19 
 1 + 3 + 15 3 + 6 + 10 
 78791083293165 
 
 
 20 
 0 + 10 + 10 
 78791083293165 
 
 
 21 
 0 + 0 + 21 0 + 6 + 15 1 + 10 + 10 3 + 3 + 15 
 78791083293165 
 
 
 22 
 0 + 1 + 21 1 + 6 + 15 6 + 6 + 10 
 78791083293165 
 
 
 23 
 1 + 1 + 21 3 + 10 + 10 
 78791083293165 
 
 
 24 
 0 + 3 + 21 3 + 6 + 15 
 78791083293165 
 
 
 25 
 0 + 10 + 15 1 + 3 + 21 
 78791083293165 
 
 
 26 
 1 + 10 + 15 6 + 10 + 10 
 78791083293165 
 
 
 27 
 0 + 6 + 21 3 + 3 + 21 6 + 6 + 15 
 78791083293165 
 
 
 28 
 0 + 0 + 28 1 + 6 + 21 3 + 10 + 15 
 78791083293165 
 
 
 29 
 0 + 1 + 28 
 78791083293165 
 
 
 30 
 0 + 15 + 15 1 + 1 + 28 3 + 6 + 21 10 + 10 + 10 
 78791083293165 
 
 
 31 
 0 + 3 + 28 0 + 10 + 21 1 + 15 + 15 6 + 10 + 15 
 78791083293165 
 
 
 32 
 1 + 3 + 28 1 + 10 + 21 
 78791083293165 
 
 
 33 
 3 + 15 + 15 6 + 6 + 21 
 78791083293165 
 
 
 34 
 0 + 6 + 28 3 + 3 + 28 3 + 10 + 21 
 78791083293165 
 
 
 35 
 1 + 6 + 28 10 + 10 + 15 
 78791083293165 
 
 
 36 
 0 + 0 + 36 0 + 15 + 21 6 + 15 + 15 
 78791083293165 
 
 
 37 
 0 + 1 + 36 1 + 15 + 21 3 + 6 + 28 6 + 10 + 21 
 78791083293165 
 
 
 38 
 0 + 10 + 28 1 + 1 + 36 
 78791083293165 
 
 
 39 
 0 + 3 + 36 1 + 10 + 28 3 + 15 + 21 
 78791083293165 
 
 
 40 
 1 + 3 + 36 6 + 6 + 28 10 + 15 + 15 
 78791083293165 
 
 
 41 
 3 + 10 + 28 10 + 10 + 21 
 78791083293165 
 
 
 42 
 0 + 6 + 36 0 + 21 + 21 3 + 3 + 36 6 + 15 + 21 
 78791083293165 
 
 
 43 
 0 + 15 + 28 1 + 6 + 36 1 + 21 + 21 
 78791083293165 
 
 
 44 
 1 + 15 + 28 6 + 10 + 28 
 78791083293165 
 
 
 45 
 0 + 0 + 45 3 + 6 + 36 3 + 21 + 21 15 + 15 + 15 
 78791083293165 
 
 
 46 
 0 + 1 + 45 0 + 10 + 36 3 + 15 + 28 10 + 15 + 21 
 78791083293165 
 
 
 47 
 1 + 1 + 45 1 + 10 + 36 
 78791083293165 
 
 
 48 
 0 + 3 + 45 6 + 6 + 36 6 + 21 + 21 10 + 10 + 28 
 78791083293165 
 
 
 49 
 0 + 21 + 28 1 + 3 + 45 3 + 10 + 36 6 + 15 + 28 
 78791083293165 
 
 
 50 
 1 + 21 + 28 
 78791083293165 
 
 
 51 
 0 + 6 + 45 0 + 15 + 36 3 + 3 + 45 15 + 15 + 21 
 78791083293165 
 
 
 52 
 1 + 6 + 45 1 + 15 + 36 3 + 21 + 28 6 + 10 + 36 10 + 21 + 21 
 78791083293165 
 
 
 53 
 10 + 15 + 28 
 78791083293165 
 
 
 54 
 3 + 6 + 45 3 + 15 + 36 
 78791083293165 
 
 
 55 
 0 + 0 + 55 0 + 10 + 45 6 + 21 + 28 
 78791083293165 
 
 
 56 
 0 + 1 + 55 0 + 28 + 28 1 + 10 + 45 10 + 10 + 36 
 78791083293165 
 
 
 57 
 0 + 21 + 36 1 + 1 + 55 1 + 28 + 28 6 + 6 + 45 6 + 15 + 36 15 + 21 + 21 
 78791083293165 
 
 
 58 
 0 + 3 + 55 1 + 21 + 36 3 + 10 + 45 15 + 15 + 28 
 78791083293165 
 
 
 59 
 1 + 3 + 55 3 + 28 + 28 10 + 21 + 28 
 78791083293165 
 
 
 60 
 0 + 15 + 45 3 + 21 + 36 
 78791083293165 
 
 
 61 
 0 + 6 + 55 1 + 15 + 45 3 + 3 + 55 6 + 10 + 45 10 + 15 + 36 
 78791083293165 
 
 
 62 
 1 + 6 + 55 6 + 28 + 28 
 78791083293165 
 
 
 63 
 3 + 15 + 45 6 + 21 + 36 21 + 21 + 21 
 78791083293165 
 
 
 64 
 0 + 28 + 36 3 + 6 + 55 15 + 21 + 28 
 78791083293165 
 
 
 65 
 0 + 10 + 55 1 + 28 + 36 10 + 10 + 45 
 78791083293165 
 
 
 66 
 0 + 0 + 66 0 + 21 + 45 1 + 10 + 55 6 + 15 + 45 10 + 28 + 28 15 + 15 + 36 
 78791083293165 
 
 
 67 
 0 + 1 + 66 1 + 21 + 45 3 + 28 + 36 6 + 6 + 55 10 + 21 + 36 
 78791083293165 
 
 
 68 
 1 + 1

In [ ]:
assert re.sub(r"\D", "", col["sums"][196]) == x

In [ ]:
x = '0911053655105106612021551201545136152815310151710619033190'

In [ ]:
%%sql
-- Indication. Triez les différentes sommes $n_1 + n_2 + n_3$ selon $n_1$, puis $n_2$.
-- Cela se fait avec la syntaxe: `group_concat(... ORDER BY ... SEPARATOR ...)`.
WITH T3 AS (
    SELECT A.n AS n3
    FROM ints A
    JOIN ints B ON A.n = B.n * (B.n + 1) / 2
    WHERE B.n < 45
    ORDER BY A.n
),
T2 AS (
    SELECT n3 AS n2
    FROM T3
    WHERE n3 <= 500
),
T1 AS (
    SELECT n2 AS n1
    FROM T2
    WHERE n2 <= 333
),
raw AS (
    SELECT
        n1 + n2 + n3 AS n,
        concat(n1, ' + ', n2, ' + ', n3) AS s,
        n1,
        n2
    FROM T1
    JOIN T2 ON n1 <= n2
    JOIN T3 ON n2 <= n3
)
SELECT n
    , group_concat(s SEPARATOR '\n') AS sums
    , salt_003(string_hash('{{x}}') + count(*) OVER ()) AS token
FROM raw
WHERE n <= 1000
GROUP BY n

1001 rows affected.

n 
 sums 
 token 
 
 
 
 
 0 
 0 + 0 + 0 
 78380705953093 
 
 
 1 
 0 + 0 + 1 
 78380705953093 
 
 
 2 
 0 + 1 + 1 
 78380705953093 
 
 
 3 
 1 + 1 + 1 0 + 0 + 3 
 78380705953093 
 
 
 4 
 0 + 1 + 3 
 78380705953093 
 
 
 5 
 1 + 1 + 3 
 78380705953093 
 
 
 6 
 0 + 3 + 3 0 + 0 + 6 
 78380705953093 
 
 
 7 
 1 + 3 + 3 0 + 1 + 6 
 78380705953093 
 
 
 8 
 1 + 1 + 6 
 78380705953093 
 
 
 9 
 3 + 3 + 3 0 + 3 + 6 
 78380705953093 
 
 
 10 
 1 + 3 + 6 0 + 0 + 10 
 78380705953093 
 
 
 11 
 0 + 1 + 10 
 78380705953093 
 
 
 12 
 0 + 6 + 6 3 + 3 + 6 1 + 1 + 10 
 78380705953093 
 
 
 13 
 1 + 6 + 6 0 + 3 + 10 
 78380705953093 
 
 
 14 
 1 + 3 + 10 
 78380705953093 
 
 
 15 
 3 + 6 + 6 0 + 0 + 15 
 78380705953093 
 
 
 16 
 0 + 6 + 10 3 + 3 + 10 0 + 1 + 15 
 78380705953093 
 
 
 17 
 1 + 6 + 10 1 + 1 + 15 
 78380705953093 
 
 
 18 
 6 + 6 + 6 0 + 3 + 15 
 78380705953093 
 
 
 19 
 3 + 6 + 10 1 + 3 + 15 
 78380705953093 
 
 
 20 
 0 + 10 + 10 
 78380705953093 
 
 
 21 
 1 + 10 + 10 0 + 6 + 15 3 + 3 + 15 0 + 0 + 21 
 78380705953093 
 
 
 22 
 6 + 6 + 10 1 + 6 + 15 0 + 1 + 21 
 78380705953093 
 
 
 23 
 3 + 10 + 10 1 + 1 + 21 
 78380705953093 
 
 
 24 
 3 + 6 + 15 0 + 3 + 21 
 78380705953093 
 
 
 25 
 0 + 10 + 15 1 + 3 + 21 
 78380705953093 
 
 
 26 
 6 + 10 + 10 1 + 10 + 15 
 78380705953093 
 
 
 27 
 6 + 6 + 15 0 + 6 + 21 3 + 3 + 21 
 78380705953093 
 
 
 28 
 3 + 10 + 15 1 + 6 + 21 0 + 0 + 28 
 78380705953093 
 
 
 29 
 0 + 1 + 28 
 78380705953093 
 
 
 30 
 10 + 10 + 10 0 + 15 + 15 3 + 6 + 21 1 + 1 + 28 
 78380705953093 
 
 
 31 
 1 + 15 + 15 6 + 10 + 15 0 + 10 + 21 0 + 3 + 28 
 78380705953093 
 
 
 32 
 1 + 10 + 21 1 + 3 + 28 
 78380705953093 
 
 
 33 
 3 + 15 + 15 6 + 6 + 21 
 78380705953093 
 
 
 34 
 3 + 10 + 21 0 + 6 + 28 3 + 3 + 28 
 78380705953093 
 
 
 35 
 10 + 10 + 15 1 + 6 + 28 
 78380705953093 
 
 
 36 
 6 + 15 + 15 0 + 15 + 21 0 + 0 + 36 
 78380705953093 
 
 
 37 
 1 + 15 + 21 6 + 10 + 21 3 + 6 + 28 0 + 1 + 36 
 78380705953093 
 
 
 38 
 0 + 10 + 28 1 + 1 + 36 
 78380705953093 
 
 
 39 
 3 + 15 + 21 1 + 10 + 28 0 + 3 + 36 
 78380705953093 
 
 
 40 
 10 + 15 + 15 6 + 6 + 28 1 + 3 + 36 
 78380705953093 
 
 
 41 
 10 + 10 + 21 3 + 10 + 28 
 78380705953093 
 
 
 42 
 0 + 21 + 21 6 + 15 + 21 0 + 6 + 36 3 + 3 + 36 
 78380705953093 
 
 
 43 
 1 + 21 + 21 0 + 15 + 28 1 + 6 + 36 
 78380705953093 
 
 
 44 
 1 + 15 + 28 6 + 10 + 28 
 78380705953093 
 
 
 45 
 15 + 15 + 15 3 + 21 + 21 3 + 6 + 36 0 + 0 + 45 
 78380705953093 
 
 
 46 
 10 + 15 + 21 3 + 15 + 28 0 + 10 + 36 0 + 1 + 45 
 78380705953093 
 
 
 47 
 1 + 10 + 36 1 + 1 + 45 
 78380705953093 
 
 
 48 
 6 + 21 + 21 10 + 10 + 28 6 + 6 + 36 0 + 3 + 45 
 78380705953093 
 
 
 49 
 0 + 21 + 28 6 + 15 + 28 3 + 10 + 36 1 + 3 + 45 
 78380705953093 
 
 
 50 
 1 + 21 + 28 
 78380705953093 
 
 
 51 
 15 + 15 + 21 0 + 15 + 36 0 + 6 + 45 3 + 3 + 45 
 78380705953093 
 
 
 52 
 10 + 21 + 21 3 + 21 + 28 1 + 15 + 36 6 + 10 + 36 1 + 6 + 45 
 78380705953093 
 
 
 53 
 10 + 15 + 28 
 78380705953093 
 
 
 54 
 3 + 15 + 36 3 + 6 + 45 
 78380705953093 
 
 
 55 
 6 + 21 + 28 0 + 10 + 45 0 + 0 + 55 
 78380705953093 
 
 
 56 
 0 + 28 + 28 10 + 10 + 36 1 + 10 + 45 0 + 1 + 55 
 78380705953093 
 
 
 57 
 15 + 21 + 21 1 + 28 + 28 0 + 21 + 36 6 + 15 + 36 6 + 6 + 45 1 + 1 + 55 
 78380705953093 
 
 
 58 
 15 + 15 + 28 1 + 21 + 36 3 + 10 + 45 0 + 3 + 55 
 78380705953093 
 
 
 59 
 3 + 28 + 28 10 + 21 + 28 1 + 3 + 55 
 78380705953093 
 
 
 60 
 3 + 21 + 36 0 + 15 + 45 
 78380705953093 
 
 
 61 
 10 + 15 + 36 1 + 15 + 45 6 + 10 + 45 0 + 6 + 55 3 + 3 + 55 
 78380705953093 
 
 
 62 
 6 + 28 + 28 1 + 6 + 55 
 78380705953093 
 
 
 63 
 21 + 21 + 21 6 + 21 + 36 3 + 15 + 45 
 78380705953093 
 
 
 64 
 15 + 21 + 28 0 + 28 + 36 3 + 6 + 55 
 78380705953093 
 
 
 65 
 1 + 28 + 36 10 + 10 + 45 0 + 10 + 55 
 78380705953093 
 
 
 66 
 10 + 28 + 28 15 + 15 + 36 0 + 21 + 45 6 + 15 + 45 1 + 10 + 55 0 + 0 + 66 
 78380705953093 
 
 
 67 
 3 + 28 + 36 10 + 21 + 36 1 + 21 + 45 6 + 6 + 55 0 + 1 + 66 
 78380705953093 
 
 
 68 
 3 + 1

In [ ]:
assert re.sub(r"\D", "", col["sums"][196]) == x

In [ ]:
raise EOFError

EOFError: 

# Annexe

### Permutation aléatoire

In [ ]:
%%sql
SELECT n
FROM ints
ORDER BY rand(42)

1001 rows affected.

n 
 
 
 
 
 61 
 
 
 253 
 
 
 874 
 
 
 474 
 
 
 444 
 
 
 749 
 
 
 362 
 
 
 175 
 
 
 577 
 
 
 484 
 
 
 687 
 
 
 319 
 
 
 734 
 
 
 983 
 
 
 424 
 
 
 345 
 
 
 295 
 
 
 409 
 
 
 155 
 
 
 807 
 
 
 107 
 
 
 925 
 
 
 592 
 
 
 820 
 
 
 130 
 
 
 505 
 
 
 208 
 
 
 757 
 
 
 122 
 
 
 437 
 
 
 338 
 
 
 306 
 
 
 829 
 
 
 352 
 
 
 512 
 
 
 292 
 
 
 17 
 
 
 280 
 
 
 858 
 
 
 89 
 
 
 418 
 
 
 794 
 
 
 942 
 
 
 823 
 
 
 817 
 
 
 487 
 
 
 152 
 
 
 370 
 
 
 145 
 
 
 875 
 
 
 203 
 
 
 849 
 
 
 943 
 
 
 586 
 
 
 810 
 
 
 302 
 
 
 261 
 
 
 813 
 
 
 941 
 
 
 243 
 
 
 683 
 
 
 740 
 
 
 376 
 
 
 395 
 
 
 852 
 
 
 69 
 
 
 128 
 
 
 573 
 
 
 857 
 
 
 622 
 
 
 831 
 
 
 950 
 
 
 174 
 
 
 626 
 
 
 637 
 
 
 13 
 
 
 531 
 
 
 63 
 
 
 177 
 
 
 249 
 
 
 223 
 
 
 313 
 
 
 5 
 
 
 940 
 
 
 483 
 
 
 182 
 
 
 679 
 
 
 286 
 
 
 57 
 
 
 571 
 
 
 169 
 
 
 520 
 
 
 417 
 
 
 755 
 
 
 336 
 
 
 833 
 
 
 517 
 
 
 806 
 
 
 193 
 
 
 605 
 
 
 84 
 
 
 519 
 
 
 133 
 
 
 966 
 
 
 359 
 
 
 822 
 
 
 663 
 
 
 258 
 
 
 716 
 
 
 382 
 
 
 895 
 
 
 380 
 
 
 918 
 
 
 532 
 
 
 828 
 
 
 402 
 
 
 198 
 
 
 320 
 
 
 799 
 
 
 309 
 
 
 964 
 
 
 906 
 
 
 778 
 
 
 470 
 
 
 712 
 
 
 446 
 
 
 944 
 
 
 576 
 
 
 689 
 
 
 200 
 
 
 401 
 
 
 737 
 
 
 196 
 
 
 997 
 
 
 269 
 
 
 479 
 
 
 214 
 
 
 1 
 
 
 946 
 
 
 891 
 
 
 567 
 
 
 615 
 
 
 877 
 
 
 416 
 
 
 45 
 
 
 926 
 
 
 226 
 
 
 744 
 
 
 854 
 
 
 98 
 
 
 974 
 
 
 708 
 
 
 800 
 
 
 928 
 
 
 288 
 
 
 373 
 
 
 669 
 
 
 881 
 
 
 733 
 
 
 770 
 
 
 766 
 
 
 138 
 
 
 215 
 
 
 843 
 
 
 105 
 
 
 579 
 
 
 976 
 
 
 723 
 
 
 473 
 
 
 546 
 
 
 634 
 
 
 758 
 
 
 157 
 
 
 999 
 
 
 64 
 
 
 245 
 
 
 449 
 
 
 521 
 
 
 803 
 
 
 165 
 
 
 989 
 
 
 291 
 
 
 159 
 
 
 560 
 
 
 493 
 
 
 672 
 
 
 731 
 
 
 384 
 
 
 201 
 
 
 726 
 
 
 611 
 
 
 71 
 
 
 18 
 
 
 43 
 
 
 673 
 
 
 447 
 
 
 827 
 
 
 92 
 
 
 213 
 
 
 108 
 
 
 923 
 
 
 60 
 
 
 207 
 
 
 844 
 
 
 403 
 
 
 677 
 
 
 350 
 
 
 294 
 
 
 763 
 
 
 95 
 
 
 645 
 
 
 282 
 
 
 82 
 
 
 597 
 
 
 467 
 
 
 410 
 
 
 581 
 
 
 686 
 
 
 181 
 
 
 323 
 
 
 385 
 
 
 635 
 
 
 582 
 
 
 366 
 
 
 947 
 
 
 694 
 
 
 353 
 
 
 633 
 
 
 606 
 
 
 220 
 
 
 903 
 
 
 151 
 
 
 283 
 
 
 349 
 
 
 81 
 
 
 415 
 
 
 7 
 
 
 699 
 
 
 379 
 
 
 608 
 
 
 429 
 
 
 882 
 
 
 933 
 
 
 503 
 
 
 710 
 
 
 166 
 
 
 315 
 
 
 671 
 
 
 221 
 
 
 430 
 
 
 450 
 
 
 861 
 
 
 251 
 
 
 455 
 
 
 715 
 
 
 695 
 
 
 780 
 
 
 58 
 
 
 355 
 
 
 136 
 
 
 787 
 
 
 932 
 
 
 774 
 
 
 324 
 
 
 368 
 
 
 876 
 
 
 870 
 
 
 36 
 
 
 281 
 
 
 435 
 
 
 391 
 
 
 337 
 
 
 977 
 
 
 572 
 
 
 311 
 
 
 593 
 
 
 86 
 
 
 826 
 
 
 621 
 
 
 867 
 
 
 263 
 
 
 394 
 
 
 754 
 
 
 233 
 
 
 539 
 
 
 77 
 
 
 438 
 
 
 917 
 
 
 697 
 
 
 290 
 
 
 783 
 
 
 276 
 
 
 513 
 
 
 888 
 
 
 594 
 
 
 612 
 
 
 333 
 
 
 116 
 
 
 314 
 
 
 953 
 
 
 72 
 
 
 21 
 
 
 88 
 
 
 498 
 
 
 561 
 
 
 659 
 
 
 272 
 
 
 106 
 
 
 619 
 
 
 412 
 
 
 866 
 
 
 462 
 
 
 897 
 
 
 90 
 
 
 80 
 
 
 363 
 
 
 838 
 
 
 318 
 
 
 316 
 
 
 47 
 
 
 700 
 
 
 924 
 
 
 998 
 
 
 228 
 
 
 298 
 
 
 398 
 
 
 439 
 
 
 956 
 
 
 642 
 
 
 730 
 
 
 351 
 
 
 310 
 
 
 347 
 
 
 631 
 
 
 456 
 
 
 356 
 
 
 814 
 
 
 760 
 
 
 678 
 
 
 769 
 
 
 158 
 
 
 647 
 
 
 83 
 
 
 835 
 
 
 685 
 
 
 920 
 
 
 670 
 
 
 516 
 
 
 205 
 
 
 533 
 
 
 297 
 
 
 514 
 
 
 459 
 
 
 741 
 
 
 894 
 
 
 378 
 
 
 969 
 
 
 67 
 
 
 254 
 
 
 850 
 
 
 227 
 
 
 785 
 
 
 371 
 
 
 545 
 
 
 189 
 
 
 529 
 
 
 524 
 
 
 557 
 
 
 618 
 
 
 463 
 
 
 728 
 
 
 541 
 
 
 603 
 
 
 711 
 
 
 24 
 
 
 26 
 
 
 397 
 
 
 761 
 
 
 777 
 
 
 126 
 
 
 641 
 
 
 979 
 
 
 847 
 
 
 339 
 
 
 312 
 
 
 714 
 
 
 725 
 
 
 855 
 
 
 137 
 
 
 690 
 
 
 980 
 
 
 3 
 
 
 23 
 
 
 646 
 
 
 994 
 
 
 558 
 
 
 616 
 
 
 534 
 
 
 461 
 
 
 443 
 
 
 674 
 
 
 194 
 
 
 825 
 
 
 

In [ ]:
%%sql
SELECT n
FROM ints
WHERE n < 10
ORDER BY rand(42)

10 rows affected.

n 
 
 
 
 
 5 
 
 
 1 
 
 
 7 
 
 
 3 
 
 
 6 
 
 
 9 
 
 
 8 
 
 
 4 
 
 
 0 
 
 
 2

In [ ]:
%%sql
WITH
digits (n) AS (
  VALUES ROW(0), ROW(1), ROW(2), ROW(3), ROW(4),
         ROW(5), ROW(6), ROW(7), ROW(8), ROW(9)
)
SELECT n
FROM digits
ORDER BY RAND(42);

10 rows affected.

n 
 
 
 
 
 5 
 
 
 1 
 
 
 7 
 
 
 3 
 
 
 6 
 
 
 9 
 
 
 8 
 
 
 4 
 
 
 0 
 
 
 2

In [ ]:
%%sql
WITH
digits (n) AS (
  VALUES ROW(0), ROW(1), ROW(2), ROW(3), ROW(4),
         ROW(5), ROW(6), ROW(7), ROW(8), ROW(9)
)
SELECT GROUP_CONCAT(n ORDER BY RAND(42) SEPARATOR '')
FROM digits

1 rows affected.

GROUP_CONCAT(n ORDER BY RAND(42) SEPARATOR '') 
 
 
 
 
 9876543210

In [ ]:
%%sql
WITH
digits AS (
    SELECT n
    FROM ints
    WHERE n < 10
    ORDER BY rand(42) -- Normally not retained, except when directly used
    LIMIT 10 -- Needed to "materialize" the CTE to retain the order
)
SELECT GROUP_CONCAT(n SEPARATOR '')
FROM digits

1 rows affected.

GROUP_CONCAT(n SEPARATOR '') 
 
 
 
 
 5173698402

In [ ]:
%%sql
WITH
digits AS (
    SELECT n
    FROM ints
    WHERE n < 10
    ORDER BY rand(42)
)
SELECT *
FROM digits

10 rows affected.

n 
 
 
 
 
 5 
 
 
 1 
 
 
 7 
 
 
 3 
 
 
 6 
 
 
 9 
 
 
 8 
 
 
 4 
 
 
 0 
 
 
 2

### Échantillon aléatoire

In [ ]:
%%sql
SELECT n
FROM ints
ORDER BY rand(42)
LIMIT 10

10 rows affected.

n 
 
 
 
 
 61 
 
 
 253 
 
 
 874 
 
 
 474 
 
 
 444 
 
 
 749 
 
 
 362 
 
 
 175 
 
 
 577 
 
 
 484

### Échantillon aléatoire trié

In [ ]:
%%sql
WITH sample AS (
    SELECT n
    FROM ints
    ORDER BY rand(42)
    LIMIT 10
)
SELECT *
FROM sample
ORDER BY 1

10 rows affected.

n 
 
 
 
 
 61 
 
 
 175 
 
 
 253 
 
 
 362 
 
 
 444 
 
 
 474 
 
 
 484 
 
 
 577 
 
 
 749 
 
 
 874

### Largest proper divisor of the n-th composite number

https://oeis.org/A160180

In [ ]:
%%sql
SELECT max(B.n)
       , salt_028(bit_xor(sum(nn(B.hash))) OVER ()) AS token
FROM ints A
JOIN ints B ON B.n BETWEEN 2 AND A.n DIV 2
   AND A.n MOD B.n = 0
GROUP BY A.n
limit 20

20 rows affected.

max(B.n) 
 token 
 
 
 
 
 2 
 214115922367998 
 
 
 3 
 214115922367998 
 
 
 4 
 214115922367998 
 
 
 3 
 214115922367998 
 
 
 5 
 214115922367998 
 
 
 6 
 214115922367998 
 
 
 7 
 214115922367998 
 
 
 5 
 214115922367998 
 
 
 8 
 214115922367998 
 
 
 9 
 214115922367998 
 
 
 10 
 214115922367998 
 
 
 7 
 214115922367998 
 
 
 11 
 214115922367998 
 
 
 12 
 214115922367998 
 
 
 5 
 214115922367998 
 
 
 13 
 214115922367998 
 
 
 9 
 214115922367998 
 
 
 14 
 214115922367998 
 
 
 15 
 214115922367998 
 
 
 16 
 214115922367998

### Nombres premiers (sans modulo)

In [ ]:
%%sql
-- Avec EXCEPT
SELECT n
FROM ints
WHERE n > 1

EXCEPT

SELECT A.n * B.n
FROM ints A
JOIN ints B ON B.n BETWEEN A.n AND 1000 DIV A.n
WHERE A.n BETWEEN 2 AND 31

168 rows affected.

n 
 
 
 
 
 2 
 
 
 3 
 
 
 5 
 
 
 7 
 
 
 11 
 
 
 13 
 
 
 17 
 
 
 19 
 
 
 23 
 
 
 29 
 
 
 31 
 
 
 37 
 
 
 41 
 
 
 43 
 
 
 47 
 
 
 53 
 
 
 59 
 
 
 61 
 
 
 67 
 
 
 71 
 
 
 73 
 
 
 79 
 
 
 83 
 
 
 89 
 
 
 97 
 
 
 101 
 
 
 103 
 
 
 107 
 
 
 109 
 
 
 113 
 
 
 127 
 
 
 131 
 
 
 137 
 
 
 139 
 
 
 149 
 
 
 151 
 
 
 157 
 
 
 163 
 
 
 167 
 
 
 173 
 
 
 179 
 
 
 181 
 
 
 191 
 
 
 193 
 
 
 197 
 
 
 199 
 
 
 211 
 
 
 223 
 
 
 227 
 
 
 229 
 
 
 233 
 
 
 239 
 
 
 241 
 
 
 251 
 
 
 257 
 
 
 263 
 
 
 269 
 
 
 271 
 
 
 277 
 
 
 281 
 
 
 283 
 
 
 293 
 
 
 307 
 
 
 311 
 
 
 313 
 
 
 317 
 
 
 331 
 
 
 337 
 
 
 347 
 
 
 349 
 
 
 353 
 
 
 359 
 
 
 367 
 
 
 373 
 
 
 379 
 
 
 383 
 
 
 389 
 
 
 397 
 
 
 401 
 
 
 409 
 
 
 419 
 
 
 421 
 
 
 431 
 
 
 433 
 
 
 439 
 
 
 443 
 
 
 449 
 
 
 457 
 
 
 461 
 
 
 463 
 
 
 467 
 
 
 479 
 
 
 487 
 
 
 491 
 
 
 499 
 
 
 503 
 
 
 509 
 
 
 521 
 
 
 523 
 
 
 541 
 
 
 547 
 
 
 557 
 
 
 563 
 
 
 569 
 
 
 571 
 
 
 577 
 
 
 587 
 
 
 593 
 
 
 599 
 
 
 601 
 
 
 607 
 
 
 613 
 
 
 617 
 
 
 619 
 
 
 631 
 
 
 641 
 
 
 643 
 
 
 647 
 
 
 653 
 
 
 659 
 
 
 661 
 
 
 673 
 
 
 677 
 
 
 683 
 
 
 691 
 
 
 701 
 
 
 709 
 
 
 719 
 
 
 727 
 
 
 733 
 
 
 739 
 
 
 743 
 
 
 751 
 
 
 757 
 
 
 761 
 
 
 769 
 
 
 773 
 
 
 787 
 
 
 797 
 
 
 809 
 
 
 811 
 
 
 821 
 
 
 823 
 
 
 827 
 
 
 829 
 
 
 839 
 
 
 853 
 
 
 857 
 
 
 859 
 
 
 863 
 
 
 877 
 
 
 881 
 
 
 883 
 
 
 887 
 
 
 907 
 
 
 911 
 
 
 919 
 
 
 929 
 
 
 937 
 
 
 941 
 
 
 947 
 
 
 953 
 
 
 967 
 
 
 971 
 
 
 977 
 
 
 983 
 
 
 991 
 
 
 997

In [ ]:
%%sql
-- Avec NOT IN
SELECT n
FROM ints
WHERE n > 1
  AND n NOT IN (
    SELECT A.n * B.n
    FROM ints A
    JOIN ints B ON B.n BETWEEN A.n AND 1000 DIV A.n
    WHERE A.n BETWEEN 2 AND 31
)

168 rows affected.

n 
 
 
 
 
 2 
 
 
 3 
 
 
 5 
 
 
 7 
 
 
 11 
 
 
 13 
 
 
 17 
 
 
 19 
 
 
 23 
 
 
 29 
 
 
 31 
 
 
 37 
 
 
 41 
 
 
 43 
 
 
 47 
 
 
 53 
 
 
 59 
 
 
 61 
 
 
 67 
 
 
 71 
 
 
 73 
 
 
 79 
 
 
 83 
 
 
 89 
 
 
 97 
 
 
 101 
 
 
 103 
 
 
 107 
 
 
 109 
 
 
 113 
 
 
 127 
 
 
 131 
 
 
 137 
 
 
 139 
 
 
 149 
 
 
 151 
 
 
 157 
 
 
 163 
 
 
 167 
 
 
 173 
 
 
 179 
 
 
 181 
 
 
 191 
 
 
 193 
 
 
 197 
 
 
 199 
 
 
 211 
 
 
 223 
 
 
 227 
 
 
 229 
 
 
 233 
 
 
 239 
 
 
 241 
 
 
 251 
 
 
 257 
 
 
 263 
 
 
 269 
 
 
 271 
 
 
 277 
 
 
 281 
 
 
 283 
 
 
 293 
 
 
 307 
 
 
 311 
 
 
 313 
 
 
 317 
 
 
 331 
 
 
 337 
 
 
 347 
 
 
 349 
 
 
 353 
 
 
 359 
 
 
 367 
 
 
 373 
 
 
 379 
 
 
 383 
 
 
 389 
 
 
 397 
 
 
 401 
 
 
 409 
 
 
 419 
 
 
 421 
 
 
 431 
 
 
 433 
 
 
 439 
 
 
 443 
 
 
 449 
 
 
 457 
 
 
 461 
 
 
 463 
 
 
 467 
 
 
 479 
 
 
 487 
 
 
 491 
 
 
 499 
 
 
 503 
 
 
 509 
 
 
 521 
 
 
 523 
 
 
 541 
 
 
 547 
 
 
 557 
 
 
 563 
 
 
 569 
 
 
 571 
 
 
 577 
 
 
 587 
 
 
 593 
 
 
 599 
 
 
 601 
 
 
 607 
 
 
 613 
 
 
 617 
 
 
 619 
 
 
 631 
 
 
 641 
 
 
 643 
 
 
 647 
 
 
 653 
 
 
 659 
 
 
 661 
 
 
 673 
 
 
 677 
 
 
 683 
 
 
 691 
 
 
 701 
 
 
 709 
 
 
 719 
 
 
 727 
 
 
 733 
 
 
 739 
 
 
 743 
 
 
 751 
 
 
 757 
 
 
 761 
 
 
 769 
 
 
 773 
 
 
 787 
 
 
 797 
 
 
 809 
 
 
 811 
 
 
 821 
 
 
 823 
 
 
 827 
 
 
 829 
 
 
 839 
 
 
 853 
 
 
 857 
 
 
 859 
 
 
 863 
 
 
 877 
 
 
 881 
 
 
 883 
 
 
 887 
 
 
 907 
 
 
 911 
 
 
 919 
 
 
 929 
 
 
 937 
 
 
 941 
 
 
 947 
 
 
 953 
 
 
 967 
 
 
 971 
 
 
 977 
 
 
 983 
 
 
 991 
 
 
 997

In [ ]:
%%sql
-- Avec NOT EXISTS
SELECT n
FROM ints C
WHERE n > 1
  AND NOT EXISTS (
    SELECT 1
    FROM ints A
    JOIN ints B ON B.n BETWEEN A.n AND 1000 DIV A.n
    WHERE A.n BETWEEN 2 AND 31
      AND A.n * B.n = C.n
  )

168 rows affected.

n 
 
 
 
 
 2 
 
 
 3 
 
 
 5 
 
 
 7 
 
 
 11 
 
 
 13 
 
 
 17 
 
 
 19 
 
 
 23 
 
 
 29 
 
 
 31 
 
 
 37 
 
 
 41 
 
 
 43 
 
 
 47 
 
 
 53 
 
 
 59 
 
 
 61 
 
 
 67 
 
 
 71 
 
 
 73 
 
 
 79 
 
 
 83 
 
 
 89 
 
 
 97 
 
 
 101 
 
 
 103 
 
 
 107 
 
 
 109 
 
 
 113 
 
 
 127 
 
 
 131 
 
 
 137 
 
 
 139 
 
 
 149 
 
 
 151 
 
 
 157 
 
 
 163 
 
 
 167 
 
 
 173 
 
 
 179 
 
 
 181 
 
 
 191 
 
 
 193 
 
 
 197 
 
 
 199 
 
 
 211 
 
 
 223 
 
 
 227 
 
 
 229 
 
 
 233 
 
 
 239 
 
 
 241 
 
 
 251 
 
 
 257 
 
 
 263 
 
 
 269 
 
 
 271 
 
 
 277 
 
 
 281 
 
 
 283 
 
 
 293 
 
 
 307 
 
 
 311 
 
 
 313 
 
 
 317 
 
 
 331 
 
 
 337 
 
 
 347 
 
 
 349 
 
 
 353 
 
 
 359 
 
 
 367 
 
 
 373 
 
 
 379 
 
 
 383 
 
 
 389 
 
 
 397 
 
 
 401 
 
 
 409 
 
 
 419 
 
 
 421 
 
 
 431 
 
 
 433 
 
 
 439 
 
 
 443 
 
 
 449 
 
 
 457 
 
 
 461 
 
 
 463 
 
 
 467 
 
 
 479 
 
 
 487 
 
 
 491 
 
 
 499 
 
 
 503 
 
 
 509 
 
 
 521 
 
 
 523 
 
 
 541 
 
 
 547 
 
 
 557 
 
 
 563 
 
 
 569 
 
 
 571 
 
 
 577 
 
 
 587 
 
 
 593 
 
 
 599 
 
 
 601 
 
 
 607 
 
 
 613 
 
 
 617 
 
 
 619 
 
 
 631 
 
 
 641 
 
 
 643 
 
 
 647 
 
 
 653 
 
 
 659 
 
 
 661 
 
 
 673 
 
 
 677 
 
 
 683 
 
 
 691 
 
 
 701 
 
 
 709 
 
 
 719 
 
 
 727 
 
 
 733 
 
 
 739 
 
 
 743 
 
 
 751 
 
 
 757 
 
 
 761 
 
 
 769 
 
 
 773 
 
 
 787 
 
 
 797 
 
 
 809 
 
 
 811 
 
 
 821 
 
 
 823 
 
 
 827 
 
 
 829 
 
 
 839 
 
 
 853 
 
 
 857 
 
 
 859 
 
 
 863 
 
 
 877 
 
 
 881 
 
 
 883 
 
 
 887 
 
 
 907 
 
 
 911 
 
 
 919 
 
 
 929 
 
 
 937 
 
 
 941 
 
 
 947 
 
 
 953 
 
 
 967 
 
 
 971 
 
 
 977 
 
 
 983 
 
 
 991 
 
 
 997

In [ ]:
%%sql
-- Avec une liste précalculée des petits nombres premiers, la seconde table ne fait plus que 1411 lignes au
-- lieu de 2550.
WITH small_primes (p) AS (
  VALUES ROW(2), ROW(3), ROW(5), ROW(7), ROW(11), ROW(13), ROW(17), ROW(19), ROW(23), ROW(29), ROW(31)
)
SELECT n
FROM ints
WHERE n > 1

EXCEPT

SELECT p * n
FROM small_primes
JOIN ints ON n BETWEEN p AND 1000 DIV p

168 rows affected.

n 
 
 
 
 
 2 
 
 
 3 
 
 
 5 
 
 
 7 
 
 
 11 
 
 
 13 
 
 
 17 
 
 
 19 
 
 
 23 
 
 
 29 
 
 
 31 
 
 
 37 
 
 
 41 
 
 
 43 
 
 
 47 
 
 
 53 
 
 
 59 
 
 
 61 
 
 
 67 
 
 
 71 
 
 
 73 
 
 
 79 
 
 
 83 
 
 
 89 
 
 
 97 
 
 
 101 
 
 
 103 
 
 
 107 
 
 
 109 
 
 
 113 
 
 
 127 
 
 
 131 
 
 
 137 
 
 
 139 
 
 
 149 
 
 
 151 
 
 
 157 
 
 
 163 
 
 
 167 
 
 
 173 
 
 
 179 
 
 
 181 
 
 
 191 
 
 
 193 
 
 
 197 
 
 
 199 
 
 
 211 
 
 
 223 
 
 
 227 
 
 
 229 
 
 
 233 
 
 
 239 
 
 
 241 
 
 
 251 
 
 
 257 
 
 
 263 
 
 
 269 
 
 
 271 
 
 
 277 
 
 
 281 
 
 
 283 
 
 
 293 
 
 
 307 
 
 
 311 
 
 
 313 
 
 
 317 
 
 
 331 
 
 
 337 
 
 
 347 
 
 
 349 
 
 
 353 
 
 
 359 
 
 
 367 
 
 
 373 
 
 
 379 
 
 
 383 
 
 
 389 
 
 
 397 
 
 
 401 
 
 
 409 
 
 
 419 
 
 
 421 
 
 
 431 
 
 
 433 
 
 
 439 
 
 
 443 
 
 
 449 
 
 
 457 
 
 
 461 
 
 
 463 
 
 
 467 
 
 
 479 
 
 
 487 
 
 
 491 
 
 
 499 
 
 
 503 
 
 
 509 
 
 
 521 
 
 
 523 
 
 
 541 
 
 
 547 
 
 
 557 
 
 
 563 
 
 
 569 
 
 
 571 
 
 
 577 
 
 
 587 
 
 
 593 
 
 
 599 
 
 
 601 
 
 
 607 
 
 
 613 
 
 
 617 
 
 
 619 
 
 
 631 
 
 
 641 
 
 
 643 
 
 
 647 
 
 
 653 
 
 
 659 
 
 
 661 
 
 
 673 
 
 
 677 
 
 
 683 
 
 
 691 
 
 
 701 
 
 
 709 
 
 
 719 
 
 
 727 
 
 
 733 
 
 
 739 
 
 
 743 
 
 
 751 
 
 
 757 
 
 
 761 
 
 
 769 
 
 
 773 
 
 
 787 
 
 
 797 
 
 
 809 
 
 
 811 
 
 
 821 
 
 
 823 
 
 
 827 
 
 
 829 
 
 
 839 
 
 
 853 
 
 
 857 
 
 
 859 
 
 
 863 
 
 
 877 
 
 
 881 
 
 
 883 
 
 
 887 
 
 
 907 
 
 
 911 
 
 
 919 
 
 
 929 
 
 
 937 
 
 
 941 
 
 
 947 
 
 
 953 
 
 
 967 
 
 
 971 
 
 
 977 
 
 
 983 
 
 
 991 
 
 
 997

In [ ]:
%%sql
-- La version sans WHERE ne semble pas plus efficace
SET profiling_history_size = 0;
SET profiling_history_size = 100; 
SET profiling = 1;

SELECT A.n * B.n
FROM (SELECT n FROM ints WHERE n BETWEEN 2 AND 31) A
JOIN ints B ON B.n BETWEEN A.n AND 1000 DIV A.n
;

SELECT A.n * B.n
FROM ints A
JOIN ints B ON B.n BETWEEN A.n AND 1000 DIV A.n
WHERE A.n BETWEEN 2 AND 31
;

SET profiling = 0;
SHOW PROFILES;

2550 rows affected.

2550 rows affected.

2 rows affected.

Query_ID 
 Duration 
 Query 
 
 
 
 
 40 
 0.006181 
 SELECT A.n * B.n FROM (SELECT n FROM ints WHERE n BETWEEN 2 AND 31) A JOIN ints B ON B.n BETWEEN A.n AND 1000 DIV A.n 
 
 
 41 
 0.003789 
 SELECT A.n * B.n FROM ints A JOIN ints B ON B.n BETWEEN A.n AND 1000 DIV A.n WHERE A.n BETWEEN 2 AND 31

In [ ]:
%%sql
-- Performance des trois versions
SET profiling_history_size = 0;
SET profiling_history_size = 100; 
SET profiling = 1;

-- Avec NOT IN
SELECT n
FROM ints
WHERE n > 1
  AND n NOT IN (
    SELECT A.n * B.n
    FROM ints A
    JOIN ints B ON B.n BETWEEN A.n AND 1000 DIV A.n
    WHERE A.n BETWEEN 2 AND 31
)
    ;

-- Avec EXCEPT
SELECT n
FROM ints
WHERE n > 1

EXCEPT

SELECT A.n * B.n
FROM ints A
JOIN ints B ON B.n BETWEEN A.n AND 1000 DIV A.n
WHERE A.n BETWEEN 2 AND 31
;

-- Avec NOT EXISTS
SELECT n
FROM ints C
WHERE n > 1
  AND NOT EXISTS (
    SELECT 1
    FROM ints A
    JOIN ints B ON B.n BETWEEN A.n AND 1000 DIV A.n
    WHERE A.n BETWEEN 2 AND 31
      AND A.n * B.n = C.n
  )
;

SET profiling = 0;
SHOW PROFILES;

168 rows affected.

168 rows affected.

168 rows affected.

3 rows affected.

Query_ID 
 Duration 
 Query 
 
 
 
 
 57 
 0.008058 
 SELECT n FROM ints WHERE n > 1 AND n NOT IN ( SELECT A.n * B.n FROM ints A JOIN ints B ON B.n BETWEEN A.n AND 1000 DIV A.n WHERE A.n BETWEEN 2 AND 31 ) 
 
 
 58 
 0.004978 
 SELECT n FROM ints WHERE n > 1 EXCEPT SELECT A.n * B.n FROM ints A JOIN ints B ON B.n BETWEEN A.n AND 1000 DIV A.n WHERE A.n BETWEEN 2 AND 31 
 
 
 59 
 0.006506 
 SELECT n FROM ints C WHERE n > 1 AND NOT EXISTS ( SELECT 1 FROM ints A JOIN ints B ON B.n BETWEEN A.n AND 1000 DIV A.n WHERE A.n BETWEEN 2 AND 31 AND A.n * B.n = C.n )

In [ ]:
a = col['chinese'][:]

In [ ]:
for i in range(1001):
    assert a[i] == num2chinese(i)

In [ ]:
#!/usr/bin/env python3
# -*- coding: utf-8 -*-

# Licensed under WTFPL or the Unlicense or CC0.
# This uses Python 3, but it's easy to port to Python 2 by changing
# strings to u'xx'.

import itertools

def num2chinese(num, big=False, simp=True, o=False, twoalt=False):
    """
    Converts numbers to Chinese representations.

    `big`   : use financial characters.
    `simp`  : use simplified characters instead of traditional characters.
    `o`     : use 〇 for zero.
    `twoalt`: use 两/兩 for two when appropriate.

    Note that `o` and `twoalt` is ignored when `big` is used, 
    and `twoalt` is ignored when `o` is used for formal representations.
    """
    # check num first
    nd = str(num)
    if abs(float(nd)) >= 1e48:
        raise ValueError('number out of range')
    elif 'e' in nd:
        raise ValueError('scientific notation is not supported')
    c_symbol = '正负点' if simp else '正負點'
    if o:  # formal
        twoalt = False
    if big:
        c_basic = '零壹贰叁肆伍陆柒捌玖' if simp else '零壹貳參肆伍陸柒捌玖'
        c_unit1 = '拾佰仟'
        c_twoalt = '贰' if simp else '貳'
    else:
        c_basic = '〇一二三四五六七八九' if o else '零一二三四五六七八九'
        c_unit1 = '十百千'
        if twoalt:
            c_twoalt = '两' if simp else '兩'
        else:
            c_twoalt = '二'
    c_unit2 = '万亿兆京垓秭穰沟涧正载' if simp else '萬億兆京垓秭穰溝澗正載'
    revuniq = lambda l: ''.join(k for k, g in itertools.groupby(reversed(l)))
    nd = str(num)
    result = []
    if nd[0] == '+':
        result.append(c_symbol[0])
    elif nd[0] == '-':
        result.append(c_symbol[1])
    if '.' in nd:
        integer, remainder = nd.lstrip('+-').split('.')
    else:
        integer, remainder = nd.lstrip('+-'), None
    if int(integer):
        splitted = [integer[max(i - 4, 0):i]
                    for i in range(len(integer), 0, -4)]
        intresult = []
        for nu, unit in enumerate(splitted):
            # special cases
            if int(unit) == 0:  # 0000
                intresult.append(c_basic[0])
                continue
            elif nu > 0 and int(unit) == 2:  # 0002
                intresult.append(c_twoalt + c_unit2[nu - 1])
                continue
            ulist = []
            unit = unit.zfill(4)
            for nc, ch in enumerate(reversed(unit)):
                if ch == '0':
                    if ulist:  # ???0
                        ulist.append(c_basic[0])
                elif nc == 0:
                    ulist.append(c_basic[int(ch)])
                elif nc == 1 and ch == '1' and unit[1] == '0':
                    # special case for tens
                    # edit the 'elif' if you don't like
                    # 十四, 三千零十四, 三千三百一十四
                    ulist.append(c_unit1[0])
                elif nc > 1 and ch == '2':
                    ulist.append(c_twoalt + c_unit1[nc - 1])
                else:
                    ulist.append(c_basic[int(ch)] + c_unit1[nc - 1])
            ustr = revuniq(ulist)
            if nu == 0:
                intresult.append(ustr)
            else:
                intresult.append(ustr + c_unit2[nu - 1])
        result.append(revuniq(intresult).strip(c_basic[0]))
    else:
        result.append(c_basic[0])
    if remainder:
        result.append(c_symbol[2])
        result.append(''.join(c_basic[int(ch)] for ch in remainder))
    return ''.join(result)

In [ ]:
b = [num2chinese(i) for i in range(1001)]

In [ ]:
a == b

True

In [ ]:
a = col['中文'][:]

In [ ]:
for i in range(1001):
    assert a[i] == num2chinese(i)

In [ ]:
def num_to_chinese(num):
    if num == 0:
        return '零'
    if num == 1000:
        return '一千'
    
    digits = '零一二三四五六七八九'
    units = '十百'
    
    result = []
    s = str(num)
    
    # Handle hundreds
    if len(s) == 3:
        result.append(digits[int(s[0])] + units[1])
        if s[1] != '0':
            result.append(digits[int(s[1])] + units[0])
        elif s[2] != '0':
            result.append('零')
        if s[2] != '0':
            result.append(digits[int(s[2])])
    
    # Handle tens
    elif len(s) == 2:
        if s[0] == '1':
            result.append(units[0])
        else:
            result.append(digits[int(s[0])] + units[0])
        if s[1] != '0':
            result.append(digits[int(s[1])])
    
    # Handle single digits
    else:
        result.append(digits[int(s)])
    
    return ''.join(result)

In [ ]:
a == [num_to_chinese(i) for i in range(1001)]

True